In [1]:
print('start')

start


In [2]:
import numpy as np
import pandas as pd
import re
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor, AdaBoostRegressor, ExtraTreesRegressor
from sklearn.linear_model import LinearRegression, LogisticRegression  # LogisticRegression is not used for regression
from sklearn.neighbors import KNeighborsRegressor
from sklearn.svm import SVR
from sklearn.neural_network import MLPRegressor
import xgboost as xgb
import lightgbm as lgb
from sklearn.model_selection import KFold, GridSearchCV
from sklearn.preprocessing import StandardScaler
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
from scipy.stats import pearsonr, spearmanr
from sklearn.model_selection import train_test_split
import matplotlib.pyplot as plt

In [3]:
def train_and_test_predict(models, X_train, y_train, X_test, y_test):
    kf = KFold(n_splits=5, shuffle=True, random_state=101)
    results = {}
    predictions = []  

    for model in models:
        model_name = model.__class__.__name__
        predictions_train = []
        actual_y_train = []

        test_predictions_folds = []

        

        for train_index, val_index in kf.split(X_train):
            X_train_fold, X_val_fold = X_train.iloc[train_index], X_train.iloc[val_index]
            y_train_fold, y_val_fold = y_train.iloc[train_index], y_train.iloc[val_index]

            model.fit(X_train_fold, y_train_fold)

            y_pred_fold = model.predict(X_val_fold)
            y_pred_fold = np.clip(y_pred_fold, -10, -4.0)
            predictions_train.extend(y_pred_fold)
            actual_y_train.extend(y_val_fold)

            predictions_test_fold = model.predict(X_test)
            predictions_test_fold = np.clip(predictions_test_fold, -10, -4.0)
            test_predictions_folds.append(predictions_test_fold)


        mse_train = mean_squared_error(actual_y_train, predictions_train)
        mae_train = mean_absolute_error(actual_y_train, predictions_train)
        rmse_train = np.sqrt(mse_train)
        r2_train = r2_score(actual_y_train, predictions_train)
        pearson_train, _ = pearsonr(actual_y_train, predictions_train)
        spearman_train, _ = spearmanr(actual_y_train, predictions_train)


        predictions_test_mean = np.mean(test_predictions_folds, axis=0)
        predictions_test_std = np.std(test_predictions_folds, axis=0)

        mse_test = mean_squared_error(y_test, predictions_test_mean)
        mae_test = mean_absolute_error(y_test, predictions_test_mean)
        rmse_test = np.sqrt(mse_test)
        r2_test = r2_score(y_test, predictions_test_mean)
        print(r2_test)
        pearson_test, _ = pearsonr(y_test, predictions_test_mean)
        spearman_test, _ = spearmanr(y_test, predictions_test_mean)
        
        

        predictions.append({
            'Model': model_name,
            'Y Train pred': predictions_train,
            'Y Test actual': y_test,
            'Test prediction folds': test_predictions_folds,
            'Test Predictions Mean': predictions_test_mean,
            'Test Predictions Std': predictions_test_std,

        })

        results[model_name] = {
            'Train MSE (5 fold cv)': f"{mse_train:.4f}",
            'Train MAE (5 fold cv)': f"{mae_train:.4f}",
            'Train RMSE (5 fold cv)': f"{rmse_train:.4f}",
            'Train RMSE (5 fold cv)': f"{rmse_train:.4f}",
            'Train R2 (5 fold cv)': f"{r2_train:.4f}",
            'Train PCC (5 fold cv)': f"{pearson_train:.4f}",
            'Train SCC (5 fold cv)': f"{spearman_train:.4f}",
            'Test MSE': f"{mse_test:.4f}",
            'Test MAE': f"{mae_test:.4f}",
            'Test RMSE': f"{rmse_test:.4f}",
            'Test R2': f"{r2_test:.4f}",
            'Test Pearson Correlation': f"{pearson_test:.4f}",
            'Test Spearman Correlation': f"{spearman_test:.4f}",
        }

    results_df = pd.DataFrame(results).T
    predictions_df = pd.DataFrame(predictions)

    return results_df, predictions_df



In [4]:
#Monomeric models
def clean_feature_names(df):
    def clean_name(name):
        return re.sub(r'[^a-zA-Z0-9_]', '_', name)

    df.columns = [clean_name(col) for col in df.columns]
    return df

In [8]:
#Monomer composition
df_mc_train = pd.read_csv('features/Monomeric/Train_mon_comp_RRCK.csv')
df_mc_train = clean_feature_names(df_mc_train)
X_train = df_mc_train.drop(['ID','SMILES','Permeability'], axis=1)
y_train = df_mc_train['Permeability']
print(X_train.shape)
print(y_train.shape)
df_mc_test = pd.read_csv('features/Monomeric/Test_mon_comp_RRCK.csv')
df_mc_test = clean_feature_names(df_mc_test)
X_test = df_mc_test.drop(['ID','SMILES','Permeability'], axis=1)
y_test = df_mc_test['Permeability']
print(X_test.shape)
print(y_test.shape)
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    xgb.XGBRegressor(random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    SVR(),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3), 
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

(140, 385)
(140,)
(36, 385)
(36,)
0.280044644383886
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000021 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 37
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 6
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] 

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-0.1523863356331674


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
ExtraTreesRegressor                      0.3290                0.4135   
LGBMRegressor                            0.4048                0.4958   
XGBRegressor                             0.3129                0.3986   
DecisionTreeRegressor                    0.4315                0.4872   
RandomForestRegressor                    0.3136                0.4054   
GradientBoostingRegressor                0.3096                0.3922   
AdaBoostRegressor                        0.3477                0.4777   
SVR                                      0.3121                0.4150   
LinearRegression                         0.5140                0.5146   
KNeighborsRegressor                      0.3399                0.4172   
MLPRegressor                             1.1830                0.8126   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
ExtraTreesRegressor                       0.5736               0.2660   
LGBMRegressor                             0.6363               0.0969   
XGBRegressor                              0.5594               0.3020   
DecisionTreeRegressor                     0.6569               0.0374   
RandomForestRegressor                     0.5600               0.3005   
GradientBoostingRegressor                 0.5564               0.3094   
AdaBoostRegressor                         0.5897               0.2244   
SVR                                       0.5586               0.3038   
LinearRegression                          0.7169              -0.1465   
KNeighborsRegressor                       0.5830               0.2419   
MLPRegressor                              1.0876              -1.6389   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
ExtraTreesRegressor                      0.5733                0.6095   
LGBMRegressor                            0.3240                0.3603   
XGBRegressor                             0.6115                0.6525   
DecisionTreeRegressor                    0.5098                0.5391   
RandomForestRegressor                    0.5616                0.5891   
GradientBoostingRegressor                0.5700                0.6085   
AdaBoostRegressor                        0.4848                0.5234   
SVR                                      0.5562                0.5492   
LinearRegression                         0.3740                0.3985   
KNeighborsRegressor                      0.5407                0.5820   
MLPRegressor                             0.1935                0.1667   

                          Test MSE Test MAE Test RMSE  Test R2  \
ExtraTreesRegressor         0.5204   0.4745    0.7214   0.2800   
LGBMRegressor               0.6288   0.6047    0.7930   0.1300   
XGBRegressor                0.5367   0.4883    0.7326   0.2575   
DecisionTreeRegressor       0.5973   0.5021    0.7729   0.1736   
RandomForestRegressor       0.5607   0.5015    0.7488   0.2243   
GradientBoostingRegressor   0.5183   0.4760    0.7199   0.2830   
AdaBoostRegressor           0.5692   0.5464    0.7545   0.2125   
SVR                         0.5708   0.5009    0.7555   0.2103   
LinearRegression            0.5939   0.5858    0.7706   0.1784   
KNeighborsRegressor         0.5766   0.4985    0.7593   0.2023   
MLPRegressor                0.8330   0.7628    0.9127  -0.1524   

                          Test Pearson Correlation Test Spearman Correlation  
ExtraTreesRegressor                         0.5800                    0.6476  
LGBMRegressor                               0.5633                    0.5940  
XGBRegressor                                0.5682                    0.6344  
DecisionTreeRegressor                       0.5013                    0.5516  
RandomForestRegressor                       0.5430                    0.6030  
GradientBoostingRegressor                   0.6211                    0.7345  
AdaBoostRegressor                           0.610

In [9]:
prediction_df

Model  \
0         ExtraTreesRegressor   
1               LGBMRegressor   
2                XGBRegressor   
3       DecisionTreeRegressor   
4       RandomForestRegressor   
5   GradientBoostingRegressor   
6           AdaBoostRegressor   
7                         SVR   
8            LinearRegression   
9         KNeighborsRegressor   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.5688999999999975, -6.250800000000006, -5.1...   
1   [-5.435194447807869, -5.921453487707277, -5.51...   
2   [-5.9810386, -5.500048, -5.1609173, -6.1795087...   
3   [-6.13, -6.62, -5.16, -6.62, -5.57, -4.4, -5.5...   
4   [-5.924199999999997, -5.947850000000005, -5.21...   
5   [-5.817499453013974, -5.838142326436363, -5.33...   
6   [-5.877826086956522, -5.908867924528305, -5.64...   
7   [-5.713091198547051, -6.179863522237482, -5.32...   
8   [-5.23933658157549, -6.202358993197268, -5.667...   
9   [-5.716666666666666, -6.19, -5.013333333333333...   
10  [-4.0, -5.650613533156039, -5.334265942497622,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-6.0078, -6.779999999999983, -6.041100000000...   
1   [[-5.435194447807869, -5.435194447807869, -5.9...   
2   [[-6.422107, -6.7394586, -6.1410713, -6.149780...   
3   [[-6.13, -6.78, -6.62, -6.46, -6.62, -5.16, -5...   
4   [[-6.164599999999999, -6.409699999999994, -5.8...   
5   [[-6.1689812224792, -6.233907101757087, -6.155...   
6   [[-6.055, -6.055, -5.908867924528305, -5.87185...   
7   [[-5.891126011806585, -6.20512562729422, -5.81...   
8   [[-7.261432253238778, -6.467908498202312, -7.3...   
9   [[-6.260000000000001, -6.260000000000001, -5.8...   
10  [[-5.243758195791692, -6.620620374459524, -9.3...   

                                Test Predictions Mean  \
0   [-6.166559999999996, -6.588079999999986, -5.84...   
1   [-5.509803594592938, -5.509803594592938, -5.89...   
2   [-6.427549, -6.584222, -5.9452333, -6.2241383,...   
3   [-6.354, -6.614, -5.806, -6.459999999999999, -...   
4   [-6.1583279999999965, -6.292819999999993, -5.8...   
5   [-6.183862133078874, -6.171055250076803, -5.91...   
6   [-6.10849123817359, -6.1010860433683956, -5.92...   
7   [-5.916854618327262, -6.126788114997646, -5.85...   
8   [-6.893803674706957, -6.263292777677549, -6.71...   
9   [-6.173333333333334, -6.114000000000001, -5.91...   
10  [-4.986629065325886, -6.202091427910052, -9.18...   

                                 Test Predictions Std  
0   [0.30527894522877996, 0.38383999999999396, 0.1...  
1   [0.03786140795581648, 0.03786140795581648, 0.0...  
2   [0.26102582, 0.3183277, 0.18391402, 0.10323646...  
3   [0.3539830504416844, 0.3320000000000001, 0.483...  
4   [0.1555075841751775, 0.25220180332423986, 0.13...  
5   [0.18301260031667324, 0.16747660768436032, 0.1...  
6   [0.12507011895366335, 0.1383020008478662, 0.09...  
7   [0.05928054160495901, 0.19105987633333996, 0.0...  
8   [0.3294713874495542, 0.3656202288705681, 0.826...  
9   [0.12044362443345336, 0.2338698593472688, 0.07...  
10  [0.6538150955252898, 0.7554941557153957, 0.434...

In [10]:
result_df.to_csv('results/Monomeric/Monomer_comp_results_RRCK.csv')
prediction_df.to_csv('results/Monomeric/Monomer_comp_prediction_data_RRCK.csv')

In [13]:
#Removal of constant columns
def remove_constant_columns(df):
    constant_columns = [col for col in df.columns if df[col].nunique() <= 1]
    
    df_cleaned = df.drop(columns=constant_columns)
    
    return df_cleaned, constant_columns

In [15]:
df_mc_train = pd.read_csv('features/Monomeric/Train_mon_comp_RRCK.csv')
df_mc_train = clean_feature_names(df_mc_train)
df_mc_train, const_col = remove_constant_columns(df_mc_train)
X_train = df_mc_train.drop(['ID','SMILES','Permeability'], axis=1)
y_train = df_mc_train['Permeability']
print(X_train.shape)
print(y_train.shape)
df_mc_test = pd.read_csv('features/Monomeric/Test_mon_comp_RRCK.csv')
df_mc_test = clean_feature_names(df_mc_test)
X_test = df_mc_test.drop(['ID','SMILES','Permeability'], axis=1)
X_test = X_test.drop(const_col, axis=1)
y_test = df_mc_test['Permeability']
print(X_test.shape)
print(y_test.shape)
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    xgb.XGBRegressor(random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    SVR(),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3), 
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

(140, 67)
(140,)
(36, 67)
(36,)
0.28493794847367626
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000012 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 37
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 6
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] 

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-0.23079075675008176


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
ExtraTreesRegressor                      0.3171                0.4029   
LGBMRegressor                            0.4048                0.4958   
XGBRegressor                             0.3129                0.3986   
DecisionTreeRegressor                    0.4080                0.4715   
RandomForestRegressor                    0.3126                0.4063   
GradientBoostingRegressor                0.3105                0.3902   
AdaBoostRegressor                        0.3415                0.4718   
SVR                                      0.3121                0.4150   
LinearRegression                         0.5140                0.5146   
KNeighborsRegressor                      0.3363                0.4173   
MLPRegressor                             1.1863                0.8309   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
ExtraTreesRegressor                       0.5631               0.2926   
LGBMRegressor                             0.6363               0.0969   
XGBRegressor                              0.5594               0.3020   
DecisionTreeRegressor                     0.6388               0.0898   
RandomForestRegressor                     0.5591               0.3026   
GradientBoostingRegressor                 0.5572               0.3074   
AdaBoostRegressor                         0.5844               0.2383   
SVR                                       0.5587               0.3038   
LinearRegression                          0.7169              -0.1465   
KNeighborsRegressor                       0.5799               0.2498   
MLPRegressor                              1.0892              -1.6463   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
ExtraTreesRegressor                      0.5898                0.6217   
LGBMRegressor                            0.3240                0.3603   
XGBRegressor                             0.6115                0.6525   
DecisionTreeRegressor                    0.5321                0.5700   
RandomForestRegressor                    0.5621                0.5936   
GradientBoostingRegressor                0.5699                0.6098   
AdaBoostRegressor                        0.5004                0.5083   
SVR                                      0.5562                0.5492   
LinearRegression                         0.3740                0.3986   
KNeighborsRegressor                      0.5469                0.5845   
MLPRegressor                             0.2254                0.1865   

                          Test MSE Test MAE Test RMSE  Test R2  \
ExtraTreesRegressor         0.5169   0.4706    0.7189   0.2849   
LGBMRegressor               0.6288   0.6047    0.7930   0.1300   
XGBRegressor                0.5367   0.4883    0.7326   0.2575   
DecisionTreeRegressor       0.6262   0.5108    0.7913   0.1337   
RandomForestRegressor       0.5564   0.5006    0.7459   0.2303   
GradientBoostingRegressor   0.5193   0.4750    0.7207   0.2815   
AdaBoostRegressor           0.5654   0.5400    0.7519   0.2178   
SVR                         0.5709   0.5009    0.7555   0.2103   
LinearRegression            0.5939   0.5858    0.7706   0.1784   
KNeighborsRegressor         0.5790   0.5005    0.7609   0.1990   
MLPRegressor                0.8897   0.7557    0.9432  -0.2308   

                          Test Pearson Correlation Test Spearman Correlation  
ExtraTreesRegressor                         0.5823                    0.6483  
LGBMRegressor                               0.5633                    0.5940  
XGBRegressor                                0.5682                    0.6344  
DecisionTreeRegressor                       0.4739                    0.5542  
RandomForestRegressor                       0.5490                    0.6071  
GradientBoostingRegressor                   0.6200                    0.7273  
AdaBoostRegressor                           0.611

In [16]:
prediction_df

Model  \
0         ExtraTreesRegressor   
1               LGBMRegressor   
2                XGBRegressor   
3       DecisionTreeRegressor   
4       RandomForestRegressor   
5   GradientBoostingRegressor   
6           AdaBoostRegressor   
7                         SVR   
8            LinearRegression   
9         KNeighborsRegressor   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.624399999999997, -6.334700000000006, -5.16...   
1   [-5.435194447807869, -5.921453487707277, -5.51...   
2   [-5.9810386, -5.500048, -5.1609173, -6.1795087...   
3   [-6.13, -6.62, -5.16, -5.58, -5.57, -4.4, -5.5...   
4   [-5.901899999999996, -5.951250000000007, -5.20...   
5   [-5.817499453013974, -5.855639926213294, -5.33...   
6   [-5.953717948717944, -5.954999999999996, -5.79...   
7   [-5.713044593865235, -6.179886545929588, -5.32...   
8   [-5.239336581575468, -6.202358993197267, -5.66...   
9   [-5.716666666666666, -6.19, -5.013333333333333...   
10  [-4.0, -5.88247965030751, -5.236037208999902, ...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.9974, -6.779999999999983, -6.112600000000...   
1   [[-5.435194447807869, -5.435194447807869, -5.9...   
2   [[-6.422107, -6.7394586, -6.1410713, -6.149780...   
3   [[-6.13, -6.78, -5.58, -6.46, -5.58, -5.16, -5...   
4   [[-6.114299999999998, -6.403599999999995, -5.9...   
5   [[-6.194981222479201, -6.233907101757087, -6.1...   
6   [[-6.010352112676055, -6.010352112676055, -5.9...   
7   [[-5.891087559751947, -6.205122660812568, -5.8...   
8   [[-7.261432253238787, -6.467908498202323, -7.3...   
9   [[-6.260000000000001, -6.260000000000001, -5.8...   
10  [[-4.791638581411773, -6.789971820706177, -9.4...   

                                Test Predictions Mean  \
0   [-6.158539999999997, -6.587919999999985, -5.85...   
1   [-5.509803594592938, -5.509803594592938, -5.89...   
2   [-6.427549, -6.584222, -5.9452333, -6.2241383,...   
3   [-6.354, -6.614, -5.68, -6.459999999999999, -5...   
4   [-6.140839999999996, -6.286539999999993, -5.85...   
5   [-6.189062133078874, -6.171055250076803, -5.91...   
6   [-6.0679815336463205, -6.0679815336463205, -5....   
7   [-5.916845826101662, -6.126789610588135, -5.85...   
8   [-6.893803674706964, -6.263292777677553, -6.71...   
9   [-6.173333333333334, -6.114000000000001, -5.91...   
10  [-4.591637339372566, -6.42156682177435, -9.702...   

                                 Test Predictions Std  
0   [0.3089407036957032, 0.3841599999999943, 0.142...  
1   [0.03786140795581648, 0.03786140795581648, 0.0...  
2   [0.26102582, 0.3183277, 0.18391402, 0.10323646...  
3   [0.3539830504416844, 0.3320000000000001, 0.394...  
4   [0.18114299986474697, 0.25951306402568464, 0.1...  
5   [0.18288523834479858, 0.16747660768436032, 0.1...  
6   [0.1803695346277304, 0.1803695346277304, 0.083...  
7   [0.05928397270291572, 0.19106032390527164, 0.0...  
8   [0.32947138744955473, 0.3656202288705669, 0.82...  
9   [0.12044362443345336, 0.2338698593472688, 0.07...  
10  [0.4951631069853615, 0.6363653451900472, 0.209...

In [17]:
const_col

['Ala_indol_2_yl_',
 'dAla_indol_2_yl_',
 'Me_Ala_indol_2_yl_',
 'Ala_5_Tet_',
 '2Abz',
 'Aib',
 'Aoc_2_',
 '5_Ava',
 'Bal',
 'Me_Bal',
 'HOCOCH2_Bal',
 'Cys_EtO2H__NH2',
 'dCha',
 'D',
 'Asp_piperidide',
 'Asp_OMe_',
 'Asp_Ph_2_NH2__',
 'dAsp_pyrrol_1_yl_',
 'E',
 'Glu_NH2',
 'Glu_3R_Me_',
 'Glu_OMe_',
 'dGlu_OMe_',
 'Phe_4_F_',
 'dPhe_4_F_',
 'Phe_4_CF3_',
 'Phe_4_NO2_',
 'Phe_CHF2_',
 'dPhe_3_4_diF_',
 'Et_Phe',
 'H2NEt_Phe',
 'Me_Phe_3_Cl_',
 'Me_Phe_4_Cl_',
 'Me_Phe_a_b_dehydro_',
 'G',
 'Bn_Gly',
 'Bn_4_Cl__Gly',
 'Bu_Gly',
 'Et_Gly',
 'EtOEt_Gly',
 'HOCOCH2_Gly_ol',
 'MeOEt_Gly',
 'NH2Bu_Gly',
 'Pr_Gly',
 'PhEt_Gly',
 'cHexCH2_Gly',
 'isoamyl_Gly',
 'pentyl_Gly',
 '3_pyridylethyl_Gly',
 'd_N__O_Gly_allyl_',
 'GABA',
 'H',
 'Me_Hph',
 'bHph',
 'Hph_2_Cl_',
 'Hph_3_Cl_',
 'Hph_4_Cl_',
 'Hse_Et_',
 'dHyp',
 'Hyp_Et_',
 'dI',
 'meI',
 'Me_dI',
 '_N__O_xiIle',
 'd_N__O_aIle',
 'K',
 'dK',
 'Me_dK',
 'Lys_Ac_',
 'Lys_Cbz_',
 'Lys_iPr_',
 'Lys_Me_',
 'Lys_Me2_',
 'Lys_Tfa_',
 'aMeLeu',

In [18]:
result_df.to_csv('results/Monomeric/Monomer_comp_constRemoval_results_RRCK.csv')
prediction_df.to_csv('results/Monomeric/Monomer_comp_constRemoval_prediction_data_RRCK.csv')

In [14]:
#Low variance column removal
def remove_low_variance_columns(df, threshold=0.005):
    variances = df.var()
    
    low_variance_columns = variances[variances < threshold].index.tolist()
    
    df_cleaned = df.drop(columns=low_variance_columns)
    
    return df_cleaned, low_variance_columns

In [20]:
df_train = pd.read_csv('features/Monomeric/Train_mon_comp_RRCK.csv')
df_mc_train = clean_feature_names(df_train)
df_mc_train = df_mc_train.drop(['ID','SMILES','Permeability'],axis=1)
df_mc, const_col = remove_low_variance_columns(df_mc_train)
X_train = df_mc
y_train = df_train['Permeability']
print(X_train.shape)
print(y_train.shape)

df_mc_test = pd.read_csv('features/Monomeric/Test_mon_comp_RRCK.csv')
df_mc_test = clean_feature_names(df_mc_test)
X_test = df_mc_test.drop(['ID','SMILES','Permeability'], axis=1)
X_test = X_test.drop(const_col, axis=1)
y_test = df_mc_test['Permeability']
print(X_test.shape)
print(y_test.shape)
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    xgb.XGBRegressor(random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    SVR(),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3), 
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

(140, 10)
(140,)
(36, 10)
(36,)
0.09368244903816247
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000030 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 32
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 5
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM]

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-0.8037102097709128


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
ExtraTreesRegressor                      0.3764                0.4626   
LGBMRegressor                            0.4048                0.4958   
XGBRegressor                             0.4519                0.5061   
DecisionTreeRegressor                    0.4305                0.4910   
RandomForestRegressor                    0.3900                0.4805   
GradientBoostingRegressor                0.3940                0.4811   
AdaBoostRegressor                        0.3669                0.4805   
SVR                                      0.3786                0.4721   
LinearRegression                         0.4287                0.5064   
KNeighborsRegressor                      0.4235                0.5158   
MLPRegressor                             0.9160                0.7339   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
ExtraTreesRegressor                       0.6135               0.1604   
LGBMRegressor                             0.6363               0.0969   
XGBRegressor                              0.6722              -0.0080   
DecisionTreeRegressor                     0.6561               0.0397   
RandomForestRegressor                     0.6245               0.1300   
GradientBoostingRegressor                 0.6277               0.1210   
AdaBoostRegressor                         0.6057               0.1815   
SVR                                       0.6153               0.1554   
LinearRegression                          0.6548               0.0436   
KNeighborsRegressor                       0.6508               0.0552   
MLPRegressor                              0.9571              -1.0433   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
ExtraTreesRegressor                      0.5000                0.5175   
LGBMRegressor                            0.3240                0.3603   
XGBRegressor                             0.4258                0.4475   
DecisionTreeRegressor                    0.4621                0.4740   
RandomForestRegressor                    0.4428                0.4558   
GradientBoostingRegressor                0.4321                0.4485   
AdaBoostRegressor                        0.4278                0.4556   
SVR                                      0.4317                0.4591   
LinearRegression                         0.3137                0.3307   
KNeighborsRegressor                      0.4067                0.4064   
MLPRegressor                             0.1991                0.2365   

                          Test MSE Test MAE Test RMSE  Test R2  \
ExtraTreesRegressor         0.6551   0.5824    0.8094   0.0937   
LGBMRegressor               0.6288   0.6047    0.7930   0.1300   
XGBRegressor                0.6647   0.5804    0.8153   0.0804   
DecisionTreeRegressor       0.6527   0.5669    0.8079   0.0970   
RandomForestRegressor       0.6268   0.5739    0.7917   0.1329   
GradientBoostingRegressor   0.6500   0.5813    0.8062   0.1008   
AdaBoostRegressor           0.6216   0.5813    0.7884   0.1400   
SVR                         0.6796   0.5812    0.8244   0.0598   
LinearRegression            0.7635   0.6208    0.8738  -0.0563   
KNeighborsRegressor         0.6903   0.6079    0.8308   0.0451   
MLPRegressor                1.3038   0.8326    1.1418  -0.8037   

                          Test Pearson Correlation Test Spearman Correlation  
ExtraTreesRegressor                         0.4381                    0.5117  
LGBMRegressor                               0.5633                    0.5940  
XGBRegressor                                0.4226                    0.5123  
DecisionTreeRegressor                       0.4318                    0.5329  
RandomForestRegressor                       0.4608                    0.5436  
GradientBoostingRegressor                   0.4274                    0.5646  
AdaBoostRegressor                           0.547

In [21]:
prediction_df

Model  \
0         ExtraTreesRegressor   
1               LGBMRegressor   
2                XGBRegressor   
3       DecisionTreeRegressor   
4       RandomForestRegressor   
5   GradientBoostingRegressor   
6           AdaBoostRegressor   
7                         SVR   
8            LinearRegression   
9         KNeighborsRegressor   
10               MLPRegressor   

                                         Y Train pred  \
0   [-6.182500000000004, -5.54750000000001, -5.160...   
1   [-5.435194447807869, -5.921453487707277, -5.51...   
2   [-6.1811376, -5.343238, -5.1590805, -6.388953,...   
3   [-6.1825, -5.35, -5.16, -6.01, -5.461428571428...   
4   [-6.143599523809526, -5.50570000000001, -5.194...   
5   [-6.082024192129701, -5.501094484382374, -5.20...   
6   [-6.01265625, -5.9071428571428575, -5.59070175...   
7   [-5.769833116390693, -5.933091670841013, -5.30...   
8   [-5.537915407041128, -5.70888468423566, -5.687...   
9   [-6.286666666666666, -5.766666666666666, -5.93...   
10  [-5.784677514885106, -4.7592139407641865, -5.5...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-6.182500000000004, -6.182500000000004, -5.7...   
1   [[-5.435194447807869, -5.435194447807869, -5.9...   
2   [[-6.1811376, -6.1811376, -5.5787435, -6.06971...   
3   [[-6.1825, -6.1825, -5.35, -6.46, -6.01, -5.16...   
4   [[-6.143599523809526, -6.143599523809526, -5.7...   
5   [[-6.082024192129701, -6.082024192129701, -5.7...   
6   [[-6.01265625, -6.01265625, -5.86142045454545,...   
7   [[-5.769833116390693, -5.769833116390693, -5.6...   
8   [[-5.537915407041128, -5.537915407041128, -5.4...   
9   [[-6.286666666666666, -6.286666666666666, -5.7...   
10  [[-5.784677514885106, -5.784677514885106, -4.4...   

                                Test Predictions Mean  \
0   [-6.2764333333333395, -6.2764333333333395, -5....   
1   [-5.509803594592938, -5.509803594592938, -5.89...   
2   [-6.2754636, -6.2754636, -5.6456575, -5.706023...   
3   [-6.276433333333334, -6.276433333333334, -5.70...   
4   [-6.248704983405483, -6.248704983405483, -5.79...   
5   [-6.186388619039126, -6.186388619039126, -5.72...   
6   [-5.977907114779875, -5.977907114779875, -5.92...   
7   [-5.785732283117556, -5.785732283117556, -5.65...   
8   [-5.589180640819773, -5.589180640819773, -5.46...   
9   [-6.3533333333333335, -6.3533333333333335, -5....   
10  [-5.804750697052418, -5.804750697052418, -4.68...   

                                 Test Predictions Std  
0   [0.06030382335400829, 0.06030382335400829, 0.1...  
1   [0.03786140795581648, 0.03786140795581648, 0.0...  
2   [0.060485173, 0.060485173, 0.3380656, 0.691104...  
3   [0.06030382335400576, 0.06030382335400576, 0.3...  
4   [0.06472076353610155, 0.06472076353610155, 0.2...  
5   [0.066904261945415, 0.066904261945415, 0.19542...  
6   [0.054015120548614265, 0.054015120548614265, 0...  
7   [0.032079070297683455, 0.032079070297683455, 0...  
8   [0.043512307683369104, 0.043512307683369104, 0...  
9   [0.1167904105652515, 0.1167904105652515, 0.100...  
10  [0.047886112961295205, 0.047886112961295205, 0...

In [22]:
result_df.to_csv('results/Monomeric/Monomer_comp_LVR_results_RRCK.csv')
prediction_df.to_csv('results/Monomeric/Monomer_comp_LVR_prediction_data_RRCK.csv')

In [23]:
#AA composition
df_aac_train = pd.read_csv('features/Monomeric/Train_aac_RRCK.csv')
X_train = df_aac_train.drop(['ID','SMILES','Permeability'], axis=1)
y_train = df_aac_train['Permeability']
print(X_train.shape)
print(y_train.shape)
df_aac_test = pd.read_csv('features/Monomeric/Test_aac_RRCK.csv')
X_test = df_aac_test.drop(['ID','SMILES','Permeability'], axis=1)
y_test = df_aac_test['Permeability']
print(X_test.shape)
print(y_test.shape)
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    xgb.XGBRegressor(random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    SVR(),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3), 
    MLPRegressor(random_state=101)
]
aac_comp,prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
aac_comp

(140, 21)
(140,)
(36, 21)
(36,)
0.21152972464058117
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000048 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 60
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 8
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] 

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-1.8752243745538566


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
ExtraTreesRegressor                      0.4865                0.5350   
LGBMRegressor                            0.3765                0.4863   
XGBRegressor                             0.4549                0.5236   
DecisionTreeRegressor                    0.4583                0.5243   
RandomForestRegressor                    0.4230                0.5096   
GradientBoostingRegressor                0.3899                0.4913   
AdaBoostRegressor                        0.3715                0.4900   
SVR                                      0.4195                0.4884   
LinearRegression                         0.3749                0.4868   
KNeighborsRegressor                      0.4902                0.5343   
MLPRegressor                             1.0191                0.7903   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
ExtraTreesRegressor                       0.6975              -0.0853   
LGBMRegressor                             0.6136               0.1602   
XGBRegressor                              0.6745              -0.0147   
DecisionTreeRegressor                     0.6770              -0.0223   
RandomForestRegressor                     0.6503               0.0565   
GradientBoostingRegressor                 0.6245               0.1301   
AdaBoostRegressor                         0.6095               0.1712   
SVR                                       0.6477               0.0642   
LinearRegression                          0.6123               0.1636   
KNeighborsRegressor                       0.7002              -0.0936   
MLPRegressor                              1.0095              -1.2733   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
ExtraTreesRegressor                      0.2871                0.3061   
LGBMRegressor                            0.4093                0.4551   
XGBRegressor                             0.3557                0.3768   
DecisionTreeRegressor                    0.3990                0.3916   
RandomForestRegressor                    0.3578                0.3964   
GradientBoostingRegressor                0.4263                0.4500   
AdaBoostRegressor                        0.4142                0.4522   
SVR                                      0.3794                0.4044   
LinearRegression                         0.4238                0.4152   
KNeighborsRegressor                      0.2835                0.3369   
MLPRegressor                             0.1739                0.1717   

                          Test MSE Test MAE Test RMSE  Test R2  \
ExtraTreesRegressor         0.5699   0.5315    0.7549   0.2115   
LGBMRegressor               0.6052   0.5535    0.7779   0.1628   
XGBRegressor                0.6560   0.5399    0.8099   0.0924   
DecisionTreeRegressor       0.6988   0.5367    0.8360   0.0332   
RandomForestRegressor       0.6695   0.5416    0.8182   0.0738   
GradientBoostingRegressor   0.6714   0.5433    0.8194   0.0712   
AdaBoostRegressor           0.6888   0.5843    0.8299   0.0471   
SVR                         0.7192   0.6009    0.8481   0.0050   
LinearRegression            0.7820   0.6568    0.8843  -0.0819   
KNeighborsRegressor         0.6850   0.6446    0.8277   0.0523   
MLPRegressor                2.0783   1.0576    1.4416  -1.8752   

                          Test Pearson Correlation Test Spearman Correlation  
ExtraTreesRegressor                         0.5400                    0.6021  
LGBMRegressor                               0.5577                    0.6153  
XGBRegressor                                0.4372                    0.5480  
DecisionTreeRegressor                       0.4137                    0.5036  
RandomForestRegressor                       0.4413                    0.5521  
GradientBoostingRegressor                   0.4348                    0.5538  
AdaBoostRegressor                           0.436

In [24]:
prediction_df

Model  \
0         ExtraTreesRegressor   
1               LGBMRegressor   
2                XGBRegressor   
3       DecisionTreeRegressor   
4       RandomForestRegressor   
5   GradientBoostingRegressor   
6           AdaBoostRegressor   
7                         SVR   
8            LinearRegression   
9         KNeighborsRegressor   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.445449999999999, -6.079750000000003, -5.07...   
1   [-5.959733429896936, -5.850785207180732, -5.51...   
2   [-5.9788427, -6.246716, -5.079993, -5.370795, ...   
3   [-6.365, -6.22, -5.08, -5.08, -6.05, -5.1, -5....   
4   [-5.847411666666666, -6.115625000000008, -5.11...   
5   [-5.819199211300774, -6.1570215442491465, -5.1...   
6   [-5.883111111111111, -5.977142857142859, -5.55...   
7   [-5.522594908354534, -5.860263707068752, -5.32...   
8   [-5.552375842562193, -5.803340984923865, -5.65...   
9   [-5.53, -6.246666666666667, -5.153333333333333...   
10  [-4.950814955967545, -4.529239703545031, -4.96...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-6.1606, -6.365000000000006, -5.707621250000...   
1   [[-6.084860559870292, -5.959733429896936, -5.8...   
2   [[-6.129233, -6.364632, -5.430443, -6.4609346,...   
3   [[-5.87, -6.365, -5.08, -6.46, -5.08, -5.08, -...   
4   [[-6.136050000000001, -6.264725000000001, -5.3...   
5   [[-6.167227238122383, -6.284029146743934, -5.4...   
6   [[-6.133846153846155, -6.133846153846155, -5.5...   
7   [[-6.011452088036632, -6.050430877547241, -5.4...   
8   [[-6.926027265141383, -6.266721071876499, -5.4...   
9   [[-6.2, -6.2, -6.103333333333334, -5.02, -6.10...   
10  [[-9.684973738707171, -6.158674607423653, -4.0...   

                                Test Predictions Mean  \
0   [-6.11379, -6.365, -5.7121053611111146, -6.367...   
1   [-6.118872178235309, -6.051852551138583, -5.75...   
2   [-6.179635, -6.3646026, -5.3644476, -6.5963073...   
3   [-6.136, -6.365, -5.0725, -6.664, -5.1818, -5....   
4   [-6.1258365, -6.279342166666664, -5.4532602103...   
5   [-6.33441550854893, -6.281958413949489, -5.433...   
6   [-6.148538461538462, -6.160126696832579, -5.53...   
7   [-5.994372703029188, -6.058943915570362, -5.50...   
8   [-6.837752206181041, -6.269327159266599, -5.49...   
9   [-6.208, -6.128666666666667, -5.96266666666666...   
10  [-9.185952845112642, -6.041481126812438, -4.0,...   

                                 Test Predictions Std  
0   [0.06926147847108237, 0.26246904579397046, 0.0...  
1   [0.07920315170515813, 0.09407708752125336, 0.1...  
2   [0.14560117, 0.26127824, 0.19980119, 0.2718335...  
3   [0.2050707195091489, 0.2624690457939755, 0.100...  
4   [0.04986056077368814, 0.1532158502313333, 0.11...  
5   [0.3349141307000285, 0.17081896150472703, 0.09...  
6   [0.13251245336140263, 0.12105412756167108, 0.2...  
7   [0.06556461654402354, 0.030512062354142125, 0....  
8   [0.1492203173084247, 0.08490918876107027, 0.03...  
9   [0.02712931993250136, 0.17422335600538097, 0.3...  
10  [0.3362949295138244, 0.15586396523051813, 0.0,...

In [25]:
aac_comp.to_csv('results/Monomeric/AAC_comp_results_RRCK.csv')
prediction_df.to_csv('results/Monomeric/AAC_comp_prediction_data_RRCK.csv')

In [27]:
#Constant column removal
df_mc_train = pd.read_csv('features/Monomeric/Train_aac_RRCK.csv')
df_mc_train, const_col = remove_constant_columns(df_mc_train)
X_train = df_mc_train.drop(['ID','SMILES','Permeability'], axis=1)
y_train = df_mc_train['Permeability']
print(X_train.shape)
print(y_train.shape)
df_mc_test = pd.read_csv('features/Monomeric/Test_aac_RRCK.csv')
X_test = df_mc_test.drop(['ID','SMILES','Permeability'], axis=1)
X_test = X_test.drop(const_col, axis=1)
y_test = df_mc_test['Permeability']
print(X_test.shape)
print(y_test.shape)
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    xgb.XGBRegressor(random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    SVR(),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3), 
    MLPRegressor(random_state=101)
]
aac_comp,prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
aac_comp

(140, 16)
(140,)
(36, 16)
(36,)
0.19096279552974194
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000027 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 60
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 8
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] 

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-1.6096281368154113


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
ExtraTreesRegressor                      0.4810                0.5304   
LGBMRegressor                            0.3765                0.4863   
XGBRegressor                             0.4549                0.5236   
DecisionTreeRegressor                    0.4491                0.5184   
RandomForestRegressor                    0.4242                0.5101   
GradientBoostingRegressor                0.3912                0.4926   
AdaBoostRegressor                        0.3623                0.4713   
SVR                                      0.4195                0.4883   
LinearRegression                         0.3749                0.4868   
KNeighborsRegressor                      0.4905                0.5352   
MLPRegressor                             0.9828                0.7701   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
ExtraTreesRegressor                       0.6935              -0.0729   
LGBMRegressor                             0.6136               0.1602   
XGBRegressor                              0.6745              -0.0147   
DecisionTreeRegressor                     0.6702              -0.0019   
RandomForestRegressor                     0.6513               0.0538   
GradientBoostingRegressor                 0.6255               0.1272   
AdaBoostRegressor                         0.6019               0.1918   
SVR                                       0.6477               0.0643   
LinearRegression                          0.6123               0.1636   
KNeighborsRegressor                       0.7003              -0.0941   
MLPRegressor                              0.9914              -1.1923   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
ExtraTreesRegressor                      0.2955                0.3176   
LGBMRegressor                            0.4093                0.4551   
XGBRegressor                             0.3557                0.3768   
DecisionTreeRegressor                    0.4225                0.4169   
RandomForestRegressor                    0.3544                0.3981   
GradientBoostingRegressor                0.4244                0.4490   
AdaBoostRegressor                        0.4391                0.4548   
SVR                                      0.3794                0.4044   
LinearRegression                         0.4238                0.4152   
KNeighborsRegressor                      0.2822                0.3368   
MLPRegressor                             0.2178                0.2006   

                          Test MSE Test MAE Test RMSE  Test R2  \
ExtraTreesRegressor         0.5848   0.5387    0.7647   0.1910   
LGBMRegressor               0.6052   0.5535    0.7779   0.1628   
XGBRegressor                0.6560   0.5399    0.8099   0.0924   
DecisionTreeRegressor       0.6917   0.5335    0.8317   0.0431   
RandomForestRegressor       0.6701   0.5408    0.8186   0.0729   
GradientBoostingRegressor   0.6773   0.5445    0.8230   0.0631   
AdaBoostRegressor           0.7030   0.5829    0.8385   0.0274   
SVR                         0.7192   0.6009    0.8481   0.0050   
LinearRegression            0.7820   0.6568    0.8843  -0.0819   
KNeighborsRegressor         0.6850   0.6446    0.8277   0.0523   
MLPRegressor                1.8863   1.0048    1.3734  -1.6096   

                          Test Pearson Correlation Test Spearman Correlation  
ExtraTreesRegressor                         0.5256                    0.5834  
LGBMRegressor                               0.5577                    0.6153  
XGBRegressor                                0.4372                    0.5480  
DecisionTreeRegressor                       0.4087                    0.4853  
RandomForestRegressor                       0.4393                    0.5497  
GradientBoostingRegressor                   0.4279                    0.5395  
AdaBoostRegressor                           0.403

In [29]:
aac_comp.to_csv('results/Monomeric/AAC_comp_const_rem_results_RRCK.csv')
prediction_df.to_csv('results/Monomeric/AAC_comp_const_rem_prediction_data_RRCK.csv')

In [30]:
#LVR column removal
df_mc_train = pd.read_csv('features/Monomeric/Train_aac_RRCK.csv')
X_train = df_mc_train.drop(['ID','SMILES','Permeability'], axis=1)
X_train, const_col = remove_low_variance_columns(X_train)

y_train = df_mc_train['Permeability']
print(X_train.shape)
print(y_train.shape)
df_mc_test = pd.read_csv('features/Monomeric/Test_aac_RRCK.csv')
X_test = df_mc_test.drop(['ID','SMILES','Permeability'], axis=1)
X_test = X_test.drop(const_col, axis=1)
y_test = df_mc_test['Permeability']
print(X_test.shape)
print(y_test.shape)
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models_mc = [
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    xgb.XGBRegressor(random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    SVR(),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3), 
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models_mc, X_train,y_train, X_test,  y_test)
result_df

(140, 7)
(140,)
(36, 7)
(36,)
0.19341181408286545
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000029 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 53
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 7
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-1.5192921849176995


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
ExtraTreesRegressor                      0.4342                0.5154   
LGBMRegressor                            0.3755                0.4834   
XGBRegressor                             0.4443                0.5228   
DecisionTreeRegressor                    0.4377                0.5130   
RandomForestRegressor                    0.4094                0.5041   
GradientBoostingRegressor                0.3956                0.4992   
AdaBoostRegressor                        0.4106                0.5017   
SVR                                      0.4235                0.5085   
LinearRegression                         0.4344                0.5305   
KNeighborsRegressor                      0.4834                0.5414   
MLPRegressor                             1.2460                0.8858   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
ExtraTreesRegressor                       0.6589               0.0315   
LGBMRegressor                             0.6128               0.1624   
XGBRegressor                              0.6666               0.0089   
DecisionTreeRegressor                     0.6616               0.0237   
RandomForestRegressor                     0.6398               0.0868   
GradientBoostingRegressor                 0.6289               0.1176   
AdaBoostRegressor                         0.6408               0.0841   
SVR                                       0.6508               0.0553   
LinearRegression                          0.6591               0.0310   
KNeighborsRegressor                       0.6953              -0.0784   
MLPRegressor                              1.1162              -1.7794   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
ExtraTreesRegressor                      0.3809                0.4126   
LGBMRegressor                            0.4112                0.4516   
XGBRegressor                             0.4004                0.4212   
DecisionTreeRegressor                    0.4266                0.4402   
RandomForestRegressor                    0.4018                0.4282   
GradientBoostingRegressor                0.4222                0.4487   
AdaBoostRegressor                        0.3258                0.3495   
SVR                                      0.3764                0.4069   
LinearRegression                         0.2643                0.3265   
KNeighborsRegressor                      0.3158                0.3341   
MLPRegressor                             0.1125                0.0885   

                          Test MSE Test MAE Test RMSE  Test R2  \
ExtraTreesRegressor         0.5830   0.5592    0.7636   0.1934   
LGBMRegressor               0.6874   0.5899    0.8291   0.0490   
XGBRegressor                0.7775   0.5957    0.8818  -0.0756   
DecisionTreeRegressor       0.7876   0.5880    0.8875  -0.0896   
RandomForestRegressor       0.7603   0.5917    0.8720  -0.0518   
GradientBoostingRegressor   0.6485   0.5418    0.8053   0.1028   
AdaBoostRegressor           0.7166   0.5889    0.8465   0.0086   
SVR                         0.6692   0.5688    0.8180   0.0743   
LinearRegression            0.7726   0.6356    0.8790  -0.0689   
KNeighborsRegressor         0.7266   0.6260    0.8524  -0.0052   
MLPRegressor                1.8210   1.0065    1.3495  -1.5193   

                          Test Pearson Correlation Test Spearman Correlation  
ExtraTreesRegressor                         0.4995                    0.5794  
LGBMRegressor                               0.4336                    0.5221  
XGBRegressor                                0.2940                    0.4028  
DecisionTreeRegressor                       0.3010                    0.4203  
RandomForestRegressor                       0.3017                    0.4071  
GradientBoostingRegressor                   0.4452                    0.5529  
AdaBoostRegressor                           0.385

In [31]:
prediction_df

Model  \
0         ExtraTreesRegressor   
1               LGBMRegressor   
2                XGBRegressor   
3       DecisionTreeRegressor   
4       RandomForestRegressor   
5   GradientBoostingRegressor   
6           AdaBoostRegressor   
7                         SVR   
8            LinearRegression   
9         KNeighborsRegressor   
10               MLPRegressor   

                                         Y Train pred  \
0   [-6.276100000000003, -6.003100000000007, -5.07...   
1   [-5.912808776851838, -5.819948965340556, -5.41...   
2   [-6.1519527, -6.2191067, -5.080466, -5.226611,...   
3   [-6.365, -6.1, -5.08, -5.08, -5.91, -5.1, -5.4...   
4   [-6.245216666666667, -6.0409750000000075, -5.1...   
5   [-6.114012045283443, -6.0864352769053784, -5.1...   
6   [-5.753684210526315, -5.909761904761905, -5.65...   
7   [-5.98992319355122, -5.972260664912005, -5.237...   
8   [-5.418149858689573, -5.780950585809417, -5.62...   
9   [-6.06, -5.986666666666667, -5.153333333333333...   
10  [-4.802155674319045, -4.535248551903006, -5.07...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-6.08725, -6.365000000000006, -5.78661000000...   
1   [[-5.932633015093644, -5.912808776851838, -5.6...   
2   [[-6.167827, -6.3648834, -5.0976486, -6.462305...   
3   [[-6.13, -6.365, -5.08, -6.46, -5.08, -5.08, -...   
4   [[-6.084025000000001, -6.254675000000001, -5.3...   
5   [[-6.218462398795427, -6.2856600369179745, -5....   
6   [[-5.753684210526315, -5.753684210526315, -5.5...   
7   [[-5.8386451282676015, -5.853732722497016, -5....   
8   [[-5.4693359419534895, -5.4151910063339415, -5...   
9   [[-6.2, -6.0, -5.830000000000001, -5.02, -5.43...   
10  [[-4.0, -4.0, -4.0, -5.634800366789274, -5.286...   

                                Test Predictions Mean  \
0   [-6.069866666666668, -6.365, -5.80375719047619...   
1   [-6.024578784682684, -6.015399774427789, -5.57...   
2   [-6.1173487, -6.365303, -5.2530785, -6.6677756...   
3   [-6.042, -6.365, -5.039199999999999, -6.664, -...   
4   [-6.069848, -6.2641546666666645, -5.3402180569...   
5   [-6.132020966277804, -6.299439858826505, -5.51...   
6   [-5.956928508771929, -5.956928508771929, -5.51...   
7   [-5.843828489280463, -5.930674086585016, -5.79...   
8   [-5.620607010366598, -5.5102855818128615, -5.5...   
9   [-6.1033333333333335, -6.010666666666667, -5.7...   
10  [-4.125058764511256, -4.069522788295544, -4.0,...   

                                 Test Predictions Std  
0   [0.07233250613966397, 0.26246904579397046, 0.1...  
1   [0.08396016951161674, 0.09366470507500912, 0.1...  
2   [0.19119553, 0.26052287, 0.18235432, 0.4141614...  
3   [0.11070682002478427, 0.2624690457939755, 0.12...  
4   [0.07842518330938791, 0.17241789042065808, 0.0...  
5   [0.1203833140283602, 0.2038776572883081, 0.154...  
6   [0.12501810005612615, 0.12501810005612615, 0.1...  
7   [0.09752068189665018, 0.06456168805123304, 0.1...  
8   [0.12774697616740696, 0.08106265305873837, 0.0...  
9   [0.16206994374857597, 0.07883597599517059, 0.2...  
10  [0.16001384772775587, 0.09203704377099094, 0.0...

In [32]:
result_df.to_csv('results/Monomeric/AAC_comp_LVR_results_RRCK.csv')
prediction_df.to_csv('results/Monomeric/AAC_comp_LVR_prediction_data_RRCK.csv')

In [33]:
#Atomic models
df_train = pd.read_csv('features/Atomic/Train_all_atomic_desc_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Atomic/Test_all_atomic_desc_RRCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models_degree = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models_degree, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 23)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 23)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000137 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 146
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 9
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positiv

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-1.63363847375732


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.3421                0.4637   
DecisionTreeRegressor                    0.3953                0.4518   
RandomForestRegressor                    0.2706                0.4007   
GradientBoostingRegressor                0.2490                0.3752   
AdaBoostRegressor                        0.3068                0.4388   
XGBRegressor                             0.2726                0.4097   
ExtraTreesRegressor                      0.2224                0.3723   
LinearRegression                         0.5002                0.5224   
KNeighborsRegressor                      0.3111                0.4221   
SVR                                      0.2766                0.4138   
MLPRegressor                             0.8453                0.6689   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.5849               0.2368   
DecisionTreeRegressor                     0.6287               0.1183   
RandomForestRegressor                     0.5202               0.3964   
GradientBoostingRegressor                 0.4990               0.4446   
AdaBoostRegressor                         0.5539               0.3157   
XGBRegressor                              0.5221               0.3920   
ExtraTreesRegressor                       0.4716               0.5039   
LinearRegression                          0.7073              -0.1159   
KNeighborsRegressor                       0.5578               0.3060   
SVR                                       0.5260               0.3829   
MLPRegressor                              0.9194              -0.8857   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.4873                0.4858   
DecisionTreeRegressor                    0.5309                0.5840   
RandomForestRegressor                    0.6348                0.6594   
GradientBoostingRegressor                0.6705                0.6890   
AdaBoostRegressor                        0.5716                0.6341   
XGBRegressor                             0.6403                0.6462   
ExtraTreesRegressor                      0.7155                0.7322   
LinearRegression                         0.3531                0.4631   
KNeighborsRegressor                      0.5945                0.6121   
SVR                                      0.6245                0.6147   
MLPRegressor                             0.3281                0.3692   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.6364   0.5452    0.7978   0.1196   
DecisionTreeRegressor       0.3749   0.4312    0.6123   0.4813   
RandomForestRegressor       0.4167   0.4521    0.6455   0.4235   
GradientBoostingRegressor   0.3446   0.4103    0.5871   0.5232   
AdaBoostRegressor           0.4961   0.5137    0.7043   0.3137   
XGBRegressor                0.3790   0.4327    0.6156   0.4757   
ExtraTreesRegressor         0.3485   0.4001    0.5904   0.5178   
LinearRegression            0.6137   0.5955    0.7834   0.1509   
KNeighborsRegressor         0.4769   0.4890    0.6905   0.3403   
SVR                         0.5527   0.5113    0.7434   0.2354   
MLPRegressor                1.9037   1.0357    1.3797  -1.6336   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.5592                    0.6038  
DecisionTreeRegressor                       0.7249                    0.7750  
RandomForestRegressor                       0.7715                    0.8072  
GradientBoostingRegressor                   0.7969                    0.8081  
AdaBoostRegressor                           0.7565                    0.8094  
XGBRegressor                                0.7633                    0.7975  
ExtraTreesRegressor                         0.772

In [34]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.873665300227856, -5.8226616351027, -5.4099...   
1   [-6.13, -6.46, -5.08, -5.4, -5.32, -5.875, -5....   
2   [-5.995999999999998, -5.903415833333335, -5.12...   
3   [-6.011366667190261, -5.865643415478956, -5.17...   
4   [-6.083333333333333, -5.983939393939394, -5.34...   
5   [-6.1204615, -5.8016634, -5.0802007, -5.398436...   
6   [-6.097599999999996, -5.575700000000005, -5.07...   
7   [-6.014487641445765, -6.094860496431176, -6.00...   
8   [-5.983333333333333, -5.733333333333333, -5.15...   
9   [-6.081208009466288, -5.724475285630279, -5.32...   
10  [-6.822685586259915, -5.622715384787336, -4.19...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-6.04930585615838, -6.04930585615838, -5.438...   
1   [[-6.13, -5.95, -7.48, -6.46, -7.48, -5.08, -6...   
2   [[-6.103549999999998, -6.028899999999998, -6.2...   
3   [[-6.367825002993948, -6.048392355985687, -6.2...   
4   [[-6.123488372093023, -6.169142857142859, -6.4...   
5   [[-5.8901014, -5.952164, -6.7859526, -6.084969...   
6   [[-6.332800000000001, -5.949999999999999, -6.2...   
7   [[-5.821904275478004, -5.857693271027201, -6.4...   
8   [[-5.983333333333333, -5.983333333333333, -6.3...   
9   [[-6.062151499957152, -5.987131520808791, -5.7...   
10  [[-7.535841266824845, -6.618485108620471, -4.7...   

                                Test Predictions Mean  \
0   [-6.046574217109014, -6.046574217109014, -5.61...   
1   [-6.516, -6.116, -6.5824, -6.412000000000001, ...   
2   [-6.2518025, -6.127687499999997, -6.2816994761...   
3   [-6.493006530515169, -6.130452323495689, -6.30...   
4   [-6.221943970714902, -6.250645238095238, -6.25...   
5   [-6.0394707, -6.102478, -6.426408, -5.978576, ...   
6   [-6.40366, -6.005179999999999, -6.259808000000...   
7   [-5.760712839409977, -5.875575458808629, -6.50...   
8   [-6.118666666666667, -6.118666666666667, -6.10...   
9   [-6.07304236689686, -6.00975872929179, -5.7032...   
10  [-7.629503636972923, -6.728744349286858, -4.66...   

                                 Test Predictions Std  
0   [0.03122094867372097, 0.03122094867372097, 0.2...  
1   [0.40410889621486923, 0.332, 0.899452633549983...  
2   [0.1068714380693, 0.13607799096473877, 0.21659...  
3   [0.1229687933832418, 0.19139470882583712, 0.19...  
4   [0.11786397921283219, 0.0939463174738281, 0.19...  
5   [0.140527, 0.30000702, 0.440582, 0.2741827, 0....  
6   [0.0769905864375617, 0.11035999999999965, 0.08...  
7   [0.07513734048391776, 0.05603689378979565, 0.0...  
8   [0.11400974617208051, 0.11400974617208051, 0.3...  
9   [0.015138000671056244, 0.012220125351811708, 0...  
10  [0.07531541465281748, 0.0903433227898384, 0.19...

In [35]:
result_df.to_csv('results/Atomic/Results_all_atomic_desc_RRCK.csv')
prediction_df.to_csv('results/Atomic/Prediction_data_all_atomic_desc_RRCK.csv')

In [7]:
#Atomic + monomeric_composition based features
df1 = pd.read_csv('features/Monomeric/Train_mon_comp_RRCK.csv')
df2 = pd.read_csv('features/Atomic/Train_all_atomic_desc_RRCK.csv')
df_train = pd.merge(df1, df2, on=['ID', 'SMILES', 'Permeability'], how='inner')
df_train

ID                                             SMILES  Permeability  \
0    2358  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](C(...         -6.13   
1    2359  C/C=C/C[C@@H](C)C(=O)[C@H]1C(=O)N[C@@H](C(C)C)...         -6.66   
2    2357  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...         -5.95   
3    2360  C/C=C/C[C@@H](C)[C@H]1OC(=O)[C@H](C(C)C)N(C)C(...         -6.78   
4    2353  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](C)...         -5.87   
..    ...                                                ...           ...   
135  2336  CC[C@@H]1NC(=O)[C@@H](CC)NC(=O)[C@H](CC(C)C)NC...         -5.39   
136  2306  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...         -4.75   
137  2334  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...         -5.58   
138  2305  CCC[C@@H]1C(=O)N(C)[C@@H](C)C(=O)N[C@@H](CC(C)...         -4.85   
139  2304  CC[C@@H]1C(=O)N(C)[C@@H](C)C(=O)N[C@@H](CC(C)C...         -5.51   

            A        dA       meA  Me_dA  Ala(tBu)  Ala(indol-2-yl)  \
0    0.090909  0.090909  0.000000    0.0       0.0              0.0   
1    0.090909  0.090909  0.000000    0.0       0.0              0.0   
2    0.090909  0.090909  0.000000    0.0       0.0              0.0   
3    0.090909  0.090909  0.000000    0.0       0.0              0.0   
4    0.181818  0.090909  0.000000    0.0       0.0              0.0   
..        ...       ...       ...    ...       ...              ...   
135  0.000000  0.000000  0.000000    0.0       0.0              0.0   
136  0.000000  0.000000  0.333333    0.0       0.0              0.0   
137  0.166667  0.166667  0.000000    0.0       0.0              0.0   
138  0.000000  0.000000  0.333333    0.0       0.0              0.0   
139  0.000000  0.000000  0.333333    0.0       0.0              0.0   

     dAla(indol-2-yl)  ...  Degree_O  Single  Double  Triple  Aromatic  \
0                 0.0  ...         1      74      12       0         0   
1                 0.0  ...         1      73      13       0         0   
2                 0.0  ...         1      73      12       0         0   
3                 0.0  ...         2      73      12       0         0   
4                 0.0  ...         1      72      12       0         0   
..                ...  ...       ...     ...     ...     ...       ...   
135               0.0  ...         1      36       6       0         6   
136               0.0  ...         1      39       6       0         0   
137               0.0  ...         1      34       6       0         6   
138               0.0  ...         1      38       6       0         0   
139               0.0  ...         1      37       6       0         0   

     Conjugated  No-bond  Overall_Formal_Charge  Is_Aromatic  Is_In_Ring  
0             0        0                    106            0           1  
1             0        0                    107            0           1  
2             0        0                    106            0           1  
3             0        0                    106            0           1  
4             0        0                    106            0           1  
..          ...      ...                    ...          ...         ...  
135           0        0                     60            1           1  
136           0        0                     54            0           1  
137           0        0                     60            1           1  
138           0        0                     54            0           1  
139           0        0                     54            0           1  

[140 rows x 411 columns]

In [8]:
df1 = pd.read_csv('features/Monomeric/Test_mon_comp_RRCK.csv')
df2 = pd.read_csv('features/Atomic/Test_all_atomic_desc_RRCK.csv')
df_test = pd.merge(df1, df2, on=['ID', 'SMILES', 'Permeability'], how='inner')
df_test

ID                                             SMILES  Permeability  \
0   2352  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H]([C...        -6.340   
1   5669  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...        -5.760   
2   1881  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
3   5666  CCCC[C@@H]1NC(=O)[C@H](CCCC)NC(=O)[C@H](CCCC)N...        -6.460   
4   1877  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
5   1873  CC(C)C[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N2CCC[C...        -4.620   
6   1878  CCC[C@H]1C(=O)N(C)[C@H](CC)C(=O)N(C)[C@@H](C)C...        -7.300   
7   1849  O=C1CN(CCCc2ccccc2)C(=O)[C@H]2CCCN2C(=O)[C@H](...        -5.920   
8   1856  CC(C)(C)C[C@@H]1NC(=O)[C@@H](Cc2ccccc2)NC(=O)[...        -5.120   
9   2367  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.930   
10  2369  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)NC(=O)[C@H](Cc2...        -6.660   
11  2370  CC(C)C[C@@H]1NC(=O)[C@H](C)NC(=O)[C@H](Cc2ccc(...        -6.230   
12    45  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.840   
13    44  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.150   
14  2373  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.340   
15   970  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)N(C)C(=O)[C@H...        -5.700   
16   966  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...        -6.000   
17   979  C/C1=C\[C@@H](CC(C)C)NC(=O)[C@@H]2CCCN2C(=O)[C...        -5.000   
18  1867  C[C@H]1C(=O)N(C)[C@H](C)C(=O)N(C)[C@H](C)C(=O)...        -7.640   
19  2350  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.860   
20  5642  CCCC[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)CSC[C@@...        -5.900   
21  2342  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.460   
22    35  CC[C@H](C)[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC...        -5.490   
23    34  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.330   
24  2340  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...        -5.020   
25    31  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.120   
26  1037  CC(C)C[C@@H]1NC(=O)CN(Cc2ccc(O)cc2)C(=O)[C@H]2...        -5.140   
27  5674  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...        -5.805   
28  2295  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@@H](...        -6.440   
29  2300  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...        -5.550   
30   928  CC[C@H](C)[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@H](...        -6.220   
31  2312  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...        -4.640   
32  2323  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -5.350   
33  2308  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -4.620   
34  2335  CC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2cccc...        -5.530   
35  2303  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...        -5.310   

           A        dA       meA     Me_dA  Ala(tBu)  Ala(indol-2-yl)  \
0   0.090909  0.090909  0.000000  0.000000  0.000000              0.0   
1   0.090909  0.090909  0.000000  0.000000  0.000000              0.0   
2   0.000000  0.000000  0.000000  0.000000  0.000000              0.0   
3   0.000000  0.000000  0.000000  0.000000  0.000000              0.0   
4   0.000000  0.000000  0.000000  0.000000  0.000000              0.0   
5   0.000000  0.000000  0.125000  0.125000  0.000000              0.0   
6   0.000000  0.000000  0.222222  0.111111  0.000000              0.0   
7   0.000000  0.000000  0.000000  0.000000  0.000000              0.0   
8   0.000000  0.000000  0.000000  0.000000  0.166667              0.0   
9   0.000000  0.000000  0.000000  0.000000  0.000000              0.0   
10  0.000000  0.000000  0.000000  0.000000  0.000000              0.0   
11  0.142857  0.000000  0.000000  0.000000  0.000000              0.0   
12  0.000000  0.000000  0.000000  0.000000  0.000000              0.0   
13  0.000000  0.000000  0.000000  0.000000  0.000000              0.0   
14  0.000000  0.000000  0.000000  0.142857  0.000000         

In [9]:
import re
def clean_feature_names(df):
    def clean_name(name):
        return re.sub(r'[^a-zA-Z0-9_]', '_', name)

    df.columns = [clean_name(col) for col in df.columns]
    return df

In [10]:
#Removal of constant columns
def remove_constant_columns(df):
    constant_columns = [col for col in df.columns if df[col].nunique() <= 1]
    
    df_cleaned = df.drop(columns=constant_columns)
    
    return df_cleaned, constant_columns

In [11]:
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = clean_feature_names(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = clean_feature_names(X_test)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 408)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 408)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000075 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 183
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 15
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with posi

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


0.07846311307106169


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.3369                0.4381   
DecisionTreeRegressor                    0.4584                0.5053   
RandomForestRegressor                    0.2518                0.3760   
GradientBoostingRegressor                0.2397                0.3567   
AdaBoostRegressor                        0.2947                0.4309   
XGBRegressor                             0.2584                0.3730   
ExtraTreesRegressor                      0.2470                0.3578   
LinearRegression                         2.5403                0.9458   
KNeighborsRegressor                      0.3327                0.4041   
SVR                                      0.2694                0.3887   
MLPRegressor                             1.0720                0.7557   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.5804               0.2485   
DecisionTreeRegressor                     0.6770              -0.0225   
RandomForestRegressor                     0.5018               0.4382   
GradientBoostingRegressor                 0.4896               0.4652   
AdaBoostRegressor                         0.5429               0.3425   
XGBRegressor                              0.5083               0.4236   
ExtraTreesRegressor                       0.4970               0.4490   
LinearRegression                          1.5938              -4.6667   
KNeighborsRegressor                       0.5768               0.2578   
SVR                                       0.5191               0.3990   
MLPRegressor                              1.0354              -1.3913   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.5032                0.5278   
DecisionTreeRegressor                    0.4617                0.4618   
RandomForestRegressor                    0.6650                0.6791   
GradientBoostingRegressor                0.6841                0.7000   
AdaBoostRegressor                        0.5868                0.6317   
XGBRegressor                             0.6699                0.6864   
ExtraTreesRegressor                      0.6805                0.6891   
LinearRegression                         0.2910                0.4448   
KNeighborsRegressor                      0.5579                0.5941   
SVR                                      0.6349                0.6323   
MLPRegressor                             0.2482                0.2416   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.6234   0.5624    0.7896   0.1375   
DecisionTreeRegressor       0.3415   0.4140    0.5844   0.5276   
RandomForestRegressor       0.4662   0.4635    0.6828   0.3551   
GradientBoostingRegressor   0.3667   0.4283    0.6055   0.4927   
AdaBoostRegressor           0.5245   0.5160    0.7243   0.2743   
XGBRegressor                0.3824   0.4158    0.6184   0.4710   
ExtraTreesRegressor         0.4328   0.4268    0.6579   0.4013   
LinearRegression            1.0111   0.7189    1.0055  -0.3988   
KNeighborsRegressor         0.5363   0.4968    0.7323   0.2581   
SVR                         0.5337   0.4884    0.7306   0.2616   
MLPRegressor                0.6661   0.6206    0.8162   0.0785   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.5258                    0.5740  
DecisionTreeRegressor                       0.7621                    0.7666  
RandomForestRegressor                       0.6854                    0.7495  
GradientBoostingRegressor                   0.7620                    0.7971  
AdaBoostRegressor                           0.6592                    0.7512  
XGBRegressor                                0.7097                    0.7729  
ExtraTreesRegressor                         0.685

In [12]:
result_df.to_csv('results/Atomic/Results_all_atomic_desc_and_mono_comp_RRCK.csv')
prediction_df.to_csv('results/Atomic/Prediction_data_all_atomic_desc_and_mono_comp_RRCK.csv')

In [13]:
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = clean_feature_names(X_train)
X_train, const_col = remove_constant_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = clean_feature_names(X_test)
X_test = X_test.drop(const_col,axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 82)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 82)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000049 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 183
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 15
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits 

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-0.1437962607050336


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.3369                0.4381   
DecisionTreeRegressor                    0.4836                0.5128   
RandomForestRegressor                    0.2497                0.3751   
GradientBoostingRegressor                0.2363                0.3523   
AdaBoostRegressor                        0.2998                0.4363   
XGBRegressor                             0.2584                0.3730   
ExtraTreesRegressor                      0.2564                0.3601   
LinearRegression                         2.5403                0.9458   
KNeighborsRegressor                      0.3289                0.4048   
SVR                                      0.2694                0.3887   
MLPRegressor                             1.1116                0.7712   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.5804               0.2485   
DecisionTreeRegressor                     0.6954              -0.0788   
RandomForestRegressor                     0.4997               0.4429   
GradientBoostingRegressor                 0.4861               0.4728   
AdaBoostRegressor                         0.5476               0.3311   
XGBRegressor                              0.5083               0.4236   
ExtraTreesRegressor                       0.5063               0.4281   
LinearRegression                          1.5938              -4.6667   
KNeighborsRegressor                       0.5735               0.2663   
SVR                                       0.5191               0.3990   
MLPRegressor                              1.0543              -1.4798   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.5032                0.5278   
DecisionTreeRegressor                    0.4544                0.4538   
RandomForestRegressor                    0.6692                0.6837   
GradientBoostingRegressor                0.6896                0.7067   
AdaBoostRegressor                        0.5788                0.6115   
XGBRegressor                             0.6699                0.6864   
ExtraTreesRegressor                      0.6669                0.6782   
LinearRegression                         0.2910                0.4448   
KNeighborsRegressor                      0.5673                0.6015   
SVR                                      0.6349                0.6323   
MLPRegressor                             0.2159                0.2160   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.6234   0.5624    0.7896   0.1375   
DecisionTreeRegressor       0.3403   0.4065    0.5834   0.5292   
RandomForestRegressor       0.4709   0.4614    0.6862   0.3486   
GradientBoostingRegressor   0.3679   0.4271    0.6066   0.4910   
AdaBoostRegressor           0.5302   0.5282    0.7281   0.2665   
XGBRegressor                0.3824   0.4158    0.6184   0.4710   
ExtraTreesRegressor         0.4348   0.4297    0.6594   0.3984   
LinearRegression            1.0111   0.7189    1.0055  -0.3988   
KNeighborsRegressor         0.5364   0.4958    0.7324   0.2579   
SVR                         0.5337   0.4884    0.7306   0.2616   
MLPRegressor                0.8268   0.7186    0.9093  -0.1438   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.5258                    0.5740  
DecisionTreeRegressor                       0.7672                    0.7889  
RandomForestRegressor                       0.6781                    0.7564  
GradientBoostingRegressor                   0.7626                    0.7996  
AdaBoostRegressor                           0.6750                    0.7223  
XGBRegressor                                0.7097                    0.7729  
ExtraTreesRegressor                         0.684

In [14]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.802444784213362, -5.7683475554749535, -5.4...   
1   [-6.13, -6.92, -5.16, -4.3, -6.96, -4.5, -5.57...   
2   [-6.074499999999998, -5.880700000000003, -5.19...   
3   [-6.034910547722071, -5.763580225049631, -5.25...   
4   [-6.205625, -6.008809523809527, -5.34617647058...   
5   [-6.1313257, -6.2896805, -5.159187, -5.0093913...   
6   [-6.045199999999999, -6.011050000000004, -5.16...   
7   [-6.3037585200177535, -5.9892467985225935, -5....   
8   [-5.716666666666666, -6.19, -5.013333333333333...   
9   [-5.771455216772495, -6.1926462687907, -5.3200...   
10  [-4.0, -5.675474059634367, -5.285200619044078,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.9841070250323645, -5.9841070250323645, -5...   
1   [[-6.13, -5.95, -5.57, -6.46, -6.46, -5.16, -4...   
2   [[-6.0875999999999975, -6.085099999999999, -5....   
3   [[-6.674966222650195, -6.279071012109364, -5.9...   
4   [[-6.2250000000000005, -6.2250000000000005, -6...   
5   [[-6.5702524, -6.590028, -6.4245596, -6.563687...   
6   [[-6.015100000000001, -5.942, -6.0459000000000...   
7   [[-6.609107085206263, -5.874403506311881, -7.3...   
8   [[-6.260000000000001, -6.260000000000001, -6.1...   
9   [[-5.938547657012659, -6.103892850118804, -5.8...   
10  [[-5.059360279387699, -6.683941556852966, -7.5...   

                                Test Predictions Mean  \
0   [-5.988971339351776, -5.988971339351776, -5.68...   
1   [-6.101999999999999, -6.122, -6.618, -6.316, -...   
2   [-6.202589999999998, -6.1943699999999975, -6.0...   
3   [-6.647113969127818, -6.292290193009951, -6.22...   
4   [-6.246907009247069, -6.242938291810631, -6.10...   
5   [-6.389728, -6.504466, -6.257691, -6.4516745, ...   
6   [-6.079960000000001, -6.070179999999998, -6.09...   
7   [-6.6529199513564, -6.7422066280623785, -7.790...   
8   [-6.114000000000001, -6.114000000000001, -5.98...   
9   [-5.956685313804375, -6.050411220384989, -5.89...   
10  [-4.994831062031119, -6.289936895522514, -8.73...   

                                 Test Predictions Std  
0   [0.08530700411593888, 0.08530700411593888, 0.2...  
1   [0.3202124294901746, 0.2752017441805193, 0.758...  
2   [0.10220774138977937, 0.14463749721285765, 0.0...  
3   [0.21849797874464758, 0.20570930342056465, 0.2...  
4   [0.05323923436223835, 0.06633795634070008, 0.2...  
5   [0.21942674, 0.2808346, 0.18625596, 0.10250749...  
6   [0.06778328997621759, 0.15078072025295275, 0.0...  
7   [1.9500868929488304, 1.6326147310561523, 1.237...  
8   [0.2338698593472688, 0.2338698593472688, 0.121...  
9   [0.05116242492971367, 0.12161697184591885, 0.0...  
10  [0.5193478547277302, 0.45241578661302806, 0.79...

In [15]:
result_df.to_csv('results/Atomic/Results_all_atomic_desc_and_mono_comp_const_rem_RRCK.csv')
prediction_df.to_csv('results/Atomic/Prediction_data_all_atomic_desc_and_mono_comp_const_rem_RRCK.csv')

In [16]:
const_col

['Ala_indol_2_yl_',
 'dAla_indol_2_yl_',
 'Me_Ala_indol_2_yl_',
 'Ala_5_Tet_',
 '2Abz',
 'Aib',
 'Aoc_2_',
 '5_Ava',
 'Bal',
 'Me_Bal',
 'HOCOCH2_Bal',
 'Cys_EtO2H__NH2',
 'dCha',
 'D',
 'Asp_piperidide',
 'Asp_OMe_',
 'Asp_Ph_2_NH2__',
 'dAsp_pyrrol_1_yl_',
 'E',
 'Glu_NH2',
 'Glu_3R_Me_',
 'Glu_OMe_',
 'dGlu_OMe_',
 'Phe_4_F_',
 'dPhe_4_F_',
 'Phe_4_CF3_',
 'Phe_4_NO2_',
 'Phe_CHF2_',
 'dPhe_3_4_diF_',
 'Et_Phe',
 'H2NEt_Phe',
 'Me_Phe_3_Cl_',
 'Me_Phe_4_Cl_',
 'Me_Phe_a_b_dehydro_',
 'G',
 'Bn_Gly',
 'Bn_4_Cl__Gly',
 'Bu_Gly',
 'Et_Gly',
 'EtOEt_Gly',
 'HOCOCH2_Gly_ol',
 'MeOEt_Gly',
 'NH2Bu_Gly',
 'Pr_Gly',
 'PhEt_Gly',
 'cHexCH2_Gly',
 'isoamyl_Gly',
 'pentyl_Gly',
 '3_pyridylethyl_Gly',
 'd_N__O_Gly_allyl_',
 'GABA',
 'H',
 'Me_Hph',
 'bHph',
 'Hph_2_Cl_',
 'Hph_3_Cl_',
 'Hph_4_Cl_',
 'Hse_Et_',
 'dHyp',
 'Hyp_Et_',
 'dI',
 'meI',
 'Me_dI',
 '_N__O_xiIle',
 'd_N__O_aIle',
 'K',
 'dK',
 'Me_dK',
 'Lys_Ac_',
 'Lys_Cbz_',
 'Lys_iPr_',
 'Lys_Me_',
 'Lys_Me2_',
 'Lys_Tfa_',
 'aMeLeu',

In [4]:
#Fingerprints models
#All fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/All_fingerprints_train_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)

df_test = pd.read_csv('features/Fingerprints/Test/All_fingerprints_test_RRCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)

scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 20188)
y_train shape:  (140,)
X_test shape:  (36, 20188)
y_test shape:  (36,)
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.010346 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 4032
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 824
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with 

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.2378                0.3696   
DecisionTreeRegressor                    0.3471                0.4271   
RandomForestRegressor                    0.2225                0.3573   
GradientBoostingRegressor                0.2049                0.3387   
AdaBoostRegressor                        0.2491                0.3973   
XGBRegressor                             0.2266                0.3542   
ExtraTreesRegressor                      0.1939                0.3285   
LinearRegression                         2.6029                1.1140   
KNeighborsRegressor                      0.4021                0.4669   
SVR                                      0.3455                0.4431   
MLPRegressor                             1.1164                0.7667   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4876               0.4696   
DecisionTreeRegressor                     0.5892               0.2256   
RandomForestRegressor                     0.4717               0.5037   
GradientBoostingRegressor                 0.4526               0.5430   
AdaBoostRegressor                         0.4991               0.4444   
XGBRegressor                              0.4760               0.4946   
ExtraTreesRegressor                       0.4404               0.5674   
LinearRegression                          1.6134              -4.8064   
KNeighborsRegressor                       0.6341               0.1030   
SVR                                       0.5878               0.2293   
MLPRegressor                              1.0566              -1.4904   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.6896                0.7043   
DecisionTreeRegressor                    0.6154                0.6241   
RandomForestRegressor                    0.7221                0.7340   
GradientBoostingRegressor                0.7443                0.7558   
AdaBoostRegressor                        0.6799                0.6750   
XGBRegressor                             0.7095                0.7207   
ExtraTreesRegressor                      0.7617                0.7943   
LinearRegression                         0.2990                0.3468   
KNeighborsRegressor                      0.4714                0.5070   
SVR                                      0.4947                0.5148   
MLPRegressor                             0.1695                0.1996   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4385   0.4635    0.6622   0.3933   
DecisionTreeRegressor       0.3048   0.3630    0.5521   0.5784   
RandomForestRegressor       0.4320   0.4399    0.6573   0.4024   
GradientBoostingRegressor   0.2751   0.3673    0.5245   0.6194   
AdaBoostRegressor           0.4385   0.4606    0.6622   0.3933   
XGBRegressor                0.3413   0.3855    0.5842   0.5279   
ExtraTreesRegressor         0.3812   0.4033    0.6174   0.4727   
LinearRegression            0.4754   0.5480    0.6895   0.3423   
KNeighborsRegressor         0.6052   0.5553    0.7779   0.1628   
SVR                         0.6347   0.5449    0.7967   0.1219   
MLPRegressor                0.9751   0.7135    0.9875  -0.3489   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.7142                    0.7548  
DecisionTreeRegressor                       0.7988                    0.8241  
RandomForestRegressor                       0.7483                    0.8036  
GradientBoostingRegressor                   0.8462                    0.8590  
AdaBoostRegressor                           0.7537                    0.7739  
XGBRegressor                                0.7853                    0.8395  
ExtraTreesRegressor                         0.763

In [5]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-6.293540351996311, -6.02616124772942, -5.358...   
1   [-6.13, -6.1850000000000005, -5.22, -5.85, -6....   
2   [-6.051099999999998, -5.943700000000003, -5.21...   
3   [-6.033879653681506, -5.627194696786993, -5.26...   
4   [-6.122105263157894, -5.791491228070174, -5.20...   
5   [-6.271129, -5.956721, -5.3172274, -6.066091, ...   
6   [-6.077099999999997, -6.0423500000000026, -5.2...   
7   [-5.189094099708547, -4.0, -4.954305555556097,...   
8   [-5.983333333333333, -6.19, -5.193333333333333...   
9   [-5.8028702717892315, -5.821384462445965, -5.3...   
10  [-4.0, -5.492612668618326, -5.208583511162155,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-6.298499033891243, -6.298499033891243, -6.3...   
1   [[-6.13, -5.95, -7.48, -6.46, -6.5, -4.72, -6....   
2   [[-6.027599999999999, -5.9963, -6.265000000000...   
3   [[-6.028705198645376, -5.966278047052107, -6.5...   
4   [[-6.122105263157894, -6.122105263157894, -6.3...   
5   [[-6.009154, -5.951429, -6.4343777, -6.45095, ...   
6   [[-6.013999999999998, -5.949999999999999, -6.2...   
7   [[-9.535351970228447, -5.949999999999609, -9.2...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-5.996569010708649, -6.001608212426845, -5.8...   
10  [[-5.632289566394183, -5.950395394574309, -5.7...   

                                Test Predictions Mean  \
0   [-6.336842475995235, -6.333227415029346, -6.26...   
1   [-6.093999999999999, -5.986, -7.14600000000000...   
2   [-6.104279999999998, -6.06102, -6.397950000000...   
3   [-6.0757133635549145, -6.001621650240036, -6.7...   
4   [-6.181860306170832, -6.122222210932737, -6.33...   
5   [-6.038414, -5.9867706, -6.468236, -6.4193563,...   
6   [-6.011849999999999, -5.962259999999999, -6.40...   
7   [-7.035603984361797, -6.109271514281189, -8.18...   
8   [-5.924666666666667, -5.924666666666667, -5.76...   
9   [-5.983802784638731, -5.983097819346977, -5.83...   
10  [-5.568524769418204, -5.881890999332601, -5.97...   

                                 Test Predictions Std  
0   [0.09854845378412454, 0.09610374466706918, 0.1...  
1   [0.07199999999999988, 0.07199999999999988, 0.4...  
2   [0.0440218763798185, 0.053634369577725466, 0.2...  
3   [0.0739590727153139, 0.07138807121396391, 0.35...  
4   [0.09753793043681339, 0.10063872821770435, 0.1...  
5   [0.08069204, 0.07263097, 0.2196782, 0.12366667...  
6   [0.05485103463016728, 0.02452000000000041, 0.2...  
7   [2.2518727930742153, 0.3185430285623466, 1.090...  
8   [0.05153639490690065, 0.05153639490690065, 0.0...  
9   [0.020481459017287713, 0.030386017509208635, 0...  
10  [0.826138784866687, 0.1340061880833704, 0.4428...

In [6]:
result_df.to_csv('results/Fingerprints/Results_All_fingerprints_fp_RRCK.csv')
prediction_df.to_csv('results/Fingerprints/Prediction_data_All_fingerprints_fp_RRCK.csv')

In [7]:
#Removal of constant columns
def remove_constant_columns(df):
    constant_columns = [col for col in df.columns if df[col].nunique() <= 1]
    
    df_cleaned = df.drop(columns=constant_columns)
    
    return df_cleaned, constant_columns

In [8]:
#Low variance column removal
def remove_low_variance_columns(df, threshold=0.005):
    df = df.drop(['ID','SMILES','Permeability'],axis=1)
    variances = df.var()
    
    low_variance_columns = variances[variances < threshold].index.tolist()
    
    df_cleaned = df.drop(columns=low_variance_columns)
    
    return df_cleaned, low_variance_columns

In [9]:
#All fingerprints constant removal
df_train = pd.read_csv('features/Fingerprints/Train/All_fingerprints_train_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train, const_col = remove_constant_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/All_fingerprints_test_RRCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 3768)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 3768)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.012965 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 4032
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 824
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further s

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.2378                0.3696   
DecisionTreeRegressor                    0.3350                0.4341   
RandomForestRegressor                    0.2259                0.3575   
GradientBoostingRegressor                0.2095                0.3444   
AdaBoostRegressor                        0.2677                0.4084   
XGBRegressor                             0.2266                0.3542   
ExtraTreesRegressor                      0.1959                0.3301   
LinearRegression                         2.6029                1.1140   
KNeighborsRegressor                      0.4021                0.4669   
SVR                                      0.3455                0.4431   
MLPRegressor                             1.2394                0.8437   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4876               0.4696   
DecisionTreeRegressor                     0.5788               0.2527   
RandomForestRegressor                     0.4753               0.4960   
GradientBoostingRegressor                 0.4577               0.5327   
AdaBoostRegressor                         0.5174               0.4029   
XGBRegressor                              0.4760               0.4946   
ExtraTreesRegressor                       0.4426               0.5629   
LinearRegression                          1.6134              -4.8064   
KNeighborsRegressor                       0.6341               0.1030   
SVR                                       0.5878               0.2293   
MLPRegressor                              1.1133              -1.7647   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.6896                0.7043   
DecisionTreeRegressor                    0.6205                0.6232   
RandomForestRegressor                    0.7171                0.7365   
GradientBoostingRegressor                0.7363                0.7434   
AdaBoostRegressor                        0.6368                0.6353   
XGBRegressor                             0.7095                0.7207   
ExtraTreesRegressor                      0.7600                0.7815   
LinearRegression                         0.2990                0.3468   
KNeighborsRegressor                      0.4714                0.5070   
SVR                                      0.4947                0.5148   
MLPRegressor                             0.1657                0.1438   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4385   0.4635    0.6622   0.3933   
DecisionTreeRegressor       0.3102   0.3768    0.5569   0.5709   
RandomForestRegressor       0.4360   0.4409    0.6603   0.3968   
GradientBoostingRegressor   0.2797   0.3684    0.5288   0.6131   
AdaBoostRegressor           0.4436   0.4655    0.6660   0.3863   
XGBRegressor                0.3413   0.3855    0.5842   0.5279   
ExtraTreesRegressor         0.3728   0.4006    0.6106   0.4842   
LinearRegression            0.4754   0.5480    0.6895   0.3423   
KNeighborsRegressor         0.6052   0.5553    0.7779   0.1628   
SVR                         0.6347   0.5448    0.7967   0.1220   
MLPRegressor                1.2816   0.7960    1.1321  -0.7729   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.7142                    0.7548  
DecisionTreeRegressor                       0.7907                    0.8245  
RandomForestRegressor                       0.7460                    0.8010  
GradientBoostingRegressor                   0.8451                    0.8554  
AdaBoostRegressor                           0.7417                    0.7634  
XGBRegressor                                0.7853                    0.8395  
ExtraTreesRegressor                         0.776

In [10]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-6.293540351996311, -6.02616124772942, -5.358...   
1   [-6.13, -5.87, -5.22, -5.85, -5.32, -5.91, -5....   
2   [-6.059549999999998, -5.949200000000002, -5.22...   
3   [-6.031506441714104, -5.649558793170612, -5.26...   
4   [-6.259500000000001, -5.791969696969696, -5.30...   
5   [-6.271129, -5.956721, -5.3172274, -6.066091, ...   
6   [-6.022699999999999, -6.076800000000003, -5.24...   
7   [-5.189094098659434, -4.0, -4.954305555555499,...   
8   [-5.983333333333333, -6.19, -5.193333333333333...   
9   [-5.802867837565931, -5.821387820331051, -5.38...   
10  [-4.0, -5.214257340104577, -5.186363649275076,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-6.298499033891243, -6.298499033891243, -6.3...   
1   [[-6.13, -5.95, -7.48, -6.22, -6.5, -4.72, -6....   
2   [[-6.029399999999999, -6.007399999999999, -6.3...   
3   [[-6.028705198645376, -5.966278047052107, -6.4...   
4   [[-6.238431372549019, -6.238431372549019, -6.3...   
5   [[-6.009154, -5.951429, -6.4343777, -6.45095, ...   
6   [[-6.0074000000000005, -5.949999999999999, -6....   
7   [[-9.535351970627698, -5.950000000000425, -9.2...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-5.996622928130576, -6.001608612480334, -5.8...   
10  [[-4.0, -5.930989961429773, -5.420543878733034...   

                                Test Predictions Mean  \
0   [-6.336842475995235, -6.333227415029346, -6.26...   
1   [-6.042, -6.0920000000000005, -7.1400000000000...   
2   [-6.084559999999999, -6.05533, -6.383720000000...   
3   [-6.065491109125154, -6.0030269327417, -6.7764...   
4   [-6.2750434173669465, -6.251186274509804, -6.3...   
5   [-6.038414, -5.9867706, -6.468236, -6.4193563,...   
6   [-6.0187, -5.9681299999999995, -6.456980000000...   
7   [-7.035603984438912, -6.109271514281525, -8.18...   
8   [-5.924666666666667, -5.924666666666667, -5.76...   
9   [-5.983824683357165, -5.9830867951849775, -5.8...   
10  [-4.294846391674378, -5.858017670454004, -5.80...   

                                 Test Predictions Std  
0   [0.09854845378412454, 0.09610374466706918, 0.1...  
1   [0.11070682002478427, 0.284, 0.416413256273140...  
2   [0.03385596550092762, 0.05501010452635092, 0.2...  
3   [0.06744669391979767, 0.07405954786421517, 0.3...  
4   [0.10269191036933618, 0.0889753301820639, 0.15...  
5   [0.08069204, 0.07263097, 0.2196782, 0.12366667...  
6   [0.04046489836883238, 0.03626000000000005, 0.2...  
7   [2.251872793164774, 0.3185430285627709, 1.0907...  
8   [0.05153639490690065, 0.05153639490690065, 0.0...  
9   [0.020486912547836578, 0.0303808745722354, 0.0...  
10  [0.5311858693494677, 0.15741332927219043, 0.42...

In [11]:
result_df.to_csv('results/Fingerprints/Results_All_const_rem_fingerprints_RRCK.csv')
prediction_df.to_csv('results/Fingerprints/Prediction_data_All_const_rem_fingerprints_RRCK.csv')

In [12]:
#Morgan fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/morgan_fp_train_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/morgan_fp_test_RRCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_morgan_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_morgan_fp

X_train shape:  (140, 2048)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 2048)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000622 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 159
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 53
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with po

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.3783                0.4862   
DecisionTreeRegressor                    0.4295                0.4672   
RandomForestRegressor                    0.2902                0.3903   
GradientBoostingRegressor                0.2652                0.3582   
AdaBoostRegressor                        0.3376                0.4521   
XGBRegressor                             0.3295                0.4095   
ExtraTreesRegressor                      0.4113                0.4588   
LinearRegression                         0.6455                0.5796   
KNeighborsRegressor                      0.3553                0.4397   
SVR                                      0.2954                0.4006   
MLPRegressor                             1.2304                0.8398   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.6151               0.1561   
DecisionTreeRegressor                     0.6554               0.0419   
RandomForestRegressor                     0.5387               0.3526   
GradientBoostingRegressor                 0.5149               0.4085   
AdaBoostRegressor                         0.5810               0.2469   
XGBRegressor                              0.5740               0.2649   
ExtraTreesRegressor                       0.6414               0.0824   
LinearRegression                          0.8034              -0.4400   
KNeighborsRegressor                       0.5961               0.2074   
SVR                                       0.5435               0.3411   
MLPRegressor                              1.1092              -1.7447   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.3987                0.3937   
DecisionTreeRegressor                    0.4949                0.5274   
RandomForestRegressor                    0.5987                0.6234   
GradientBoostingRegressor                0.6434                0.6607   
AdaBoostRegressor                        0.5016                0.5328   
XGBRegressor                             0.5883                0.6180   
ExtraTreesRegressor                      0.4972                0.5305   
LinearRegression                         0.3567                0.3965   
KNeighborsRegressor                      0.5231                0.5529   
SVR                                      0.5909                0.6007   
MLPRegressor                             0.1206                0.1132   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.7074   0.6140    0.8410   0.0214   
DecisionTreeRegressor       0.5801   0.4878    0.7617   0.1975   
RandomForestRegressor       0.5822   0.5074    0.7630   0.1946   
GradientBoostingRegressor   0.5769   0.4980    0.7595   0.2019   
AdaBoostRegressor           0.6304   0.5785    0.7940   0.1279   
XGBRegressor                0.6038   0.4775    0.7770   0.1647   
ExtraTreesRegressor         0.5686   0.4847    0.7540   0.2134   
LinearRegression            1.0545   0.7214    1.0269  -0.4589   
KNeighborsRegressor         0.6787   0.5560    0.8239   0.0610   
SVR                         0.6517   0.5279    0.8073   0.0985   
MLPRegressor                1.1747   0.8414    1.0838  -0.6251   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.3838                    0.4511  
DecisionTreeRegressor                       0.5294                    0.5503  
RandomForestRegressor                       0.5661                    0.6106  
GradientBoostingRegressor                   0.5584                    0.6330  
AdaBoostRegressor                           0.5990                    0.6114  
XGBRegressor                                0.5237                    0.6205  
ExtraTreesRegressor                         0.540

In [13]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.531297470505814, -5.711366959090028, -5.63...   
1   [-6.13, -5.975, -5.3933333333333335, -6.62, -5...   
2   [-5.973599999999998, -6.156198809523816, -5.35...   
3   [-5.972068389176766, -6.183780872896161, -5.40...   
4   [-5.873749999999999, -6.359999999999999, -5.13...   
5   [-5.9941473, -6.1927757, -5.390035, -6.620369,...   
6   [-5.916899999999999, -6.245900000000007, -5.39...   
7   [-6.723197754770655, -6.215215993585295, -5.39...   
8   [-5.9433333333333325, -6.19, -5.39333333333333...   
9   [-5.7653970736065725, -5.918701900446836, -5.3...   
10  [-4.0, -6.6510116638899, -6.293553990240281, -...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.531297470505814, -5.7112121441245245, -5....   
1   [[-6.13, -5.95, -5.975, -4.3, -6.62, -5.073333...   
2   [[-6.019099999999997, -5.898099999999999, -5.6...   
3   [[-6.039598104633682, -5.963114848301747, -5.6...   
4   [[-5.873749999999999, -5.873749999999999, -5.8...   
5   [[-6.092258, -5.9514093, -5.2211976, -6.232823...   
6   [[-6.129999999999996, -5.949999999999999, -5.9...   
7   [[-4.752145417372643, -5.949999999999997, -4.4...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-5.873209832758758, -5.949423519958586, -5.7...   
10  [[-5.395684016523861, -6.806127426248824, -6.1...   

                                Test Predictions Mean  \
0   [-5.646703300474309, -5.701439679613568, -5.72...   
1   [-6.078, -5.909999999999999, -5.53700000000000...   
2   [-6.066566666666665, -5.9182766666666655, -5.6...   
3   [-6.07317950159807, -5.979787078482948, -5.692...   
4   [-5.900670561454756, -5.856769718844985, -5.81...   
5   [-6.085742, -5.92769, -5.2932577, -5.981988, -...   
6   [-6.091619999999997, -5.909999999999999, -5.51...   
7   [-5.36775096483848, -5.918128500986197, -4.999...   
8   [-5.924666666666667, -5.924666666666667, -5.74...   
9   [-5.9115543492208875, -5.940738324416255, -5.7...   
10  [-5.388450192982764, -6.586685868819262, -5.88...   

                                 Test Predictions Std  
0   [0.09524436964780744, 0.10091586369235374, 0.1...  
1   [0.10399999999999991, 0.08000000000000007, 0.2...  
2   [0.049734811193412436, 0.023152469510711975, 0...  
3   [0.022374509717948247, 0.028078845841266718, 0...  
4   [0.10571207292556929, 0.11048425107418011, 0.0...  
5   [0.06650973, 0.044220783, 0.22009273, 0.699378...  
6   [0.07675999999999697, 0.07999999999999971, 0.2...  
7   [0.8627431625145794, 0.06374299802760008, 0.65...  
8   [0.05153639490690065, 0.05153639490690065, 0.0...  
9   [0.03229220302843119, 0.027546787352388913, 0....  
10  [1.3568070999767212, 0.6241227272434007, 0.249...

In [14]:
df_morgan_fp.to_csv('results/Fingerprints/Results_Morgan_fp_RRCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_Morgan_fp_RRCK.csv')

In [15]:
#Morgan count fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/count_morgan_fp_train_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/count_morgan_fp_test_RRCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_morgan_count_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_morgan_count_fp

X_train shape:  (140, 2048)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 2048)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000991 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 439
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 69
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with po

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-0.16089629423586715


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.2993                0.4220   
DecisionTreeRegressor                    0.4773                0.4682   
RandomForestRegressor                    0.2769                0.3787   
GradientBoostingRegressor                0.2742                0.3819   
AdaBoostRegressor                        0.2991                0.4388   
XGBRegressor                             0.2987                0.3863   
ExtraTreesRegressor                      0.2979                0.3954   
LinearRegression                         0.7021                0.5355   
KNeighborsRegressor                      0.3712                0.4414   
SVR                                      0.2785                0.3861   
MLPRegressor                             1.1587                0.7968   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.5471               0.3324   
DecisionTreeRegressor                     0.6908              -0.0646   
RandomForestRegressor                     0.5262               0.3823   
GradientBoostingRegressor                 0.5236               0.3884   
AdaBoostRegressor                         0.5469               0.3328   
XGBRegressor                              0.5465               0.3337   
ExtraTreesRegressor                       0.5458               0.3354   
LinearRegression                          0.8379              -0.5663   
KNeighborsRegressor                       0.6093               0.1719   
SVR                                       0.5277               0.3788   
MLPRegressor                              1.0764              -1.5847   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.5781                0.5956   
DecisionTreeRegressor                    0.4955                0.5420   
RandomForestRegressor                    0.6278                0.6628   
GradientBoostingRegressor                0.6389                0.6622   
AdaBoostRegressor                        0.5820                0.6123   
XGBRegressor                             0.6174                0.6623   
ExtraTreesRegressor                      0.6117                0.6458   
LinearRegression                         0.4522                0.5695   
KNeighborsRegressor                      0.5498                0.5814   
SVR                                      0.6207                0.6240   
MLPRegressor                             0.1857                0.1816   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.6148   0.5500    0.7841   0.1495   
DecisionTreeRegressor       0.5208   0.4467    0.7217   0.2795   
RandomForestRegressor       0.5592   0.4813    0.7478   0.2264   
GradientBoostingRegressor   0.5200   0.4563    0.7211   0.2806   
AdaBoostRegressor           0.5769   0.5381    0.7596   0.2019   
XGBRegressor                0.5178   0.4366    0.7195   0.2837   
ExtraTreesRegressor         0.4935   0.4353    0.7025   0.3173   
LinearRegression            0.6057   0.5876    0.7782   0.1621   
KNeighborsRegressor         0.5471   0.5181    0.7396   0.2432   
SVR                         0.5563   0.4946    0.7459   0.2303   
MLPRegressor                0.8391   0.6928    0.9160  -0.1609   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.5492                    0.6293  
DecisionTreeRegressor                       0.6123                    0.6913  
RandomForestRegressor                       0.6084                    0.7333  
GradientBoostingRegressor                   0.6343                    0.7163  
AdaBoostRegressor                           0.6046                    0.6640  
XGBRegressor                                0.6127                    0.7064  
ExtraTreesRegressor                         0.651

In [16]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.695304983511653, -5.986359301270523, -5.63...   
1   [-6.58, -6.92, -5.09, -5.4, -6.05, -6.2, -6.05...   
2   [-5.986899999999999, -5.817466666666673, -5.13...   
3   [-5.977550832386751, -6.247992153573798, -5.17...   
4   [-5.897234042553189, -6.1167142857142895, -5.4...   
5   [-6.1615295, -6.249744, -5.0908656, -5.473682,...   
6   [-6.076599999999997, -6.324633333333337, -5.08...   
7   [-6.356217818897776, -6.030992714937686, -5.80...   
8   [-5.9433333333333325, -6.19, -5.19333333333333...   
9   [-5.821270995600824, -5.789733128135689, -5.32...   
10  [-4.0, -5.770196713591996, -6.152883077166018,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.695304983511653, -5.893698792108244, -5.8...   
1   [[-6.13, -5.95, -6.1, -6.2, -5.4, -5.073333333...   
2   [[-5.999874999999999, -5.944399999999999, -5.6...   
3   [[-6.03237579586137, -5.98024463625589, -5.730...   
4   [[-5.897234042553189, -6.142954545454546, -6.0...   
5   [[-6.1060667, -5.950252, -5.6400223, -6.469012...   
6   [[-6.049599999999999, -5.949999999999999, -5.8...   
7   [[-5.228509451763848, -5.950000000000001, -6.5...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-5.8954490999150835, -5.939444513348278, -5....   
10  [[-4.856442201262638, -6.534483490603626, -5.1...   

                                Test Predictions Mean  \
0   [-5.891479641086361, -5.971690945885567, -5.76...   
1   [-6.002000000000001, -5.933999999999999, -5.8,...   
2   [-6.049084999999998, -5.935519999999998, -5.73...   
3   [-6.062282540872021, -5.9861973228796685, -5.8...   
4   [-6.051963642487472, -6.074461682461683, -5.93...   
5   [-6.0654554, -5.99138, -5.7818804, -6.3692617,...   
6   [-6.0327, -5.94368, -5.7431400000000075, -6.16...   
7   [-5.62294590279239, -5.966277654960579, -6.469...   
8   [-5.924666666666667, -5.924666666666667, -5.82...   
9   [-5.931270314379397, -5.937763902456055, -5.78...   
10  [-4.937195237063321, -6.321243355872222, -5.80...   

                                 Test Predictions Std  
0   [0.12951606373926675, 0.10232965863020972, 0.1...  
1   [0.16129476122924755, 0.03200000000000003, 0.3...  
2   [0.03417363603715502, 0.05647685012463111, 0.1...  
3   [0.06181435273702747, 0.03808285304530232, 0.1...  
4   [0.15758910106623844, 0.16405549220668797, 0.2...  
5   [0.0710769, 0.08284783, 0.21647198, 0.13671055...  
6   [0.03751842214166105, 0.012639999999998961, 0....  
7   [1.0205705659380804, 0.03255530992115512, 0.25...  
8   [0.05153639490690065, 0.05153639490690065, 0.0...  
9   [0.04436570949512518, 0.006955513126242185, 0....  
10  [0.9315521815226413, 0.30457013612477274, 0.39...

In [17]:
df_morgan_count_fp.to_csv('results/Fingerprints/Results_Count_Morgan_fp_RRCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_Count_Morgan_fp_RRCK.csv')

In [18]:
#AtomPairs2d fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/AtomPairs2D_train_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/AtomPairs2D_test_RRCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_AtomPairs2D_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_AtomPairs2D_fp

X_train shape:  (140, 780)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 780)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001161 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 57
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 19
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with posit

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.4308                0.5452   
DecisionTreeRegressor                    0.4272                0.5348   
RandomForestRegressor                    0.4094                0.5300   
GradientBoostingRegressor                0.4068                0.5253   
AdaBoostRegressor                        0.4060                0.5238   
XGBRegressor                             0.4045                0.5251   
ExtraTreesRegressor                      0.4155                0.5290   
LinearRegression                         0.3968                0.5131   
KNeighborsRegressor                      0.6859                0.6835   
SVR                                      0.4286                0.5353   
MLPRegressor                             0.7381                0.7187   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.6564               0.0390   
DecisionTreeRegressor                     0.6536               0.0470   
RandomForestRegressor                     0.6398               0.0868   
GradientBoostingRegressor                 0.6378               0.0926   
AdaBoostRegressor                         0.6372               0.0943   
XGBRegressor                              0.6360               0.0976   
ExtraTreesRegressor                       0.6446               0.0732   
LinearRegression                          0.6299               0.1149   
KNeighborsRegressor                       0.8282              -0.5300   
SVR                                       0.6547               0.0439   
MLPRegressor                              0.8591              -0.6465   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.2183                0.1929   
DecisionTreeRegressor                    0.2984                0.2461   
RandomForestRegressor                    0.3231                0.2575   
GradientBoostingRegressor                0.3404                0.2710   
AdaBoostRegressor                        0.3274                0.3123   
XGBRegressor                             0.3438                0.2626   
ExtraTreesRegressor                      0.3187                0.2607   
LinearRegression                         0.3767                0.2902   
KNeighborsRegressor                      0.1761                0.1476   
SVR                                      0.2546                0.2301   
MLPRegressor                             0.0927                0.0646   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.7391   0.6434    0.8597  -0.0225   
DecisionTreeRegressor       0.7891   0.6580    0.8883  -0.0916   
RandomForestRegressor       0.7872   0.6549    0.8873  -0.0891   
GradientBoostingRegressor   0.7840   0.6547    0.8854  -0.0846   
AdaBoostRegressor           0.7466   0.6438    0.8641  -0.0329   
XGBRegressor                0.7889   0.6577    0.8882  -0.0914   
ExtraTreesRegressor         0.7891   0.6580    0.8883  -0.0916   
LinearRegression            0.7938   0.6497    0.8909  -0.0981   
KNeighborsRegressor         0.6014   0.6054    0.7755   0.1680   
SVR                         0.7850   0.6463    0.8860  -0.0860   
MLPRegressor                0.7388   0.6846    0.8595  -0.0221   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4641                    0.4903  
DecisionTreeRegressor                       0.3285                    0.3223  
RandomForestRegressor                       0.3280                    0.3328  
GradientBoostingRegressor                   0.3299                    0.3316  
AdaBoostRegressor                           0.3653                    0.3935  
XGBRegressor                                0.3288                    0.3223  
ExtraTreesRegressor                         0.328

In [19]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.286939751613404, -5.7675784994515995, -5.7...   
1   [-5.983333333333333, -5.723048780487803, -5.72...   
2   [-5.956641309523811, -5.716945145636179, -5.71...   
3   [-5.953268549052178, -5.7233825568538395, -5.7...   
4   [-5.5022222222222235, -5.723378378378379, -5.7...   
5   [-5.9834375, -5.723186, -5.723186, -5.723186, ...   
6   [-5.98333333333334, -5.723048780487817, -5.723...   
7   [-5.639013135138875, -5.724854164504859, -5.72...   
8   [-5.983333333333333, -6.289999999999999, -6.28...   
9   [-5.814107793539646, -5.699921526874601, -5.69...   
10  [-5.506126781279458, -6.2810261641359, -6.2810...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.286939751613404, -5.286939751613404, -5.7...   
1   [[-5.983333333333333, -5.983333333333333, -5.7...   
2   [[-5.956641309523811, -5.956641309523811, -5.7...   
3   [[-5.953268549052178, -5.953268549052178, -5.7...   
4   [[-5.5022222222222235, -5.5022222222222235, -5...   
5   [[-5.9834375, -5.9834375, -5.723186, -5.122092...   
6   [[-5.98333333333334, -5.98333333333334, -5.723...   
7   [[-5.639013135138875, -5.639013135138875, -5.7...   
8   [[-5.983333333333333, -5.983333333333333, -6.2...   
9   [[-5.814107793539646, -5.814107793539646, -5.6...   
10  [[-5.506126781279458, -5.506126781279458, -6.2...   

                                Test Predictions Mean  \
0   [-5.422778328595897, -5.422778328595897, -5.74...   
1   [-6.1525, -6.1525, -5.685047356996378, -5.1950...   
2   [-6.1295850337474125, -6.1295850337474125, -5....   
3   [-6.107109555212862, -6.107109555212862, -5.68...   
4   [-6.000652094717669, -6.000652094717669, -5.75...   
5   [-6.1525064, -6.1525064, -5.6851683, -5.195113...   
6   [-6.152500000000005, -6.152500000000005, -5.68...   
7   [-5.860212302471344, -5.860212302471344, -5.69...   
8   [-6.171333333333333, -6.171333333333333, -6.29...   
9   [-5.853396824836513, -5.853396824836513, -5.66...   
10  [-5.453688268121063, -5.453688268121063, -6.26...   

                                 Test Predictions Std  
0   [0.08484817398042653, 0.08484817398042653, 0.0...  
1   [0.09175753072333853, 0.09175753072333853, 0.0...  
2   [0.09353693557378943, 0.09353693557378943, 0.0...  
3   [0.08344055611904098, 0.08344055611904098, 0.0...  
4   [0.3327445815131407, 0.3327445815131407, 0.030...  
5   [0.09179446, 0.09179446, 0.0442632, 0.11001804...  
6   [0.09175753072333921, 0.09175753072333921, 0.0...  
7   [0.12300519441467392, 0.12300519441467392, 0.0...  
8   [0.09918781287145202, 0.09918781287145202, 0.0...  
9   [0.04813464823741424, 0.04813464823741424, 0.0...  
10  [0.2139854242328304, 0.2139854242328304, 0.043...

In [20]:
df_AtomPairs2D_fp.to_csv('results/Fingerprints/Results_AtomPairs2D_fp_RRCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_AtomPairs2D_fp_RRCK.csv')

In [21]:
#AtomPairs2d Count fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/AtomPairs2DCount_train_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/AtomPairs2DCount_test_RRCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_AtomPairs2DCount_fp , pred_df= train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_AtomPairs2DCount_fp

X_train shape:  (140, 780)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 780)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.006722 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 762
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 60
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with posi

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't 

0.08239028264906334


/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.2817                0.4111   
DecisionTreeRegressor                    0.4410                0.5016   
RandomForestRegressor                    0.2559                0.3903   
GradientBoostingRegressor                0.2679                0.3981   
AdaBoostRegressor                        0.2735                0.4191   
XGBRegressor                             0.2774                0.3991   
ExtraTreesRegressor                      0.2227                0.3522   
LinearRegression                         1.5068                0.7197   
KNeighborsRegressor                      0.2952                0.3925   
SVR                                      0.2918                0.4151   
MLPRegressor                             0.4075                0.4830   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.5307               0.3717   
DecisionTreeRegressor                     0.6641               0.0163   
RandomForestRegressor                     0.5059               0.4291   
GradientBoostingRegressor                 0.5176               0.4024   
AdaBoostRegressor                         0.5230               0.3899   
XGBRegressor                              0.5267               0.3811   
ExtraTreesRegressor                       0.4720               0.5031   
LinearRegression                          1.2275              -2.3613   
KNeighborsRegressor                       0.5434               0.3414   
SVR                                       0.5402               0.3490   
MLPRegressor                              0.6384               0.0909   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.6101                0.6149   
DecisionTreeRegressor                    0.4644                0.4556   
RandomForestRegressor                    0.6595                0.6570   
GradientBoostingRegressor                0.6522                0.6507   
AdaBoostRegressor                        0.6281                0.6348   
XGBRegressor                             0.6439                0.6468   
ExtraTreesRegressor                      0.7153                0.7157   
LinearRegression                         0.3840                0.5352   
KNeighborsRegressor                      0.6191                0.6489   
SVR                                      0.6053                0.6287   
MLPRegressor                             0.4854                0.5388   

                          Test MSE Test MAE Test RMSE Test R2  \
LGBMRegressor               0.4674   0.4722    0.6837  0.3533   
DecisionTreeRegressor       0.3751   0.4299    0.6124  0.4811   
RandomForestRegressor       0.4132   0.4298    0.6428  0.4284   
GradientBoostingRegressor   0.3157   0.3835    0.5619  0.5632   
AdaBoostRegressor           0.4361   0.4778    0.6603  0.3967   
XGBRegressor                0.3464   0.4030    0.5885  0.5208   
ExtraTreesRegressor         0.3610   0.4030    0.6009  0.5005   
LinearRegression            0.6221   0.5704    0.7887  0.1394   
KNeighborsRegressor         0.6070   0.5110    0.7791  0.1603   
SVR                         0.6085   0.5488    0.7801  0.1582   
MLPRegressor                0.6633   0.6010    0.8144  0.0824   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6999                    0.7521  
DecisionTreeRegressor                       0.7763                    0.7625  
RandomForestRegressor                       0.7619                    0.8032  
GradientBoostingRegressor                   0.8189                    0.8308  
AdaBoostRegressor                           0.7710                    0.7583  
XGBRegressor                                0.7825                    0.7986  
ExtraTreesRegressor                         0.7750           

In [22]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-6.174722296925258, -5.811231849162886, -5.30...   
1   [-6.13, -5.57, -5.4, -6.22, -5.4, -6.58, -5.4,...   
2   [-6.1020999999999965, -5.86745, -5.2341, -5.92...   
3   [-6.106200077986232, -6.344998862038213, -5.24...   
4   [-6.13, -6.115, -5.238124999999999, -6.0917073...   
5   [-6.129661, -5.9377437, -5.3395033, -6.1105967...   
6   [-6.129999999999996, -6.090199999999995, -5.30...   
7   [-6.126034955452054, -6.3765561171432115, -5.9...   
8   [-5.983333333333333, -5.890000000000001, -5.19...   
9   [-6.052887344882163, -5.66333786713414, -5.447...   
10  [-6.113372158580415, -5.789195943702515, -5.34...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-6.174722296925258, -6.174722296925258, -6.3...   
1   [[-6.05, -5.95, -6.78, -6.46, -5.35, -4.72, -6...   
2   [[-6.102099999999998, -5.963299999999999, -6.5...   
3   [[-6.054609219869423, -5.981616493256371, -6.7...   
4   [[-6.109999999999999, -6.109999999999999, -6.5...   
5   [[-5.9515038, -5.9505663, -6.9154034, -6.45473...   
6   [[-6.090149999999999, -5.949999999999999, -6.9...   
7   [[-4.0, -5.993924298526641, -6.861568642235872...   
8   [[-5.983333333333333, -5.983333333333333, -6.3...   
9   [[-6.020565120422604, -6.006596091659966, -5.9...   
10  [[-5.654065549631591, -5.935759729594135, -6.9...   

                                Test Predictions Mean  \
0   [-6.202887160256114, -6.178989873364112, -6.27...   
1   [-5.85, -5.83, -7.0120000000000005, -6.048, -5...   
2   [-6.198464499999999, -6.0783231666666655, -6.5...   
3   [-6.105868140136444, -6.035693801833756, -6.88...   
4   [-6.1341871794871805, -6.081461234991423, -6.5...   
5   [-5.9960513, -5.9922028, -6.9584756, -6.302946...   
6   [-6.120649999999998, -5.992519999999999, -6.76...   
7   [-6.86240927341324, -6.102368433259525, -6.510...   
8   [-6.171333333333333, -6.154, -6.22799999999999...   
9   [-6.069998682643051, -6.038159051164101, -5.88...   
10  [-5.586878920408173, -6.027754580804202, -7.07...   

                                 Test Predictions Std  
0   [0.07027520523501173, 0.08560694791903788, 0.0...  
1   [0.2529822128134705, 0.24000000000000024, 0.39...  
2   [0.05473067714728151, 0.07774882932737848, 0.1...  
3   [0.06393240980493652, 0.08734882396807951, 0.3...  
4   [0.06338044513187786, 0.11799236321740199, 0.2...  
5   [0.08044295, 0.08206079, 0.3856949, 0.26830214...  
6   [0.06404927009732307, 0.08503999999999935, 0.3...  
7   [1.9012337489789244, 0.06786547733396986, 0.27...  
8   [0.09918781287145202, 0.09180655992054389, 0.1...  
9   [0.03239908724185192, 0.01659351512624975, 0.0...  
10  [0.2888456093299325, 0.07988206236398683, 0.13...

In [23]:
df_AtomPairs2DCount_fp.to_csv('results/Fingerprints/Results_AtomPairs2D_Count_fp_RRCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_df_AtomPairs2D_Count_fp_RRCK.csv')

In [24]:
#EState fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/EState_train_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/EState_test_RRCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_estate_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_estate_fp

X_train shape:  (140, 79)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 79)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.010782 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 3
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 1
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive 

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-0.1682114631281033


/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.4208                0.5366   
DecisionTreeRegressor                    0.4150                0.5335   
RandomForestRegressor                    0.4112                0.5323   
GradientBoostingRegressor                0.4011                0.5221   
AdaBoostRegressor                        0.4063                0.5249   
XGBRegressor                             0.4058                0.5256   
ExtraTreesRegressor                      0.4123                0.5313   
LinearRegression                         0.4372                0.5478   
KNeighborsRegressor                      0.9205                0.7747   
SVR                                      0.4605                0.5632   
MLPRegressor                             0.7049                0.6587   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.6487               0.0612   
DecisionTreeRegressor                     0.6442               0.0742   
RandomForestRegressor                     0.6413               0.0827   
GradientBoostingRegressor                 0.6333               0.1053   
AdaBoostRegressor                         0.6374               0.0936   
XGBRegressor                              0.6370               0.0948   
ExtraTreesRegressor                       0.6421               0.0803   
LinearRegression                          0.6612               0.0247   
KNeighborsRegressor                       0.9594              -1.0534   
SVR                                       0.6786              -0.0274   
MLPRegressor                              0.8396              -0.5724   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.2491                0.1581   
DecisionTreeRegressor                    0.3202                0.2518   
RandomForestRegressor                    0.3115                0.2632   
GradientBoostingRegressor                0.3415                0.2600   
AdaBoostRegressor                        0.3114                0.2515   
XGBRegressor                             0.3358                0.2709   
ExtraTreesRegressor                      0.3261                0.2524   
LinearRegression                         0.2458                0.2366   
KNeighborsRegressor                      0.0337               -0.0377   
SVR                                      0.2082                0.2355   
MLPRegressor                             0.0343                0.1151   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.7594   0.6452    0.8714  -0.0505   
DecisionTreeRegressor       0.8022   0.6728    0.8956  -0.1097   
RandomForestRegressor       0.8006   0.6756    0.8947  -0.1075   
GradientBoostingRegressor   0.7958   0.6695    0.8921  -0.1009   
AdaBoostRegressor           0.7519   0.6629    0.8671  -0.0403   
XGBRegressor                0.8000   0.6697    0.8944  -0.1068   
ExtraTreesRegressor         0.8022   0.6728    0.8956  -0.1097   
LinearRegression            0.7956   0.6715    0.8919  -0.1006   
KNeighborsRegressor         0.9062   0.7656    0.9520  -0.2537   
SVR                         0.8627   0.6752    0.9288  -0.1934   
MLPRegressor                0.8444   0.7002    0.9189  -0.1682   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.3636                    0.3484  
DecisionTreeRegressor                       0.3150                    0.2388  
RandomForestRegressor                       0.3252                    0.2399  
GradientBoostingRegressor                   0.3224                    0.2328  
AdaBoostRegressor                           0.4504                    0.4342  
XGBRegressor                                0.3142                    0.2328  
ExtraTreesRegressor                         0.315

In [25]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.307054751846478, -5.733086951432175, -5.73...   
1   [-6.78, -5.761875000000001, -5.761875000000001...   
2   [-5.977085696248188, -5.7400533879357845, -5.7...   
3   [-6.635883161387998, -5.756717266510805, -5.75...   
4   [-6.78, -5.79417808219178, -5.79417808219178, ...   
5   [-6.6676383, -5.7617073, -5.7617073, -5.761707...   
6   [-6.779999999999983, -5.7618749999999945, -5.7...   
7   [-5.489770500878781, -5.761875000000001, -5.76...   
8   [-5.983333333333333, -6.289999999999999, -6.28...   
9   [-5.812803170309143, -5.500339343057642, -5.50...   
10  [-5.562644789418256, -5.749594775809043, -5.74...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.733086951432175, -5.733086951432175, -5.7...   
1   [[-5.686, -5.686, -5.761875000000001, -5.02444...   
2   [[-5.672280984848485, -5.672280984848485, -5.7...   
3   [[-5.685146179340739, -5.685146179340739, -5.7...   
4   [[-5.651810344827585, -5.651810344827585, -5.7...   
5   [[-5.685873, -5.685873, -5.7617073, -5.0246015...   
6   [[-5.6859999999999955, -5.6859999999999955, -5...   
7   [[-5.862331605498172, -5.862331605498172, -5.7...   
8   [[-5.983333333333333, -5.983333333333333, -6.2...   
9   [[-5.770129081178809, -5.770129081178809, -5.5...   
10  [[-5.709927500206028, -5.709927500206028, -5.7...   

                                Test Predictions Mean  \
0   [-5.716147069640357, -5.716147069640357, -5.71...   
1   [-5.6934, -5.6934, -5.7013710407239815, -5.124...   
2   [-5.6899965858585855, -5.6899965858585855, -5....   
3   [-5.687809606570104, -5.687809606570104, -5.70...   
4   [-5.619743887147336, -5.619743887147336, -5.78...   
5   [-5.6932855, -5.6932855, -5.701349, -5.124449,...   
6   [-5.693399999999996, -5.693399999999996, -5.70...   
7   [-6.025502850452247, -6.025502850452247, -5.70...   
8   [-5.816000000000001, -5.816000000000001, -6.29...   
9   [-5.878196169195936, -5.878196169195936, -5.54...   
10  [-5.823752771796778, -5.823752771796778, -5.68...   

                                 Test Predictions Std  
0   [0.027026951970261587, 0.027026951970261587, 0...  
1   [0.09566060375677687, 0.09566060375677687, 0.0...  
2   [0.08684929683805728, 0.08684929683805728, 0.0...  
3   [0.0901893473413318, 0.0901893473413318, 0.086...  
4   [0.12904152690784967, 0.12904152690784967, 0.0...  
5   [0.09572181, 0.09572181, 0.093075044, 0.092036...  
6   [0.09566060375678095, 0.09566060375678095, 0.0...  
7   [0.10029037407240912, 0.10029037407240912, 0.0...  
8   [0.16407857196409817, 0.16407857196409817, 0.0...  
9   [0.10551241572577515, 0.10551241572577515, 0.1...  
10  [0.1037890004374814, 0.1037890004374814, 0.096...

In [26]:
df_estate_fp.to_csv('results/Fingerprints/Results_EState_fp_RRCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_EState_fp_RRCK.csv')

In [27]:
#Extended fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/Extended_train_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/Extended_test_RRCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_extended_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_extended_fp

X_train shape:  (140, 1024)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 1024)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.002219 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 501
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 167
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with p

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.3734                0.4808   
DecisionTreeRegressor                    0.4790                0.5153   
RandomForestRegressor                    0.3885                0.4731   
GradientBoostingRegressor                0.3734                0.4670   
AdaBoostRegressor                        0.3793                0.4856   
XGBRegressor                             0.4364                0.5056   
ExtraTreesRegressor                      0.4792                0.5195   
LinearRegression                         0.4911                0.5389   
KNeighborsRegressor                      0.4372                0.4880   
SVR                                      0.4362                0.5082   
MLPRegressor                             1.1586                0.8743   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.6110               0.1671   
DecisionTreeRegressor                     0.6921              -0.0686   
RandomForestRegressor                     0.6233               0.1333   
GradientBoostingRegressor                 0.6111               0.1669   
AdaBoostRegressor                         0.6159               0.1539   
XGBRegressor                              0.6606               0.0266   
ExtraTreesRegressor                       0.6922              -0.0689   
LinearRegression                          0.7008              -0.0956   
KNeighborsRegressor                       0.6612               0.0248   
SVR                                       0.6604               0.0270   
MLPRegressor                              1.0764              -1.5845   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.4177                0.4227   
DecisionTreeRegressor                    0.3472                0.3605   
RandomForestRegressor                    0.4162                0.4595   
GradientBoostingRegressor                0.4491                0.4892   
AdaBoostRegressor                        0.4152                0.4400   
XGBRegressor                             0.3700                0.3947   
ExtraTreesRegressor                      0.3341                0.3542   
LinearRegression                         0.3413                0.3629   
KNeighborsRegressor                      0.4136                0.4502   
SVR                                      0.2950                0.3471   
MLPRegressor                             0.0546                0.0902   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.6634   0.5923    0.8145   0.0822   
DecisionTreeRegressor       0.8007   0.6588    0.8948  -0.1077   
RandomForestRegressor       0.7107   0.6044    0.8430   0.0168   
GradientBoostingRegressor   0.6858   0.5963    0.8281   0.0513   
AdaBoostRegressor           0.6880   0.6254    0.8294   0.0482   
XGBRegressor                0.7109   0.6237    0.8432   0.0165   
ExtraTreesRegressor         0.7868   0.6499    0.8870  -0.0884   
LinearRegression            0.6742   0.6226    0.8211   0.0672   
KNeighborsRegressor         0.7925   0.6820    0.8902  -0.0964   
SVR                         0.8223   0.6776    0.9068  -0.1376   
MLPRegressor                1.1787   0.9159    1.0857  -0.6306   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.5005                    0.5295  
DecisionTreeRegressor                       0.3231                    0.3515  
RandomForestRegressor                       0.4469                    0.4802  
GradientBoostingRegressor                   0.4618                    0.4977  
AdaBoostRegressor                           0.4601                    0.4929  
XGBRegressor                                0.4282                    0.4277  
ExtraTreesRegressor                         0.334

In [28]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.795313932255152, -5.914337442746655, -5.72...   
1   [-5.53, -5.975, -5.544444444444444, -5.975, -5...   
2   [-5.6659847619047605, -6.0401454474692, -5.565...   
3   [-5.678348178183033, -5.940574780044496, -5.57...   
4   [-5.746666666666667, -6.0486, -6.0486, -6.0486...   
5   [-5.501156, -6.2012396, -5.545777, -6.2012396,...   
6   [-5.529999999999986, -6.026216666666674, -5.54...   
7   [-6.544099542651379, -5.94908973113055, -5.489...   
8   [-5.983333333333333, -5.766666666666666, -6.07...   
9   [-5.736299097780264, -5.73893103046754, -5.500...   
10  [-4.0, -6.407865156935288, -6.628602192747598,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-6.011919220081905, -6.011919220081905, -5.9...   
1   [[-6.04, -6.04, -5.975, -5.132, -5.975, -5.544...   
2   [[-5.984655, -5.995355000000001, -6.0401454474...   
3   [[-5.6119174091382895, -6.0075881098865676, -5...   
4   [[-5.995, -5.995, -6.0486, -5.27470588235294, ...   
5   [[-6.045834, -6.039532, -6.2012396, -5.1320395...   
6   [[-6.184599999999994, -6.040000000000003, -6.0...   
7   [[-5.773934320076065, -6.039999999999998, -5.9...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-5.975748739414786, -6.00980059943213, -5.73...   
10  [[-5.206702464804116, -5.531648302384958, -6.4...   

                                Test Predictions Mean  \
0   [-6.0452010356377235, -6.0452010356377235, -5....   
1   [-6.04, -6.04, -5.827, -5.154733333333334, -5....   
2   [-5.960914333333331, -6.012649333333331, -5.85...   
3   [-5.871500198498891, -6.017608651039191, -5.84...   
4   [-5.994884615384615, -5.994884615384615, -5.99...   
5   [-5.988635, -6.0396967, -5.8748627, -5.1548576...   
6   [-6.100819999999999, -6.040000000000001, -5.83...   
7   [-5.805372481205483, -6.039999999999997, -5.84...   
8   [-6.118666666666667, -6.118666666666667, -5.92...   
9   [-5.975094444485063, -6.0055719293821195, -5.6...   
10  [-5.076632111595447, -5.466531029413682, -6.49...   

                                 Test Predictions Std  
0   [0.02942150785768537, 0.02942150785768537, 0.0...  
1   [0.05692099788303074, 0.05692099788303074, 0.0...  
2   [0.04782011773999092, 0.045212303839158134, 0....  
3   [0.14567814525322847, 0.045062581451394655, 0....  
4   [0.037026617644624005, 0.037026617644624005, 0...  
5   [0.06601441, 0.056452252, 0.16321759, 0.284458...  
6   [0.1208006357599135, 0.0569209978830299, 0.094...  
7   [0.09852917734372195, 0.05692099788303046, 0.0...  
8   [0.11400974617208051, 0.11400974617208051, 0.2...  
9   [0.03263860900915797, 0.036345227680330064, 0....  
10  [0.14848808946224187, 0.14227270288713892, 0.1...

In [29]:
df_extended_fp.to_csv('results/Fingerprints/Results_Extended_fp_RRCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_Extended_fp_RRCK.csv')

In [30]:
#Fingerprinter fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/Fingerprinter_train_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/Fingerprinter_test_RRCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_fingerprinter_fp , pred_df= train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_fingerprinter_fp

X_train shape:  (140, 1024)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 1024)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.011172 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 468
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 156
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with p

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.3641                0.4872   
DecisionTreeRegressor                    0.4422                0.4869   
RandomForestRegressor                    0.3778                0.4667   
GradientBoostingRegressor                0.4117                0.4890   
AdaBoostRegressor                        0.3904                0.5080   
XGBRegressor                             0.4367                0.5021   
ExtraTreesRegressor                      0.4270                0.4889   
LinearRegression                         0.4639                0.5203   
KNeighborsRegressor                      0.4450                0.4860   
SVR                                      0.4270                0.5018   
MLPRegressor                             1.1126                0.8396   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.6034               0.1878   
DecisionTreeRegressor                     0.6650               0.0136   
RandomForestRegressor                     0.6147               0.1572   
GradientBoostingRegressor                 0.6416               0.0816   
AdaBoostRegressor                         0.6248               0.1292   
XGBRegressor                              0.6608               0.0259   
ExtraTreesRegressor                       0.6535               0.0475   
LinearRegression                          0.6811              -0.0349   
KNeighborsRegressor                       0.6671               0.0072   
SVR                                       0.6535               0.0475   
MLPRegressor                              1.0548              -1.4820   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.4338                0.4587   
DecisionTreeRegressor                    0.4051                0.4353   
RandomForestRegressor                    0.4408                0.4782   
GradientBoostingRegressor                0.3948                0.4523   
AdaBoostRegressor                        0.3803                0.3850   
XGBRegressor                             0.3806                0.4054   
ExtraTreesRegressor                      0.4090                0.4448   
LinearRegression                         0.4034                0.4362   
KNeighborsRegressor                      0.4175                0.4502   
SVR                                      0.3124                0.3660   
MLPRegressor                             0.0758                0.1354   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.6530   0.6023    0.8081   0.0966   
DecisionTreeRegressor       0.7971   0.6589    0.8928  -0.1028   
RandomForestRegressor       0.7392   0.6361    0.8598  -0.0227   
GradientBoostingRegressor   0.7127   0.6283    0.8442   0.0141   
AdaBoostRegressor           0.7035   0.6213    0.8387   0.0268   
XGBRegressor                0.7597   0.6416    0.8716  -0.0510   
ExtraTreesRegressor         0.7849   0.6531    0.8859  -0.0858   
LinearRegression            0.6849   0.6205    0.8276   0.0526   
KNeighborsRegressor         0.7645   0.6489    0.8744  -0.0577   
SVR                         0.8320   0.6850    0.9122  -0.1510   
MLPRegressor                1.1592   0.8394    1.0767  -0.6036   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.5085                    0.4525  
DecisionTreeRegressor                       0.3250                    0.3560  
RandomForestRegressor                       0.4017                    0.4045  
GradientBoostingRegressor                   0.4130                    0.4590  
AdaBoostRegressor                           0.4188                    0.4587  
XGBRegressor                                0.3748                    0.4014  
ExtraTreesRegressor                         0.339

In [31]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.776024623454233, -5.991102690129882, -5.76...   
1   [-5.132, -6.065833333333333, -5.54090909090909...   
2   [-5.803215238095239, -6.052048095238101, -5.55...   
3   [-5.593305484751483, -5.906208942513288, -5.59...   
4   [-6.005999999999999, -5.80904761904762, -5.809...   
5   [-5.380657, -6.138579, -5.5417986, -6.138579, ...   
6   [-5.132000000000004, -6.002891666666675, -5.54...   
7   [-6.278044070703841, -6.00471131747885, -5.501...   
8   [-5.983333333333333, -5.766666666666666, -6.07...   
9   [-5.745239836764945, -5.747006681054585, -5.49...   
10  [-4.0, -6.299693456730743, -6.538220878687118,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.877498673984496, -5.877498673984496, -5.9...   
1   [[-6.04, -6.04, -6.065833333333333, -5.132, -6...   
2   [[-5.998255833333332, -5.991755833333332, -6.0...   
3   [[-6.008439485280536, -6.008439485280536, -5.9...   
4   [[-6.005999999999999, -6.005999999999999, -5.8...   
5   [[-6.0392056, -6.039688, -6.138579, -5.1319304...   
6   [[-6.0401000000000025, -6.040000000000003, -6....   
7   [[-6.154156942433332, -6.040000000000002, -6.0...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-5.9812702988603705, -5.997582760741254, -5....   
10  [[-5.578798223044618, -5.876625892771602, -6.2...   

                                Test Predictions Mean  \
0   [-5.918891099140959, -5.918891099140959, -5.99...   
1   [-6.04, -6.04, -5.845166666666666, -5.15473333...   
2   [-6.027918944444442, -6.026912277777776, -5.87...   
3   [-6.020965683198359, -6.018656701497865, -5.82...   
4   [-6.049044444444445, -6.049044444444445, -5.88...   
5   [-6.040491, -6.040538, -5.8633127, -5.154841, ...   
6   [-6.04002, -6.040000000000001, -5.832578333333...   
7   [-6.069803236894624, -6.040000000000001, -5.87...   
8   [-6.118666666666667, -6.118666666666667, -5.92...   
9   [-5.984255681294913, -5.998686926186851, -5.70...   
10  [-5.651628345891257, -5.9157927524664515, -6.4...   

                                 Test Predictions Std  
0   [0.07230267776412432, 0.07230267776412432, 0.0...  
1   [0.05692099788303074, 0.05692099788303074, 0.1...  
2   [0.06804502212188496, 0.06148568730782769, 0.0...  
3   [0.057676335541644926, 0.056272817995200314, 0...  
4   [0.0996469719175935, 0.0996469719175935, 0.081...  
5   [0.057073142, 0.056992337, 0.13767058, 0.28444...  
6   [0.056921011937595536, 0.0569209978830299, 0.0...  
7   [0.10126283424988687, 0.05692099788303046, 0.0...  
8   [0.11400974617208051, 0.11400974617208051, 0.2...  
9   [0.03716793137008103, 0.03712419933876382, 0.0...  
10  [0.10771498925582197, 0.120500012648737, 0.092...

In [32]:
df_fingerprinter_fp.to_csv('results/Fingerprints/Results_Fingerprinter_fp_RRCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_Fingerprinter_fp_RRCK.csv')

In [33]:
#GraphOnly fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/Graphonly_train_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/Graphonly_test_RRCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_graph_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_graph_fp

X_train shape:  (140, 1024)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 1024)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001739 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 186
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 62
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with po

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.4177                0.5391   
DecisionTreeRegressor                    0.4510                0.5255   
RandomForestRegressor                    0.4121                0.5120   
GradientBoostingRegressor                0.4227                0.5214   
AdaBoostRegressor                        0.4057                0.5127   
XGBRegressor                             0.4330                0.5174   
ExtraTreesRegressor                      0.4394                0.5242   
LinearRegression                         0.4474                0.5353   
KNeighborsRegressor                      0.5702                0.5870   
SVR                                      0.4868                0.5453   
MLPRegressor                             1.0705                0.8358   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.6463               0.0683   
DecisionTreeRegressor                     0.6716              -0.0060   
RandomForestRegressor                     0.6419               0.0808   
GradientBoostingRegressor                 0.6502               0.0570   
AdaBoostRegressor                         0.6369               0.0950   
XGBRegressor                              0.6581               0.0340   
ExtraTreesRegressor                       0.6629               0.0198   
LinearRegression                          0.6689               0.0019   
KNeighborsRegressor                       0.7551              -0.2720   
SVR                                       0.6977              -0.0860   
MLPRegressor                              1.0346              -1.3879   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.2792                0.2679   
DecisionTreeRegressor                    0.3286                0.2907   
RandomForestRegressor                    0.3462                0.3497   
GradientBoostingRegressor                0.3333                0.3332   
AdaBoostRegressor                        0.3389                0.3425   
XGBRegressor                             0.3500                0.3319   
ExtraTreesRegressor                      0.3382                0.3024   
LinearRegression                         0.3252                0.2921   
KNeighborsRegressor                      0.2481                0.2633   
SVR                                      0.1551                0.2250   
MLPRegressor                             0.0163                0.0430   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.6729   0.5957    0.8203   0.0691   
DecisionTreeRegressor       0.7092   0.6253    0.8421   0.0189   
RandomForestRegressor       0.7129   0.6184    0.8443   0.0138   
GradientBoostingRegressor   0.7184   0.6200    0.8476   0.0061   
AdaBoostRegressor           0.6926   0.6187    0.8322   0.0418   
XGBRegressor                0.7381   0.6358    0.8591  -0.0211   
ExtraTreesRegressor         0.7182   0.6286    0.8475   0.0064   
LinearRegression            0.6766   0.6156    0.8225   0.0640   
KNeighborsRegressor         0.7313   0.6430    0.8552  -0.0118   
SVR                         0.7345   0.6308    0.8570  -0.0161   
MLPRegressor                1.2396   0.8541    1.1134  -0.7149   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4805                    0.4890  
DecisionTreeRegressor                       0.3712                    0.4830  
RandomForestRegressor                       0.3905                    0.4640  
GradientBoostingRegressor                   0.3863                    0.4572  
AdaBoostRegressor                           0.4542                    0.4602  
XGBRegressor                                0.3437                    0.4411  
ExtraTreesRegressor                         0.359

In [34]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.811379245539471, -5.852372518820406, -5.85...   
1   [-5.787291666666666, -5.787291666666666, -5.78...   
2   [-5.925394422799423, -5.768635813211602, -5.76...   
3   [-6.002897653486404, -5.798143232239564, -5.79...   
4   [-5.921486486486484, -5.933088235294116, -5.93...   
5   [-5.9001036, -5.787367, -5.787367, -5.787367, ...   
6   [-5.871916666666665, -5.787291666666658, -5.78...   
7   [-5.56409232302851, -5.7872916666666665, -5.78...   
8   [-5.983333333333333, -6.289999999999999, -6.28...   
9   [-5.842141845123626, -5.74977046149222, -5.749...   
10  [-6.310007661941453, -6.776797073461899, -6.77...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.876278070986813, -5.876278070986813, -5.8...   
1   [[-6.04, -6.04, -5.787291666666666, -5.3533333...   
2   [[-5.859866785714286, -6.011935000000001, -5.7...   
3   [[-5.930804932272198, -6.016327190930974, -5.7...   
4   [[-5.921486486486484, -5.921486486486484, -5.9...   
5   [[-5.934048, -6.0395107, -5.787367, -5.353075,...   
6   [[-6.040000000000003, -6.040000000000003, -5.7...   
7   [[-5.838828079041079, -6.040000000000002, -5.7...   
8   [[-5.983333333333333, -5.983333333333333, -6.2...   
9   [[-5.938478134971531, -5.96463676737004, -5.74...   
10  [[-6.407176301160989, -6.309769972679063, -6.7...   

                                Test Predictions Mean  \
0   [-5.838158446264808, -5.838158446264808, -5.78...   
1   [-5.93, -6.04, -5.724974793703625, -5.35386666...   
2   [-5.852463686147186, -6.058895333333331, -5.71...   
3   [-5.765616764178778, -6.1267179898776885, -5.7...   
4   [-5.894608055811228, -6.043218349928876, -5.84...   
5   [-5.6844106, -6.0414248, -5.7250185, -5.353698...   
6   [-5.824143333333334, -6.040000000000001, -5.72...   
7   [-5.823639342277671, -6.040000000000004, -5.72...   
8   [-6.171333333333333, -6.171333333333333, -6.29...   
9   [-5.974789674960382, -6.0042984499080925, -5.6...   
10  [-6.507673420438165, -6.425944289577439, -6.68...   

                                 Test Predictions Std  
0   [0.05987362058391206, 0.05987362058391206, 0.0...  
1   [0.5472111109983055, 0.05692099788303074, 0.06...  
2   [0.09748863643506192, 0.055694702295440865, 0....  
3   [0.38071230968489256, 0.10162582534535164, 0.0...  
4   [0.27437394505290913, 0.10117913772909091, 0.0...  
5   [0.3672762, 0.057444543, 0.06275605, 0.3128520...  
6   [0.464783041333389, 0.0569209978830299, 0.0627...  
7   [0.16326154785556354, 0.05692099788302793, 0.0...  
8   [0.09918781287145229, 0.09918781287145229, 0.0...  
9   [0.05808453431194321, 0.05568102486782862, 0.0...  
10  [0.14835820447675693, 0.1706797011258013, 0.07...

In [35]:
df_graph_fp.to_csv('results/Fingerprints/Results_Graphonly_fp_RRCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_Graphonly_fp_RRCK.csv')

In [36]:
#KlekotaRoth fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/KlekotaRoth_train_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/KlekotaRoth_test_RRCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_KlekotaRoth_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_KlekotaRoth_fp

X_train shape:  (140, 4860)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 4860)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.000673 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 126
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 42
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with po

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-0.5437019464996429


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.3227                0.4361   
DecisionTreeRegressor                    0.4160                0.4444   
RandomForestRegressor                    0.3203                0.4071   
GradientBoostingRegressor                0.3407                0.4244   
AdaBoostRegressor                        0.3661                0.4856   
XGBRegressor                             0.3615                0.4116   
ExtraTreesRegressor                      0.3986                0.4282   
LinearRegression                         0.4716                0.5040   
KNeighborsRegressor                      0.4048                0.4544   
SVR                                      0.3666                0.4299   
MLPRegressor                             1.0223                0.6796   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.5681               0.2802   
DecisionTreeRegressor                     0.6450               0.0721   
RandomForestRegressor                     0.5659               0.2856   
GradientBoostingRegressor                 0.5837               0.2400   
AdaBoostRegressor                         0.6051               0.1833   
XGBRegressor                              0.6012               0.1937   
ExtraTreesRegressor                       0.6314               0.1107   
LinearRegression                          0.6867              -0.0520   
KNeighborsRegressor                       0.6363               0.0970   
SVR                                       0.6054               0.1823   
MLPRegressor                              1.0111              -1.2805   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.5315                0.5520   
DecisionTreeRegressor                    0.4915                0.5308   
RandomForestRegressor                    0.5581                0.5874   
GradientBoostingRegressor                0.5164                0.5384   
AdaBoostRegressor                        0.4366                0.4757   
XGBRegressor                             0.5422                0.5701   
ExtraTreesRegressor                      0.5049                0.5499   
LinearRegression                         0.3978                0.4833   
KNeighborsRegressor                      0.4590                0.4857   
SVR                                      0.4621                0.4966   
MLPRegressor                             0.0629                0.1511   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.6877   0.6078    0.8292   0.0487   
DecisionTreeRegressor       0.5255   0.5288    0.7249   0.2730   
RandomForestRegressor       0.6150   0.5376    0.7843   0.1491   
GradientBoostingRegressor   0.6214   0.5334    0.7883   0.1403   
AdaBoostRegressor           0.6673   0.6024    0.8169   0.0768   
XGBRegressor                0.6302   0.5391    0.7938   0.1282   
ExtraTreesRegressor         0.5554   0.5330    0.7453   0.2316   
LinearRegression            0.9346   0.6549    0.9668  -0.2930   
KNeighborsRegressor         0.5810   0.5773    0.7622   0.1963   
SVR                         0.6739   0.5581    0.8209   0.0677   
MLPRegressor                1.1159   0.7629    1.0563  -0.5437   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4443                    0.3873  
DecisionTreeRegressor                       0.6417                    0.6231  
RandomForestRegressor                       0.5796                    0.6008  
GradientBoostingRegressor                   0.5328                    0.5554  
AdaBoostRegressor                           0.5040                    0.5169  
XGBRegressor                                0.5384                    0.5438  
ExtraTreesRegressor                         0.614

In [37]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.969401987098618, -5.966544106185766, -5.54...   
1   [-6.0, -5.975, -5.233333333333333, -6.62, -6.0...   
2   [-5.930873333333328, -6.027715476190484, -5.25...   
3   [-6.426165625697367, -6.233332931024105, -5.33...   
4   [-5.889444444444447, -6.532000000000001, -5.50...   
5   [-6.49573, -5.9755917, -5.233335, -6.6189723, ...   
6   [-5.798399999999995, -5.975000000000011, -5.23...   
7   [-6.3487178711531635, -5.975000000000008, -5.3...   
8   [-5.73, -6.19, -5.153333333333333, -6.19, -5.4...   
9   [-5.829689151644861, -5.950163670944254, -5.31...   
10  [-4.0, -6.249215828897968, -5.407939131998739,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-6.054758943099081, -6.105018619279476, -5.7...   
1   [[-6.0, -5.95, -5.975, -4.3, -6.62, -5.2333333...   
2   [[-6.004720476190478, -5.9728666666666665, -5....   
3   [[-6.0231136062221875, -5.991233895031017, -5....   
4   [[-5.889444444444447, -5.889444444444447, -5.9...   
5   [[-5.999808, -5.9491425, -5.5855203, -4.302839...   
6   [[-6.0, -5.949999999999999, -5.975000000000011...   
7   [[-6.089269504883119, -5.771460990233754, -4.4...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-5.969917097529209, -5.973169581141942, -5.7...   
10  [[-6.001815225929926, -5.9370734672332155, -5....   

                                Test Predictions Mean  \
0   [-6.087714552921868, -6.138406846098204, -5.77...   
1   [-6.0, -5.959999999999999, -6.133, -4.732, -6....   
2   [-6.022380190476191, -5.990239428571426, -5.81...   
3   [-6.026414402025165, -6.014515572670147, -5.68...   
4   [-5.951375017783469, -5.974069578766388, -5.82...   
5   [-5.9999094, -5.942426, -5.703902, -4.7131753,...   
6   [-6.0, -5.959999999999999, -6.001586666666664,...   
7   [-6.086221737191485, -5.8037505101404205, -4.8...   
8   [-5.924666666666667, -5.924666666666667, -5.88...   
9   [-5.982014581965722, -5.985191783472696, -5.81...   
10  [-5.989524747975204, -5.962322853796299, -5.61...   

                                 Test Predictions Std  
0   [0.06716214430496417, 0.09403039789805377, 0.0...  
1   [0.08221921916437779, 0.019999999999999928, 0....  
2   [0.04539541659323426, 0.028686512942465988, 0....  
3   [0.05090468091294241, 0.029799270534094414, 0....  
4   [0.05142891320465866, 0.1461814303840214, 0.18...  
5   [0.0819541, 0.014704871, 0.24887095, 0.8196254...  
6   [0.08221921916437555, 0.020000000000000285, 0....  
7   [0.05492017798340823, 0.06268364946015938, 0.7...  
8   [0.05153639490690065, 0.05153639490690065, 0.1...  
9   [0.024096993682865452, 0.023434124028062272, 0...  
10  [0.042858552863258195, 0.043168595977236275, 0...

In [38]:
df_KlekotaRoth_fp.to_csv('results/Fingerprints/Results_KlekotaRoth_fp_RRCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_KlekotaRoth_fp_RRCK.csv')

In [39]:
#KlekotaRoth Count fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/KlekotaRothCount_train_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/KlekotaRothCount_test_RRCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_KlekotaRothCount_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_KlekotaRothCount_fp

X_train shape:  (140, 4860)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 4860)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001474 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 978
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 115
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with p

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't 

-0.5060689921767687


/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.2810                0.4092   
DecisionTreeRegressor                    0.2195                0.3542   
RandomForestRegressor                    0.2301                0.3651   
GradientBoostingRegressor                0.2297                0.3631   
AdaBoostRegressor                        0.2710                0.4200   
XGBRegressor                             0.2117                0.3596   
ExtraTreesRegressor                      0.2296                0.3467   
LinearRegression                         0.6652                0.6279   
KNeighborsRegressor                      0.3672                0.4302   
SVR                                      0.2798                0.3916   
MLPRegressor                             0.8063                0.6154   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.5301               0.3731   
DecisionTreeRegressor                     0.4685               0.5103   
RandomForestRegressor                     0.4797               0.4867   
GradientBoostingRegressor                 0.4793               0.4875   
AdaBoostRegressor                         0.5206               0.3955   
XGBRegressor                              0.4601               0.5278   
ExtraTreesRegressor                       0.4791               0.4879   
LinearRegression                          0.8156              -0.4840   
KNeighborsRegressor                       0.6059               0.1810   
SVR                                       0.5290               0.3758   
MLPRegressor                              0.8979              -0.7986   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.6146                0.6503   
DecisionTreeRegressor                    0.7426                0.7345   
RandomForestRegressor                    0.7108                0.7237   
GradientBoostingRegressor                0.7094                0.7296   
AdaBoostRegressor                        0.6423                0.6612   
XGBRegressor                             0.7355                0.7368   
ExtraTreesRegressor                      0.7085                0.7305   
LinearRegression                         0.3858                0.4361   
KNeighborsRegressor                      0.5326                0.5495   
SVR                                      0.6183                0.6343   
MLPRegressor                             0.2989                0.3509   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4425   0.4843    0.6652   0.3878   
DecisionTreeRegressor       0.2151   0.3537    0.4638   0.7024   
RandomForestRegressor       0.3899   0.4212    0.6244   0.4606   
GradientBoostingRegressor   0.2797   0.3811    0.5289   0.6130   
AdaBoostRegressor           0.4246   0.4771    0.6517   0.4125   
XGBRegressor                0.2844   0.3550    0.5333   0.6066   
ExtraTreesRegressor         0.3636   0.3950    0.6030   0.4970   
LinearRegression            0.9922   0.7263    0.9961  -0.3726   
KNeighborsRegressor         0.5784   0.5507    0.7605   0.1998   
SVR                         0.5265   0.4838    0.7256   0.2716   
MLPRegressor                1.0886   0.7266    1.0434  -0.5061   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.7216                    0.7734  
DecisionTreeRegressor                       0.8769                    0.8547  
RandomForestRegressor                       0.7948                    0.8506  
GradientBoostingRegressor                   0.8309                    0.8340  
AdaBoostRegressor                           0.7854                    0.7922  
XGBRegressor                                0.8429                    0.8671  
ExtraTreesRegressor                         0.775

In [40]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-6.152365028269188, -5.880228473966994, -5.39...   
1   [-6.13, -5.85, -5.08, -5.85, -6.05, -4.0, -5.5...   
2   [-5.983187499999997, -5.860755000000004, -5.10...   
3   [-6.148926619733519, -6.064779248425036, -5.18...   
4   [-6.106428571428572, -5.914482758620689, -5.39...   
5   [-6.552158, -6.0017843, -5.079845, -5.8452153,...   
6   [-6.037799999999996, -6.054500000000006, -5.07...   
7   [-7.72505647150127, -6.176072281030752, -5.679...   
8   [-5.816666666666666, -6.463333333333334, -5.15...   
9   [-5.965903993055895, -5.973780843285969, -5.31...   
10  [-4.0, -5.777974080879052, -5.282643172094314,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-6.152365028269188, -6.152365028269188, -6.3...   
1   [[-5.95, -5.95, -6.22, -6.46, -6.22, -5.08, -6...   
2   [[-6.015487499999998, -5.972319999999999, -6.3...   
3   [[-6.132191573704119, -6.028819205528163, -6.7...   
4   [[-6.103846153846154, -5.970833333333332, -6.4...   
5   [[-6.088332, -5.9509273, -6.5791316, -6.444233...   
6   [[-5.957400000000002, -5.949999999999999, -6.3...   
7   [[-6.0741329519061, -5.857350247147322, -7.105...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-6.022863473027267, -5.9868188323950395, -5....   
10  [[-6.081631997576217, -5.948336843608861, -5.1...   

                                Test Predictions Mean  \
0   [-6.1770176366852265, -6.167559636108885, -6.2...   
1   [-5.97, -5.933999999999999, -6.884, -6.172, -6...   
2   [-6.0709775, -6.061763999999999, -6.2435835714...   
3   [-6.1182403563772585, -6.037239853550033, -6.6...   
4   [-6.18847052947053, -6.116188515406163, -6.356...   
5   [-6.0781803, -6.005694, -6.4812117, -6.29535, ...   
6   [-5.994159999999999, -5.972599999999999, -6.24...   
7   [-6.681030325789566, -5.839376835037964, -6.58...   
8   [-5.924666666666667, -5.924666666666667, -5.76...   
9   [-6.021602941339276, -5.979372992798597, -5.82...   
10  [-6.008465779500499, -5.937802366250139, -5.79...   

                                 Test Predictions Std  
0   [0.11604630767510929, 0.13007760341596117, 0.1...  
1   [0.08579044235810879, 0.03200000000000003, 0.5...  
2   [0.05420036000802919, 0.08568191631843941, 0.1...  
3   [0.017700181803187744, 0.05005084780900712, 0....  
4   [0.08801293849790826, 0.13565161908387485, 0.0...  
5   [0.06692856, 0.11055781, 0.09122321, 0.3989631...  
6   [0.0608133735291828, 0.04520000000000018, 0.11...  
7   [0.9830724082689085, 0.08609001329407302, 0.35...  
8   [0.05153639490690065, 0.05153639490690065, 0.0...  
9   [0.009937980847251091, 0.009221867661003259, 0...  
10  [0.36039237210110686, 0.0486579566412765, 0.52...

In [41]:
df_KlekotaRothCount_fp.to_csv('results/Fingerprints/Results_KlekotaRoth_Count_fp_RRCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_KlekotaRoth_Count_fp_RRCK.csv')

In [42]:
#MACCS fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/MACCS_train_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/MACCS_test_RRCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_MACCS_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_MACCS_fp

X_train shape:  (140, 166)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 166)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.086235 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 57
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 19
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with posit

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't 

-0.6722431171466088


/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.3365                0.4520   
DecisionTreeRegressor                    0.4445                0.4865   
RandomForestRegressor                    0.3484                0.4296   
GradientBoostingRegressor                0.3118                0.4066   
AdaBoostRegressor                        0.3883                0.4980   
XGBRegressor                             0.3958                0.4629   
ExtraTreesRegressor                      0.4108                0.4729   
LinearRegression                         0.5911                0.5924   
KNeighborsRegressor                      0.3880                0.4424   
SVR                                      0.3688                0.4530   
MLPRegressor                             0.8180                0.6599   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.5801               0.2493   
DecisionTreeRegressor                     0.6667               0.0085   
RandomForestRegressor                     0.5903               0.2228   
GradientBoostingRegressor                 0.5584               0.3045   
AdaBoostRegressor                         0.6231               0.1338   
XGBRegressor                              0.6291               0.1171   
ExtraTreesRegressor                       0.6410               0.0835   
LinearRegression                          0.7688              -0.3185   
KNeighborsRegressor                       0.6229               0.1344   
SVR                                       0.6073               0.1773   
MLPRegressor                              0.9044              -0.8246   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.4995                0.4936   
DecisionTreeRegressor                    0.4461                0.4832   
RandomForestRegressor                    0.5125                0.5563   
GradientBoostingRegressor                0.5678                0.5939   
AdaBoostRegressor                        0.3785                0.4077   
XGBRegressor                             0.4873                0.5291   
ExtraTreesRegressor                      0.4695                0.5085   
LinearRegression                         0.3437                0.3969   
KNeighborsRegressor                      0.4704                0.4908   
SVR                                      0.4511                0.4618   
MLPRegressor                             0.1567                0.2339   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.6684   0.5749    0.8176   0.0753   
DecisionTreeRegressor       0.6634   0.5687    0.8145   0.0822   
RandomForestRegressor       0.6177   0.5285    0.7859   0.1454   
GradientBoostingRegressor   0.6131   0.5098    0.7830   0.1518   
AdaBoostRegressor           0.6555   0.5825    0.8096   0.0931   
XGBRegressor                0.6270   0.5429    0.7919   0.1325   
ExtraTreesRegressor         0.6384   0.5504    0.7990   0.1168   
LinearRegression            0.7139   0.6271    0.8449   0.0124   
KNeighborsRegressor         0.5233   0.5177    0.7234   0.2761   
SVR                         0.6398   0.5113    0.7999   0.1149   
MLPRegressor                1.2088   0.7887    1.0994  -0.6722   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4528                    0.4776  
DecisionTreeRegressor                       0.5420                    0.5997  
RandomForestRegressor                       0.5745                    0.6323  
GradientBoostingRegressor                   0.5523                    0.6058  
AdaBoostRegressor                           0.5412                    0.5617  
XGBRegressor                                0.5601                    0.6357  
ExtraTreesRegressor                         0.555

In [43]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.714305257520165, -5.7351627215585195, -5.6...   
1   [-6.0, -6.62, -5.3933333333333335, -6.62, -6.0...   
2   [-5.726783333333334, -6.3171074603174615, -5.3...   
3   [-6.011125206017631, -6.24705565523601, -5.491...   
4   [-5.983684210526315, -5.701931818181817, -5.48...   
5   [-6.0250797, -6.6187816, -5.3933473, -6.618781...   
6   [-6.0, -6.620000000000004, -5.393333333333327,...   
7   [-5.697555622499471, -5.958346317257138, -5.49...   
8   [-5.916666666666667, -5.6000000000000005, -5.3...   
9   [-5.6890735282038225, -5.742176694664073, -5.3...   
10  [-5.272638871613968, -5.913430222869271, -5.61...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.7229386857991065, -5.908164798495146, -5....   
1   [[-6.0, -5.95, -5.924000000000001, -4.915, -5....   
2   [[-5.944150476190478, -5.927961666666665, -5.8...   
3   [[-6.011125206017631, -5.9747449321520785, -5....   
4   [[-5.983684210526315, -5.983684210526315, -6.0...   
5   [[-5.999671, -5.950577, -5.9242854, -4.914399,...   
6   [[-6.0, -5.949999999999999, -5.92399999999999,...   
7   [[-5.996218598601658, -5.957562802796689, -6.0...   
8   [[-5.983333333333333, -5.983333333333333, -6.2...   
9   [[-5.970022752433978, -5.932125605971171, -5.7...   
10  [[-5.94233448474221, -6.091186526698036, -5.91...   

                                Test Predictions Mean  \
0   [-5.758408402046882, -5.8729129281157695, -5.7...   
1   [-6.0, -6.116, -5.8691, -4.946, -5.8691, -5.56...   
2   [-5.999196857142858, -5.929596476190474, -5.88...   
3   [-6.037799406362517, -6.03824610836174, -5.885...   
4   [-5.843443619128466, -5.705415971234392, -5.91...   
5   [-6.0003157, -6.010991, -5.8691444, -4.945909,...   
6   [-6.0, -6.0973599999999974, -5.869099999999994...   
7   [-6.003146048317563, -5.880487546290653, -6.01...   
8   [-6.118666666666667, -6.118666666666667, -6.24...   
9   [-6.011574804811504, -5.954565737367078, -5.74...   
10  [-5.971487659758323, -6.008736399283924, -5.85...   

                                 Test Predictions Std  
0   [0.05326518403918413, 0.0765128527445992, 0.09...  
1   [0.08221921916437779, 0.332, 0.254591515962335...  
2   [0.08005322221322991, 0.028838569044276858, 0....  
3   [0.054443065118369965, 0.15226692707373737, 0....  
4   [0.0984116014353851, 0.16957428376957479, 0.22...  
5   [0.08192728, 0.12242932, 0.2544323, 0.32176912...  
6   [0.08221921916437555, 0.29471999999999704, 0.2...  
7   [0.11616390984851654, 0.1708480014802227, 0.12...  
8   [0.11400974617208051, 0.11400974617208051, 0.0...  
9   [0.035479089298743695, 0.0165812970343375, 0.1...  
10  [0.062255596945280156, 0.08513740533457709, 0....

In [44]:
df_MACCS_fp.to_csv('results/Fingerprints/Results_MACCS_fp_RRCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_MACCS_fp_RRCK.csv')

In [45]:
#PubChem fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/PubChem_train_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/PubChem_test_RRCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_PubChem_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_PubChem_fp

X_train shape:  (140, 881)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 881)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.001062 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 138
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 46
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with posi

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-0.006931325020985701


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.3519                0.4817   
DecisionTreeRegressor                    0.4732                0.5288   
RandomForestRegressor                    0.3976                0.4878   
GradientBoostingRegressor                0.3715                0.4759   
AdaBoostRegressor                        0.3603                0.4820   
XGBRegressor                             0.4473                0.5099   
ExtraTreesRegressor                      0.4566                0.5175   
LinearRegression                         0.4199                0.5261   
KNeighborsRegressor                      0.5113                0.5552   
SVR                                      0.3797                0.4898   
MLPRegressor                             0.9366                0.7280   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.5932               0.2150   
DecisionTreeRegressor                     0.6879              -0.0556   
RandomForestRegressor                     0.6305               0.1131   
GradientBoostingRegressor                 0.6095               0.1712   
AdaBoostRegressor                         0.6003               0.1962   
XGBRegressor                              0.6688               0.0023   
ExtraTreesRegressor                       0.6757              -0.0186   
LinearRegression                          0.6480               0.0633   
KNeighborsRegressor                       0.7150              -0.1405   
SVR                                       0.6162               0.1529   
MLPRegressor                              0.9678              -1.0894   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.4641                0.4516   
DecisionTreeRegressor                    0.3794                0.4040   
RandomForestRegressor                    0.4210                0.4637   
GradientBoostingRegressor                0.4564                0.4703   
AdaBoostRegressor                        0.4506                0.4381   
XGBRegressor                             0.4002                0.4278   
ExtraTreesRegressor                      0.3926                0.4143   
LinearRegression                         0.4038                0.4071   
KNeighborsRegressor                      0.2847                0.2840   
SVR                                      0.4170                0.3994   
MLPRegressor                             0.0200                0.1005   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.6873   0.6070    0.8290   0.0491   
DecisionTreeRegressor       0.5937   0.5448    0.7705   0.1786   
RandomForestRegressor       0.5814   0.5635    0.7625   0.1957   
GradientBoostingRegressor   0.5872   0.5531    0.7663   0.1876   
AdaBoostRegressor           0.6460   0.5951    0.8038   0.1062   
XGBRegressor                0.5746   0.5408    0.7581   0.2050   
ExtraTreesRegressor         0.5988   0.5481    0.7738   0.1717   
LinearRegression            0.7005   0.5771    0.8370   0.0309   
KNeighborsRegressor         0.6487   0.6229    0.8054   0.1026   
SVR                         0.7829   0.5988    0.8848  -0.0831   
MLPRegressor                0.7279   0.6349    0.8531  -0.0069   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4513                    0.5058  
DecisionTreeRegressor                       0.5170                    0.6273  
RandomForestRegressor                       0.5528                    0.6309  
GradientBoostingRegressor                   0.5475                    0.6329  
AdaBoostRegressor                           0.4980                    0.5160  
XGBRegressor                                0.5342                    0.6204  
ExtraTreesRegressor                         0.512

In [46]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.753866958463793, -5.854455918609657, -5.85...   
1   [-6.46, -6.039999999999999, -5.554285714285714...   
2   [-5.976008333333331, -5.970340008325008, -5.58...   
3   [-5.777679540299164, -6.002454654198335, -5.60...   
4   [-5.9513043478260865, -5.9513043478260865, -5....   
5   [-6.1351423, -6.0396934, -5.554266, -6.0396934...   
6   [-6.461849999999999, -6.040000000000003, -5.55...   
7   [-5.7938634263049, -6.040000000000003, -5.7280...   
8   [-5.983333333333333, -6.289999999999999, -5.99...   
9   [-5.722729745617715, -5.555846132110769, -5.46...   
10  [-4.0, -5.8846550274515, -5.699947950554582, -...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.878149226881638, -5.878149226881638, -5.8...   
1   [[-5.983333333333333, -5.983333333333333, -6.0...   
2   [[-5.997853809523812, -5.997853809523812, -5.9...   
3   [[-5.950060603605846, -5.950060603605846, -6.0...   
4   [[-5.9513043478260865, -5.9513043478260865, -5...   
5   [[-5.983199, -5.983199, -6.0396934, -6.460977,...   
6   [[-5.98333333333334, -5.98333333333334, -6.040...   
7   [[-5.983333333333326, -5.983333333333326, -6.0...   
8   [[-5.983333333333333, -5.983333333333333, -6.2...   
9   [[-5.969635125484497, -5.969635125484497, -5.5...   
10  [[-5.985606658032811, -5.985606658032811, -5.8...   

                                Test Predictions Mean  \
0   [-5.923264893294471, -5.923264893294471, -5.79...   
1   [-5.983333333333333, -5.983333333333333, -5.96...   
2   [-5.989216984126985, -5.989216984126985, -5.97...   
3   [-6.0063293107505, -6.0063293107505, -5.920147...   
4   [-5.981022159887798, -5.981022159887798, -5.88...   
5   [-5.9832635, -5.9832635, -5.9684286, -6.274962...   
6   [-5.983333333333337, -5.983333333333337, -5.96...   
7   [-5.983333333333332, -5.983333333333332, -5.94...   
8   [-5.806666666666667, -5.806666666666667, -6.15...   
9   [-5.95779285177184, -5.95779285177184, -5.5661...   
10  [-6.059482045445904, -6.059482045445904, -5.83...   

                                 Test Predictions Std  
0   [0.07177404166900563, 0.07177404166900563, 0.0...  
1   [0.04211096452627664, 0.04211096452627664, 0.0...  
2   [0.018170567574966958, 0.018170567574966958, 0...  
3   [0.04453418056679399, 0.04453418056679399, 0.1...  
4   [0.21863556169254136, 0.21863556169254136, 0.1...  
5   [0.042107865, 0.042107865, 0.095423594, 0.3668...  
6   [0.0421109645262755, 0.0421109645262755, 0.095...  
7   [0.04211096452627161, 0.04211096452627161, 0.0...  
8   [0.14695426348206275, 0.14695426348206275, 0.2...  
9   [0.05884937467876745, 0.05884937467876745, 0.0...  
10  [0.11322377484230711, 0.11322377484230711, 0.1...

In [47]:
df_PubChem_fp.to_csv('results/Fingerprints/Results_PubChem_fp_RRCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_PubChem_fp_RRCK.csv')

In [48]:
#Substructure fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/Substructure_train_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/Substructure_test_RRCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_Substructure_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_Substructure_fp

X_train shape:  (140, 307)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 307)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000216 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 6
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 2
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits w

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't 

-0.2797587211086854


/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.4250                0.5387   
DecisionTreeRegressor                    0.4208                0.5361   
RandomForestRegressor                    0.4129                0.5295   
GradientBoostingRegressor                0.4143                0.5320   
AdaBoostRegressor                        0.3992                0.5176   
XGBRegressor                             0.4224                0.5410   
ExtraTreesRegressor                      0.4190                0.5366   
LinearRegression                         0.4402                0.5435   
KNeighborsRegressor                      0.8065                0.6999   
SVR                                      0.4421                0.5516   
MLPRegressor                             0.8722                0.7211   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.6519               0.0519   
DecisionTreeRegressor                     0.6487               0.0613   
RandomForestRegressor                     0.6426               0.0790   
GradientBoostingRegressor                 0.6436               0.0759   
AdaBoostRegressor                         0.6318               0.1096   
XGBRegressor                              0.6499               0.0577   
ExtraTreesRegressor                       0.6473               0.0653   
LinearRegression                          0.6634               0.0181   
KNeighborsRegressor                       0.8981              -0.7992   
SVR                                       0.6649               0.0139   
MLPRegressor                              0.9339              -0.9457   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.2334                0.1666   
DecisionTreeRegressor                    0.3087                0.2847   
RandomForestRegressor                    0.3117                0.3013   
GradientBoostingRegressor                0.3145                0.2874   
AdaBoostRegressor                        0.3363                0.3266   
XGBRegressor                             0.3031                0.2980   
ExtraTreesRegressor                      0.3111                0.2908   
LinearRegression                         0.2594                0.2699   
KNeighborsRegressor                     -0.0873               -0.0468   
SVR                                      0.2362                0.2501   
MLPRegressor                            -0.0871               -0.0087   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.7419   0.6609    0.8613  -0.0264   
DecisionTreeRegressor       0.6855   0.6412    0.8280   0.0517   
RandomForestRegressor       0.6807   0.6386    0.8251   0.0582   
GradientBoostingRegressor   0.6976   0.6460    0.8353   0.0349   
AdaBoostRegressor           0.7249   0.6583    0.8514  -0.0028   
XGBRegressor                0.6835   0.6332    0.8268   0.0544   
ExtraTreesRegressor         0.6822   0.6364    0.8260   0.0562   
LinearRegression            0.7324   0.6704    0.8558  -0.0132   
KNeighborsRegressor         0.8424   0.7184    0.9178  -0.1654   
SVR                         0.7524   0.6544    0.8674  -0.0409   
MLPRegressor                0.9251   0.7360    0.9618  -0.2798   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4574                    0.5202  
DecisionTreeRegressor                       0.5511                    0.4765  
RandomForestRegressor                       0.5566                    0.4844  
GradientBoostingRegressor                   0.4899                    0.3886  
AdaBoostRegressor                           0.4350                    0.4351  
XGBRegressor                                0.5200                    0.4612  
ExtraTreesRegressor                         0.553

In [49]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.331757615267175, -5.822754608356731, -5.76...   
1   [-5.983333333333333, -6.04, -5.685, -6.04, -5....   
2   [-5.7315751984127, -5.970340008325009, -5.6866...   
3   [-5.764487828854021, -6.011506158998895, -5.69...   
4   [-5.803333333333334, -5.861666666666667, -5.68...   
5   [-5.7749543, -6.039609, -5.6852345, -6.039609,...   
6   [-5.98333333333334, -6.040000000000003, -5.684...   
7   [-4.645333333333331, -6.037526076491041, -5.68...   
8   [-5.53, -6.289999999999999, -5.993333333333333...   
9   [-5.773177325907158, -5.840387052176771, -5.61...   
10  [-4.0, -5.589830143084306, -5.758282207256368,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.331757615267175, -5.331757615267175, -5.8...   
1   [[-5.983333333333333, -5.983333333333333, -6.0...   
2   [[-5.950953809523813, -5.950953809523813, -5.9...   
3   [[-5.96439545084737, -5.96439545084737, -6.011...   
4   [[-5.803333333333334, -5.803333333333334, -5.8...   
5   [[-5.983357, -5.983357, -6.039609, -5.1223154,...   
6   [[-5.98333333333334, -5.98333333333334, -6.040...   
7   [[-5.983333333333331, -5.983333333333331, -6.0...   
8   [[-5.983333333333333, -5.983333333333333, -6.2...   
9   [[-5.9700794763955916, -5.9700794763955916, -5...   
10  [[-6.003071105693502, -6.003071105693502, -5.5...   

                                Test Predictions Mean  \
0   [-5.347479367976341, -5.347479367976341, -5.78...   
1   [-5.983333333333333, -5.983333333333333, -5.96...   
2   [-5.935148515873016, -5.935148515873016, -5.96...   
3   [-5.956764585740325, -5.956764585740325, -5.93...   
4   [-5.979066666666666, -5.979066666666666, -5.84...   
5   [-5.9832067, -5.9832067, -5.968057, -5.1953177...   
6   [-5.983333333333337, -5.983333333333337, -5.96...   
7   [-5.983333333333333, -5.983333333333333, -5.96...   
8   [-5.806666666666667, -5.806666666666667, -6.15...   
9   [-5.957876134059558, -5.957876134059558, -5.80...   
10  [-5.976572757850227, -5.976572757850227, -5.54...   

                                 Test Predictions Std  
0   [0.028872876421998397, 0.028872876421998397, 0...  
1   [0.04211096452627664, 0.04211096452627664, 0.0...  
2   [0.04782697157945389, 0.04782697157945389, 0.0...  
3   [0.05049147911454359, 0.05049147911454359, 0.0...  
4   [0.14132993706611166, 0.14132993706611166, 0.0...  
5   [0.042183686, 0.042183686, 0.09539337, 0.11009...  
6   [0.0421109645262755, 0.0421109645262755, 0.095...  
7   [0.04211096452627709, 0.04211096452627709, 0.0...  
8   [0.14695426348206275, 0.14695426348206275, 0.2...  
9   [0.05886333837942849, 0.05886333837942849, 0.1...  
10  [0.04597420804318838, 0.04597420804318838, 0.1...

In [50]:
df_Substructure_fp.to_csv('results/Fingerprints/Results_Substructure_fp_RRCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_Substructure_fp_RRCK.csv')

In [51]:
#Substructure Count fingerprints
df_train = pd.read_csv('features/Fingerprints/Train/SubstructureCount_train_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Fingerprints/Test/SubstructureCount_test_RRCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
df_SubstructureCount_fp, pred_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
df_SubstructureCount_fp

X_train shape:  (140, 307)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 307)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000291 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 152
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 13
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further split

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't 

-0.35108525340014984


/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/neural_network/_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.3076                0.4464   
DecisionTreeRegressor                    0.4231                0.4820   
RandomForestRegressor                    0.2495                0.3876   
GradientBoostingRegressor                0.2929                0.4182   
AdaBoostRegressor                        0.2884                0.4363   
XGBRegressor                             0.2545                0.3771   
ExtraTreesRegressor                      0.2656                0.3848   
LinearRegression                         0.4224                0.4943   
KNeighborsRegressor                      0.3574                0.4462   
SVR                                      0.3372                0.4432   
MLPRegressor                             0.9578                0.7176   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.5547               0.3137   
DecisionTreeRegressor                     0.6504               0.0563   
RandomForestRegressor                     0.4995               0.4434   
GradientBoostingRegressor                 0.5412               0.3465   
AdaBoostRegressor                         0.5370               0.3567   
XGBRegressor                              0.5045               0.4322   
ExtraTreesRegressor                       0.5153               0.4076   
LinearRegression                          0.6499               0.0578   
KNeighborsRegressor                       0.5979               0.2027   
SVR                                       0.5807               0.2477   
MLPRegressor                              0.9787              -1.1367   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.5620                0.5827   
DecisionTreeRegressor                    0.4961                0.4926   
RandomForestRegressor                    0.6709                0.6956   
GradientBoostingRegressor                0.6059                0.6208   
AdaBoostRegressor                        0.6012                0.6251   
XGBRegressor                             0.6722                0.6765   
ExtraTreesRegressor                      0.6527                0.6754   
LinearRegression                         0.4306                0.4840   
KNeighborsRegressor                      0.5340                0.5692   
SVR                                      0.5189                0.5472   
MLPRegressor                             0.1178                0.1838   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.6537   0.5759    0.8085   0.0957   
DecisionTreeRegressor       0.3684   0.4144    0.6070   0.4903   
RandomForestRegressor       0.4711   0.4611    0.6864   0.3483   
GradientBoostingRegressor   0.3513   0.4074    0.5927   0.5139   
AdaBoostRegressor           0.5285   0.5253    0.7270   0.2688   
XGBRegressor                0.4329   0.4187    0.6579   0.4011   
ExtraTreesRegressor         0.4532   0.4363    0.6732   0.3731   
LinearRegression            0.6415   0.5990    0.8010   0.1125   
KNeighborsRegressor         0.6021   0.5459    0.7759   0.1671   
SVR                         0.6560   0.5876    0.8099   0.0925   
MLPRegressor                0.9766   0.7257    0.9882  -0.3511   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.4875                    0.5324  
DecisionTreeRegressor                       0.7334                    0.7848  
RandomForestRegressor                       0.6801                    0.7202  
GradientBoostingRegressor                   0.7738                    0.8029  
AdaBoostRegressor                           0.6486                    0.7033  
XGBRegressor                                0.6899                    0.7726  
ExtraTreesRegressor                         0.667

In [52]:
pred_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.944464865258419, -5.635052653466851, -5.51...   
1   [-6.13, -5.08, -5.08, -5.4, -6.05, -6.2, -5.57...   
2   [-6.010399999999999, -5.425216031746036, -5.12...   
3   [-5.959694613336954, -5.274320184470579, -5.11...   
4   [-6.057083333333335, -5.713333333333335, -5.31...   
5   [-6.128929, -5.3090863, -5.080198, -5.4003363,...   
6   [-6.047399999999997, -5.539200000000001, -5.07...   
7   [-4.426033202701838, -5.929105145061196, -5.50...   
8   [-5.983333333333333, -5.533333333333334, -5.15...   
9   [-5.905444524254662, -5.772972007201016, -5.39...   
10  [-4.0, -5.309866707651774, -5.201255876223265,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.944464865258419, -5.944464865258419, -5.6...   
1   [[-6.13, -5.95, -6.46, -6.46, -7.48, -5.08, -5...   
2   [[-6.023599999999998, -5.9536, -6.023783333333...   
3   [[-6.00217794382563, -5.9713448596144385, -6.1...   
4   [[-6.057083333333335, -6.057083333333335, -6.0...   
5   [[-5.9565606, -5.9533124, -6.024044, -6.466758...   
6   [[-6.0295999999999985, -5.949999999999999, -5....   
7   [[-6.743472345835985, -6.012766707376365, -6.2...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-5.994128292195161, -5.994709368797728, -6.0...   
10  [[-5.304952448000886, -5.772005074585194, -5.7...   

                                Test Predictions Mean  \
0   [-6.001314772131197, -6.001314772131197, -5.62...   
1   [-6.2, -5.986, -6.117999999999999, -6.41200000...   
2   [-6.107889999999998, -6.0810699999999995, -6.0...   
3   [-6.021231619808823, -6.005497102370802, -6.15...   
4   [-6.1083956140350875, -6.1083956140350875, -6....   
5   [-5.9826574, -5.944065, -5.942799, -6.3996835,...   
6   [-6.034679999999999, -5.976859999999999, -5.87...   
7   [-6.801604983273843, -6.023761848286085, -6.33...   
8   [-5.924666666666667, -5.924666666666667, -5.69...   
9   [-5.991491969725333, -5.987653453328037, -5.96...   
10  [-5.275192317162038, -5.784305351431352, -6.36...   

                                 Test Predictions Std  
0   [0.09468251270009752, 0.09468251270009752, 0.0...  
1   [0.24033310217279685, 0.07199999999999988, 0.4...  
2   [0.049507983194632725, 0.08761111573310829, 0....  
3   [0.06712402227890822, 0.04491198232978034, 0.0...  
4   [0.051692814727876714, 0.051692814727876714, 0...  
5   [0.026419247, 0.01588873, 0.10191754, 0.128357...  
6   [0.044410737440397, 0.053720000000000205, 0.14...  
7   [0.28650014513941713, 0.05504217301855721, 0.1...  
8   [0.05153639490690065, 0.05153639490690065, 0.1...  
9   [0.03180110496156662, 0.030703671806024926, 0....  
10  [0.09640818204425769, 0.03521613682829495, 0.5...

In [53]:
df_SubstructureCount_fp.to_csv('results/Fingerprints/Results_Substructure_Count_fp_RRCK.csv')
pred_df.to_csv('results/Fingerprints/Prediction_data_Substructure_Count_fp_RRCK.csv')

In [94]:
#Descriptors models
#2d RDKit descriptors
df_train = pd.read_csv('features/Descriptors/Train_2d_RDKit_des_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_RDKit_des_RRCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models_2drdkit = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models_2drdkit, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 217)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 217)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000522 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2859
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 117
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spl

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


0.1245769361026926


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.2370                0.3553   
DecisionTreeRegressor                    0.4035                0.4595   
RandomForestRegressor                    0.2195                0.3532   
GradientBoostingRegressor                0.2230                0.3457   
AdaBoostRegressor                        0.2553                0.3935   
XGBRegressor                             0.2335                0.3613   
ExtraTreesRegressor                      0.1947                0.3274   
LinearRegression                         3.2099                1.1820   
KNeighborsRegressor                      0.3124                0.4019   
SVR                                      0.2056                0.3341   
MLPRegressor                             0.7883                0.5870   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4868               0.4713   
DecisionTreeRegressor                     0.6353               0.0998   
RandomForestRegressor                     0.4685               0.5104   
GradientBoostingRegressor                 0.4723               0.5025   
AdaBoostRegressor                         0.5053               0.4304   
XGBRegressor                              0.4832               0.4791   
ExtraTreesRegressor                       0.4412               0.5658   
LinearRegression                          1.7916              -6.1605   
KNeighborsRegressor                       0.5589               0.3032   
SVR                                       0.4534               0.5414   
MLPRegressor                              0.8879              -0.7586   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.6887                0.7113   
DecisionTreeRegressor                    0.5743                0.5936   
RandomForestRegressor                    0.7249                0.7408   
GradientBoostingRegressor                0.7124                0.7188   
AdaBoostRegressor                        0.6704                0.6673   
XGBRegressor                             0.7009                0.7014   
ExtraTreesRegressor                      0.7608                0.7731   
LinearRegression                         0.3155                0.3398   
KNeighborsRegressor                      0.6184                0.6459   
SVR                                      0.7449                0.7628   
MLPRegressor                             0.3141                0.3518   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.5246   0.4760    0.7243   0.2742   
DecisionTreeRegressor       0.3200   0.3850    0.5657   0.5573   
RandomForestRegressor       0.4632   0.4532    0.6806   0.3592   
GradientBoostingRegressor   0.3887   0.4009    0.6235   0.4623   
AdaBoostRegressor           0.5126   0.4873    0.7160   0.2908   
XGBRegressor                0.4798   0.4649    0.6927   0.3362   
ExtraTreesRegressor         0.3913   0.4171    0.6256   0.4586   
LinearRegression            1.0421   0.7823    1.0208  -0.4417   
KNeighborsRegressor         0.4943   0.5017    0.7031   0.3161   
SVR                         0.4234   0.4407    0.6507   0.4142   
MLPRegressor                0.6328   0.5562    0.7955   0.1246   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6220                    0.7254  
DecisionTreeRegressor                       0.7732                    0.7706  
RandomForestRegressor                       0.7093                    0.7482  
GradientBoostingRegressor                   0.7520                    0.8023  
AdaBoostRegressor                           0.7002                    0.7464  
XGBRegressor                                0.6585                    0.6768  
ExtraTreesRegressor                         0.740

In [95]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.93835987288455, -5.762486820527443, -5.244...   
1   [-6.13, -6.46, -5.22, -4.92, -6.15, -4.0, -6.1...   
2   [-6.0016, -5.764133333333333, -5.1121000000000...   
3   [-5.9512253473473615, -5.558338989754418, -5.0...   
4   [-5.9, -5.521836734693875, -5.210875, -5.37524...   
5   [-6.1026864, -5.3469954, -5.0746627, -5.12929,...   
6   [-6.053099999999997, -5.643450000000001, -5.05...   
7   [-4.0, -5.494905840954672, -5.084799965957416,...   
8   [-5.983333333333333, -5.890000000000001, -5.07...   
9   [-6.10967609215014, -5.705788111659985, -5.216...   
10  [-4.0, -5.836066795393169, -5.055885085364734,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-6.348698928507222, -6.159982280669087, -6.0...   
1   [[-6.13, -5.95, -7.48, -6.5, -7.48, -4.72, -6....   
2   [[-6.0619499999999995, -6.023399999999998, -6....   
3   [[-5.978721093957619, -5.9633574814749615, -6....   
4   [[-5.976666666666667, -5.976666666666667, -6.0...   
5   [[-5.789037, -5.9500117, -6.0749774, -5.768519...   
6   [[-6.060299999999997, -5.949999999999999, -6.3...   
7   [[-5.188757338687253, -5.927155234796089, -5.4...   
8   [[-5.983333333333333, -5.983333333333333, -6.3...   
9   [[-6.066532700789061, -5.969497994045415, -6.2...   
10  [[-6.032400305820445, -5.880126055380714, -7.0...   

                                Test Predictions Mean  \
0   [-6.320802528332644, -6.251922628884051, -5.99...   
1   [-6.2299999999999995, -6.052, -6.8580000000000...   
2   [-6.125453190476191, -6.058525714285713, -6.19...   
3   [-6.3160505443908175, -6.003442476614646, -6.4...   
4   [-6.090144081805252, -6.181590090090089, -6.05...   
5   [-6.009329, -6.0117903, -6.089252, -5.234092, ...   
6   [-6.095261333333333, -5.9932799999999995, -6.4...   
7   [-5.991807303864134, -5.553979930527265, -8.40...   
8   [-5.924666666666667, -5.924666666666667, -6.19...   
9   [-6.0900001726033555, -5.968102157911325, -6.1...   
10  [-5.870743160820529, -5.952684961317034, -6.97...   

                                 Test Predictions Std  
0   [0.0371313667093177, 0.06321831468574877, 0.10...  
1   [0.28446440902158565, 0.20399999999999993, 0.7...  
2   [0.0975147506680879, 0.05968811142009827, 0.15...  
3   [0.1955404100609013, 0.0674073215586169, 0.238...  
4   [0.09204693791553567, 0.13389765499980477, 0.1...  
5   [0.211859, 0.12290845, 0.34433013, 0.6226411, ...  
6   [0.07409313459273964, 0.0865599999999997, 0.17...  
7   [2.2472698578631456, 0.7770320298594786, 1.650...  
8   [0.05153639490690065, 0.05153639490690065, 0.1...  
9   [0.02041119487560847, 0.027503661844547247, 0....  
10  [0.3897074075847448, 0.07547849747504547, 1.46...

In [96]:
result_df.to_csv('results/Descriptors/Results_2d_RDKit_desc_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2d_RDKit_desc_RRCK.csv')

In [97]:
#2d Mordred descriptors
df_train = pd.read_csv('features/Descriptors/Train_2d_Mordred_desc_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_Mordred_desc_RRCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = X_test.select_dtypes(include=['number'])
X_test = X_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models_2dM = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df , prediction_df= train_and_test_predict(models_2dM, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 1430)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 1430)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002430 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 38899
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 1111
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.1849                0.3170   
DecisionTreeRegressor                    0.3915                0.4377   
RandomForestRegressor                    0.1818                0.3186   
GradientBoostingRegressor                0.1800                0.3109   
AdaBoostRegressor                        0.2116                0.3606   
XGBRegressor                             0.2262                0.3495   
ExtraTreesRegressor                      0.1733                0.3059   
LinearRegression                         0.7643                0.6221   
KNeighborsRegressor                      0.2873                0.3885   
SVR                                      0.1892                0.3014   
MLPRegressor                             0.7418                0.5830   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4300               0.5876   
DecisionTreeRegressor                     0.6257               0.1267   
RandomForestRegressor                     0.4264               0.5944   
GradientBoostingRegressor                 0.4243               0.5985   
AdaBoostRegressor                         0.4600               0.5279   
XGBRegressor                              0.4756               0.4955   
ExtraTreesRegressor                       0.4162               0.6135   
LinearRegression                          0.8743              -0.7050   
KNeighborsRegressor                       0.5360               0.3592   
SVR                                       0.4349               0.5780   
MLPRegressor                              0.8613              -0.6548   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.7750                0.8056   
DecisionTreeRegressor                    0.5221                0.5477   
RandomForestRegressor                    0.7927                0.8120   
GradientBoostingRegressor                0.7783                0.7897   
AdaBoostRegressor                        0.7408                0.7538   
XGBRegressor                             0.7078                0.7196   
ExtraTreesRegressor                      0.7921                0.8117   
LinearRegression                         0.4778                0.5478   
KNeighborsRegressor                      0.6410                0.6614   
SVR                                      0.7678                0.7889   
MLPRegressor                             0.3519                0.3817   

                          Test MSE Test MAE Test RMSE Test R2  \
LGBMRegressor               0.4376   0.4193    0.6615  0.3946   
DecisionTreeRegressor       0.2967   0.3822    0.5447  0.5895   
RandomForestRegressor       0.4509   0.4470    0.6715  0.3762   
GradientBoostingRegressor   0.3722   0.3998    0.6101  0.4851   
AdaBoostRegressor           0.4802   0.4566    0.6930  0.3356   
XGBRegressor                0.4588   0.4400    0.6774  0.3652   
ExtraTreesRegressor         0.4354   0.4203    0.6598  0.3977   
LinearRegression            0.4260   0.4833    0.6527  0.4107   
KNeighborsRegressor         0.5536   0.4957    0.7440  0.2341   
SVR                         0.4159   0.4107    0.6449  0.4246   
MLPRegressor                0.5989   0.5465    0.7739  0.1714   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.7041                    0.7979  
DecisionTreeRegressor                       0.8008                    0.7920  
RandomForestRegressor                       0.7180                    0.7930  
GradientBoostingRegressor                   0.7508                    0.8230  
AdaBoostRegressor                           0.7030                    0.7752  
XGBRegressor                                0.6773                    0.7516  
ExtraTreesRegressor                         0.7045           

In [98]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.910141696269743, -6.161793987607897, -5.15...   
1   [-5.21, -5.85, -4.72, -5.02, -5.32, -6.46, -5....   
2   [-5.994349999999998, -6.064000000000008, -5.07...   
3   [-6.09884285066795, -6.00455029676722, -4.9890...   
4   [-6.0, -6.191428571428572, -5.1783333333333355...   
5   [-5.910527, -5.9518404, -4.9645486, -5.1917067...   
6   [-6.058599999999999, -6.025200000000002, -4.95...   
7   [-6.028067990745983, -5.426419979973455, -5.35...   
8   [-5.983333333333333, -6.039999999999999, -5.02...   
9   [-6.05043537180491, -5.856851789129326, -5.226...   
10  [-5.350699957390987, -5.917476144678228, -5.05...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.91895199403101, -6.0594222330234695, -6.0...   
1   [[-4.6, -5.95, -7.48, -6.46, -7.48, -4.72, -6....   
2   [[-5.654166666666666, -5.96145, -6.29740000000...   
3   [[-5.477661308181957, -5.958295064354016, -6.5...   
4   [[-6.13, -6.136666666666667, -5.886, -6.01475,...   
5   [[-5.4869833, -5.9503827, -6.074064, -5.76294,...   
6   [[-6.083399999999999, -5.949999999999999, -6.2...   
7   [[-6.98251282097078, -5.950000000000013, -7.60...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-6.037712785994414, -6.027298502190129, -6.0...   
10  [[-6.275056456581941, -5.985582593116003, -6.3...   

                                Test Predictions Mean  \
0   [-6.05603627351805, -6.077932022591685, -6.114...   
1   [-5.918, -5.933999999999999, -6.73799999999999...   
2   [-6.042965833333333, -6.0453899999999985, -6.1...   
3   [-6.00864009521185, -6.032885926086662, -6.303...   
4   [-6.2259932126696835, -6.0760700000000005, -6....   
5   [-5.9810205, -5.944532, -6.0122857, -5.697724,...   
6   [-6.2022900000000005, -6.002979999999999, -6.2...   
7   [-5.652689665055912, -5.863085364244387, -7.46...   
8   [-6.118666666666667, -5.997333333333334, -5.75...   
9   [-6.08354509709049, -6.062131013647689, -5.977...   
10  [-6.2436379683899235, -5.982062941834646, -6.7...   

                                 Test Predictions Std  
0   [0.11070492901527226, 0.09231332670294543, 0.1...  
1   [0.7186765614655874, 0.03200000000000003, 0.74...  
2   [0.2052031476569825, 0.06524620601996699, 0.16...  
3   [0.3187051205024514, 0.15339208394983397, 0.34...  
4   [0.1379009094159843, 0.07838777994333362, 0.08...  
5   [0.33251268, 0.011460449, 0.21454109, 0.251155...  
6   [0.06937457315184002, 0.10595999999999997, 0.2...  
7   [1.168829365029526, 0.17382927151130348, 1.778...  
8   [0.11400974617208051, 0.13330666399946667, 0.0...  
9   [0.04393336812883024, 0.036540383792336824, 0....  
10  [0.19805774972788243, 0.027270413567472937, 0....

In [99]:
result_df.to_csv('results/Descriptors/Results_2d_Mordred_desc_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2d_Mordred_desc_RRCK.csv')

In [100]:
#Removal of constant columns
def remove_constant_columns(df):
    constant_columns = [col for col in df.columns if df[col].nunique() <= 1]
    
    df_cleaned = df.drop(columns=constant_columns)
    
    return df_cleaned, constant_columns

In [101]:
#Low variance column removal
def remove_low_variance_columns(df, threshold=0.005):
    variances = df.var()
    
    low_variance_columns = variances[variances < threshold].index.tolist()
    
    df_cleaned = df.drop(columns=low_variance_columns)
    
    return df_cleaned, low_variance_columns

In [102]:
#2d RDKit descriptors const removal
df_train = pd.read_csv('features/Descriptors/Train_2d_RDKit_des_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train, const_col = remove_constant_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_RDKit_des_RRCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = X_test.drop(const_col,axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 160)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 160)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000487 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2859
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 117
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spl

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


0.19066528570698915


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.2370                0.3553   
DecisionTreeRegressor                    0.4109                0.4679   
RandomForestRegressor                    0.2208                0.3530   
GradientBoostingRegressor                0.2199                0.3472   
AdaBoostRegressor                        0.2665                0.4022   
XGBRegressor                             0.2335                0.3613   
ExtraTreesRegressor                      0.1910                0.3237   
LinearRegression                         3.2099                1.1820   
KNeighborsRegressor                      0.3124                0.4019   
SVR                                      0.2056                0.3341   
MLPRegressor                             0.8475                0.6188   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4868               0.4713   
DecisionTreeRegressor                     0.6410               0.0834   
RandomForestRegressor                     0.4699               0.5075   
GradientBoostingRegressor                 0.4689               0.5095   
AdaBoostRegressor                         0.5163               0.4054   
XGBRegressor                              0.4832               0.4791   
ExtraTreesRegressor                       0.4370               0.5740   
LinearRegression                          1.7916              -6.1605   
KNeighborsRegressor                       0.5589               0.3032   
SVR                                       0.4534               0.5414   
MLPRegressor                              0.9206              -0.8905   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.6887                0.7113   
DecisionTreeRegressor                    0.5841                0.5869   
RandomForestRegressor                    0.7228                0.7400   
GradientBoostingRegressor                0.7176                0.7266   
AdaBoostRegressor                        0.6500                0.6716   
XGBRegressor                             0.7009                0.7014   
ExtraTreesRegressor                      0.7648                0.7719   
LinearRegression                         0.3155                0.3398   
KNeighborsRegressor                      0.6184                0.6459   
SVR                                      0.7449                0.7627   
MLPRegressor                             0.2682                0.3169   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.5246   0.4760    0.7243   0.2742   
DecisionTreeRegressor       0.3413   0.4084    0.5842   0.5279   
RandomForestRegressor       0.4666   0.4531    0.6831   0.3545   
GradientBoostingRegressor   0.3985   0.4039    0.6313   0.4487   
AdaBoostRegressor           0.4792   0.4753    0.6923   0.3370   
XGBRegressor                0.4798   0.4649    0.6927   0.3362   
ExtraTreesRegressor         0.3781   0.4150    0.6149   0.4769   
LinearRegression            1.0421   0.7823    1.0208  -0.4417   
KNeighborsRegressor         0.4943   0.5017    0.7031   0.3161   
SVR                         0.4236   0.4410    0.6509   0.4139   
MLPRegressor                0.5850   0.5599    0.7649   0.1907   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6220                    0.7254  
DecisionTreeRegressor                       0.7582                    0.7754  
RandomForestRegressor                       0.7069                    0.7498  
GradientBoostingRegressor                   0.7435                    0.8027  
AdaBoostRegressor                           0.7252                    0.7552  
XGBRegressor                                0.6585                    0.6768  
ExtraTreesRegressor                         0.750

In [103]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.93835987288455, -5.762486820527443, -5.244...   
1   [-6.13, -6.92, -4.72, -4.92, -6.05, -4.0, -6.0...   
2   [-6.059800000000001, -5.779, -5.10570000000000...   
3   [-5.950203698175421, -5.485281991097383, -5.00...   
4   [-5.830000000000001, -5.653571428571428, -5.26...   
5   [-6.1026864, -5.3469954, -5.0746627, -5.12929,...   
6   [-6.1362, -5.696700000000004, -5.0348000000000...   
7   [-4.0, -5.494905840962645, -5.084799965956051,...   
8   [-5.983333333333333, -5.890000000000001, -5.07...   
9   [-6.109675600467604, -5.70578819712073, -5.216...   
10  [-4.0, -5.773769540823386, -5.069057670508134,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-6.348698928507222, -6.159982280669087, -6.0...   
1   [[-6.13, -5.95, -7.48, -6.46, -7.48, -5.4, -6....   
2   [[-6.1035, -6.023399999999999, -6.188650000000...   
3   [[-6.081467942262058, -5.956408498940884, -6.6...   
4   [[-5.958606557377045, -6.001666666666666, -6.2...   
5   [[-5.789037, -5.9500117, -6.0749774, -5.768519...   
6   [[-6.0559, -5.949999999999999, -6.444600000000...   
7   [[-5.188757338418725, -5.927155234874078, -5.4...   
8   [[-5.983333333333333, -5.983333333333333, -6.3...   
9   [[-6.066532351116907, -5.969497843816715, -6.2...   
10  [[-6.626372854704779, -5.94324074827595, -7.95...   

                                Test Predictions Mean  \
0   [-6.320802528332644, -6.251922628884051, -5.99...   
1   [-6.306, -6.0920000000000005, -6.728, -6.33799...   
2   [-6.1369886904761906, -6.069018333333333, -6.2...   
3   [-6.33020336225544, -5.9964755512598185, -6.32...   
4   [-6.133591796425241, -6.20989090909091, -6.124...   
5   [-6.009329, -6.0117903, -6.089252, -5.234092, ...   
6   [-6.071533333333333, -5.993079999999999, -6.51...   
7   [-5.991807304015241, -5.553979930541504, -8.40...   
8   [-5.924666666666667, -5.924666666666667, -6.19...   
9   [-6.089940263045203, -5.968082768247543, -6.17...   
10  [-6.549665480539938, -6.096567156514998, -7.22...   

                                 Test Predictions Std  
0   [0.0371313667093177, 0.06321831468574877, 0.10...  
1   [0.2964186228967405, 0.284, 0.9344816745126684...  
2   [0.09233705042218272, 0.0649783182642059, 0.16...  
3   [0.1650208991254781, 0.05750759490218278, 0.29...  
4   [0.1504264077553014, 0.1068085567982552, 0.262...  
5   [0.211859, 0.12290845, 0.34433013, 0.6226411, ...  
6   [0.04600661305121625, 0.08615999999999956, 0.2...  
7   [2.2472698579532855, 0.7770320298662645, 1.650...  
8   [0.05153639490690065, 0.05153639490690065, 0.1...  
9   [0.020487311288602424, 0.027527694330146978, 0...  
10  [0.5460579123277922, 0.2592347004748893, 1.591...

In [104]:
result_df.to_csv('results/Descriptors/Results_2d_rdkit_const_rem_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2d_rdkit_const_rem_RRCK.csv')

In [105]:
#2d Mordred descriptors const removal
df_train = pd.read_csv('features/Descriptors/Train_2d_Mordred_desc_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
X_train, const_col = remove_constant_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_Mordred_desc_RRCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = X_test.select_dtypes(include=['number'])
X_test = X_test.drop(const_col,axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models_2dM = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models_2dM, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 1186)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 1186)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.005690 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 38899
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 1111
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.1849                0.3170   
DecisionTreeRegressor                    0.3933                0.4364   
RandomForestRegressor                    0.1860                0.3222   
GradientBoostingRegressor                0.1821                0.3149   
AdaBoostRegressor                        0.2041                0.3555   
XGBRegressor                             0.2262                0.3495   
ExtraTreesRegressor                      0.1667                0.2992   
LinearRegression                         0.7643                0.6221   
KNeighborsRegressor                      0.2757                0.3747   
SVR                                      0.1892                0.3014   
MLPRegressor                             0.8101                0.6195   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4300               0.5876   
DecisionTreeRegressor                     0.6272               0.1226   
RandomForestRegressor                     0.4313               0.5851   
GradientBoostingRegressor                 0.4267               0.5938   
AdaBoostRegressor                         0.4518               0.5447   
XGBRegressor                              0.4756               0.4955   
ExtraTreesRegressor                       0.4083               0.6281   
LinearRegression                          0.8743              -0.7050   
KNeighborsRegressor                       0.5251               0.3850   
SVR                                       0.4349               0.5780   
MLPRegressor                              0.9000              -0.8070   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.7750                0.8056   
DecisionTreeRegressor                    0.5121                0.5311   
RandomForestRegressor                    0.7873                0.8054   
GradientBoostingRegressor                0.7752                0.7904   
AdaBoostRegressor                        0.7571                0.7655   
XGBRegressor                             0.7078                0.7196   
ExtraTreesRegressor                      0.8033                0.8215   
LinearRegression                         0.4778                0.5478   
KNeighborsRegressor                      0.6532                0.6751   
SVR                                      0.7677                0.7889   
MLPRegressor                             0.3410                0.3422   

                          Test MSE Test MAE Test RMSE Test R2  \
LGBMRegressor               0.4376   0.4193    0.6615  0.3946   
DecisionTreeRegressor       0.3496   0.4232    0.5913  0.5163   
RandomForestRegressor       0.4519   0.4471    0.6723  0.3748   
GradientBoostingRegressor   0.3793   0.4050    0.6158  0.4753   
AdaBoostRegressor           0.4695   0.4658    0.6852  0.3505   
XGBRegressor                0.4588   0.4400    0.6774  0.3652   
ExtraTreesRegressor         0.4305   0.4157    0.6562  0.4044   
LinearRegression            0.4260   0.4833    0.6527  0.4107   
KNeighborsRegressor         0.5319   0.4807    0.7293  0.2642   
SVR                         0.4159   0.4107    0.6449  0.4246   
MLPRegressor                0.7011   0.5521    0.8373  0.0300   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.7041                    0.7979  
DecisionTreeRegressor                       0.7697                    0.7598  
RandomForestRegressor                       0.7186                    0.7992  
GradientBoostingRegressor                   0.7473                    0.8160  
AdaBoostRegressor                           0.7292                    0.7852  
XGBRegressor                                0.6773                    0.7516  
ExtraTreesRegressor                         0.7078           

In [106]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.910141696269743, -6.161793987607897, -5.15...   
1   [-5.27, -5.85, -4.96, -5.02, -5.4, -6.46, -5.5...   
2   [-5.982149999999997, -6.063800000000003, -5.12...   
3   [-6.123367042345114, -5.959793107475603, -4.99...   
4   [-6.050000000000001, -6.165428571428572, -5.19...   
5   [-5.910527, -5.9518404, -4.9645486, -5.1917067...   
6   [-6.051399999999998, -5.808100000000004, -4.98...   
7   [-6.028067990745973, -5.4264199799735655, -5.3...   
8   [-5.983333333333333, -6.039999999999999, -5.02...   
9   [-6.050435408053784, -5.856851649250858, -5.22...   
10  [-4.590754289030113, -5.82819741815689, -5.078...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.91895199403101, -6.0594222330234695, -6.0...   
1   [[-4.6, -5.95, -7.48, -6.46, -5.85, -4.96, -6....   
2   [[-5.662833333333333, -5.983850000000001, -6.3...   
3   [[-5.486373418633038, -5.958295064354016, -6.5...   
4   [[-6.111590909090908, -6.017272727272727, -6.1...   
5   [[-5.4869833, -5.9503827, -6.074064, -5.76294,...   
6   [[-6.089849999999999, -5.949999999999999, -6.4...   
7   [[-6.982512820970865, -5.950000000000016, -7.6...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-6.037712829140469, -6.0272985594992665, -6....   
10  [[-6.160968161823005, -6.0589159949929385, -6....   

                                Test Predictions Mean  \
0   [-6.05603627351805, -6.077932022591685, -6.114...   
1   [-6.002000000000001, -5.933999999999999, -6.74...   
2   [-6.023353333333333, -6.055689999999999, -6.09...   
3   [-5.973699818006027, -6.017190649701306, -6.31...   
4   [-6.178018181818181, -6.056378837752109, -6.03...   
5   [-5.9810205, -5.944532, -6.0122857, -5.697724,...   
6   [-6.190266666666667, -5.99142, -6.311750000000...   
7   [-5.652689665056057, -5.863085364244375, -7.46...   
8   [-6.118666666666667, -5.997333333333334, -5.75...   
9   [-6.083501292361208, -6.0620855037124395, -5.9...   
10  [-6.146969396182243, -6.071169499810956, -6.15...   

                                 Test Predictions Std  
0   [0.11070492901527226, 0.09231332670294543, 0.1...  
1   [0.7757937870336422, 0.03200000000000003, 0.63...  
2   [0.19818948996688224, 0.06029200112784414, 0.1...  
3   [0.2979198630293542, 0.12204393959575797, 0.45...  
4   [0.09626257393450458, 0.10060528948648971, 0.1...  
5   [0.33251268, 0.011460449, 0.21454109, 0.251155...  
6   [0.05793824969549737, 0.08284000000000055, 0.1...  
7   [1.1688293650294197, 0.17382927151133237, 1.77...  
8   [0.11400974617208051, 0.13330666399946667, 0.0...  
9   [0.04391504148235846, 0.03655566913657778, 0.0...  
10  [0.1095395854217651, 0.07461267073883161, 0.60...

In [107]:
result_df.to_csv('results/Descriptors/Results_2d_Mordred_const_rem_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_df_2d_Mordred_const_rem_RRCK.csv')

In [108]:
#2d RDKit descriptors LVR
df_train = pd.read_csv('features/Descriptors/Train_2d_RDKit_des_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train, const_col = remove_low_variance_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_RDKit_des_RRCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = X_test.drop(const_col,axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models_LVR_rdkit = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models_LVR_rdkit, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 151)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 151)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000299 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 2523
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 108
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spl

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-0.2262621277749297


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.2452                0.3639   
DecisionTreeRegressor                    0.3452                0.4397   
RandomForestRegressor                    0.2203                0.3515   
GradientBoostingRegressor                0.2266                0.3430   
AdaBoostRegressor                        0.2712                0.4034   
XGBRegressor                             0.2250                0.3612   
ExtraTreesRegressor                      0.1838                0.3210   
LinearRegression                         2.5034                0.9827   
KNeighborsRegressor                      0.3101                0.3955   
SVR                                      0.2111                0.3393   
MLPRegressor                             0.8980                0.6397   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4951               0.4531   
DecisionTreeRegressor                     0.5875               0.2299   
RandomForestRegressor                     0.4694               0.5085   
GradientBoostingRegressor                 0.4761               0.4944   
AdaBoostRegressor                         0.5208               0.3949   
XGBRegressor                              0.4744               0.4980   
ExtraTreesRegressor                       0.4287               0.5901   
LinearRegression                          1.5822              -4.5843   
KNeighborsRegressor                       0.5569               0.3082   
SVR                                       0.4594               0.5292   
MLPRegressor                              0.9476              -1.0033   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.6747                0.6982   
DecisionTreeRegressor                    0.6204                0.6232   
RandomForestRegressor                    0.7237                0.7374   
GradientBoostingRegressor                0.7067                0.7151   
AdaBoostRegressor                        0.6389                0.6588   
XGBRegressor                             0.7143                0.7135   
ExtraTreesRegressor                      0.7765                0.7851   
LinearRegression                         0.3177                0.3847   
KNeighborsRegressor                      0.6163                0.6531   
SVR                                      0.7370                0.7540   
MLPRegressor                             0.2361                0.2698   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4890   0.4767    0.6993   0.3235   
DecisionTreeRegressor       0.3637   0.4106    0.6031   0.4968   
RandomForestRegressor       0.4415   0.4502    0.6645   0.3891   
GradientBoostingRegressor   0.3740   0.3991    0.6116   0.4826   
AdaBoostRegressor           0.4518   0.4686    0.6722   0.3750   
XGBRegressor                0.4300   0.4491    0.6558   0.4051   
ExtraTreesRegressor         0.3853   0.4189    0.6207   0.4670   
LinearRegression            0.8626   0.6234    0.9287  -0.1933   
KNeighborsRegressor         0.4958   0.4984    0.7041   0.3141   
SVR                         0.4244   0.4454    0.6515   0.4128   
MLPRegressor                0.8864   0.6569    0.9415  -0.2263   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6662                    0.7537  
DecisionTreeRegressor                       0.7378                    0.7690  
RandomForestRegressor                       0.7249                    0.7516  
GradientBoostingRegressor                   0.7613                    0.8118  
AdaBoostRegressor                           0.7563                    0.7721  
XGBRegressor                                0.7047                    0.6848  
ExtraTreesRegressor                         0.742

In [109]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.845539719965485, -5.782674456035341, -5.24...   
1   [-6.13, -5.85, -5.22, -4.96, -5.335, -4.0, -5....   
2   [-6.014699999999998, -5.708850000000001, -5.11...   
3   [-5.9292780754812116, -5.417244788096263, -5.0...   
4   [-6.153235294117647, -6.23, -5.382857142857143...   
5   [-6.090651, -5.271743, -4.99249, -5.347108, -5...   
6   [-6.1151, -5.631850000000001, -5.0400000000000...   
7   [-10.0, -5.489937817158172, -5.097898522698841...   
8   [-5.983333333333333, -5.890000000000001, -5.07...   
9   [-6.1029741034208325, -5.702227741023407, -5.2...   
10  [-4.0, -5.618763549664063, -5.052488142647947,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-6.331797070419781, -6.126348515483489, -6.1...   
1   [[-6.13, -5.95, -7.48, -6.46, -7.48, -5.4, -4....   
2   [[-6.0349499999999985, -6.05252857142857, -6.4...   
3   [[-6.049708089975782, -5.972039532934815, -6.6...   
4   [[-5.912631578947368, -6.23, -6.43883720930232...   
5   [[-5.794349, -5.950972, -6.407552, -5.6887646,...   
6   [[-6.100899999999999, -5.949999999999999, -6.4...   
7   [[-4.322694572590507, -5.8981446787330185, -6....   
8   [[-5.983333333333333, -5.983333333333333, -6.3...   
9   [[-6.070823768649641, -5.978907368213092, -6.2...   
10  [[-6.051957701364231, -5.884356487211379, -6.3...   

                                Test Predictions Mean  \
0   [-6.261330418542597, -6.202585219997639, -6.13...   
1   [-6.290000000000001, -6.0920000000000005, -6.7...   
2   [-6.0808505, -6.081905714285712, -6.3542800000...   
3   [-6.2602871564537805, -6.00528483274836, -6.43...   
4   [-6.0741929824561405, -6.19352380952381, -6.29...   
5   [-5.9727006, -5.996957, -6.377507, -5.201325, ...   
6   [-6.0821966666666665, -5.984219999999999, -6.4...   
7   [-5.628798277714884, -5.545863734817898, -8.17...   
8   [-5.924666666666667, -5.924666666666667, -6.19...   
9   [-6.09002197281381, -5.969587374748736, -6.191...   
10  [-6.00801927822493, -5.94585835542918, -5.9839...   

                                 Test Predictions Std  
0   [0.11962600530635428, 0.044499290272702635, 0....  
1   [0.3166701754191576, 0.284, 0.9344816745126684...  
2   [0.05862866416788905, 0.05046412716586148, 0.1...  
3   [0.16618750814625413, 0.06514601868553792, 0.2...  
4   [0.11187465505018472, 0.05110355854678931, 0.0...  
5   [0.09466652, 0.09276803, 0.27976292, 0.6452367...  
6   [0.07326158641774289, 0.06844000000000038, 0.1...  
7   [2.0498866287015742, 0.7731477879100248, 1.033...  
8   [0.05153639490690065, 0.05153639490690065, 0.1...  
9   [0.018909837286720663, 0.022670879132164316, 0...  
10  [0.27472686332666474, 0.04213749806587839, 1.0...

In [110]:
result_df.to_csv('results/Descriptors/Results_2d_rdkit_LVR_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2d_rdkit_LVR_RRCK.csv')

In [111]:
#2d Mordred descriptors LVR
df_train = pd.read_csv('features/Descriptors/Train_2d_Mordred_desc_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
X_train, const_col = remove_low_variance_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_Mordred_desc_RRCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = X_test.select_dtypes(include=['number'])
X_test = X_test.drop(const_col,axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
results_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
results_df

X_train shape:  (140, 852)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 852)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.003454 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 26830
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 783
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further sp

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.2058                0.3360   
DecisionTreeRegressor                    0.3688                0.4425   
RandomForestRegressor                    0.2014                0.3285   
GradientBoostingRegressor                0.2131                0.3373   
AdaBoostRegressor                        0.2339                0.3629   
XGBRegressor                             0.2402                0.3638   
ExtraTreesRegressor                      0.1744                0.3046   
LinearRegression                         1.0250                0.7253   
KNeighborsRegressor                      0.2931                0.3903   
SVR                                      0.2060                0.3185   
MLPRegressor                             0.7740                0.5711   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4537               0.5408   
DecisionTreeRegressor                     0.6073               0.1772   
RandomForestRegressor                     0.4488               0.5508   
GradientBoostingRegressor                 0.4616               0.5247   
AdaBoostRegressor                         0.4836               0.4782   
XGBRegressor                              0.4901               0.4642   
ExtraTreesRegressor                       0.4176               0.6109   
LinearRegression                          1.0124              -1.2864   
KNeighborsRegressor                       0.5414               0.3462   
SVR                                       0.4539               0.5405   
MLPRegressor                              0.8798              -0.7265   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.7412                0.7653   
DecisionTreeRegressor                    0.5424                0.5594   
RandomForestRegressor                    0.7608                0.7796   
GradientBoostingRegressor                0.7271                0.7355   
AdaBoostRegressor                        0.6957                0.7142   
XGBRegressor                             0.6846                0.6902   
ExtraTreesRegressor                      0.7919                0.8128   
LinearRegression                         0.4238                0.4663   
KNeighborsRegressor                      0.6235                0.6601   
SVR                                      0.7411                0.7712   
MLPRegressor                             0.3432                0.3849   

                          Test MSE Test MAE Test RMSE Test R2  \
LGBMRegressor               0.4434   0.4295    0.6659  0.3865   
DecisionTreeRegressor       0.3839   0.4445    0.6196  0.4688   
RandomForestRegressor       0.4641   0.4586    0.6813  0.3579   
GradientBoostingRegressor   0.4081   0.4067    0.6388  0.4355   
AdaBoostRegressor           0.4667   0.4656    0.6832  0.3543   
XGBRegressor                0.4924   0.4419    0.7017  0.3188   
ExtraTreesRegressor         0.4373   0.4242    0.6613  0.3950   
LinearRegression            0.5850   0.5361    0.7649  0.1906   
KNeighborsRegressor         0.5655   0.4978    0.7520  0.2177   
SVR                         0.4466   0.4325    0.6683  0.3821   
MLPRegressor                0.5981   0.5331    0.7734  0.1726   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6952                    0.7804  
DecisionTreeRegressor                       0.7314                    0.7543  
RandomForestRegressor                       0.7004                    0.7656  
GradientBoostingRegressor                   0.7196                    0.7887  
AdaBoostRegressor                           0.7164                    0.7701  
XGBRegressor                                0.6391                    0.7177  
ExtraTreesRegressor                         0.7026           

In [112]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-6.093634008837347, -6.13794839523806, -5.093...   
1   [-6.78, -5.85, -4.96, -5.4, -6.05, -6.49, -5.5...   
2   [-6.019499999999999, -6.046500000000005, -5.07...   
3   [-6.0792922448898725, -6.008668359529459, -4.9...   
4   [-6.1433333333333335, -6.140000000000001, -5.2...   
5   [-6.0197544, -5.763892, -5.1152167, -5.2285433...   
6   [-6.080999999999997, -5.9159500000000005, -4.9...   
7   [-6.795902324133721, -5.372767575496746, -5.48...   
8   [-5.983333333333333, -5.890000000000001, -5.02...   
9   [-6.047027703173879, -5.812193768520956, -5.24...   
10  [-4.0, -6.029191537810755, -5.173368376260485,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.869023607183717, -5.9830588695675075, -6....   
1   [[-4.85, -5.95, -7.48, -6.46, -7.48, -4.72, -6...   
2   [[-5.6323383333333314, -5.999850000000001, -6....   
3   [[-5.546151244669781, -5.9680187484965, -6.355...   
4   [[-5.972173913043478, -6.0649999999999995, -6....   
5   [[-5.6473403, -5.950748, -6.146745, -5.5296054...   
6   [[-6.017049999999999, -5.949999999999999, -6.3...   
7   [[-7.151668633006642, -5.950000000000012, -8.1...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-6.03162723770627, -6.023091935472627, -5.95...   
10  [[-5.9601688745263095, -6.003809139667652, -6....   

                                Test Predictions Mean  \
0   [-5.926783790589573, -6.081498373399899, -6.08...   
1   [-5.814, -5.933999999999999, -6.35, -6.088, -6...   
2   [-6.042284333333332, -6.067059999999999, -6.11...   
3   [-5.920546894150406, -5.991734707053967, -6.22...   
4   [-6.203188410101452, -6.133919254658385, -6.23...   
5   [-5.9843483, -5.9277716, -5.9350777, -5.649126...   
6   [-6.179711999999999, -6.002659999999999, -6.28...   
7   [-5.953250356112609, -5.849747792271744, -8.03...   
8   [-6.118666666666667, -6.134666666666667, -5.92...   
9   [-6.087716870109624, -6.062322945420763, -5.94...   
10  [-6.122419335971783, -6.033368011298853, -6.28...   

                                 Test Predictions Std  
0   [0.13499380262429966, 0.09530227603083953, 0.1...  
1   [0.5840753376063744, 0.03200000000000003, 0.57...  
2   [0.21090203200538446, 0.05596180304457581, 0.1...  
3   [0.22488893221132691, 0.06504708081258444, 0.4...  
4   [0.13556274442733743, 0.06082546838644596, 0.3...  
5   [0.24958701, 0.044840433, 0.15002201, 0.292244...  
6   [0.09659386717592336, 0.10531999999999897, 0.2...  
7   [1.6142557849049197, 0.20050441545651473, 1.58...  
8   [0.11400974617208051, 0.12515945385343025, 0.2...  
9   [0.048509352783831845, 0.039632720263368164, 0...  
10  [0.26586297770199324, 0.02153165042741826, 0.9...

In [113]:
results_df.to_csv('results/Descriptors/Results_2d_Mordred_LVR_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2d_Mordred_LVR_RRCK.csv')

In [114]:
#2d Padel descriptors
df_train = pd.read_csv('features/Descriptors/Train_2d_padel_RRCK.csv')
df_train['ID'] = df_train['Name'].str.extract(r'_(\d+)$')
df_train['ID'] = df_train['ID'].astype(int)
df_train = df_train.drop('Name',axis=1)
df_train = df_train.fillna(0)
df_train

nAcid   ALogP    ALogp2       AMR        apol  naAromAtom  nAromBond  \
0        0 -2.5450  6.477025  193.2906  119.101580           0          0   
1        0 -1.9676  3.871450  190.2914  119.101580           0          0   
2        0  0.2800  0.078400  202.2946  127.250959           0          0   
3        0 -1.3788  1.901089  199.0992  125.288752           0          0   
4        0 -1.2765  1.629452  204.7959  128.382338           0          0   
..     ...     ...       ...       ...         ...         ...        ...   
135      0 -2.3982  5.751363  253.4017  141.852408           0          0   
136      0 -2.2959  5.271157  259.0984  144.945994           0          0   
137      0 -2.1936  4.811881  264.7951  148.039580           0          0   
138      0 -1.7280  2.985984  262.2301  148.226373           0          0   
139      0 -2.5560  6.533136  270.2864  150.419580           0          0   

     nAtom  nHeavyAtom  nH  ...      WTPT-1    WTPT-2     WTPT-3     WTPT-4  \
0      111          51  60  ...  100.950923  1.979430  38.389707  17.922198   
1      111          51  60  ...  100.952062  1.979452  37.702286  17.921964   
2      119          56  63  ...  110.218442  1.968186  42.006878  15.364330   
3      117          53  64  ...  104.584374  1.973290  37.327689  17.880877   
4      120          54  66  ...  106.403540  1.970436  37.505267  17.862423   
..     ...         ...  ..  ...         ...       ...        ...        ...   
135    121          65  56  ...  133.210563  2.049393  43.712429  15.474678   
136    124          66  58  ...  135.026472  2.045856  43.876374  15.452959   
137    127          67  60  ...  136.842632  2.042427  44.044180  15.431464   
138    128          67  61  ...  137.323641  2.049607  37.713596  15.473904   
139    129          69  60  ...  142.106575  2.059516  40.853520  15.481971   

        WTPT-5    WPATH   WPOL  XLogP  Zagreb    ID  
0    20.467508   9274.0   80.0  1.183   254.0  1040  
1    19.780322   9274.0   80.0  3.523   254.0  1039  
2    19.497913  11674.0   94.0  6.461   284.0  1042  
3    19.446812   9956.0   88.0  4.667   266.0  1034  
4    19.642844  10348.0   92.0  4.380   272.0  1032  
..         ...      ...    ...    ...     ...   ...  
135  25.255779  18261.0   99.0  5.308   332.0  1851  
136  25.442427  18776.0  103.0  5.021   338.0  1860  
137  25.631764  19280.0  107.0  4.734   344.0  1861  
138  22.239692  19914.0  103.0  6.777   340.0  1850  
139  25.371548  21217.0  109.0  5.760   358.0  1848  

[140 rows x 1445 columns]

In [115]:
df = pd.read_csv('features/Descriptors/Train_2d_Mordred_desc_RRCK.csv')
df 


ID                                             SMILES  Permeability  \
0    2358  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](C(...         -6.13   
1    2359  C/C=C/C[C@@H](C)C(=O)[C@H]1C(=O)N[C@@H](C(C)C)...         -6.66   
2    2357  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...         -5.95   
3    2360  C/C=C/C[C@@H](C)[C@H]1OC(=O)[C@H](C(C)C)N(C)C(...         -6.78   
4    2353  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](C)...         -5.87   
..    ...                                                ...           ...   
135  2336  CC[C@@H]1NC(=O)[C@@H](CC)NC(=O)[C@H](CC(C)C)NC...         -5.39   
136  2306  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...         -4.75   
137  2334  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...         -5.58   
138  2305  CCC[C@@H]1C(=O)N(C)[C@@H](C)C(=O)N[C@@H](CC(C)...         -4.85   
139  2304  CC[C@@H]1C(=O)N(C)[C@@H](C)C(=O)N[C@@H](CC(C)C...         -5.51   

                                              ABCIndex  \
0    module 'numpy' has no attribute 'float'.\n`np....   
1    module 'numpy' has no attribute 'float'.\n`np....   
2    module 'numpy' has no attribute 'float'.\n`np....   
3    module 'numpy' has no attribute 'float'.\n`np....   
4    module 'numpy' has no attribute 'float'.\n`np....   
..                                                 ...   
135  module 'numpy' has no attribute 'float'.\n`np....   
136  module 'numpy' has no attribute 'float'.\n`np....   
137  module 'numpy' has no attribute 'float'.\n`np....   
138  module 'numpy' has no attribute 'float'.\n`np....   
139  module 'numpy' has no attribute 'float'.\n`np....   

                                            ABCGGIndex  AcidicGroupCount  \
0    module 'numpy' has no attribute 'float'.\n`np....                 0   
1    module 'numpy' has no attribute 'float'.\n`np....                 0   
2    module 'numpy' has no attribute 'float'.\n`np....                 0   
3    module 'numpy' has no attribute 'float'.\n`np....                 0   
4    module 'numpy' has no attribute 'float'.\n`np....                 0   
..                                                 ...               ...   
135  module 'numpy' has no attribute 'float'.\n`np....                 0   
136  module 'numpy' has no attribute 'float'.\n`np....                 0   
137  module 'numpy' has no attribute 'float'.\n`np....                 0   
138  module 'numpy' has no attribute 'float'.\n`np....                 0   
139  module 'numpy' has no attribute 'float'.\n`np....                 0   

     BasicGroupCount  AdjacencyMatrix  AdjacencyMatrix.1  AdjacencyMatrix.2  \
0                  0       100.888651           2.446436           4.892748   
1                  0       100.888651           2.446436           4.892748   
2                  0       100.134733           2.444935           4.889759   
3                  1       100.268636           2.427280           4.854560   
4                  0        98.550044           2.444219           4.888335   
..               ...              ...                ...                ...   
135                0        56.766056           2.420826           4.789951   
136                0        52.776707           2.440186           4.848090   
137                0        53.640751           2.419606           4.784653   
138                0        52.045329           2.439503           4.844153   
139                0        50.591075           2.439146           4.842060   

     ...  WalkCount.19  WalkCount.20       Weight  Weight.1  WienerIndex  \
0    ...     11.228478    126.484444  1215.857018  6.109834        38268   
1    ...     11.228478    126.484444  1213.841368  6.161631        38268   
2    ...     11.208585    125.402718  1201.841368  6.131844        37337   
3    ...     11.184019    125.341576  1201.841368  6.131844        37826   
4    ...     11.198475    124.353468  1187.825718  6.154537        36408   
..   ...           ...           ...          ...      

In [116]:
merged_df = df_train.merge(df[['ID', 'SMILES', 'Permeability']], on='ID', how='left')
merged_df = merged_df[['ID', 'SMILES', 'Permeability'] + [col for col in merged_df.columns if col not in ['ID', 'SMILES', 'Permeability']]]
merged_df

ID                                             SMILES  Permeability  \
0    1040  CC(C)CN1CC(=O)N(CC(C)C)CC(=O)N(CC(C)C)CC(=O)N2...         -6.40   
1    1039  CC(C)C[C@@H]1NC(=O)CN(Cc2ccc(O)cc2)C(=O)[C@H]2...         -5.54   
2    1042  CC(C)C[C@@H]1NC(=O)CN(Cc2cccc(C(F)(F)F)c2)C(=O...         -6.00   
3    1034  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...         -5.51   
4    1032  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@@H...         -5.26   
..    ...                                                ...           ...   
135  1851  O=C1CN(CCCc2ccccc2)C(=O)[C@H]2CCCN2C(=O)[C@H](...         -6.15   
136  1860  CN1C(=O)[C@@H](Cc2ccccc2)NC(=O)[C@H](CCCc2cccc...         -5.57   
137  1861  CN1C(=O)[C@@H](Cc2ccccc2)N(C)C(=O)[C@H](CCCc2c...         -5.40   
138  1850  O=C1CN(CCCc2ccccc2)C(=O)[C@H]2CCCN2C(=O)[C@H](...         -5.74   
139  1848  O=C1CN(CCCc2ccccc2)C(=O)[C@H]2CCCN2C(=O)[C@H](...         -6.05   

     nAcid   ALogP    ALogp2       AMR        apol  naAromAtom  nAromBond  \
0        0 -2.5450  6.477025  193.2906  119.101580           0          0   
1        0 -1.9676  3.871450  190.2914  119.101580           0          0   
2        0  0.2800  0.078400  202.2946  127.250959           0          0   
3        0 -1.3788  1.901089  199.0992  125.288752           0          0   
4        0 -1.2765  1.629452  204.7959  128.382338           0          0   
..     ...     ...       ...       ...         ...         ...        ...   
135      0 -2.3982  5.751363  253.4017  141.852408           0          0   
136      0 -2.2959  5.271157  259.0984  144.945994           0          0   
137      0 -2.1936  4.811881  264.7951  148.039580           0          0   
138      0 -1.7280  2.985984  262.2301  148.226373           0          0   
139      0 -2.5560  6.533136  270.2864  150.419580           0          0   

     ...       AMW      WTPT-1    WTPT-2     WTPT-3     WTPT-4     WTPT-5  \
0    ...  6.418490  100.950923  1.979430  38.389707  17.922198  20.467508   
1    ...  6.418490  100.952062  1.979452  37.702286  17.921964  19.780322   
2    ...  6.659463  110.218442  1.968186  42.006878  15.364330  19.497913   
3    ...  6.328920  104.584374  1.973290  37.327689  17.880877  19.446812   
4    ...  6.287494  106.403540  1.970436  37.505267  17.862423  19.642844   
..   ...       ...         ...       ...        ...        ...        ...   
135  ...  7.408300  133.210563  2.049393  43.712429  15.474678  25.255779   
136  ...  7.342097  135.026472  2.045856  43.876374  15.452959  25.442427   
137  ...  7.279021  136.842632  2.042427  44.044180  15.431464  25.631764   
138  ...  7.058346  137.323641  2.049607  37.713596  15.473904  22.239692   
139  ...  7.197392  142.106575  2.059516  40.853520  15.481971  25.371548   

       WPATH   WPOL  XLogP  Zagreb  
0     9274.0   80.0  1.183   254.0  
1     9274.0   80.0  3.523   254.0  
2    11674.0   94.0  6.461   284.0  
3     9956.0   88.0  4.667   266.0  
4    10348.0   92.0  4.380   272.0  
..       ...    ...    ...     ...  
135  18261.0   99.0  5.308   332.0  
136  18776.0  103.0  5.021   338.0  
137  19280.0  107.0  4.734   344.0  
138  19914.0  103.0  6.777   340.0  
139  21217.0  109.0  5.760   358.0  

[140 rows x 1447 columns]

In [117]:
df_ordered = merged_df.merge(df[['ID']], on='ID', how='right')
df_ordered = df_ordered.reindex(df.index)
df_ordered

ID                                             SMILES  Permeability  \
0    2358  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](C(...         -6.13   
1    2359  C/C=C/C[C@@H](C)C(=O)[C@H]1C(=O)N[C@@H](C(C)C)...         -6.66   
2    2357  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...         -5.95   
3    2360  C/C=C/C[C@@H](C)[C@H]1OC(=O)[C@H](C(C)C)N(C)C(...         -6.78   
4    2353  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](C)...         -5.87   
..    ...                                                ...           ...   
135  2336  CC[C@@H]1NC(=O)[C@@H](CC)NC(=O)[C@H](CC(C)C)NC...         -5.39   
136  2306  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...         -4.75   
137  2334  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...         -5.58   
138  2305  CCC[C@@H]1C(=O)N(C)[C@@H](C)C(=O)N[C@@H](CC(C)...         -4.85   
139  2304  CC[C@@H]1C(=O)N(C)[C@@H](C)C(=O)N[C@@H](CC(C)C...         -5.51   

     nAcid   ALogP     ALogp2       AMR        apol  naAromAtom  nAromBond  \
0        0 -2.3118   5.344419  324.4169  207.951609           0          0   
1        0 -1.9035   3.623312  324.6192  206.618023           0          0   
2        0 -3.1214   9.743138  318.9594  204.858023           0          0   
3        0 -2.5378   6.440429  318.5450  204.858023           0          0   
4        0 -2.8334   8.028156  316.0478  201.764437           0          0   
..     ...     ...        ...       ...         ...         ...        ...   
135      0 -2.8620   8.191044  164.7821  105.925236           0          0   
136      0 -2.4208   5.860273  160.1675  105.072408           0          0   
137      0 -2.2860   5.225796  158.9589   99.738064           0          0   
138      0 -3.7740  14.243076  153.1698  101.978822           0          0   
139      0 -3.4860  12.152196  150.2582   98.885236           0          0   

     ...       AMW      WTPT-1    WTPT-2     WTPT-3     WTPT-4     WTPT-5  \
0    ...  6.109834  165.660911  1.926290  64.869552  30.340460  34.529092   
1    ...  6.161631  165.660911  1.926290  64.869552  30.340460  34.529092   
2    ...  6.131844  163.824465  1.927347  64.851242  30.333765  34.517477   
3    ...  6.131844  164.030378  1.929769  64.941671  30.873015  34.068656   
4    ...  6.154537  161.805840  1.926260  64.748500  30.296198  34.452302   
..   ...       ...         ...       ...        ...        ...        ...   
135  ...  6.534641   91.402117  1.987003  33.999411  15.357748  18.641663   
136  ...  6.204261   85.761816  1.949132  34.302616  15.219294  19.083322   
137  ...  6.656125   87.363105  1.985525  33.788693  15.284672  18.504021   
138  ...  6.251654   83.927240  1.951796  34.294802  15.216440  19.078362   
139  ...  6.302073   81.919106  1.950455  34.250954  15.200426  19.050528   

       WPATH   WPOL  XLogP  Zagreb  
0    38268.0  152.0  8.704   418.0  
1    38268.0  152.0  7.824   418.0  
2    37337.0  150.0  8.407   412.0  
3    37826.0  148.0  8.690   410.0  
4    36408.0  148.0  8.049   408.0  
..       ...    ...    ...     ...  
135   7064.0   74.0  5.393   228.0  
136   6071.0   77.0  4.002   220.0  
137   6341.0   70.0  4.677   220.0  
138   5725.0   76.0  3.494   214.0  
139   5381.0   75.0  2.925   210.0  

[140 rows x 1447 columns]

In [118]:
df_ordered.to_csv('features/Descriptors/Train_2d_padel_curated_RRCK.csv', index=False)

In [119]:
#2d test padel descriptors
df_test = pd.read_csv('features/Descriptors/Test_2d_padel_RRCK.csv')
df_test['ID'] = df_test['Name'].str.extract(r'_(\d+)$')
df_test['ID'] = df_test['ID'].astype(int)
df_test = df_test.drop('Name',axis=1)
df_test = df_test.fillna(0)
df_test

nAcid    ALogP      ALogp2       AMR        apol  naAromAtom  nAromBond  \
0       0  -3.1980   10.227204  147.3466   95.791650           0          0   
1       0  -2.2671    5.139742  178.9606  112.112408           0          0   
2       0  -1.2947    1.676248  186.2062  119.101580           0          0   
3       0  -1.5766    2.485668  194.4885  122.195166           0          0   
4       0  -1.2947    1.676248  186.2062  119.101580           0          0   
5       0  -2.5740    6.625476  161.8705  102.831650           0          0   
6       0  -2.8302    8.010032  180.5661  112.914408           0          0   
7       0  -5.1686   26.714426  208.1255  124.665580           0          0   
8       0  -9.7766   95.581908  254.7111  174.162956           0          0   
9       0  -1.2019    1.444564  188.8699  118.299580           0          0   
10      0  -2.0598    4.242776  259.4091  161.788612           0          0   
11      0  -7.2469   52.517560  245.0432  153.743061           0          0   
12      0 -10.9909  120.799883  282.8940  193.959679           0          0   
13      0  -1.9634    3.854940  190.7741  126.246752           0          0   
14      0  -2.2650    5.130225  191.8535  119.903580           0          0   
15      0  -3.0917    9.558609  216.9864  130.470373           0          0   
16      0  -2.2757    5.178810  196.4379  122.997166           0          0   
17      0  -1.9196    3.684864  201.9223  128.382338           0          0   
18      0  -3.3441   11.183005  322.0103  205.660023           0          0   
19      0  -4.5484   20.687943  189.9498  131.100338           0          0   
20      0  -5.1115   26.127432  191.5553  131.902338           0          0   
21      0  -6.8641   47.115869  187.9268  126.861959           0          0   
22      0  -2.9203    8.528152  213.2577  138.096303           0          0   
23      0  -1.8728    3.507380  245.6888  143.697545           0          0   
24      0  -1.7182    2.952211  234.2419  134.416787           0          0   
25      0  -1.1966    1.431852  242.6110  140.603959           0          0   
26      0  -3.2571   10.608700  214.7266  137.564717           0          0   
27      0  -1.2947    1.676248  186.2062  119.101580           0          0   
28      0  -5.5059   30.314935  177.5106  115.107615           0          0   
29      0  -9.7664   95.382569  255.8125  175.736163           0          0   
30      0  -1.6048    2.575383  206.9829  137.612268           0          0   
31      0  -1.6048    2.575383  206.9829  137.612268           0          0   
32      0  -3.1214    9.743138  318.9594  204.858023           0          0   
33      0  -0.2147    0.046096  211.0718  138.570268           0          0   
34      0  -0.1663    0.027656  240.8474  135.809822           0          0   
35      0  -2.0160    4.064256  265.1417  151.319959           0          0   

    nAtom  nHeavyAtom   nH  ...      WTPT-1    WTPT-2     WTPT-3     WTPT-4  \
0      91          41   50  ...   79.902837  1.948850  34.163259  15.168400   
1     104          48   56  ...   94.840191  1.975837  34.452790  15.271386   
2     111          51   60  ...  100.950923  1.979430  36.643890  17.922198   
3     114          52   62  ...  102.770477  1.976355  37.538804  17.903031   
4     111          51   60  ...  100.950923  1.979430  36.643890  17.922198   
5      95          45   50  ...   89.382185  1.986271  33.894145  15.321219   
6     105          49   56  ...   96.698242  1.973434  36.974399  17.792362   
7     116          56   60  ...  109.523983  1.955785  48.253608  22.597529   
8     164          72   92  ...  141.688270  1.967893  49.102754  22.908473   
9     110          50   60  ...   98.681938  1.973639  34.501384  15.289963   
10    152          68   84  ...  132.962740  1.955334  48.807355  22.800364   
11    144          67   77  ...  131.063020  1.956164  54.288367  25.229170   
12    183          80  103  ...  157.176722  1.964709

In [120]:
df = pd.read_csv('features/Descriptors/Test_2d_Mordred_desc_RRCK.csv')
df

ID                                             SMILES  Permeability  \
0   2352  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H]([C...        -6.340   
1   5669  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...        -5.760   
2   1881  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
3   5666  CCCC[C@@H]1NC(=O)[C@H](CCCC)NC(=O)[C@H](CCCC)N...        -6.460   
4   1877  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
5   1873  CC(C)C[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N2CCC[C...        -4.620   
6   1878  CCC[C@H]1C(=O)N(C)[C@H](CC)C(=O)N(C)[C@@H](C)C...        -7.300   
7   1849  O=C1CN(CCCc2ccccc2)C(=O)[C@H]2CCCN2C(=O)[C@H](...        -5.920   
8   1856  CC(C)(C)C[C@@H]1NC(=O)[C@@H](Cc2ccccc2)NC(=O)[...        -5.120   
9   2367  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.930   
10  2369  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)NC(=O)[C@H](Cc2...        -6.660   
11  2370  CC(C)C[C@@H]1NC(=O)[C@H](C)NC(=O)[C@H](Cc2ccc(...        -6.230   
12    45  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.840   
13    44  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.150   
14  2373  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.340   
15   970  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)N(C)C(=O)[C@H...        -5.700   
16   966  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...        -6.000   
17   979  C/C1=C\[C@@H](CC(C)C)NC(=O)[C@@H]2CCCN2C(=O)[C...        -5.000   
18  1867  C[C@H]1C(=O)N(C)[C@H](C)C(=O)N(C)[C@H](C)C(=O)...        -7.640   
19  2350  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.860   
20  5642  CCCC[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)CSC[C@@...        -5.900   
21  2342  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.460   
22    35  CC[C@H](C)[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC...        -5.490   
23    34  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.330   
24  2340  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...        -5.020   
25    31  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.120   
26  1037  CC(C)C[C@@H]1NC(=O)CN(Cc2ccc(O)cc2)C(=O)[C@H]2...        -5.140   
27  5674  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...        -5.805   
28  2295  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@@H](...        -6.440   
29  2300  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...        -5.550   
30   928  CC[C@H](C)[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@H](...        -6.220   
31  2312  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...        -4.640   
32  2323  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -5.350   
33  2308  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -4.620   
34  2335  CC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2cccc...        -5.530   
35  2303  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...        -5.310   

                                             ABCIndex  \
0   module 'numpy' has no attribute 'float'.\n`np....   
1   module 'numpy' has no attribute 'float'.\n`np....   
2   module 'numpy' has no attribute 'float'.\n`np....   
3   module 'numpy' has no attribute 'float'.\n`np....   
4   module 'numpy' has no attribute 'float'.\n`np....   
5   module 'numpy' has no attribute 'float'.\n`np....   
6   module 'numpy' has no attribute 'float'.\n`np....   
7   module 'numpy' has no attribute 'float'.\n`np....   
8   module 'numpy' has no attribute 'float'.\n`np....   
9   module 'numpy' has no attribute 'float'.\n`np....   
10  module 'numpy' has no attribute 'float'.\n`np....   
11  module 'numpy' has no attribute 'float'.\n`np....   
12  module 'numpy' has no attribute 'float'.\n`np....   
13  module 'numpy' has no attribute 'float'.\n`np....   
14  module 'numpy' has no attribute 'float'.\n`np....   
15  module 'numpy' has no attribute 'float'.\n`np....   
16  module 'numpy' has no attribute 'float'.\n`np....   
17  module 'numpy' has no attribute 'float'.\n`np....   
18  module 'numpy' has no attribute 'float'.\n`np....   
19  module 'nump

In [121]:
merged_df = df_test.merge(df[['ID', 'SMILES', 'Permeability']], on='ID', how='left')
merged_df = merged_df[['ID', 'SMILES', 'Permeability'] + [col for col in merged_df.columns if col not in ['ID', 'SMILES', 'Permeability']]]
merged_df

ID                                             SMILES  Permeability  \
0   2303  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...        -5.310   
1   2308  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -4.620   
2   2295  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@@H](...        -6.440   
3   1037  CC(C)C[C@@H]1NC(=O)CN(Cc2ccc(O)cc2)C(=O)[C@H]2...        -5.140   
4   2300  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...        -5.550   
5   2335  CC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2cccc...        -5.530   
6   2323  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -5.350   
7   1867  C[C@H]1C(=O)N(C)[C@H](C)C(=O)N(C)[C@H](C)C(=O)...        -7.640   
8   1877  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
9   2312  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...        -4.640   
10  1873  CC(C)C[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N2CCC[C...        -4.620   
11  1878  CCC[C@H]1C(=O)N(C)[C@H](CC)C(=O)N(C)[C@@H](C)C...        -7.300   
12  1881  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
13  2340  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...        -5.020   
14    31  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.120   
15  2373  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.340   
16    34  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.330   
17    35  CC[C@H](C)[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC...        -5.490   
18  2352  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H]([C...        -6.340   
19  2342  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.460   
20  2350  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.860   
21  5642  CCCC[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)CSC[C@@...        -5.900   
22    44  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.150   
23  2367  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.930   
24  2370  CC(C)C[C@@H]1NC(=O)[C@H](C)NC(=O)[C@H](Cc2ccc(...        -6.230   
25  2369  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)NC(=O)[C@H](Cc2...        -6.660   
26    45  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.840   
27  5674  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...        -5.805   
28   928  CC[C@H](C)[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@H](...        -6.220   
29  5666  CCCC[C@@H]1NC(=O)[C@H](CCCC)NC(=O)[C@H](CCCC)N...        -6.460   
30   966  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...        -6.000   
31   970  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)N(C)C(=O)[C@H...        -5.700   
32  5669  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...        -5.760   
33   979  C/C1=C\[C@@H](CC(C)C)NC(=O)[C@@H]2CCCN2C(=O)[C...        -5.000   
34  1856  CC(C)(C)C[C@@H]1NC(=O)[C@@H](Cc2ccccc2)NC(=O)[...        -5.120   
35  1849  O=C1CN(CCCc2ccccc2)C(=O)[C@H]2CCCN2C(=O)[C@H](...        -5.920   

    nAcid    ALogP      ALogp2       AMR        apol  naAromAtom  nAromBond  \
0       0  -3.1980   10.227204  147.3466   95.791650           0          0   
1       0  -2.2671    5.139742  178.9606  112.112408           0          0   
2       0  -1.2947    1.676248  186.2062  119.101580           0          0   
3       0  -1.5766    2.485668  194.4885  122.195166           0          0   
4       0  -1.2947    1.676248  186.2062  119.101580           0          0   
5       0  -2.5740    6.625476  161.8705  102.831650           0          0   
6       0  -2.8302    8.010032  180.5661  112.914408           0          0   
7       0  -5.1686   26.714426  208.1255  124.665580           0          0   
8       0  -9.7766   95.581908  254.7111  174.162956           0          0   
9       0  -1.2019    1.444564  188.8699  118.299580           0          0   
10      0  -2.0598    4.242776  259.4091  161.788612           0          0   
11      0  -7.2469   52.517560  245.0432  153.743061           0          0   
12      0 -10.9909  120.799883  282.8940  193.959679           0          0   
13      0  -1.9634    3.854940  190.7741  126.2467

In [122]:
df_ordered = merged_df.merge(df[['ID']], on='ID', how='right')
df_ordered = df_ordered.reindex(df.index)
df_ordered

ID                                             SMILES  Permeability  \
0   2352  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H]([C...        -6.340   
1   5669  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...        -5.760   
2   1881  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
3   5666  CCCC[C@@H]1NC(=O)[C@H](CCCC)NC(=O)[C@H](CCCC)N...        -6.460   
4   1877  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
5   1873  CC(C)C[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N2CCC[C...        -4.620   
6   1878  CCC[C@H]1C(=O)N(C)[C@H](CC)C(=O)N(C)[C@@H](C)C...        -7.300   
7   1849  O=C1CN(CCCc2ccccc2)C(=O)[C@H]2CCCN2C(=O)[C@H](...        -5.920   
8   1856  CC(C)(C)C[C@@H]1NC(=O)[C@@H](Cc2ccccc2)NC(=O)[...        -5.120   
9   2367  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.930   
10  2369  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)NC(=O)[C@H](Cc2...        -6.660   
11  2370  CC(C)C[C@@H]1NC(=O)[C@H](C)NC(=O)[C@H](Cc2ccc(...        -6.230   
12    45  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.840   
13    44  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.150   
14  2373  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.340   
15   970  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)N(C)C(=O)[C@H...        -5.700   
16   966  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...        -6.000   
17   979  C/C1=C\[C@@H](CC(C)C)NC(=O)[C@@H]2CCCN2C(=O)[C...        -5.000   
18  1867  C[C@H]1C(=O)N(C)[C@H](C)C(=O)N(C)[C@H](C)C(=O)...        -7.640   
19  2350  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.860   
20  5642  CCCC[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)CSC[C@@...        -5.900   
21  2342  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.460   
22    35  CC[C@H](C)[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC...        -5.490   
23    34  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.330   
24  2340  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...        -5.020   
25    31  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.120   
26  1037  CC(C)C[C@@H]1NC(=O)CN(Cc2ccc(O)cc2)C(=O)[C@H]2...        -5.140   
27  5674  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...        -5.805   
28  2295  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@@H](...        -6.440   
29  2300  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...        -5.550   
30   928  CC[C@H](C)[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@H](...        -6.220   
31  2312  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...        -4.640   
32  2323  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -5.350   
33  2308  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -4.620   
34  2335  CC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2cccc...        -5.530   
35  2303  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...        -5.310   

    nAcid    ALogP      ALogp2       AMR        apol  naAromAtom  nAromBond  \
0       0  -3.3441   11.183005  322.0103  205.660023           0          0   
1       0  -3.1214    9.743138  318.9594  204.858023           0          0   
2       0 -10.9909  120.799883  282.8940  193.959679           0          0   
3       0  -9.7664   95.382569  255.8125  175.736163           0          0   
4       0  -9.7766   95.581908  254.7111  174.162956           0          0   
5       0  -2.0598    4.242776  259.4091  161.788612           0          0   
6       0  -7.2469   52.517560  245.0432  153.743061           0          0   
7       0  -2.0160    4.064256  265.1417  151.319959           0          0   
8       0  -0.1663    0.027656  240.8474  135.809822           0          0   
9       0  -1.8728    3.507380  245.6888  143.697545           0          0   
10      0  -1.1966    1.431852  242.6110  140.603959           0          0   
11      0  -1.7182    2.952211  234.2419  134.416787           0          0   
12      0  -3.2571   10.608700  214.7266  137.564717           0          0   
13      0  -2.9203    8.528152  213.2577  138.0963

In [123]:
df_ordered.to_csv('features/Descriptors/Test_2d_padel_curated_RRCK.csv', index=False)

In [124]:
#3d Train descriptors
df_train = pd.read_csv('features/Descriptors/Train_3d_padel_RRCK.csv')
df_train['ID'] = df_train['Name'].str.extract(r'_(\d+)$')
df_train['ID'] = df_train['ID'].astype(int)
df_train = df_train.drop('Name',axis=1)
df_train = df_train.fillna(0)
df_train

TDB1u     TDB2u     TDB3u     TDB4u     TDB5u     TDB6u     TDB7u  \
0    1.260126  2.168178  2.985414  3.703081  4.572657  5.287775  5.971320   
1    1.261929  2.183718  3.022837  3.765240  4.602265  5.340855  6.057819   
2    1.260152  2.179188  3.016652  3.748089  4.609748  5.394682  5.995122   
3    1.260469  2.175286  3.023047  3.751040  4.584167  5.239129  5.956658   
4    1.266721  2.187884  3.011559  3.736029  4.581380  5.280846  5.885916   
..        ...       ...       ...       ...       ...       ...       ...   
135  1.262636  2.185491  3.021505  3.760947  4.607480  5.407457  6.113102   
136  1.260372  2.184931  3.011288  3.729456  4.584852  5.351579  6.027140   
137  1.263251  2.184426  3.010162  3.744587  4.554198  5.366878  6.097769   
138  1.256794  2.165785  2.997731  3.718485  4.571866  5.356003  6.129648   
139  1.256326  2.164148  2.998092  3.720226  4.572042  5.327300  6.090557   

        TDB8u     TDB9u    TDB10u  ...       P2s       E1s       E2s  \
0    6.600131  7.308308  7.949725  ...  0.372674  0.395227  0.414936   
1    6.792770  7.619819  8.431458  ...  0.394478  0.518283  0.482646   
2    6.705751  7.484998  8.119839  ...  0.325168  0.400722  0.449515   
3    6.707209  7.145874  7.895867  ...  0.317821  0.460343  0.508610   
4    6.604646  7.208371  7.831496  ...  0.337734  0.488826  0.459264   
..        ...       ...       ...  ...       ...       ...       ...   
135  6.815279  7.531610  8.182586  ...  0.379354  0.445017  0.396838   
136  6.781283  7.452356  8.186011  ...  0.305299  0.407700  0.362010   
137  6.782195  7.631979  8.378278  ...  0.358796  0.423582  0.468075   
138  7.011115  7.773337  8.483838  ...  0.421759  0.542612  0.495238   
139  6.908860  7.675048  8.371063  ...  0.358670  0.566599  0.514880   

          E3s         Ts          As           Vs        Ks        Ds    ID  
0    0.366470  27.705985  239.114381   882.761686  0.245173  1.176633  1043  
1    0.467701  32.523701  294.735295   866.959016  0.387571  1.468629  1035  
2    0.371177  28.987882  256.206923   962.139853  0.258833  1.221414  1032  
3    0.424126  29.554902  246.248308   809.952598  0.351179  1.393079  1040  
4    0.390336  30.205968  260.245984   863.471017  0.332230  1.338426  1042  
..        ...        ...         ...          ...       ...       ...   ...  
135  0.307687  28.273510  247.318593   909.546204  0.258821  1.149542  5670  
136  0.364220  30.492034  265.493473   931.787768  0.346891  1.133930  5671  
137  0.449225  35.468099  340.606285  1027.537753  0.392870  1.340882    46  
138  0.403767  36.220082  366.528479  1114.400589  0.395228  1.441617   977  
139  0.365331  34.518992  349.135622  1312.792222  0.318420  1.446810   978  

[140 rows x 432 columns]

In [125]:
df = pd.read_csv('features/Descriptors/Train_2d_Mordred_desc_RRCK.csv')
df 

ID                                             SMILES  Permeability  \
0    2358  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](C(...         -6.13   
1    2359  C/C=C/C[C@@H](C)C(=O)[C@H]1C(=O)N[C@@H](C(C)C)...         -6.66   
2    2357  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...         -5.95   
3    2360  C/C=C/C[C@@H](C)[C@H]1OC(=O)[C@H](C(C)C)N(C)C(...         -6.78   
4    2353  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](C)...         -5.87   
..    ...                                                ...           ...   
135  2336  CC[C@@H]1NC(=O)[C@@H](CC)NC(=O)[C@H](CC(C)C)NC...         -5.39   
136  2306  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...         -4.75   
137  2334  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...         -5.58   
138  2305  CCC[C@@H]1C(=O)N(C)[C@@H](C)C(=O)N[C@@H](CC(C)...         -4.85   
139  2304  CC[C@@H]1C(=O)N(C)[C@@H](C)C(=O)N[C@@H](CC(C)C...         -5.51   

                                              ABCIndex  \
0    module 'numpy' has no attribute 'float'.\n`np....   
1    module 'numpy' has no attribute 'float'.\n`np....   
2    module 'numpy' has no attribute 'float'.\n`np....   
3    module 'numpy' has no attribute 'float'.\n`np....   
4    module 'numpy' has no attribute 'float'.\n`np....   
..                                                 ...   
135  module 'numpy' has no attribute 'float'.\n`np....   
136  module 'numpy' has no attribute 'float'.\n`np....   
137  module 'numpy' has no attribute 'float'.\n`np....   
138  module 'numpy' has no attribute 'float'.\n`np....   
139  module 'numpy' has no attribute 'float'.\n`np....   

                                            ABCGGIndex  AcidicGroupCount  \
0    module 'numpy' has no attribute 'float'.\n`np....                 0   
1    module 'numpy' has no attribute 'float'.\n`np....                 0   
2    module 'numpy' has no attribute 'float'.\n`np....                 0   
3    module 'numpy' has no attribute 'float'.\n`np....                 0   
4    module 'numpy' has no attribute 'float'.\n`np....                 0   
..                                                 ...               ...   
135  module 'numpy' has no attribute 'float'.\n`np....                 0   
136  module 'numpy' has no attribute 'float'.\n`np....                 0   
137  module 'numpy' has no attribute 'float'.\n`np....                 0   
138  module 'numpy' has no attribute 'float'.\n`np....                 0   
139  module 'numpy' has no attribute 'float'.\n`np....                 0   

     BasicGroupCount  AdjacencyMatrix  AdjacencyMatrix.1  AdjacencyMatrix.2  \
0                  0       100.888651           2.446436           4.892748   
1                  0       100.888651           2.446436           4.892748   
2                  0       100.134733           2.444935           4.889759   
3                  1       100.268636           2.427280           4.854560   
4                  0        98.550044           2.444219           4.888335   
..               ...              ...                ...                ...   
135                0        56.766056           2.420826           4.789951   
136                0        52.776707           2.440186           4.848090   
137                0        53.640751           2.419606           4.784653   
138                0        52.045329           2.439503           4.844153   
139                0        50.591075           2.439146           4.842060   

     ...  WalkCount.19  WalkCount.20       Weight  Weight.1  WienerIndex  \
0    ...     11.228478    126.484444  1215.857018  6.109834        38268   
1    ...     11.228478    126.484444  1213.841368  6.161631        38268   
2    ...     11.208585    125.402718  1201.841368  6.131844        37337   
3    ...     11.184019    125.341576  1201.841368  6.131844        37826   
4    ...     11.198475    124.353468  1187.825718  6.154537        36408   
..   ...           ...           ...          ...      

In [126]:
merged_df = df_train.merge(df[['ID', 'SMILES', 'Permeability']], on='ID', how='left')
merged_df = merged_df[['ID', 'SMILES', 'Permeability'] + [col for col in merged_df.columns if col not in ['ID', 'SMILES', 'Permeability']]]
merged_df

ID                                             SMILES  Permeability  \
0    1043  CC(C)C[C@@H]1NC(=O)CN(CN2CCOCC2)C(=O)[C@H]2CCC...        -5.090   
1    1035  CC(C)C[C@@H]1NC(=O)CN(Cc2ccc(O)cc2)C(=O)[C@H]2...        -5.200   
2    1032  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@@H...        -5.260   
3    1040  CC(C)CN1CC(=O)N(CC(C)C)CC(=O)N(CC(C)C)CC(=O)N2...        -6.400   
4    1042  CC(C)C[C@@H]1NC(=O)CN(Cc2cccc(C(F)(F)F)c2)C(=O...        -6.000   
..    ...                                                ...           ...   
135  5670  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.225   
136  5671  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.255   
137    46  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.920   
138   977  C/C1=C\[C@@H](CC(C)C)NC(=O)[C@@H]2CCCN2C(=O)[C...        -4.960   
139   978  C/C1=C\[C@H](CC(C)C)NC(=O)[C@@H]2CCCN2C(=O)[C@...        -5.520   

        TDB1u     TDB2u     TDB3u     TDB4u     TDB5u     TDB6u     TDB7u  \
0    1.260126  2.168178  2.985414  3.703081  4.572657  5.287775  5.971320   
1    1.261929  2.183718  3.022837  3.765240  4.602265  5.340855  6.057819   
2    1.260152  2.179188  3.016652  3.748089  4.609748  5.394682  5.995122   
3    1.260469  2.175286  3.023047  3.751040  4.584167  5.239129  5.956658   
4    1.266721  2.187884  3.011559  3.736029  4.581380  5.280846  5.885916   
..        ...       ...       ...       ...       ...       ...       ...   
135  1.262636  2.185491  3.021505  3.760947  4.607480  5.407457  6.113102   
136  1.260372  2.184931  3.011288  3.729456  4.584852  5.351579  6.027140   
137  1.263251  2.184426  3.010162  3.744587  4.554198  5.366878  6.097769   
138  1.256794  2.165785  2.997731  3.718485  4.571866  5.356003  6.129648   
139  1.256326  2.164148  2.998092  3.720226  4.572042  5.327300  6.090557   

     ...       P1s       P2s       E1s       E2s       E3s         Ts  \
0    ...  0.457441  0.372674  0.395227  0.414936  0.366470  27.705985   
1    ...  0.530569  0.394478  0.518283  0.482646  0.467701  32.523701   
2    ...  0.505889  0.325168  0.400722  0.449515  0.371177  28.987882   
3    ...  0.567453  0.317821  0.460343  0.508610  0.424126  29.554902   
4    ...  0.550420  0.337734  0.488826  0.459264  0.390336  30.205968   
..   ...       ...       ...       ...       ...       ...        ...   
135  ...  0.459860  0.379354  0.445017  0.396838  0.307687  28.273510   
136  ...  0.564594  0.305299  0.407700  0.362010  0.364220  30.492034   
137  ...  0.569785  0.358796  0.423582  0.468075  0.449225  35.468099   
138  ...  0.508392  0.421759  0.542612  0.495238  0.403767  36.220082   
139  ...  0.520277  0.358670  0.566599  0.514880  0.365331  34.518992   

             As           Vs        Ks        Ds  
0    239.114381   882.761686  0.245173  1.176633  
1    294.735295   866.959016  0.387571  1.468629  
2    256.206923   962.139853  0.258833  1.221414  
3    246.248308   809.952598  0.351179  1.393079  
4    260.245984   863.471017  0.332230  1.338426  
..          ...          ...       ...       ...  
135  247.318593   909.546204  0.258821  1.149542  
136  265.493473   931.787768  0.346891  1.133930  
137  340.606285  1027.537753  0.392870  1.340882  
138  366.528479  1114.400589  0.395228  1.441617  
139  349.135622  1312.792222  0.318420  1.446810  

[140 rows x 434 columns]

In [127]:
df_ordered = merged_df.merge(df[['ID']], on='ID', how='right')
df_ordered = df_ordered.reindex(df.index)
df_ordered

ID                                             SMILES  Permeability  \
0    2358  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](C(...         -6.13   
1    2359  C/C=C/C[C@@H](C)C(=O)[C@H]1C(=O)N[C@@H](C(C)C)...         -6.66   
2    2357  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...         -5.95   
3    2360  C/C=C/C[C@@H](C)[C@H]1OC(=O)[C@H](C(C)C)N(C)C(...         -6.78   
4    2353  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](C)...         -5.87   
..    ...                                                ...           ...   
135  2336  CC[C@@H]1NC(=O)[C@@H](CC)NC(=O)[C@H](CC(C)C)NC...         -5.39   
136  2306  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...         -4.75   
137  2334  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...         -5.58   
138  2305  CCC[C@@H]1C(=O)N(C)[C@@H](C)C(=O)N[C@@H](CC(C)...         -4.85   
139  2304  CC[C@@H]1C(=O)N(C)[C@@H](C)C(=O)N[C@@H](CC(C)C...         -5.51   

        TDB1u     TDB2u     TDB3u     TDB4u     TDB5u     TDB6u     TDB7u  \
0    1.254180  2.166274  3.007142  3.700183  4.513361  5.316459  5.976700   
1    1.254432  2.166147  3.010365  3.691038  4.507068  5.364784  6.037048   
2    1.253592  2.162722  3.007509  3.718467  4.525201  5.252066  5.960072   
3    1.254398  2.163519  3.003287  3.701928  4.523709  5.373313  6.109207   
4    1.254467  2.167174  3.008550  3.695675  4.528104  5.365112  6.076403   
..        ...       ...       ...       ...       ...       ...       ...   
135  1.259866  2.193760  2.990089  3.742024  4.661808  5.479539  6.218067   
136  1.258750  2.168440  3.010535  3.753370  4.529155  5.339332  6.100139   
137  1.263336  2.200888  3.010521  3.768007  4.659284  5.461330  6.179759   
138  1.258069  2.171925  2.998728  3.734575  4.547098  5.378378  6.132871   
139  1.259847  2.173288  3.009934  3.741646  4.515695  5.357686  6.146936   

     ...       P1s       P2s       E1s       E2s       E3s         Ts  \
0    ...  0.584742  0.289275  0.526481  0.467149  0.355332  51.237177   
1    ...  0.562959  0.330424  0.573577  0.533312  0.392941  52.061975   
2    ...  0.505864  0.386967  0.530722  0.572866  0.283984  52.691795   
3    ...  0.543224  0.390435  0.549748  0.553013  0.367643  60.025118   
4    ...  0.559155  0.365398  0.567980  0.530505  0.368965  55.664600   
..   ...       ...       ...       ...       ...       ...        ...   
135  ...  0.480821  0.450969  0.447622  0.401417  0.374652  28.991239   
136  ...  0.587350  0.351181  0.540411  0.549950  0.480266  27.093819   
137  ...  0.603934  0.302221  0.478983  0.563029  0.379015  26.877338   
138  ...  0.573506  0.364677  0.497225  0.533337  0.460216  26.843623   
139  ...  0.597941  0.312068  0.477574  0.513718  0.429588  25.998557   

             As           Vs        Ks        Ds  
0    733.133564  3650.811196  0.377113  1.348962  
1    762.354776  3612.998411  0.344438  1.499831  
2    809.151889  3930.912570  0.339246  1.387572  
3    987.347841  4090.444574  0.400488  1.470405  
4    849.215301  3563.631478  0.386829  1.467450  
..          ...          ...       ...       ...  
135  235.667908   625.054603  0.397685  1.223691  
136  193.764285   473.031633  0.407795  1.570627  
137  193.282773   552.730401  0.405901  1.421027  
138  192.495908   469.419500  0.407274  1.490778  
139  181.479702   502.568103  0.396911  1.420879  

[140 rows x 434 columns]

In [128]:
df_ordered.to_csv('features/Descriptors/Train_3d_padel_curated_RRCK.csv', index=False)

In [129]:
#3d test padel descriptors
df_test = pd.read_csv('features/Descriptors/Test_3d_padel_RRCK.csv')
df_test['ID'] = df_test['Name'].str.extract(r'_(\d+)$')
df_test['ID'] = df_test['ID'].astype(int)
df_test = df_test.drop('Name',axis=1)
df_test = df_test.fillna(0)
df_test

TDB1u     TDB2u     TDB3u     TDB4u     TDB5u     TDB6u     TDB7u  \
0   1.261799  2.186755  3.020058  3.756445  4.529348  5.352167  6.150114   
1   1.284135  2.238134  3.059687  3.813058  4.667183  5.416410  6.164273   
2   1.270762  2.233409  3.036703  3.836601  4.654813  5.419781  6.132307   
3   1.263047  2.186342  3.024238  3.763724  4.579603  5.397958  6.117764   
4   1.263868  2.200103  3.004710  3.777100  4.728870  5.516489  6.218313   
5   1.261647  2.188305  3.022598  3.756810  4.541332  5.311648  6.120919   
6   1.260551  2.175014  3.035593  3.793677  4.492913  5.263191  6.041626   
7   1.259174  2.171089  2.999404  3.773822  4.545005  5.333920  5.960234   
8   1.267424  2.201333  2.978891  3.757086  4.610687  5.469140  6.193896   
9   1.263156  2.195266  2.984549  3.721556  4.594043  5.402468  6.192703   
10  1.267748  2.205327  2.974218  3.727569  4.608054  5.471468  6.195522   
11  1.258385  2.170534  3.028905  3.750750  4.482363  5.254493  5.962375   
12  1.264707  2.204852  3.047072  3.823369  4.589295  5.380218  6.174379   
13  1.259060  2.173024  3.010827  3.727928  4.497116  5.392062  6.168688   
14  1.266426  2.211234  3.051207  3.809748  4.602414  5.423193  6.212098   
15  1.263648  2.201101  3.036491  3.784101  4.579562  5.418990  6.166464   
16  1.267460  2.212219  3.056112  3.834633  4.626691  5.377677  6.120626   
17  1.262518  2.181694  3.006259  3.760700  4.546769  5.351567  6.108918   
18  1.265350  2.189680  3.011231  3.764379  4.608435  5.383710  6.028784   
19  1.254423  2.166133  3.004162  3.702798  4.517434  5.280055  6.003941   
20  1.260079  2.181115  3.004100  3.721189  4.549943  5.314059  6.019337   
21  1.261825  2.185281  3.028712  3.784328  4.537942  5.342471  6.065764   
22  1.262466  2.192994  3.000326  3.738274  4.684302  5.451281  6.156736   
23  1.264232  2.198839  2.987364  3.760402  4.605291  5.429383  6.151066   
24  1.258134  2.168095  3.005712  3.781677  4.501400  5.263147  5.900071   
25  1.259025  2.181485  2.987621  3.750304  4.515982  5.352705  6.112851   
26  1.265762  2.199593  3.003494  3.794673  4.621234  5.442915  6.163846   
27  1.255775  2.168187  2.991854  3.704240  4.474229  5.308317  6.037090   
28  1.252975  2.164230  3.007035  3.698789  4.498476  5.322587  6.062136   
29  1.257087  2.168427  2.993740  3.714018  4.528309  5.346478  6.110769   
30  1.260777  2.184370  3.010586  3.734567  4.612172  5.364629  6.133756   
31  1.262054  2.196760  2.998120  3.710277  4.616379  5.409779  6.146439   
32  1.263462  2.183569  3.069260  3.819187  4.461594  5.323691  6.155005   
33  1.260651  2.185951  3.021138  3.753764  4.566948  5.366399  6.148918   
34  1.259800  2.190382  2.997800  3.725730  4.583084  5.341682  6.057332   
35  1.256031  2.168414  2.998419  3.706643  4.563724  5.376190  6.071788   

       TDB8u     TDB9u    TDB10u  ...       P2s       E1s       E2s       E3s  \
0   6.928809  7.779645  8.584120  ...  0.394757  0.497851  0.542970  0.398595   
1   6.862916  7.462712  8.138391  ...  0.357070  0.434281  0.561102  0.351591   
2   6.780357  7.446888  8.096509  ...  0.413066  0.490229  0.356166  0.318931   
3   6.859126  7.473837  8.092249  ...  0.358262  0.460196  0.434979  0.435413   
4   6.902843  7.576359  8.342238  ...  0.373398  0.510431  0.394462  0.389608   
5   6.926018  7.714005  8.497336  ...  0.402075  0.502233  0.582808  0.399787   
6   6.979851  7.728414  8.383715  ...  0.331118  0.541763  0.498942  0.284356   
7   6.736934  7.518592  8.161337  ...  0.367710  0.524581  0.567214  0.404237   
8   6.939528  7.667159  8.357169  ...  0.318526  0.486564  0.535319  0.298116   
9   6.865545  7.439082  7.935941  ...  0.368571  0.428115  0.482597  0.354128   
10  6.888634  7.531194  8.275164  ...  0.376825  0.426092  0.487701  0.309542   
11  6.859266  7.712872  8.426401  ...  0.344873  0.529573  0.541000  0.350437   
12  6.890525  7.652888  8.226844  ...  0.361967  0.501315  0.546106  0.373435   
13  6.874471  7.623211  8.229420  ...  0.335878  0.456446  0

In [130]:
df = pd.read_csv('features/Descriptors/Test_2d_Mordred_desc_RRCK.csv')
df

ID                                             SMILES  Permeability  \
0   2352  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H]([C...        -6.340   
1   5669  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...        -5.760   
2   1881  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
3   5666  CCCC[C@@H]1NC(=O)[C@H](CCCC)NC(=O)[C@H](CCCC)N...        -6.460   
4   1877  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
5   1873  CC(C)C[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N2CCC[C...        -4.620   
6   1878  CCC[C@H]1C(=O)N(C)[C@H](CC)C(=O)N(C)[C@@H](C)C...        -7.300   
7   1849  O=C1CN(CCCc2ccccc2)C(=O)[C@H]2CCCN2C(=O)[C@H](...        -5.920   
8   1856  CC(C)(C)C[C@@H]1NC(=O)[C@@H](Cc2ccccc2)NC(=O)[...        -5.120   
9   2367  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.930   
10  2369  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)NC(=O)[C@H](Cc2...        -6.660   
11  2370  CC(C)C[C@@H]1NC(=O)[C@H](C)NC(=O)[C@H](Cc2ccc(...        -6.230   
12    45  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.840   
13    44  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.150   
14  2373  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.340   
15   970  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)N(C)C(=O)[C@H...        -5.700   
16   966  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...        -6.000   
17   979  C/C1=C\[C@@H](CC(C)C)NC(=O)[C@@H]2CCCN2C(=O)[C...        -5.000   
18  1867  C[C@H]1C(=O)N(C)[C@H](C)C(=O)N(C)[C@H](C)C(=O)...        -7.640   
19  2350  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.860   
20  5642  CCCC[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)CSC[C@@...        -5.900   
21  2342  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.460   
22    35  CC[C@H](C)[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC...        -5.490   
23    34  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.330   
24  2340  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...        -5.020   
25    31  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.120   
26  1037  CC(C)C[C@@H]1NC(=O)CN(Cc2ccc(O)cc2)C(=O)[C@H]2...        -5.140   
27  5674  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...        -5.805   
28  2295  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@@H](...        -6.440   
29  2300  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...        -5.550   
30   928  CC[C@H](C)[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@H](...        -6.220   
31  2312  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...        -4.640   
32  2323  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -5.350   
33  2308  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -4.620   
34  2335  CC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2cccc...        -5.530   
35  2303  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...        -5.310   

                                             ABCIndex  \
0   module 'numpy' has no attribute 'float'.\n`np....   
1   module 'numpy' has no attribute 'float'.\n`np....   
2   module 'numpy' has no attribute 'float'.\n`np....   
3   module 'numpy' has no attribute 'float'.\n`np....   
4   module 'numpy' has no attribute 'float'.\n`np....   
5   module 'numpy' has no attribute 'float'.\n`np....   
6   module 'numpy' has no attribute 'float'.\n`np....   
7   module 'numpy' has no attribute 'float'.\n`np....   
8   module 'numpy' has no attribute 'float'.\n`np....   
9   module 'numpy' has no attribute 'float'.\n`np....   
10  module 'numpy' has no attribute 'float'.\n`np....   
11  module 'numpy' has no attribute 'float'.\n`np....   
12  module 'numpy' has no attribute 'float'.\n`np....   
13  module 'numpy' has no attribute 'float'.\n`np....   
14  module 'numpy' has no attribute 'float'.\n`np....   
15  module 'numpy' has no attribute 'float'.\n`np....   
16  module 'numpy' has no attribute 'float'.\n`np....   
17  module 'numpy' has no attribute 'float'.\n`np....   
18  module 'numpy' has no attribute 'float'.\n`np....   
19  module 'nump

In [131]:
merged_df = df_test.merge(df[['ID', 'SMILES', 'Permeability']], on='ID', how='left')
merged_df = merged_df[['ID', 'SMILES', 'Permeability'] + [col for col in merged_df.columns if col not in ['ID', 'SMILES', 'Permeability']]]
merged_df

ID                                             SMILES  Permeability  \
0   2308  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -4.620   
1   1856  CC(C)(C)C[C@@H]1NC(=O)[C@@H](Cc2ccccc2)NC(=O)[...        -5.120   
2   1849  O=C1CN(CCCc2ccccc2)C(=O)[C@H]2CCCN2C(=O)[C@H](...        -5.920   
3   2312  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...        -4.640   
4   2335  CC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2cccc...        -5.530   
5   2323  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -5.350   
6   1878  CCC[C@H]1C(=O)N(C)[C@H](CC)C(=O)N(C)[C@@H](C)C...        -7.300   
7   1877  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
8   2342  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.460   
9   2340  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...        -5.020   
10  2350  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.860   
11  1873  CC(C)C[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N2CCC[C...        -4.620   
12  2367  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.930   
13  2303  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...        -5.310   
14  2369  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)NC(=O)[C@H](Cc2...        -6.660   
15  2373  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.340   
16  2370  CC(C)C[C@@H]1NC(=O)[C@H](C)NC(=O)[C@H](Cc2ccc(...        -6.230   
17    44  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.150   
18    45  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.840   
19  2352  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H]([C...        -6.340   
20    35  CC[C@H](C)[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC...        -5.490   
21    31  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.120   
22  2295  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@@H](...        -6.440   
23  5642  CCCC[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)CSC[C@@...        -5.900   
24  1881  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
25  5666  CCCC[C@@H]1NC(=O)[C@H](CCCC)NC(=O)[C@H](CCCC)N...        -6.460   
26   928  CC[C@H](C)[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@H](...        -6.220   
27   970  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)N(C)C(=O)[C@H...        -5.700   
28  5669  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...        -5.760   
29   966  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...        -6.000   
30  1037  CC(C)C[C@@H]1NC(=O)CN(Cc2ccc(O)cc2)C(=O)[C@H]2...        -5.140   
31  2300  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...        -5.550   
32  1867  C[C@H]1C(=O)N(C)[C@H](C)C(=O)N(C)[C@H](C)C(=O)...        -7.640   
33    34  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.330   
34  5674  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...        -5.805   
35   979  C/C1=C\[C@@H](CC(C)C)NC(=O)[C@@H]2CCCN2C(=O)[C...        -5.000   

       TDB1u     TDB2u     TDB3u     TDB4u     TDB5u     TDB6u     TDB7u  ...  \
0   1.261799  2.186755  3.020058  3.756445  4.529348  5.352167  6.150114  ...   
1   1.284135  2.238134  3.059687  3.813058  4.667183  5.416410  6.164273  ...   
2   1.270762  2.233409  3.036703  3.836601  4.654813  5.419781  6.132307  ...   
3   1.263047  2.186342  3.024238  3.763724  4.579603  5.397958  6.117764  ...   
4   1.263868  2.200103  3.004710  3.777100  4.728870  5.516489  6.218313  ...   
5   1.261647  2.188305  3.022598  3.756810  4.541332  5.311648  6.120919  ...   
6   1.260551  2.175014  3.035593  3.793677  4.492913  5.263191  6.041626  ...   
7   1.259174  2.171089  2.999404  3.773822  4.545005  5.333920  5.960234  ...   
8   1.267424  2.201333  2.978891  3.757086  4.610687  5.469140  6.193896  ...   
9   1.263156  2.195266  2.984549  3.721556  4.594043  5.402468  6.192703  ...   
10  1.267748  2.205327  2.974218  3.727569  4.608054  5.471468  6.195522  ...   
11  1.258385  2.170534  3.028905  3.750750  4.482363  5.254493  5.962375  ...   
12  1.264707  2.204852  3.047072  3.823369  4.589295  5.380218  6.174379  ...   
13  1.259060  2.173024

In [132]:
df_ordered = merged_df.merge(df[['ID']], on='ID', how='right')
df_ordered = df_ordered.reindex(df.index)
df_ordered

ID                                             SMILES  Permeability  \
0   2352  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H]([C...        -6.340   
1   5669  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...        -5.760   
2   1881  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
3   5666  CCCC[C@@H]1NC(=O)[C@H](CCCC)NC(=O)[C@H](CCCC)N...        -6.460   
4   1877  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
5   1873  CC(C)C[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N2CCC[C...        -4.620   
6   1878  CCC[C@H]1C(=O)N(C)[C@H](CC)C(=O)N(C)[C@@H](C)C...        -7.300   
7   1849  O=C1CN(CCCc2ccccc2)C(=O)[C@H]2CCCN2C(=O)[C@H](...        -5.920   
8   1856  CC(C)(C)C[C@@H]1NC(=O)[C@@H](Cc2ccccc2)NC(=O)[...        -5.120   
9   2367  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.930   
10  2369  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)NC(=O)[C@H](Cc2...        -6.660   
11  2370  CC(C)C[C@@H]1NC(=O)[C@H](C)NC(=O)[C@H](Cc2ccc(...        -6.230   
12    45  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.840   
13    44  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.150   
14  2373  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.340   
15   970  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)N(C)C(=O)[C@H...        -5.700   
16   966  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...        -6.000   
17   979  C/C1=C\[C@@H](CC(C)C)NC(=O)[C@@H]2CCCN2C(=O)[C...        -5.000   
18  1867  C[C@H]1C(=O)N(C)[C@H](C)C(=O)N(C)[C@H](C)C(=O)...        -7.640   
19  2350  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.860   
20  5642  CCCC[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)CSC[C@@...        -5.900   
21  2342  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.460   
22    35  CC[C@H](C)[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC...        -5.490   
23    34  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.330   
24  2340  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...        -5.020   
25    31  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.120   
26  1037  CC(C)C[C@@H]1NC(=O)CN(Cc2ccc(O)cc2)C(=O)[C@H]2...        -5.140   
27  5674  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...        -5.805   
28  2295  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@@H](...        -6.440   
29  2300  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...        -5.550   
30   928  CC[C@H](C)[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@H](...        -6.220   
31  2312  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...        -4.640   
32  2323  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -5.350   
33  2308  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -4.620   
34  2335  CC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2cccc...        -5.530   
35  2303  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...        -5.310   

       TDB1u     TDB2u     TDB3u     TDB4u     TDB5u     TDB6u     TDB7u  ...  \
0   1.254423  2.166133  3.004162  3.702798  4.517434  5.280055  6.003941  ...   
1   1.252975  2.164230  3.007035  3.698789  4.498476  5.322587  6.062136  ...   
2   1.258134  2.168095  3.005712  3.781677  4.501400  5.263147  5.900071  ...   
3   1.259025  2.181485  2.987621  3.750304  4.515982  5.352705  6.112851  ...   
4   1.259174  2.171089  2.999404  3.773822  4.545005  5.333920  5.960234  ...   
5   1.258385  2.170534  3.028905  3.750750  4.482363  5.254493  5.962375  ...   
6   1.260551  2.175014  3.035593  3.793677  4.492913  5.263191  6.041626  ...   
7   1.270762  2.233409  3.036703  3.836601  4.654813  5.419781  6.132307  ...   
8   1.284135  2.238134  3.059687  3.813058  4.667183  5.416410  6.164273  ...   
9   1.264707  2.204852  3.047072  3.823369  4.589295  5.380218  6.174379  ...   
10  1.266426  2.211234  3.051207  3.809748  4.602414  5.423193  6.212098  ...   
11  1.267460  2.212219  3.056112  3.834633  4.626691  5.377677  6.120626  ...   
12  1.265350  2.189680  3.011231  3.764379  4.608435  5.383710  6.028784  ...   
13  1.262518  2.181694

In [133]:
df_ordered.to_csv('features/Descriptors/Test_3d_padel_curated_RRCK.csv', index=False)

In [134]:
#2d Padel descriptors
df_train = pd.read_csv('features/Descriptors/Train_2d_padel_curated_RRCK.csv')
df_train = df_train.dropna()
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_padel_curated_RRCK.csv')
df_test = df_test.dropna()
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 1444)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 1444)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002025 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 33389
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 965
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further 

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.1922                0.3182   
DecisionTreeRegressor                    0.3292                0.4309   
RandomForestRegressor                    0.1938                0.3290   
GradientBoostingRegressor                0.1880                0.3134   
AdaBoostRegressor                        0.2093                0.3483   
XGBRegressor                             0.2310                0.3564   
ExtraTreesRegressor                      0.1786                0.3053   
LinearRegression                         7.2656                2.1847   
KNeighborsRegressor                      0.2941                0.3863   
SVR                                      0.1949                0.3066   
MLPRegressor                             0.6415                0.5273   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4384               0.5712   
DecisionTreeRegressor                     0.5738               0.2656   
RandomForestRegressor                     0.4402               0.5678   
GradientBoostingRegressor                 0.4336               0.5806   
AdaBoostRegressor                         0.4575               0.5332   
XGBRegressor                              0.4806               0.4846   
ExtraTreesRegressor                       0.4226               0.6016   
LinearRegression                          2.6955             -15.2076   
KNeighborsRegressor                       0.5423               0.3440   
SVR                                       0.4415               0.5652   
MLPRegressor                              0.8009              -0.4310   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.7648                0.7960   
DecisionTreeRegressor                    0.6121                0.6103   
RandomForestRegressor                    0.7738                0.8060   
GradientBoostingRegressor                0.7667                0.7933   
AdaBoostRegressor                        0.7415                0.7653   
XGBRegressor                             0.7035                0.7259   
ExtraTreesRegressor                      0.7881                0.8156   
LinearRegression                         0.0550                0.0541   
KNeighborsRegressor                      0.6370                0.6662   
SVR                                      0.7592                0.7785   
MLPRegressor                             0.4536                0.4999   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4447   0.4282    0.6668   0.3848   
DecisionTreeRegressor       0.3936   0.4422    0.6274   0.4554   
RandomForestRegressor       0.4571   0.4513    0.6761   0.3676   
GradientBoostingRegressor   0.3514   0.4000    0.5928   0.5139   
AdaBoostRegressor           0.4556   0.4689    0.6750   0.3697   
XGBRegressor                0.3669   0.4091    0.6057   0.4924   
ExtraTreesRegressor         0.3999   0.4167    0.6324   0.4467   
LinearRegression            3.4996   1.3951    1.8707  -3.8415   
KNeighborsRegressor         0.5338   0.4701    0.7306   0.2615   
SVR                         0.4611   0.4322    0.6791   0.3620   
MLPRegressor                0.6003   0.5509    0.7748   0.1696   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6956                    0.7660  
DecisionTreeRegressor                       0.7221                    0.7451  
RandomForestRegressor                       0.7164                    0.7983  
GradientBoostingRegressor                   0.7708                    0.8244  
AdaBoostRegressor                           0.7038                    0.7757  
XGBRegressor                                0.7754                    0.8440  
ExtraTreesRegressor                         0.745

In [135]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.9561471228459055, -6.091054642002129, -5.2...   
1   [-5.75, -5.85, -5.22, -5.1, -5.58, -6.46, -5.5...   
2   [-5.9642, -5.995000000000005, -5.2262000000000...   
3   [-6.012002592790874, -6.016243124628508, -5.04...   
4   [-6.0675, -6.137272727272727, -5.2786206896551...   
5   [-6.366995, -6.308828, -4.9082127, -5.4593754,...   
6   [-6.147549999999996, -5.860500000000001, -4.97...   
7   [-4.0, -9.647014368519224, -5.897624791841157,...   
8   [-5.983333333333333, -5.890000000000001, -4.96...   
9   [-6.083389918450342, -5.822177075737425, -5.23...   
10  [-4.489394554934353, -6.481084121959549, -5.03...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.78780820950081, -5.981651754671699, -6.21...   
1   [[-4.96, -5.95, -6.1, -6.46, -6.1, -5.4, -6.92...   
2   [[-5.735899999999999, -5.989400000000001, -6.2...   
3   [[-5.6697531591805665, -5.952955103077377, -6....   
4   [[-6.025, -6.043333333333333, -6.3435714285714...   
5   [[-5.7993255, -5.950652, -6.185632, -6.156246,...   
6   [[-6.127799999999999, -5.949999999999999, -6.4...   
7   [[-4.0, -5.949999999999498, -10.0, -4.86863962...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-6.055962985191872, -6.003501047103598, -5.9...   
10  [[-6.018937426390556, -6.051657604046438, -6.6...   

                                Test Predictions Mean  \
0   [-6.071802287545527, -6.079849210765806, -6.04...   
1   [-5.656, -5.909999999999999, -6.48799999999999...   
2   [-6.037091666666668, -6.05651, -6.088372666666...   
3   [-6.025299593371571, -5.982801238491815, -6.35...   
4   [-6.158384920634921, -6.078541666666666, -6.20...   
5   [-6.0891733, -5.950171, -6.3495092, -6.0568247...   
6   [-6.161899999999999, -5.976379999999999, -6.34...   
7   [-7.220374138271107, -5.744041432940826, -7.6,...   
8   [-6.118666666666667, -6.118666666666667, -5.79...   
9   [-6.119912882097452, -6.037356642908497, -5.91...   
10  [-5.905510947666131, -6.027474607143462, -6.79...   

                                 Test Predictions Std  
0   [0.1716574347422476, 0.09348883081174193, 0.16...  
1   [0.653990825623724, 0.08000000000000007, 0.541...  
2   [0.15884169880034074, 0.07253411886829621, 0.1...  
3   [0.20921485662237696, 0.06524950245829574, 0.2...  
4   [0.0811917519954377, 0.06486979480295772, 0.21...  
5   [0.32636833, 0.00052849064, 0.22824572, 0.2263...  
6   [0.02680559643059607, 0.05275999999999996, 0.2...  
7   [1.9074627469816234, 0.41191713411790876, 2.93...  
8   [0.11400974617208051, 0.11400974617208051, 0.1...  
9   [0.032460989969283614, 0.017408845449402216, 0...  
10  [0.061362814377877405, 0.02780068102098455, 0....

In [136]:
result_df.to_csv('results/Descriptors/Results_2D_padel_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_padel_RRCK.csv')

In [137]:
#2d padel descriptors const removal
df_train = pd.read_csv('features/Descriptors/Train_2d_padel_curated_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train, const_col = remove_constant_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_padel_curated_RRCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = X_test.drop(const_col,axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 1032)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 1032)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002067 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 33389
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 965
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further 

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.1922                0.3182   
DecisionTreeRegressor                    0.3313                0.4405   
RandomForestRegressor                    0.1960                0.3306   
GradientBoostingRegressor                0.1886                0.3145   
AdaBoostRegressor                        0.2251                0.3516   
XGBRegressor                             0.2310                0.3564   
ExtraTreesRegressor                      0.1787                0.3095   
LinearRegression                         7.2656                2.1847   
KNeighborsRegressor                      0.2941                0.3863   
SVR                                      0.1949                0.3066   
MLPRegressor                             0.6785                0.5508   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4384               0.5712   
DecisionTreeRegressor                     0.5756               0.2609   
RandomForestRegressor                     0.4428               0.5627   
GradientBoostingRegressor                 0.4343               0.5793   
AdaBoostRegressor                         0.4745               0.4978   
XGBRegressor                              0.4806               0.4846   
ExtraTreesRegressor                       0.4227               0.6014   
LinearRegression                          2.6955             -15.2076   
KNeighborsRegressor                       0.5423               0.3440   
SVR                                       0.4415               0.5652   
MLPRegressor                              0.8237              -0.5135   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.7648                0.7960   
DecisionTreeRegressor                    0.6057                0.6086   
RandomForestRegressor                    0.7704                0.8012   
GradientBoostingRegressor                0.7662                0.7960   
AdaBoostRegressor                        0.7124                0.7349   
XGBRegressor                             0.7035                0.7259   
ExtraTreesRegressor                      0.7878                0.8142   
LinearRegression                         0.0550                0.0541   
KNeighborsRegressor                      0.6370                0.6662   
SVR                                      0.7593                0.7783   
MLPRegressor                             0.4375                0.4653   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4447   0.4282    0.6668   0.3848   
DecisionTreeRegressor       0.4045   0.4472    0.6360   0.4404   
RandomForestRegressor       0.4608   0.4523    0.6788   0.3625   
GradientBoostingRegressor   0.3592   0.4050    0.5993   0.5031   
AdaBoostRegressor           0.4491   0.4632    0.6701   0.3787   
XGBRegressor                0.3669   0.4091    0.6057   0.4924   
ExtraTreesRegressor         0.4118   0.4190    0.6417   0.4303   
LinearRegression            3.4996   1.3951    1.8707  -3.8415   
KNeighborsRegressor         0.5338   0.4701    0.7306   0.2615   
SVR                         0.4612   0.4322    0.6791   0.3620   
MLPRegressor                0.4873   0.5048    0.6981   0.3258   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6956                    0.7660  
DecisionTreeRegressor                       0.7076                    0.7670  
RandomForestRegressor                       0.7113                    0.7900  
GradientBoostingRegressor                   0.7642                    0.8175  
AdaBoostRegressor                           0.7101                    0.7884  
XGBRegressor                                0.7754                    0.8440  
ExtraTreesRegressor                         0.736

In [138]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.9561471228459055, -6.091054642002129, -5.2...   
1   [-5.75, -5.95, -5.22, -4.96, -5.58, -6.49, -5....   
2   [-5.9412499999999975, -5.9485500000000044, -5....   
3   [-6.007734794007788, -6.016243124628508, -5.04...   
4   [-6.101000000000001, -6.073194444444446, -5.24...   
5   [-6.366995, -6.308828, -4.9082127, -5.4593754,...   
6   [-6.069249999999998, -5.859900000000003, -5.02...   
7   [-4.0, -9.647014368519471, -5.897624791841887,...   
8   [-5.983333333333333, -5.890000000000001, -4.96...   
9   [-6.0833898899563135, -5.8221764643379394, -5....   
10  [-4.205865464417492, -6.737391453937806, -5.00...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.78780820950081, -5.981651754671699, -6.21...   
1   [[-5.1, -5.95, -6.1, -6.46, -6.1, -5.4, -6.92,...   
2   [[-5.727620833333332, -5.9965, -6.266200000000...   
3   [[-5.685261442711315, -5.952955103077377, -6.4...   
4   [[-6.0059999999999985, -6.0059999999999985, -6...   
5   [[-5.7993255, -5.950652, -6.185632, -6.156246,...   
6   [[-6.047250000000002, -5.949999999999999, -6.3...   
7   [[-4.0, -5.949999999999547, -10.0, -4.86863962...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-6.055962829491517, -6.003500984275534, -5.9...   
10  [[-6.687996359566984, -5.90774979427691, -7.47...   

                                Test Predictions Mean  \
0   [-6.071802287545527, -6.079849210765806, -6.04...   
1   [-5.801, -5.933999999999999, -6.37799999999999...   
2   [-6.053627499999999, -6.067299999999999, -6.11...   
3   [-6.017868816390469, -5.98284368185833, -6.333...   
4   [-6.168892602134707, -6.114985294117647, -6.16...   
5   [-6.0891733, -5.950171, -6.3495092, -6.0568247...   
6   [-6.16845, -5.978369999999999, -6.325360000000...   
7   [-7.220374138266202, -5.744041432941204, -7.6,...   
8   [-6.118666666666667, -6.118666666666667, -5.79...   
9   [-6.119789816070937, -6.037217738658109, -5.91...   
10  [-7.037893710587651, -5.894811824057509, -7.37...   

                                 Test Predictions Std  
0   [0.1716574347422476, 0.09348883081174193, 0.16...  
1   [0.5466113793180674, 0.03200000000000003, 0.59...  
2   [0.1699601023361403, 0.08935751227512959, 0.11...  
3   [0.1994044053197292, 0.06533415492825123, 0.23...  
4   [0.09823580382068528, 0.08031658487652753, 0.0...  
5   [0.32636833, 0.00052849064, 0.22824572, 0.2263...  
6   [0.07534626069022878, 0.05673999999999957, 0.2...  
7   [1.9074627469813683, 0.41191713411716735, 2.93...  
8   [0.11400974617208051, 0.11400974617208051, 0.1...  
9   [0.03238799639269755, 0.01730779554560215, 0.0...  
10  [0.2331962070559508, 0.0590849734521063, 0.234...

In [139]:
result_df.to_csv('results/Descriptors/Results_2D_padel_const_rem_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_padel_const_rem_RRCK.csv')

In [140]:
#2d padel descriptors LVR
df_train = pd.read_csv('features/Descriptors/Train_2d_padel_curated_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train, const_col = remove_low_variance_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_padel_curated_RRCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
X_test = X_test.drop(const_col,axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 718)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 718)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001495 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 22157
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 662
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further sp

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.1916                0.3253   
DecisionTreeRegressor                    0.3248                0.3988   
RandomForestRegressor                    0.1985                0.3315   
GradientBoostingRegressor                0.2037                0.3250   
AdaBoostRegressor                        0.2022                0.3455   
XGBRegressor                             0.2321                0.3453   
ExtraTreesRegressor                      0.1680                0.3045   
LinearRegression                         6.9977                2.1456   
KNeighborsRegressor                      0.3018                0.3944   
SVR                                      0.2020                0.3132   
MLPRegressor                             0.8182                0.6184   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4377               0.5727   
DecisionTreeRegressor                     0.5699               0.2755   
RandomForestRegressor                     0.4455               0.5573   
GradientBoostingRegressor                 0.4513               0.5457   
AdaBoostRegressor                         0.4497               0.5490   
XGBRegressor                              0.4818               0.4823   
ExtraTreesRegressor                       0.4098               0.6253   
LinearRegression                          2.6453             -14.6101   
KNeighborsRegressor                       0.5494               0.3267   
SVR                                       0.4495               0.5494   
MLPRegressor                              0.9045              -0.8252   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.7655                0.7987   
DecisionTreeRegressor                    0.6236                0.6692   
RandomForestRegressor                    0.7657                0.7994   
GradientBoostingRegressor                0.7496                0.7722   
AdaBoostRegressor                        0.7513                0.7767   
XGBRegressor                             0.7057                0.7451   
ExtraTreesRegressor                      0.8017                0.8266   
LinearRegression                         0.1620                0.1548   
KNeighborsRegressor                      0.6228                0.6553   
SVR                                      0.7490                0.7724   
MLPRegressor                             0.3680                0.3716   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4555   0.4401    0.6749   0.3698   
DecisionTreeRegressor       0.2964   0.4125    0.5444   0.5899   
RandomForestRegressor       0.4511   0.4541    0.6716   0.3759   
GradientBoostingRegressor   0.3773   0.4211    0.6143   0.4780   
AdaBoostRegressor           0.4816   0.4676    0.6940   0.3338   
XGBRegressor                0.4228   0.4255    0.6502   0.4151   
ExtraTreesRegressor         0.4300   0.4282    0.6557   0.4052   
LinearRegression            3.4251   1.3520    1.8507  -3.7384   
KNeighborsRegressor         0.5478   0.4730    0.7401   0.2422   
SVR                         0.4988   0.4485    0.7063   0.3099   
MLPRegressor                0.7132   0.6011    0.8445   0.0133   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6909                    0.7832  
DecisionTreeRegressor                       0.8068                    0.8063  
RandomForestRegressor                       0.7222                    0.7952  
GradientBoostingRegressor                   0.7581                    0.7972  
AdaBoostRegressor                           0.6706                    0.7514  
XGBRegressor                                0.7189                    0.7774  
ExtraTreesRegressor                         0.718

In [141]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.938703787296294, -6.232094304780872, -5.28...   
1   [-5.75, -5.87, -5.4, -5.1, -5.57, -6.46, -5.57...   
2   [-5.943299999999999, -6.018803333333335, -5.20...   
3   [-6.027730617410095, -6.080286155832058, -5.09...   
4   [-6.123534482758622, -6.123780487804877, -5.22...   
5   [-5.877562, -6.1120234, -4.950026, -5.4803996,...   
6   [-6.111399999999998, -5.927500000000001, -5.00...   
7   [-10.0, -10.0, -5.244022848044642, -8.87204520...   
8   [-5.983333333333333, -5.890000000000001, -4.96...   
9   [-6.090387156372305, -5.77209850864664, -5.239...   
10  [-4.0, -6.906367369105128, -5.101930280704156,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.8044514849747735, -6.001548586065553, -6....   
1   [[-5.16, -5.95, -6.1, -6.46, -6.1, -5.4, -6.92...   
2   [[-5.7148166666666675, -5.976599999999999, -6....   
3   [[-5.442522304790104, -5.950168933851341, -6.3...   
4   [[-6.04, -6.075083333333338, -6.18270833333333...   
5   [[-5.865114, -5.9497194, -6.2232904, -5.925979...   
6   [[-6.088600000000001, -5.949999999999999, -6.3...   
7   [[-4.0, -5.949999999999579, -10.0, -7.35448179...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-6.0504420658890545, -5.999385066557721, -5....   
10  [[-6.5007129482776165, -6.057812936856622, -7....   

                                Test Predictions Mean  \
0   [-6.0146456503875685, -6.088986174357419, -6.0...   
1   [-5.717999999999999, -5.909999999999999, -6.72...   
2   [-6.044983333333333, -6.04512, -6.159120000000...   
3   [-5.927893881724126, -5.994967907058017, -6.38...   
4   [-6.183201190476192, -6.107500183150184, -6.16...   
5   [-6.2035356, -5.959027, -6.1810255, -6.0425653...   
6   [-6.160036666666668, -5.973139999999999, -6.31...   
7   [-6.8989335519801385, -6.4993748385513, -7.6, ...   
8   [-6.118666666666667, -6.118666666666667, -5.92...   
9   [-6.107608347173828, -6.0205758618288145, -5.8...   
10  [-6.447860247754801, -6.056996366565235, -7.47...   

                                 Test Predictions Std  
0   [0.1925185448293264, 0.0972410311133326, 0.143...  
1   [0.37145120810141397, 0.08000000000000007, 0.6...  
2   [0.19473983784640558, 0.05953158489407159, 0.1...  
3   [0.3610784030293262, 0.08020965851631814, 0.19...  
4   [0.11346621851354799, 0.0712714388881046, 0.13...  
5   [0.34634006, 0.017979342, 0.17707849, 0.123275...  
6   [0.09105661633169813, 0.046280000000000855, 0....  
7   [2.6554483218931138, 1.0987496771029484, 2.939...  
8   [0.11400974617208051, 0.11400974617208051, 0.2...  
9   [0.029073301287539308, 0.017412944329614422, 0...  
10  [0.398542479589777, 0.06197644656372157, 0.603...

In [142]:
result_df.to_csv('results/Descriptors/Results_2D_padel_LVR_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_padel_const_LVR_RRCK.csv')

In [143]:
#2d All descriptors
df_train_padel = pd.read_csv('features/Descriptors/Train_2d_padel_curated_RRCK.csv')
df_train_rdkit = pd.read_csv('features/Descriptors/Train_2d_RDKit_des_RRCK.csv')
df_train_mordred = pd.read_csv('features/Descriptors/Train_2d_Mordred_desc_RRCK.csv')

df_2d_train = df_train_rdkit.merge(df_train_mordred, on=['ID', 'SMILES', 'Permeability'], how='inner').merge(df_train_padel, on=['ID', 'SMILES', 'Permeability'], how='inner')
df_2d_train

ID                                             SMILES  Permeability  \
0    2358  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](C(...         -6.13   
1    2359  C/C=C/C[C@@H](C)C(=O)[C@H]1C(=O)N[C@@H](C(C)C)...         -6.66   
2    2357  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...         -5.95   
3    2360  C/C=C/C[C@@H](C)[C@H]1OC(=O)[C@H](C(C)C)N(C)C(...         -6.78   
4    2353  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](C)...         -5.87   
..    ...                                                ...           ...   
135  2336  CC[C@@H]1NC(=O)[C@@H](CC)NC(=O)[C@H](CC(C)C)NC...         -5.39   
136  2306  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...         -4.75   
137  2334  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...         -5.58   
138  2305  CCC[C@@H]1C(=O)N(C)[C@@H](C)C(=O)N[C@@H](CC(C)...         -4.85   
139  2304  CC[C@@H]1C(=O)N(C)[C@@H](C)C(=O)N[C@@H](CC(C)C...         -5.51   

     MaxAbsEStateIndex  MaxEStateIndex  MinAbsEStateIndex  MinEStateIndex  \
0            15.193873       15.193873           0.130769       -1.621791   
1            15.152762       15.152762           0.128114       -1.816236   
2            15.129540       15.129540           0.022871       -1.609940   
3            15.028142       15.028142           0.097424       -1.231351   
4            15.068092       15.068092           0.128760       -1.611421   
..                 ...             ...                ...             ...   
135          13.940180       13.940180           0.023137       -1.031903   
136          13.929912       13.929912           0.048761       -0.934108   
137          13.805528       13.805528           0.023859       -1.030988   
138          13.850263       13.850263           0.054388       -0.925132   
139          13.811409       13.811409           0.054806       -0.925415   

          qed        SPS     MolWt  ...       AMW      WTPT-1    WTPT-2  \
0    0.147476  26.802326  1216.662  ...  6.109834  165.660911  1.926290   
1    0.134993  26.372093  1214.646  ...  6.161631  165.660911  1.926290   
2    0.147925  26.905882  1202.635  ...  6.131844  163.824465  1.927347   
3    0.116062  27.411765  1202.635  ...  6.131844  164.030378  1.929769   
4    0.157205  27.083333  1188.608  ...  6.154537  161.805840  1.926260   
..        ...        ...       ...  ...       ...         ...       ...   
135  0.289440  27.260870   640.826  ...  6.534641   91.402117  1.987003   
136  0.462849  28.954545   620.836  ...  6.204261   85.761816  1.949132   
137  0.318688  27.954545   612.772  ...  6.656125   87.363105  1.985525   
138  0.468423  29.209302   606.809  ...  6.251654   83.927240  1.951796   
139  0.488135  29.619048   592.782  ...  6.302073   81.919106  1.950455   

        WTPT-3     WTPT-4     WTPT-5    WPATH   WPOL  XLogP  Zagreb  
0    64.869552  30.340460  34.529092  38268.0  152.0  8.704   418.0  
1    64.869552  30.340460  34.529092  38268.0  152.0  7.824   418.0  
2    64.851242  30.333765  34.517477  37337.0  150.0  8.407   412.0  
3    64.941671  30.873015  34.068656  37826.0  148.0  8.690   410.0  
4    64.748500  30.296198  34.452302  36408.0  148.0  8.049   408.0  
..         ...        ...        ...      ...    ...    ...     ...  
135  33.999411  15.357748  18.641663   7064.0   74.0  5.393   228.0  
136  34.302616  15.219294  19.083322   6071.0   77.0  4.002   220.0  
137  33.788693  15.284672  18.504021   6341.0   70.0  4.677   220.0  
138  34.294802  15.216440  19.078362   5725.0   76.0  3.494   214.0  
139  34.250954  15.200426  19.050528   5381.0   75.0  2.925   210.0  

[140 rows x 3277 columns]

In [144]:
df_2d_train.to_csv('features/Descriptors/Train_2d_all_descriptors_RRCK.csv', index=False)

In [145]:
df_test_padel = pd.read_csv('features/Descriptors/Test_2d_padel_curated_RRCK.csv')
df_test_rdkit = pd.read_csv('features/Descriptors/Test_2d_RDKit_des_RRCK.csv')
df_test_mordred = pd.read_csv('features/Descriptors/Test_2d_Mordred_desc_RRCK.csv')

df_2d_test = df_test_rdkit.merge(df_test_mordred, on=['ID', 'SMILES', 'Permeability'], how='inner').merge(df_test_padel, on=['ID', 'SMILES', 'Permeability'], how='inner')
df_2d_test

ID                                             SMILES  Permeability  \
0   2352  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H]([C...        -6.340   
1   5669  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...        -5.760   
2   1881  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
3   5666  CCCC[C@@H]1NC(=O)[C@H](CCCC)NC(=O)[C@H](CCCC)N...        -6.460   
4   1877  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
5   1873  CC(C)C[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N2CCC[C...        -4.620   
6   1878  CCC[C@H]1C(=O)N(C)[C@H](CC)C(=O)N(C)[C@@H](C)C...        -7.300   
7   1849  O=C1CN(CCCc2ccccc2)C(=O)[C@H]2CCCN2C(=O)[C@H](...        -5.920   
8   1856  CC(C)(C)C[C@@H]1NC(=O)[C@@H](Cc2ccccc2)NC(=O)[...        -5.120   
9   2367  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.930   
10  2369  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)NC(=O)[C@H](Cc2...        -6.660   
11  2370  CC(C)C[C@@H]1NC(=O)[C@H](C)NC(=O)[C@H](Cc2ccc(...        -6.230   
12    45  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.840   
13    44  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.150   
14  2373  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.340   
15   970  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)N(C)C(=O)[C@H...        -5.700   
16   966  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...        -6.000   
17   979  C/C1=C\[C@@H](CC(C)C)NC(=O)[C@@H]2CCCN2C(=O)[C...        -5.000   
18  1867  C[C@H]1C(=O)N(C)[C@H](C)C(=O)N(C)[C@H](C)C(=O)...        -7.640   
19  2350  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.860   
20  5642  CCCC[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)CSC[C@@...        -5.900   
21  2342  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.460   
22    35  CC[C@H](C)[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC...        -5.490   
23    34  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.330   
24  2340  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...        -5.020   
25    31  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.120   
26  1037  CC(C)C[C@@H]1NC(=O)CN(Cc2ccc(O)cc2)C(=O)[C@H]2...        -5.140   
27  5674  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...        -5.805   
28  2295  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@@H](...        -6.440   
29  2300  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...        -5.550   
30   928  CC[C@H](C)[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@H](...        -6.220   
31  2312  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...        -4.640   
32  2323  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -5.350   
33  2308  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -4.620   
34  2335  CC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2cccc...        -5.530   
35  2303  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...        -5.310   

    MaxAbsEStateIndex  MaxEStateIndex  MinAbsEStateIndex  MinEStateIndex  \
0           15.144490       15.144490           0.113131       -1.744209   
1           15.129540       15.129540           0.022871       -1.609940   
2           15.256898       15.256898           0.000530       -1.187472   
3           14.719159       14.719159           0.026230       -1.109554   
4           15.077973       15.077973           0.025700       -1.150959   
5           15.069391       15.069391           0.013388       -1.165871   
6           14.916791       14.916791           0.003780       -1.181760   
7           14.898914       14.898914           0.085369       -1.142615   
8           14.676408       14.676408           0.002283       -1.335295   
9           14.782868       14.782868           0.013476       -1.206234   
10          14.744014       14.744014           0.011771       -1.206518   
11          14.654702       14.654702           0.010614       -1.196147   
12          14.771120       14.771120           0.039064       -1.300557   
13          14.775750       14.775750           0.004655       -1.076575   
14          14.5

In [146]:
df_2d_test.to_csv('features/Descriptors/Test_2d_all_descriptors_RRCK.csv', index=False)

In [147]:
#2d All descriptors
df_train = pd.read_csv('features/Descriptors/Train_2d_all_descriptors_RRCK.csv')
df_train = df_train.dropna()
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_all_descriptors_RRCK.csv')
df_test = df_test.dropna()
X_test = df_test[X_train.columns]
# X_test = X_test.select_dtypes(include=['number'])
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)

models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 3091)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 3091)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.005085 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 75145
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 2193
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.1893                0.3141   
DecisionTreeRegressor                    0.3379                0.4285   
RandomForestRegressor                    0.1948                0.3307   
GradientBoostingRegressor                0.1787                0.3027   
AdaBoostRegressor                        0.2098                0.3435   
XGBRegressor                             0.2196                0.3458   
ExtraTreesRegressor                      0.1730                0.3035   
LinearRegression                         6.9854                2.1410   
KNeighborsRegressor                      0.2996                0.3888   
SVR                                      0.1879                0.3024   
MLPRegressor                             0.8489                0.6298   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4351               0.5778   
DecisionTreeRegressor                     0.5813               0.2461   
RandomForestRegressor                     0.4413               0.5655   
GradientBoostingRegressor                 0.4228               0.6013   
AdaBoostRegressor                         0.4581               0.5319   
XGBRegressor                              0.4686               0.5102   
ExtraTreesRegressor                       0.4159               0.6142   
LinearRegression                          2.6430             -14.5825   
KNeighborsRegressor                       0.5473               0.3317   
SVR                                       0.4335               0.5808   
MLPRegressor                              0.9213              -0.8936   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.7653                0.8017   
DecisionTreeRegressor                    0.6011                0.6280   
RandomForestRegressor                    0.7705                0.7986   
GradientBoostingRegressor                0.7839                0.8164   
AdaBoostRegressor                        0.7399                0.7698   
XGBRegressor                             0.7199                0.7439   
ExtraTreesRegressor                      0.7951                0.8165   
LinearRegression                         0.0987                0.0713   
KNeighborsRegressor                      0.6263                0.6580   
SVR                                      0.7703                0.7885   
MLPRegressor                             0.3336                0.3453   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4412   0.4219    0.6642   0.3896   
DecisionTreeRegressor       0.3858   0.4403    0.6211   0.4663   
RandomForestRegressor       0.4578   0.4507    0.6766   0.3666   
GradientBoostingRegressor   0.3838   0.4075    0.6195   0.4691   
AdaBoostRegressor           0.4689   0.4647    0.6848   0.3512   
XGBRegressor                0.4221   0.4370    0.6497   0.4160   
ExtraTreesRegressor         0.3945   0.4104    0.6281   0.4542   
LinearRegression            3.8410   1.5482    1.9598  -4.3138   
KNeighborsRegressor         0.5297   0.4764    0.7278   0.2672   
SVR                         0.4277   0.4199    0.6540   0.4083   
MLPRegressor                0.7458   0.6148    0.8636  -0.0317   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6939                    0.7594  
DecisionTreeRegressor                       0.7339                    0.7747  
RandomForestRegressor                       0.7126                    0.7967  
GradientBoostingRegressor                   0.7472                    0.8208  
AdaBoostRegressor                           0.6879                    0.7725  
XGBRegressor                                0.7364                    0.8023  
ExtraTreesRegressor                         0.749

In [148]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.970369177318453, -6.132392137741762, -5.17...   
1   [-5.27, -5.85, -5.22, -4.79, -5.4, -6.65, -5.5...   
2   [-5.920199999999997, -5.948350000000004, -5.19...   
3   [-5.882595138241643, -6.098838380233682, -5.01...   
4   [-5.95, -6.178181818181819, -5.145714285714286...   
5   [-6.0313396, -6.393152, -4.9681315, -5.866849,...   
6   [-5.898099999999997, -5.975550000000002, -4.95...   
7   [-4.0, -9.893764330543565, -4.0, -6.6463292364...   
8   [-5.983333333333333, -6.039999999999999, -4.96...   
9   [-6.065991221478246, -5.837746879033769, -5.25...   
10  [-4.0, -6.204473690082046, -4.898314911275242,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.9658917935958025, -5.998107739358907, -6....   
1   [[-4.72, -5.95, -6.96, -6.65, -6.96, -5.4, -6....   
2   [[-5.759412500000001, -5.9544999999999995, -6....   
3   [[-5.794753250371877, -5.966750021959288, -6.7...   
4   [[-5.955, -6.0042857142857144, -6.021521739130...   
5   [[-5.8122888, -5.9500756, -6.1149626, -6.35422...   
6   [[-5.9818999999999996, -5.949999999999999, -6....   
7   [[-8.166542568299457, -5.949999999999946, -9.8...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-6.048915611556839, -6.016429888761645, -5.9...   
10  [[-6.755778633869973, -5.936198705943453, -6.4...   

                                Test Predictions Mean  \
0   [-6.144806789454829, -6.1018733508854535, -6.1...   
1   [-5.838, -5.933999999999999, -6.626, -6.432, -...   
2   [-6.064482499999999, -6.051379999999999, -6.09...   
3   [-6.041528340792622, -5.973687524696051, -6.22...   
4   [-6.159155397543633, -6.088994548588667, -6.02...   
5   [-6.0518813, -5.948022, -6.1634297, -5.9530115...   
6   [-6.141050000000001, -5.9746, -6.3648700000000...   
7   [-8.994984114726659, -5.560000000000005, -6.37...   
8   [-6.118666666666667, -5.924666666666667, -5.79...   
9   [-6.096416932880845, -6.03834784835753, -5.979...   
10  [-6.470855406104593, -5.943222981500718, -6.12...   

                                 Test Predictions Std  
0   [0.12607544189411532, 0.13832945963000004, 0.1...  
1   [0.6555730317821198, 0.03200000000000003, 0.52...  
2   [0.15420117128284025, 0.09414965533659743, 0.1...  
3   [0.21477861369986082, 0.02955278799078915, 0.4...  
4   [0.1137633154378726, 0.10439863285736561, 0.27...  
5   [0.26566187, 0.004322454, 0.39732587, 0.258586...  
6   [0.09643472403652163, 0.04920000000000009, 0.1...  
7   [1.3036665572481307, 0.7800000000000027, 2.907...  
8   [0.11400974617208051, 0.05153639490690065, 0.1...  
9   [0.029458314550472927, 0.01217190585715695, 0....  
10  [0.335695235744313, 0.012118779588710542, 0.91...

In [149]:
result_df.to_csv('results/Descriptors/Results_2D_All_desc_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_All_desc_RRCK.csv')

In [150]:
#2d All descriptors const rem
df_train = pd.read_csv('features/Descriptors/Train_2d_all_descriptors_RRCK.csv')
df_train = df_train.dropna()
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
X_train, const_col =  remove_constant_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_all_descriptors_RRCK.csv')
df_test = df_test.dropna()
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)

models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 2378)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 2378)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.007553 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 75145
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 2193
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.1893                0.3141   
DecisionTreeRegressor                    0.2890                0.4085   
RandomForestRegressor                    0.1955                0.3309   
GradientBoostingRegressor                0.1777                0.3004   
AdaBoostRegressor                        0.2184                0.3468   
XGBRegressor                             0.2196                0.3458   
ExtraTreesRegressor                      0.1671                0.2987   
LinearRegression                         6.9854                2.1410   
KNeighborsRegressor                      0.2996                0.3888   
SVR                                      0.1879                0.3024   
MLPRegressor                             0.7657                0.6192   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4351               0.5778   
DecisionTreeRegressor                     0.5376               0.3554   
RandomForestRegressor                     0.4421               0.5640   
GradientBoostingRegressor                 0.4215               0.6037   
AdaBoostRegressor                         0.4673               0.5128   
XGBRegressor                              0.4686               0.5102   
ExtraTreesRegressor                       0.4088               0.6272   
LinearRegression                          2.6430             -14.5825   
KNeighborsRegressor                       0.5473               0.3317   
SVR                                       0.4335               0.5808   
MLPRegressor                              0.8750              -0.7081   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.7653                0.8017   
DecisionTreeRegressor                    0.6494                0.6584   
RandomForestRegressor                    0.7696                0.7983   
GradientBoostingRegressor                0.7851                0.8174   
AdaBoostRegressor                        0.7242                0.7511   
XGBRegressor                             0.7199                0.7439   
ExtraTreesRegressor                      0.8068                0.8413   
LinearRegression                         0.0987                0.0713   
KNeighborsRegressor                      0.6263                0.6580   
SVR                                      0.7703                0.7885   
MLPRegressor                             0.3779                0.3922   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4412   0.4219    0.6642   0.3896   
DecisionTreeRegressor       0.4446   0.4387    0.6668   0.3849   
RandomForestRegressor       0.4494   0.4491    0.6704   0.3783   
GradientBoostingRegressor   0.3894   0.4096    0.6240   0.4613   
AdaBoostRegressor           0.4742   0.4615    0.6886   0.3440   
XGBRegressor                0.4221   0.4370    0.6497   0.4160   
ExtraTreesRegressor         0.4167   0.4194    0.6456   0.4235   
LinearRegression            3.8410   1.5482    1.9598  -4.3138   
KNeighborsRegressor         0.5297   0.4764    0.7278   0.2672   
SVR                         0.4277   0.4199    0.6540   0.4083   
MLPRegressor                0.5272   0.5005    0.7261   0.2707   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6939                    0.7594  
DecisionTreeRegressor                       0.6804                    0.7533  
RandomForestRegressor                       0.7214                    0.8046  
GradientBoostingRegressor                   0.7393                    0.8130  
AdaBoostRegressor                           0.6794                    0.7799  
XGBRegressor                                0.7364                    0.8023  
ExtraTreesRegressor                         0.730

In [151]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.970369177318453, -6.132392137741762, -5.17...   
1   [-5.06, -5.85, -5.22, -5.1, -5.57, -6.46, -5.5...   
2   [-5.9144999999999985, -5.958300000000004, -5.1...   
3   [-5.858083603547437, -6.090725928202099, -5.01...   
4   [-6.154038461538462, -6.105925925925924, -5.17...   
5   [-6.0313396, -6.393152, -4.9681315, -5.866849,...   
6   [-6.061199999999999, -5.890700000000001, -4.97...   
7   [-4.0, -9.893764330554976, -4.0, -6.6463292364...   
8   [-5.983333333333333, -6.039999999999999, -4.96...   
9   [-6.065991176813832, -5.837746800094085, -5.25...   
10  [-4.184562947711421, -5.909087945122975, -4.89...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.9658917935958025, -5.998107739358907, -6....   
1   [[-5.04, -5.95, -5.9, -6.46, -5.9, -5.4, -6.92...   
2   [[-5.778566666666666, -5.9626, -6.285050000000...   
3   [[-5.880550537402026, -5.966750021959288, -6.5...   
4   [[-6.0875, -6.105925925925924, -6.240357142857...   
5   [[-5.8122888, -5.9500756, -6.1149626, -6.35422...   
6   [[-6.063950000000001, -5.949999999999999, -6.3...   
7   [[-8.166542568292709, -5.950000000000008, -9.8...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-6.048915546498334, -6.0164298353037236, -5....   
10  [[-6.116035506468438, -5.980624337217116, -6.6...   

                                Test Predictions Mean  \
0   [-6.144806789454829, -6.1018733508854535, -6.1...   
1   [-5.848, -5.933999999999999, -6.31600000000000...   
2   [-6.059755952380952, -6.051929999999999, -6.13...   
3   [-6.06835169001967, -5.971738427290516, -6.244...   
4   [-6.1290733333333325, -6.07913201776437, -6.03...   
5   [-6.0518813, -5.948022, -6.1634297, -5.9530115...   
6   [-6.14544, -5.980459999999999, -6.309740000000...   
7   [-8.994984114737571, -5.55999999999998, -6.374...   
8   [-6.118666666666667, -5.924666666666667, -5.79...   
9   [-6.09638127541406, -6.038309374361353, -5.979...   
10  [-6.0829651676316825, -5.980647033277496, -6.7...   

                                 Test Predictions Std  
0   [0.12607544189411532, 0.13832945963000004, 0.1...  
1   [0.515418276742298, 0.03200000000000003, 0.275...  
2   [0.14220358951827505, 0.07092159473672335, 0.1...  
3   [0.20824653529098228, 0.025849448771656496, 0....  
4   [0.09863502510659018, 0.09144519338557816, 0.1...  
5   [0.26566187, 0.004322454, 0.39732587, 0.258586...  
6   [0.06385295138049563, 0.06091999999999977, 0.1...  
7   [1.3036665572284245, 0.7799999999999903, 2.907...  
8   [0.11400974617208051, 0.05153639490690065, 0.1...  
9   [0.02942561150665576, 0.012142830020049095, 0....  
10  [0.3589696154335196, 0.0346756379610031, 0.589...

In [152]:
result_df.to_csv('results/Descriptors/Results_2D_All_desc_const_rem_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_All_desc_const_rem_RRCK.csv')

In [153]:
#2d All descriptors LVR
df_train = pd.read_csv('features/Descriptors/Train_2d_all_descriptors_RRCK.csv')
df_train = df_train.dropna()
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
X_train, const_col = remove_low_variance_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_all_descriptors_RRCK.csv')
df_test = df_test.dropna()
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)

models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 1721)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 1721)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.007328 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 51508
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 1553
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.1987                0.3243   
DecisionTreeRegressor                    0.3129                0.4013   
RandomForestRegressor                    0.1980                0.3312   
GradientBoostingRegressor                0.2013                0.3182   
AdaBoostRegressor                        0.2070                0.3404   
XGBRegressor                             0.2459                0.3683   
ExtraTreesRegressor                      0.1714                0.3047   
LinearRegression                         6.6726                2.0579   
KNeighborsRegressor                      0.3046                0.3934   
SVR                                      0.1982                0.3131   
MLPRegressor                             0.8233                0.6136   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4458               0.5567   
DecisionTreeRegressor                     0.5594               0.3020   
RandomForestRegressor                     0.4450               0.5583   
GradientBoostingRegressor                 0.4487               0.5509   
AdaBoostRegressor                         0.4550               0.5383   
XGBRegressor                              0.4959               0.4515   
ExtraTreesRegressor                       0.4140               0.6177   
LinearRegression                          2.5831             -13.8849   
KNeighborsRegressor                       0.5519               0.3205   
SVR                                       0.4452               0.5580   
MLPRegressor                              0.9074              -0.8366   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.7530                0.7906   
DecisionTreeRegressor                    0.6178                0.6328   
RandomForestRegressor                    0.7641                0.7923   
GradientBoostingRegressor                0.7493                0.7808   
AdaBoostRegressor                        0.7429                0.7744   
XGBRegressor                             0.6777                0.7130   
ExtraTreesRegressor                      0.7972                0.8248   
LinearRegression                         0.1800                0.1753   
KNeighborsRegressor                      0.6161                0.6548   
SVR                                      0.7555                0.7809   
MLPRegressor                             0.3176                0.3594   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4459   0.4316    0.6677   0.3832   
DecisionTreeRegressor       0.3964   0.4544    0.6296   0.4516   
RandomForestRegressor       0.4570   0.4541    0.6760   0.3677   
GradientBoostingRegressor   0.3429   0.3916    0.5856   0.5256   
AdaBoostRegressor           0.4642   0.4670    0.6813   0.3579   
XGBRegressor                0.4076   0.4359    0.6384   0.4362   
ExtraTreesRegressor         0.4311   0.4268    0.6566   0.4036   
LinearRegression            4.0516   1.6252    2.0129  -4.6051   
KNeighborsRegressor         0.5622   0.4797    0.7498   0.2222   
SVR                         0.4577   0.4387    0.6765   0.3668   
MLPRegressor                0.6439   0.5930    0.8024   0.1092   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6889                    0.7824  
DecisionTreeRegressor                       0.7200                    0.7151  
RandomForestRegressor                       0.7116                    0.7957  
GradientBoostingRegressor                   0.7838                    0.8393  
AdaBoostRegressor                           0.6922                    0.7611  
XGBRegressor                                0.7417                    0.7779  
ExtraTreesRegressor                         0.716

In [154]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-6.042740855827409, -6.130015020955236, -5.12...   
1   [-5.75, -5.85, -5.4, -4.96, -5.39, -6.5, -5.57...   
2   [-5.97545, -5.960400000000002, -5.189500000000...   
3   [-6.098484066049467, -6.250006105051718, -5.01...   
4   [-6.183541666666666, -6.183541666666666, -5.19...   
5   [-6.0916457, -6.236822, -5.117636, -5.336735, ...   
6   [-6.146099999999998, -5.9387000000000025, -4.9...   
7   [-10.0, -10.0, -4.0, -9.141282098854738, -4.0,...   
8   [-5.983333333333333, -5.890000000000001, -4.96...   
9   [-6.0683822629088215, -5.797269607299271, -5.2...   
10  [-4.0, -6.159423373743877, -5.084402562386631,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-6.054159473685268, -6.006641824153537, -6.3...   
1   [[-4.96, -5.95, -7.48, -6.22, -6.96, -5.4, -6....   
2   [[-5.6920375000000005, -5.983499999999998, -6....   
3   [[-5.776933808058342, -5.953281568330001, -6.6...   
4   [[-6.256929824561404, -6.2327499999999985, -5....   
5   [[-5.9109235, -5.9507823, -6.506944, -5.875622...   
6   [[-5.981000000000002, -5.949999999999999, -6.4...   
7   [[-5.9485167983413, -5.949999999999967, -10.0,...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-6.0462166925957765, -6.013816070526946, -5....   
10  [[-6.043840430816421, -5.863763096807048, -6.4...   

                                Test Predictions Mean  \
0   [-6.053750049081272, -6.086965147509413, -6.09...   
1   [-6.166, -5.933999999999999, -6.45999999999999...   
2   [-6.035511166666666, -6.041489999999999, -6.10...   
3   [-6.099437579592107, -5.955640067017364, -6.51...   
4   [-6.201460499073771, -6.177264046822742, -6.13...   
5   [-6.0789757, -5.9413376, -6.2795434, -5.771903...   
6   [-6.128196666666668, -5.98042, -6.292200000000...   
7   [-9.189703359668261, -5.92722042369775, -6.4, ...   
8   [-6.118666666666667, -5.924666666666667, -5.92...   
9   [-6.090290802825197, -6.0299482448349035, -5.9...   
10  [-6.015125539584215, -5.894783990651258, -6.76...   

                                 Test Predictions Std  
0   [0.1545513555943005, 0.11752660344468674, 0.15...  
1   [0.6312400494265237, 0.03200000000000003, 0.57...  
2   [0.18724740209264357, 0.04970521501814553, 0.1...  
3   [0.24984169222556724, 0.011022839891349587, 0....  
4   [0.09536881361803985, 0.12313561243654257, 0.3...  
5   [0.28696758, 0.017888887, 0.3709551, 0.2487358...  
6   [0.08918066706286591, 0.0608399999999996, 0.21...  
7   [1.6205932806634797, 0.04555915260454953, 2.93...  
8   [0.11400974617208051, 0.05153639490690065, 0.2...  
9   [0.027256844176875527, 0.012804813812981944, 0...  
10  [0.40642611507707316, 0.028393423828297706, 0....

In [155]:
result_df.to_csv('results/Descriptors/Results_2D_All_desc_LVR_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_All_desc_LVR_RRCK.csv')

In [156]:
#2d All descriptors LVR
df_train = pd.read_csv('features/Descriptors/Train_2d_all_descriptors_RRCK.csv')
df_train = df_train.dropna()
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
X_train, const_col = remove_low_variance_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_all_descriptors_RRCK.csv')
df_test = df_test.dropna()
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)

models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 1721)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 1721)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.010554 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 51508
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 1553
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.1987                0.3243   
DecisionTreeRegressor                    0.3129                0.4013   
RandomForestRegressor                    0.1980                0.3312   
GradientBoostingRegressor                0.2013                0.3182   
AdaBoostRegressor                        0.2070                0.3404   
XGBRegressor                             0.2459                0.3683   
ExtraTreesRegressor                      0.1714                0.3047   
LinearRegression                         6.6726                2.0579   
KNeighborsRegressor                      0.3046                0.3934   
SVR                                      0.1982                0.3131   
MLPRegressor                             0.8233                0.6136   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4458               0.5567   
DecisionTreeRegressor                     0.5594               0.3020   
RandomForestRegressor                     0.4450               0.5583   
GradientBoostingRegressor                 0.4487               0.5509   
AdaBoostRegressor                         0.4550               0.5383   
XGBRegressor                              0.4959               0.4515   
ExtraTreesRegressor                       0.4140               0.6177   
LinearRegression                          2.5831             -13.8849   
KNeighborsRegressor                       0.5519               0.3205   
SVR                                       0.4452               0.5580   
MLPRegressor                              0.9074              -0.8366   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.7530                0.7906   
DecisionTreeRegressor                    0.6178                0.6328   
RandomForestRegressor                    0.7641                0.7923   
GradientBoostingRegressor                0.7493                0.7808   
AdaBoostRegressor                        0.7429                0.7744   
XGBRegressor                             0.6777                0.7130   
ExtraTreesRegressor                      0.7972                0.8248   
LinearRegression                         0.1800                0.1753   
KNeighborsRegressor                      0.6161                0.6548   
SVR                                      0.7555                0.7809   
MLPRegressor                             0.3176                0.3594   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4459   0.4316    0.6677   0.3832   
DecisionTreeRegressor       0.3964   0.4544    0.6296   0.4516   
RandomForestRegressor       0.4570   0.4541    0.6760   0.3677   
GradientBoostingRegressor   0.3429   0.3916    0.5856   0.5256   
AdaBoostRegressor           0.4642   0.4670    0.6813   0.3579   
XGBRegressor                0.4076   0.4359    0.6384   0.4362   
ExtraTreesRegressor         0.4311   0.4268    0.6566   0.4036   
LinearRegression            4.0516   1.6252    2.0129  -4.6051   
KNeighborsRegressor         0.5622   0.4797    0.7498   0.2222   
SVR                         0.4577   0.4387    0.6765   0.3668   
MLPRegressor                0.6439   0.5930    0.8024   0.1092   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6889                    0.7824  
DecisionTreeRegressor                       0.7200                    0.7151  
RandomForestRegressor                       0.7116                    0.7957  
GradientBoostingRegressor                   0.7838                    0.8393  
AdaBoostRegressor                           0.6922                    0.7611  
XGBRegressor                                0.7417                    0.7779  
ExtraTreesRegressor                         0.716

In [157]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-6.042740855827409, -6.130015020955236, -5.12...   
1   [-5.75, -5.85, -5.4, -4.96, -5.39, -6.5, -5.57...   
2   [-5.9754499999999995, -5.960400000000002, -5.1...   
3   [-6.098484066049467, -6.250006105051718, -5.01...   
4   [-6.183541666666666, -6.183541666666666, -5.19...   
5   [-6.0916457, -6.236822, -5.117636, -5.336735, ...   
6   [-6.146099999999998, -5.938700000000003, -4.99...   
7   [-10.0, -10.0, -4.0, -9.141282098854738, -4.0,...   
8   [-5.983333333333333, -5.890000000000001, -4.96...   
9   [-6.0683822629088215, -5.797269607299271, -5.2...   
10  [-4.0, -6.159423373743877, -5.084402562386631,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-6.054159473685268, -6.006641824153537, -6.3...   
1   [[-4.96, -5.95, -7.48, -6.22, -6.96, -5.4, -6....   
2   [[-5.692037499999999, -5.983499999999998, -6.2...   
3   [[-5.776933808058342, -5.953281568330001, -6.6...   
4   [[-6.256929824561404, -6.2327499999999985, -5....   
5   [[-5.9109235, -5.9507823, -6.506944, -5.875622...   
6   [[-5.981, -5.949999999999999, -6.4587000000000...   
7   [[-5.9485167983413, -5.949999999999967, -10.0,...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-6.0462166925957765, -6.013816070526946, -5....   
10  [[-6.043840430816421, -5.863763096807048, -6.4...   

                                Test Predictions Mean  \
0   [-6.053750049081272, -6.086965147509413, -6.09...   
1   [-6.166, -5.933999999999999, -6.45999999999999...   
2   [-6.035511166666666, -6.041489999999999, -6.10...   
3   [-6.099437579592107, -5.955640067017364, -6.51...   
4   [-6.201460499073771, -6.177264046822742, -6.13...   
5   [-6.0789757, -5.9413376, -6.2795434, -5.771903...   
6   [-6.128196666666666, -5.98042, -6.292200000000...   
7   [-9.189703359668261, -5.92722042369775, -6.4, ...   
8   [-6.118666666666667, -5.924666666666667, -5.92...   
9   [-6.090290802825197, -6.0299482448349035, -5.9...   
10  [-6.015125539584215, -5.894783990651258, -6.76...   

                                 Test Predictions Std  
0   [0.1545513555943005, 0.11752660344468674, 0.15...  
1   [0.6312400494265237, 0.03200000000000003, 0.57...  
2   [0.18724740209264407, 0.04970521501814566, 0.1...  
3   [0.24984169222556724, 0.011022839891349587, 0....  
4   [0.09536881361803985, 0.12313561243654257, 0.3...  
5   [0.28696758, 0.017888887, 0.3709551, 0.2487358...  
6   [0.0891806670628665, 0.0608399999999996, 0.219...  
7   [1.6205932806634797, 0.04555915260454953, 2.93...  
8   [0.11400974617208051, 0.05153639490690065, 0.2...  
9   [0.027256844176875527, 0.012804813812981944, 0...  
10  [0.40642611507707316, 0.028393423828297706, 0....

In [158]:
def features(df, target_column='Permeability', threshold=0.9):
    correlation_matrix = df.corr()
    
    features_to_drop = set()
    
    for feature in correlation_matrix.columns:
        if feature == target_column:
            continue 
        target_corr = correlation_matrix[target_column][feature]
        
        for other_feature in correlation_matrix.columns:
            if other_feature == feature or other_feature == target_column:
                continue
            
            if abs(correlation_matrix[feature][other_feature]) > threshold:
                other_target_corr = correlation_matrix[target_column][other_feature]

                if abs(other_target_corr) < abs(target_corr):
                    features_to_drop.add(other_feature)
                else:
                    features_to_drop.add(feature)
    selected_features = [col for col in df.columns if col not in features_to_drop and col != target_column]
    
    return selected_features

In [159]:
def remove_low_variance_columns(df, threshold=0.005):
    # df = df.drop(['ID','SMILES','Permeability'],axis=1)
    variances = df.var()
    
    low_variance_columns = variances[variances < threshold].index.tolist()
    
    df_cleaned = df.drop(columns=low_variance_columns)
    
    return df_cleaned, low_variance_columns

In [160]:
df_train = pd.read_csv('features/Descriptors/Train_2d_all_descriptors_RRCK.csv')
df_train =df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
X_train = df_train[selected_features] 
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_all_descriptors_RRCK.csv')
df_test =df_test.dropna()
X_test =  df_test[X_train.columns]
y_test =  df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 200)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 200)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000751 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 6368
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 183
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further spl

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.2137                0.3283   
DecisionTreeRegressor                    0.3933                0.4630   
RandomForestRegressor                    0.2099                0.3391   
GradientBoostingRegressor                0.2042                0.3199   
AdaBoostRegressor                        0.2125                0.3475   
XGBRegressor                             0.2296                0.3399   
ExtraTreesRegressor                      0.1674                0.2896   
LinearRegression                        10.3504                2.7293   
KNeighborsRegressor                      0.2475                0.3469   
SVR                                      0.1831                0.2984   
MLPRegressor                             0.8175                0.6444   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4622               0.5234   
DecisionTreeRegressor                     0.6271               0.1226   
RandomForestRegressor                     0.4581               0.5319   
GradientBoostingRegressor                 0.4519               0.5445   
AdaBoostRegressor                         0.4610               0.5260   
XGBRegressor                              0.4791               0.4879   
ExtraTreesRegressor                       0.4092               0.6265   
LinearRegression                          3.2172             -22.0891   
KNeighborsRegressor                       0.4975               0.4479   
SVR                                       0.4279               0.5915   
MLPRegressor                              0.9041              -0.8235   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.7266                0.7498   
DecisionTreeRegressor                    0.5375                0.5785   
RandomForestRegressor                    0.7449                0.7776   
GradientBoostingRegressor                0.7423                0.7630   
AdaBoostRegressor                        0.7321                0.7661   
XGBRegressor                             0.7084                0.7374   
ExtraTreesRegressor                      0.8039                0.8286   
LinearRegression                        -0.0550               -0.0578   
KNeighborsRegressor                      0.7125                0.7413   
SVR                                      0.7788                0.8017   
MLPRegressor                             0.3549                0.4014   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.4561   0.4375    0.6753   0.3690   
DecisionTreeRegressor       0.5516   0.4584    0.7427   0.2369   
RandomForestRegressor       0.4756   0.4540    0.6896   0.3421   
GradientBoostingRegressor   0.3961   0.4113    0.6293   0.4521   
AdaBoostRegressor           0.4589   0.4713    0.6775   0.3651   
XGBRegressor                0.4629   0.4377    0.6804   0.3596   
ExtraTreesRegressor         0.3980   0.4004    0.6308   0.4494   
LinearRegression            3.6156   1.4842    1.9015  -4.0020   
KNeighborsRegressor         0.5002   0.4372    0.7072   0.3080   
SVR                         0.4177   0.4272    0.6463   0.4222   
MLPRegressor                0.8669   0.6902    0.9311  -0.1992   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6751                    0.7531  
DecisionTreeRegressor                       0.6094                    0.7116  
RandomForestRegressor                       0.6942                    0.7826  
GradientBoostingRegressor                   0.7336                    0.8048  
AdaBoostRegressor                           0.7091                    0.7837  
XGBRegressor                                0.6716                    0.7568  
ExtraTreesRegressor                         0.736

In [161]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.964825361867922, -6.077557099554694, -5.37...   
1   [-5.75, -6.92, -4.72, -5.35, -5.57, -6.2, -5.3...   
2   [-5.938850000000002, -6.0618000000000025, -5.2...   
3   [-5.957059228573685, -5.974052517076113, -5.17...   
4   [-5.960999999999999, -6.340000000000001, -5.22...   
5   [-5.987833, -6.585021, -5.0471787, -5.843211, ...   
6   [-6.043899999999997, -6.035900000000002, -4.99...   
7   [-10.0, -10.0, -10.0, -10.0, -4.0, -4.0, -4.0,...   
8   [-5.983333333333333, -5.956666666666666, -4.96...   
9   [-6.086433033735662, -6.003214623674186, -5.14...   
10  [-4.514701368086937, -6.415603959149268, -5.10...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-6.062920239971026, -6.046056711494199, -6.1...   
1   [[-6.13, -5.95, -6.46, -6.96, -6.46, -4.72, -6...   
2   [[-6.021049999999999, -5.952899999999999, -6.0...   
3   [[-5.877567455757229, -5.9472873677240115, -6....   
4   [[-5.928461538461539, -5.984196428571429, -6.2...   
5   [[-6.207873, -5.9503126, -6.5326333, -6.522365...   
6   [[-6.034799999999998, -5.949999999999999, -6.2...   
7   [[-10.0, -5.949995756149292, -10.0, -4.0, -10....   
8   [[-5.983333333333333, -5.983333333333333, -5.6...   
9   [[-6.038152242726986, -6.004717886322186, -6.1...   
10  [[-6.159352198626121, -6.006461483171463, -6.6...   

                                Test Predictions Mean  \
0   [-6.2123817498350595, -6.099024971665787, -6.0...   
1   [-6.2299999999999995, -5.909999999999999, -5.6...   
2   [-6.1039, -6.015899999999999, -5.9589600000000...   
3   [-6.068035855570859, -5.9624130098537576, -6.2...   
4   [-6.003092307692308, -5.991048809523809, -6.15...   
5   [-6.221828, -5.981726, -6.391731, -6.4018874, ...   
6   [-6.12787, -5.9624, -6.15050333333334, -6.2563...   
7   [-8.8, -6.7600058685056865, -8.8, -8.8, -7.6, ...   
8   [-6.118666666666667, -5.924666666666667, -5.59...   
9   [-6.08329100909606, -6.006315510035184, -6.033...   
10  [-6.038851186344752, -5.986370910148574, -6.02...   

                                 Test Predictions Std  
0   [0.08899109390533108, 0.08366785956757977, 0.0...  
1   [0.40630038149132963, 0.08000000000000007, 0.6...  
2   [0.06550886962847223, 0.046350965469988445, 0....  
3   [0.16102305285259572, 0.021021184693871285, 0....  
4   [0.10442120440309986, 0.06718877866472982, 0.1...  
5   [0.12702148, 0.06331007, 0.22075535, 0.0991331...  
6   [0.05718154947183715, 0.02480000000000082, 0.1...  
7   [2.4, 1.6199970657997123, 2.4, 2.4, 2.93938769...  
8   [0.11400974617208051, 0.05153639490690065, 0.0...  
9   [0.028653453042295433, 0.007113596218060493, 0...  
10  [0.5171296865632818, 0.028363077778388823, 0.8...

In [162]:
result_df.to_csv('results/Descriptors/Results_2D_All_desc_LVR_remove_corr_features_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_All_desc_LVRremove_corr_features_RRCK.csv')

In [163]:
#3d RDKit descriptors
df_train = pd.read_csv('features/Descriptors/Train_3d_RDKit_desc_RRCK.csv')
df_train = df_train.fillna(0)
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_3d_RDKit_desc_RRCK.csv')
df_test = df_test.fillna(0)
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 11)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 11)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000160 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 429
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 11
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits 

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-4.102362540664324


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.4171                0.5321   
DecisionTreeRegressor                    0.7283                0.6369   
RandomForestRegressor                    0.4255                0.5230   
GradientBoostingRegressor                0.4802                0.5527   
AdaBoostRegressor                        0.4075                0.5227   
XGBRegressor                             0.5549                0.5911   
ExtraTreesRegressor                      0.4267                0.5125   
LinearRegression                         0.3937                0.5100   
KNeighborsRegressor                      0.4776                0.5526   
SVR                                      0.4128                0.5032   
MLPRegressor                             1.5401                1.0519   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.6459               0.0695   
DecisionTreeRegressor                     0.8534              -0.6246   
RandomForestRegressor                     0.6523               0.0509   
GradientBoostingRegressor                 0.6930              -0.0712   
AdaBoostRegressor                         0.6384               0.0909   
XGBRegressor                              0.7449              -0.2378   
ExtraTreesRegressor                       0.6533               0.0480   
LinearRegression                          0.6275               0.1217   
KNeighborsRegressor                       0.6911              -0.0653   
SVR                                       0.6425               0.0792   
MLPRegressor                              1.2410              -2.4356   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.3434                0.3533   
DecisionTreeRegressor                    0.1887                0.2321   
RandomForestRegressor                    0.3475                0.3355   
GradientBoostingRegressor                0.2986                0.3163   
AdaBoostRegressor                        0.3669                0.3532   
XGBRegressor                             0.2782                0.2638   
ExtraTreesRegressor                      0.3579                0.3593   
LinearRegression                         0.3908                0.3933   
KNeighborsRegressor                      0.2720                0.2538   
SVR                                      0.3576                0.3770   
MLPRegressor                             0.2383                0.2428   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.7117   0.6103    0.8436   0.0154   
DecisionTreeRegressor       0.6613   0.6065    0.8132   0.0851   
RandomForestRegressor       0.6616   0.5853    0.8134   0.0848   
GradientBoostingRegressor   0.7728   0.6550    0.8791  -0.0691   
AdaBoostRegressor           0.7177   0.6009    0.8472   0.0071   
XGBRegressor                0.7189   0.6086    0.8479   0.0054   
ExtraTreesRegressor         0.6589   0.6012    0.8117   0.0884   
LinearRegression            0.7267   0.6479    0.8525  -0.0054   
KNeighborsRegressor         0.6708   0.6277    0.8190   0.0720   
SVR                         0.7149   0.6180    0.8455   0.0110   
MLPRegressor                3.6882   1.6204    1.9205  -4.1024   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.5157                    0.5045  
DecisionTreeRegressor                       0.3956                    0.3891  
RandomForestRegressor                       0.5223                    0.5197  
GradientBoostingRegressor                   0.3654                    0.4007  
AdaBoostRegressor                           0.4682                    0.5293  
XGBRegressor                                0.4615                    0.4777  
ExtraTreesRegressor                         0.552

In [164]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.872003524851464, -5.942129055819188, -5.31...   
1   [-6.78, -6.05, -5.42, -6.05, -6.2, -6.2, -5.15...   
2   [-6.299199999999996, -5.87615, -5.365150000000...   
3   [-5.904479547823848, -5.773721757026033, -5.30...   
4   [-6.26777777777778, -5.799999999999999, -4.885...   
5   [-6.2667065, -6.00524, -5.41745, -6.151754, -5...   
6   [-6.149899999999994, -5.91865, -5.193099999999...   
7   [-6.179801415444179, -5.618190818597676, -5.53...   
8   [-6.1000000000000005, -5.373333333333332, -5.4...   
9   [-5.966884806434886, -5.645558420755609, -5.13...   
10  [-6.785353232381543, -5.006341059804458, -4.0,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.755940552295383, -5.856191468088004, -5.9...   
1   [[-6.78, -5.84, -5.27, -6.46, -6.46, -5.42, -6...   
2   [[-6.523199999999998, -5.798650000000001, -6.2...   
3   [[-6.903864880670385, -5.915039155870065, -6.2...   
4   [[-6.26777777777778, -6.0, -6.05, -6.267777777...   
5   [[-5.8767705, -5.5623827, -6.2302837, -6.46231...   
6   [[-6.551199999999995, -5.759200000000001, -6.3...   
7   [[-6.786285968466434, -6.030062181191648, -5.9...   
8   [[-6.396666666666667, -5.816666666666666, -6.6...   
9   [[-6.409146270334343, -5.717958608151982, -6.3...   
10  [[-8.27174296584065, -6.952825441788487, -6.39...   

                                Test Predictions Mean  \
0   [-5.795272979695544, -5.953710163105655, -5.81...   
1   [-6.628, -6.014, -6.222, -6.736, -6.5179999999...   
2   [-6.503379999999998, -5.898920000000002, -6.12...   
3   [-6.63451808711072, -5.8174296957989595, -6.03...   
4   [-6.379655555555556, -5.91436234931315, -5.960...   
5   [-6.4135537, -5.591857, -6.3050094, -6.5786386...   
6   [-6.537019999999998, -5.839330000000002, -6.36...   
7   [-6.69649226219903, -5.929780987620515, -6.046...   
8   [-6.462666666666666, -6.003333333333333, -6.44...   
9   [-6.446659390877706, -5.924377573856949, -6.24...   
10  [-8.234165181373251, -7.057935837789826, -6.45...   

                                 Test Predictions Std  
0   [0.09840001832947044, 0.11618448601482735, 0.1...  
1   [0.14400000000000013, 0.32927799805027974, 0.4...  
2   [0.0908385689010977, 0.11954100802653297, 0.23...  
3   [0.3195249532101394, 0.22835808247725112, 0.25...  
4   [0.19669131797794523, 0.11880587095018216, 0.2...  
5   [0.31780335, 0.2158499, 0.16549943, 0.14937702...  
6   [0.12561077023885894, 0.17077601002482506, 0.0...  
7   [0.21159755836590985, 0.09627386048396676, 0.1...  
8   [0.0945727233402952, 0.10654159333852271, 0.20...  
9   [0.22078497324284418, 0.14375954333557256, 0.1...  
10  [0.1622461237602918, 0.18270252316205662, 0.10...

In [165]:
result_df.to_csv('results/Descriptors/Results_3D_RDKit_desc_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_3D_RDKit_desc_RRCK.csv')

In [166]:
#3d Padel descriptors
df_train = pd.read_csv('features/Descriptors/Train_3d_padel_curated_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_3d_padel_curated_RRCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)

models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 431)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 431)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000850 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 16797
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 431
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further sp

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-0.6656756991038764


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.2801                0.4068   
DecisionTreeRegressor                    0.5784                0.5636   
RandomForestRegressor                    0.2948                0.4193   
GradientBoostingRegressor                0.2808                0.3969   
AdaBoostRegressor                        0.3015                0.4214   
XGBRegressor                             0.3327                0.4403   
ExtraTreesRegressor                      0.2491                0.3897   
LinearRegression                         0.9267                0.7425   
KNeighborsRegressor                      0.2747                0.3981   
SVR                                      0.2898                0.4083   
MLPRegressor                             1.2690                0.9153   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.5293               0.3751   
DecisionTreeRegressor                     0.7605              -0.2902   
RandomForestRegressor                     0.5430               0.3424   
GradientBoostingRegressor                 0.5299               0.3735   
AdaBoostRegressor                         0.5491               0.3274   
XGBRegressor                              0.5768               0.2578   
ExtraTreesRegressor                       0.4991               0.4442   
LinearRegression                          0.9626              -1.0672   
KNeighborsRegressor                       0.5242               0.3871   
SVR                                       0.5384               0.3535   
MLPRegressor                              1.1265              -1.8309   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.6133                0.6163   
DecisionTreeRegressor                    0.3273                0.3475   
RandomForestRegressor                    0.5914                0.5812   
GradientBoostingRegressor                0.6125                0.6244   
AdaBoostRegressor                        0.5730                0.5966   
XGBRegressor                             0.5315                0.5241   
ExtraTreesRegressor                      0.6719                0.6764   
LinearRegression                         0.3621                0.3981   
KNeighborsRegressor                      0.6353                0.6394   
SVR                                      0.5977                0.6075   
MLPRegressor                             0.2694                0.2579   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.5844   0.4899    0.7645   0.1915   
DecisionTreeRegressor       0.6083   0.5419    0.7799   0.1585   
RandomForestRegressor       0.5902   0.5144    0.7682   0.1835   
GradientBoostingRegressor   0.5733   0.4886    0.7572   0.2069   
AdaBoostRegressor           0.5530   0.4869    0.7436   0.2350   
XGBRegressor                0.6013   0.4877    0.7754   0.1681   
ExtraTreesRegressor         0.5400   0.4828    0.7349   0.2529   
LinearRegression            0.5654   0.6081    0.7519   0.2178   
KNeighborsRegressor         0.6030   0.5397    0.7765   0.1658   
SVR                         0.5958   0.5037    0.7719   0.1757   
MLPRegressor                1.2040   0.8230    1.0973  -0.6657   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.5505                    0.6311  
DecisionTreeRegressor                       0.5109                    0.5802  
RandomForestRegressor                       0.5680                    0.6517  
GradientBoostingRegressor                   0.5368                    0.6383  
AdaBoostRegressor                           0.5864                    0.6700  
XGBRegressor                                0.5124                    0.6199  
ExtraTreesRegressor                         0.606

In [167]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-6.083883518850135, -5.527057402178294, -5.53...   
1   [-5.87, -6.0, -4.72, -4.72, -5.32, -6.15, -5.4...   
2   [-6.025799999999996, -5.931700000000002, -5.54...   
3   [-6.003805726670968, -5.676413695862027, -5.22...   
4   [-6.080000000000001, -6.176756756756755, -5.70...   
5   [-6.1610446, -5.70738, -5.0716186, -5.33462, -...   
6   [-6.007500000000001, -5.693450000000005, -5.22...   
7   [-6.581426525696719, -6.10630925923904, -5.337...   
8   [-5.983333333333333, -5.62, -5.013333333333333...   
9   [-5.960503535423703, -5.349923221552294, -5.38...   
10  [-5.465308042772654, -5.519455317150743, -4.81...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.8292324717894095, -6.086972703160939, -5....   
1   [[-6.13, -6.78, -5.4, -6.2, -4.72, -4.0, -6.92...   
2   [[-5.9885, -6.352349999999999, -5.412949999999...   
3   [[-6.046919364450175, -6.761120253690717, -5.1...   
4   [[-6.121666666666667, -6.176756756756755, -5.4...   
5   [[-5.979779, -6.515469, -5.46173, -6.58951, -5...   
6   [[-6.015900000000001, -6.267299999999998, -5.7...   
7   [[-4.270765796533121, -5.6361231459939924, -7....   
8   [[-5.8566666666666665, -6.2, -5.83333333333333...   
9   [[-5.869916628005446, -6.183782287558216, -5.6...   
10  [[-6.046969288785053, -6.2817257287908985, -7....   

                                Test Predictions Mean  \
0   [-6.119379305882473, -6.265640295321556, -5.43...   
1   [-6.418000000000001, -6.332, -5.258, -6.226000...   
2   [-6.054090000000002, -6.31396, -5.475569999999...   
3   [-6.19881270627492, -6.564540918707979, -5.408...   
4   [-6.1878404220779215, -6.296777858071977, -5.5...   
5   [-6.068549, -6.4852037, -5.175097, -6.12424, -...   
6   [-6.105640000000003, -6.368019999999999, -5.83...   
7   [-4.740603282211241, -6.172600226959391, -6.89...   
8   [-6.115333333333333, -6.194, -5.94133333333333...   
9   [-6.039845328072169, -6.1699153499668125, -5.7...   
10  [-6.906502626675426, -5.624676247389368, -8.41...   

                                 Test Predictions Std  
0   [0.20211151015170611, 0.21118330209146374, 0.1...  
1   [0.6548098960767165, 0.4363209827638366, 0.513...  
2   [0.08850796800288632, 0.10720117256821184, 0.1...  
3   [0.2037177583456372, 0.2660755471137488, 0.303...  
4   [0.11380767642821006, 0.11916346305000047, 0.1...  
5   [0.32355437, 0.22838202, 0.30195123, 0.3099596...  
6   [0.08206737719703305, 0.06039335725061076, 0.1...  
7   [0.6439077156744848, 0.8156642804422526, 0.838...  
8   [0.1347854261821771, 0.03349295116554826, 0.21...  
9   [0.0899343155732827, 0.13173625856950746, 0.07...  
10  [0.5544585424498438, 0.8457669504588029, 0.795...

In [168]:
result_df.to_csv('results/Descriptors/Results_3D_padel_desc_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_3D_padel_desc_RRCK.csv')

In [169]:
df_train_rdkit = pd.read_csv('features/Descriptors/Train_3d_RDKit_desc_RRCK.csv')
df_train_rdkit = df_train_rdkit.fillna(0)
df_train_padel = pd.read_csv('features/Descriptors/Train_3d_padel_curated_RRCK.csv')

df_3d_descriptors = df_train_rdkit.merge(df_train_padel, on=['ID', 'SMILES', 'Permeability'], how='inner')
df_3d_descriptors

ID                                             SMILES  Permeability  \
0    2358  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](C(...         -6.13   
1    2359  C/C=C/C[C@@H](C)C(=O)[C@H]1C(=O)N[C@@H](C(C)C)...         -6.66   
2    2357  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...         -5.95   
3    2360  C/C=C/C[C@@H](C)[C@H]1OC(=O)[C@H](C(C)C)N(C)C(...         -6.78   
4    2353  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](C)...         -5.87   
..    ...                                                ...           ...   
135  2336  CC[C@@H]1NC(=O)[C@@H](CC)NC(=O)[C@H](CC(C)C)NC...         -5.39   
136  2306  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...         -4.75   
137  2334  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...         -5.58   
138  2305  CCC[C@@H]1C(=O)N(C)[C@@H](C)C(=O)N[C@@H](CC(C)...         -4.85   
139  2304  CC[C@@H]1C(=O)N(C)[C@@H](C)C(=O)N[C@@H](CC(C)C...         -5.51   

       3d_rdkit_1    3d_rdkit_2    3d_rdkit_3  3d_rdkit_4  3d_rdkit_5  \
0    25557.550768  38719.861789  59078.304374    0.432605    0.655399   
1    25195.527353  38098.222481  54940.535676    0.458596    0.693445   
2    27673.061526  37624.458338  57474.870399    0.481481    0.654625   
3    27053.583076  35398.003591  54685.502768    0.494712    0.647301   
4    25621.505581  37274.558430  58032.092029    0.441506    0.642309   
..            ...           ...           ...         ...         ...   
135   6396.621513   8859.792939  12249.856286    0.522179    0.723257   
136   5807.131702   8158.649035  11412.673395    0.508832    0.714876   
137   6143.538968   9226.806179  12259.349342    0.501131    0.752634   
138   5497.580476   7708.634196  10921.176551    0.503387    0.705843   
139   5067.194628   7061.682449  10603.344186    0.477886    0.665986   

     3d_rdkit_6  3d_rdkit_7  ...       P1s       P2s       E1s       E2s  \
0      7.119995    0.000026  ...  0.584742  0.289275  0.526481  0.467149   
1      6.976408    0.000028  ...  0.562959  0.330424  0.573577  0.533312   
2      7.144444    0.000024  ...  0.505864  0.386967  0.530722  0.572866   
3      6.978552    0.000024  ...  0.543224  0.390435  0.549748  0.553013   
4      7.132297    0.000025  ...  0.559155  0.365398  0.567980  0.530505   
..          ...         ...  ...       ...       ...       ...       ...   
135    4.632664    0.000113  ...  0.480821  0.450969  0.447622  0.401417   
136    4.520944    0.000123  ...  0.587350  0.351181  0.540411  0.549950   
137    4.748141    0.000123  ...  0.603934  0.302221  0.478983  0.563029   
138    4.458761    0.000128  ...  0.573506  0.364677  0.497225  0.533337   
139    4.378834    0.000131  ...  0.597941  0.312068  0.477574  0.513718   

          E3s         Ts          As           Vs        Ks        Ds  
0    0.355332  51.237177  733.133564  3650.811196  0.377113  1.348962  
1    0.392941  52.061975  762.354776  3612.998411  0.344438  1.499831  
2    0.283984  52.691795  809.151889  3930.912570  0.339246  1.387572  
3    0.367643  60.025118  987.347841  4090.444574  0.400488  1.470405  
4    0.368965  55.664600  849.215301  3563.631478  0.386829  1.467450  
..        ...        ...         ...          ...       ...       ...  
135  0.374652  28.991239  235.667908   625.054603  0.397685  1.223691  
136  0.480266  27.093819  193.764285   473.031633  0.407795  1.570627  
137  0.379015  26.877338  193.282773   552.730401  0.405901  1.421027  
138  0.460216  26.843623  192.495908   469.419500  0.407274  1.490778  
139  0.429588  25.998557  181.479702   502.568103  0.396911  1.420879  

[140 rows x 445 columns]

In [170]:
nan_rows = df_3d_descriptors[df_3d_descriptors.isna().any(axis=1)]
nan_rows

Empty DataFrame
Columns: [ID, SMILES, Permeability, 3d_rdkit_1, 3d_rdkit_2, 3d_rdkit_3, 3d_rdkit_4, 3d_rdkit_5, 3d_rdkit_6, 3d_rdkit_7, 3d_rdkit_8, 3d_rdkit_9, 3d_rdkit_10, 3d_rdkit_11, TDB1u, TDB2u, TDB3u, TDB4u, TDB5u, TDB6u, TDB7u, TDB8u, TDB9u, TDB10u, TDB1m, TDB2m, TDB3m, TDB4m, TDB5m, TDB6m, TDB7m, TDB8m, TDB9m, TDB10m, TDB1v, TDB2v, TDB3v, TDB4v, TDB5v, TDB6v, TDB7v, TDB8v, TDB9v, TDB10v, TDB1e, TDB2e, TDB3e, TDB4e, TDB5e, TDB6e, TDB7e, TDB8e, TDB9e, TDB10e, TDB1p, TDB2p, TDB3p, TDB4p, TDB5p, TDB6p, TDB7p, TDB8p, TDB9p, TDB10p, TDB1i, TDB2i, TDB3i, TDB4i, TDB5i, TDB6i, TDB7i, TDB8i, TDB9i, TDB10i, TDB1s, TDB2s, TDB3s, TDB4s, TDB5s, TDB6s, TDB7s, TDB8s, TDB9s, TDB10s, TDB1r, TDB2r, TDB3r, TDB4r, TDB5r, TDB6r, TDB7r, TDB8r, TDB9r, TDB10r, PPSA-1, PPSA-2, PPSA-3, PNSA-1, PNSA-2, PNSA-3, ...]
Index: []

[0 rows x 445 columns]

In [171]:
df_3d_descriptors.to_csv('features/Descriptors/Train_3d_all_descriptors_RRCK.csv', index=False)

In [172]:
df_test_rdkit = pd.read_csv('features/Descriptors/Test_3d_RDKit_desc_RRCK.csv')
df_test_rdkit = df_test_rdkit.fillna(0)
df_test_padel = pd.read_csv('features/Descriptors/Test_3d_padel_curated_RRCK.csv')

df_3d_descriptors = df_test_rdkit.merge(df_test_padel, on=['ID', 'SMILES', 'Permeability'], how='inner')
df_3d_descriptors

ID                                             SMILES  Permeability  \
0   2352  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H]([C...        -6.340   
1   5669  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...        -5.760   
2   1881  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
3   5666  CCCC[C@@H]1NC(=O)[C@H](CCCC)NC(=O)[C@H](CCCC)N...        -6.460   
4   1877  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
5   1873  CC(C)C[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N2CCC[C...        -4.620   
6   1878  CCC[C@H]1C(=O)N(C)[C@H](CC)C(=O)N(C)[C@@H](C)C...        -7.300   
7   1849  O=C1CN(CCCc2ccccc2)C(=O)[C@H]2CCCN2C(=O)[C@H](...        -5.920   
8   1856  CC(C)(C)C[C@@H]1NC(=O)[C@@H](Cc2ccccc2)NC(=O)[...        -5.120   
9   2367  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.930   
10  2369  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)NC(=O)[C@H](Cc2...        -6.660   
11  2370  CC(C)C[C@@H]1NC(=O)[C@H](C)NC(=O)[C@H](Cc2ccc(...        -6.230   
12    45  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.840   
13    44  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.150   
14  2373  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.340   
15   970  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)N(C)C(=O)[C@H...        -5.700   
16   966  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...        -6.000   
17   979  C/C1=C\[C@@H](CC(C)C)NC(=O)[C@@H]2CCCN2C(=O)[C...        -5.000   
18  1867  C[C@H]1C(=O)N(C)[C@H](C)C(=O)N(C)[C@H](C)C(=O)...        -7.640   
19  2350  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.860   
20  5642  CCCC[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)CSC[C@@...        -5.900   
21  2342  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.460   
22    35  CC[C@H](C)[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC...        -5.490   
23    34  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.330   
24  2340  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...        -5.020   
25    31  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.120   
26  1037  CC(C)C[C@@H]1NC(=O)CN(Cc2ccc(O)cc2)C(=O)[C@H]2...        -5.140   
27  5674  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...        -5.805   
28  2295  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@@H](...        -6.440   
29  2300  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...        -5.550   
30   928  CC[C@H](C)[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@H](...        -6.220   
31  2312  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...        -4.640   
32  2323  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -5.350   
33  2308  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -4.620   
34  2335  CC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2cccc...        -5.530   
35  2303  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...        -5.310   

      3d_rdkit_1    3d_rdkit_2    3d_rdkit_3  3d_rdkit_4  3d_rdkit_5  \
0   29235.649823  34655.335992  53592.422815    0.545518    0.646646   
1   24087.943860  41198.827889  58197.846259    0.413898    0.707910   
2   22337.453461  27133.737115  43092.072922    0.518366    0.629669   
3   21040.064822  23207.945553  36960.965663    0.569251    0.627904   
4   16994.956964  24094.700818  35431.898340    0.479651    0.680029   
5   17472.947386  17989.322133  28544.470331    0.612131    0.630221   
6   13628.705114  21498.885200  30535.503048    0.446323    0.704062   
7   14236.954483  23107.885866  33197.287392    0.428859    0.696078   
8   14226.804330  17829.943731  27524.068649    0.516886    0.647795   
9   11077.747263  22031.587026  31047.115110    0.356804    0.709618   
10  11326.023581  14897.695490  20875.976524    0.542539    0.713629   
11   9661.578795  17425.969585  23043.313808    0.419279    0.756227   
12  10220.582964  15788.331748  22826.296192    0.447755    0.691673   
13   8421.400126  18518.486738  22795.149909    0.369438    0.812387   
14  12991.462588  13644.177504  20700.057195    0.627605    0.659137   
15  

In [173]:
nan_rows = df_3d_descriptors[df_3d_descriptors.isna().any(axis=1)]
nan_rows

Empty DataFrame
Columns: [ID, SMILES, Permeability, 3d_rdkit_1, 3d_rdkit_2, 3d_rdkit_3, 3d_rdkit_4, 3d_rdkit_5, 3d_rdkit_6, 3d_rdkit_7, 3d_rdkit_8, 3d_rdkit_9, 3d_rdkit_10, 3d_rdkit_11, TDB1u, TDB2u, TDB3u, TDB4u, TDB5u, TDB6u, TDB7u, TDB8u, TDB9u, TDB10u, TDB1m, TDB2m, TDB3m, TDB4m, TDB5m, TDB6m, TDB7m, TDB8m, TDB9m, TDB10m, TDB1v, TDB2v, TDB3v, TDB4v, TDB5v, TDB6v, TDB7v, TDB8v, TDB9v, TDB10v, TDB1e, TDB2e, TDB3e, TDB4e, TDB5e, TDB6e, TDB7e, TDB8e, TDB9e, TDB10e, TDB1p, TDB2p, TDB3p, TDB4p, TDB5p, TDB6p, TDB7p, TDB8p, TDB9p, TDB10p, TDB1i, TDB2i, TDB3i, TDB4i, TDB5i, TDB6i, TDB7i, TDB8i, TDB9i, TDB10i, TDB1s, TDB2s, TDB3s, TDB4s, TDB5s, TDB6s, TDB7s, TDB8s, TDB9s, TDB10s, TDB1r, TDB2r, TDB3r, TDB4r, TDB5r, TDB6r, TDB7r, TDB8r, TDB9r, TDB10r, PPSA-1, PPSA-2, PPSA-3, PNSA-1, PNSA-2, PNSA-3, ...]
Index: []

[0 rows x 445 columns]

In [174]:
df_3d_descriptors.to_csv('features/Descriptors/Test_3d_all_descriptors_RRCK.csv', index=False)

In [175]:
#3d All descriptors
df_train = pd.read_csv('features/Descriptors/Train_3d_all_descriptors_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_3d_all_descriptors_RRCK.csv')
X_test = df_test.drop(['ID','SMILES','Permeability'],axis=1)
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)

models_3dall = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models_3dall, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 442)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 442)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001889 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 17226
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 442
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further sp

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-0.9620996450272525


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.2815                0.4166   
DecisionTreeRegressor                    0.5402                0.5613   
RandomForestRegressor                    0.2887                0.4169   
GradientBoostingRegressor                0.2820                0.4093   
AdaBoostRegressor                        0.2868                0.4103   
XGBRegressor                             0.3386                0.4460   
ExtraTreesRegressor                      0.2447                0.3869   
LinearRegression                         0.8107                0.6945   
KNeighborsRegressor                      0.3083                0.4118   
SVR                                      0.2828                0.4112   
MLPRegressor                             1.4356                0.9482   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.5306               0.3720   
DecisionTreeRegressor                     0.7350              -0.2050   
RandomForestRegressor                     0.5374               0.3559   
GradientBoostingRegressor                 0.5310               0.3710   
AdaBoostRegressor                         0.5356               0.3601   
XGBRegressor                              0.5819               0.2447   
ExtraTreesRegressor                       0.4947               0.4541   
LinearRegression                          0.9004              -0.8085   
KNeighborsRegressor                       0.5552               0.3123   
SVR                                       0.5318               0.3691   
MLPRegressor                              1.1982              -2.2025   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.6100                0.6170   
DecisionTreeRegressor                    0.3819                0.4014   
RandomForestRegressor                    0.6044                0.5985   
GradientBoostingRegressor                0.6095                0.6173   
AdaBoostRegressor                        0.6025                0.6143   
XGBRegressor                             0.5240                0.5119   
ExtraTreesRegressor                      0.6826                0.6916   
LinearRegression                         0.3745                0.3949   
KNeighborsRegressor                      0.5860                0.5926   
SVR                                      0.6116                0.6289   
MLPRegressor                             0.1903                0.1783   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.5896   0.4864    0.7679   0.1843   
DecisionTreeRegressor       0.6216   0.5510    0.7884   0.1401   
RandomForestRegressor       0.5965   0.5106    0.7723   0.1748   
GradientBoostingRegressor   0.5547   0.4756    0.7448   0.2326   
AdaBoostRegressor           0.6020   0.4988    0.7759   0.1671   
XGBRegressor                0.5615   0.4785    0.7494   0.2231   
ExtraTreesRegressor         0.5433   0.4873    0.7371   0.2484   
LinearRegression            0.5279   0.5985    0.7266   0.2697   
KNeighborsRegressor         0.5707   0.5204    0.7555   0.2104   
SVR                         0.5813   0.4905    0.7624   0.1958   
MLPRegressor                1.4183   0.9472    1.1909  -0.9621   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.5498                    0.6456  
DecisionTreeRegressor                       0.5060                    0.5632  
RandomForestRegressor                       0.5609                    0.6615  
GradientBoostingRegressor                   0.5684                    0.6759  
AdaBoostRegressor                           0.5419                    0.6662  
XGBRegressor                                0.5625                    0.6649  
ExtraTreesRegressor                         0.607

In [176]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-6.061280204336053, -5.642516435070985, -5.63...   
1   [-6.13, -6.0, -4.96, -4.92, -5.32, -6.1, -5.64...   
2   [-6.049149999999998, -5.893850000000001, -5.49...   
3   [-5.877677273988712, -5.641289130325236, -4.96...   
4   [-6.075999999999999, -5.79909090909091, -5.354...   
5   [-5.9296527, -5.7853117, -5.1196985, -5.320116...   
6   [-6.076999999999998, -5.634750000000006, -5.22...   
7   [-6.704425652392967, -5.942027064982862, -5.23...   
8   [-5.983333333333333, -5.62, -5.013333333333333...   
9   [-5.982090047018158, -5.356810667292101, -5.37...   
10  [-6.008430281023746, -4.888556886196576, -4.80...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.9279174118521665, -6.118134729855113, -5....   
1   [[-5.57, -6.78, -5.52, -6.2, -5.255, -4.0, -6....   
2   [[-6.0302000000000024, -6.325849999999999, -5....   
3   [[-5.974122401074046, -6.606321263160108, -5.2...   
4   [[-6.075999999999999, -6.386666666666666, -5.4...   
5   [[-5.923534, -6.290812, -5.238607, -6.2919836,...   
6   [[-6.125200000000001, -6.153999999999999, -5.8...   
7   [[-4.7115342758379395, -6.427760858178813, -7....   
8   [[-5.8566666666666665, -6.2, -5.83333333333333...   
9   [[-5.902489096417722, -6.200665883282355, -5.7...   
10  [[-6.328939395527414, -6.8815056671718065, -8....   

                                Test Predictions Mean  \
0   [-6.125998388780452, -6.276067685891588, -5.41...   
1   [-6.248, -6.578, -5.2780000000000005, -6.15799...   
2   [-6.099100000000002, -6.2869, -5.426, -5.93548...   
3   [-6.196383999264733, -6.497362121604473, -5.38...   
4   [-6.1279564102564095, -6.287823333333334, -5.4...   
5   [-5.977851, -6.294189, -5.295204, -6.0961604, ...   
6   [-6.2767800000000005, -6.27912, -5.90778999999...   
7   [-5.019749770770046, -6.595834625294442, -6.81...   
8   [-6.115333333333333, -6.194, -5.94133333333333...   
9   [-6.062269622460747, -6.176095126637981, -5.79...   
10  [-6.612094666635156, -5.8637663300689935, -9.2...   

                                 Test Predictions Std  
0   [0.14383906188286094, 0.1537500222151755, 0.14...  
1   [0.5553161261839962, 0.601544678307439, 0.5262...  
2   [0.10746236550532345, 0.11825796801907063, 0.1...  
3   [0.2783375982040261, 0.24256085435893085, 0.16...  
4   [0.07019450932034847, 0.07619581032518243, 0.1...  
5   [0.31703836, 0.29552066, 0.22809951, 0.2183583...  
6   [0.15398305621073985, 0.12019216946207216, 0.1...  
7   [0.48009957083890836, 0.8044439316210611, 0.70...  
8   [0.1347854261821771, 0.03349295116554826, 0.21...  
9   [0.08652478856876819, 0.1287023318712948, 0.06...  
10  [0.7249246481226181, 0.5512078399494664, 0.692...

In [177]:
result_df.to_csv('results/Descriptors/Results_3D_All_desc_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_3D_All_desc_RRCK.csv')

In [178]:
#3d All descriptors const rem
df_train = pd.read_csv('features/Descriptors/Train_3d_all_descriptors_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train,  const_col =  remove_constant_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_3d_all_descriptors_RRCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)

models_3dall = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models_3dall, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 442)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 442)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001106 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 17226
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 442
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further sp

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-0.9620996450272525


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.2815                0.4166   
DecisionTreeRegressor                    0.5402                0.5613   
RandomForestRegressor                    0.2887                0.4169   
GradientBoostingRegressor                0.2820                0.4093   
AdaBoostRegressor                        0.2868                0.4103   
XGBRegressor                             0.3386                0.4460   
ExtraTreesRegressor                      0.2447                0.3869   
LinearRegression                         0.8107                0.6945   
KNeighborsRegressor                      0.3083                0.4118   
SVR                                      0.2828                0.4112   
MLPRegressor                             1.4356                0.9482   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.5306               0.3720   
DecisionTreeRegressor                     0.7350              -0.2050   
RandomForestRegressor                     0.5374               0.3559   
GradientBoostingRegressor                 0.5310               0.3710   
AdaBoostRegressor                         0.5356               0.3601   
XGBRegressor                              0.5819               0.2447   
ExtraTreesRegressor                       0.4947               0.4541   
LinearRegression                          0.9004              -0.8085   
KNeighborsRegressor                       0.5552               0.3123   
SVR                                       0.5318               0.3691   
MLPRegressor                              1.1982              -2.2025   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.6100                0.6170   
DecisionTreeRegressor                    0.3819                0.4014   
RandomForestRegressor                    0.6044                0.5985   
GradientBoostingRegressor                0.6095                0.6173   
AdaBoostRegressor                        0.6025                0.6143   
XGBRegressor                             0.5240                0.5119   
ExtraTreesRegressor                      0.6826                0.6916   
LinearRegression                         0.3745                0.3949   
KNeighborsRegressor                      0.5860                0.5926   
SVR                                      0.6116                0.6289   
MLPRegressor                             0.1903                0.1783   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.5896   0.4864    0.7679   0.1843   
DecisionTreeRegressor       0.6216   0.5510    0.7884   0.1401   
RandomForestRegressor       0.5965   0.5106    0.7723   0.1748   
GradientBoostingRegressor   0.5547   0.4756    0.7448   0.2326   
AdaBoostRegressor           0.6020   0.4988    0.7759   0.1671   
XGBRegressor                0.5615   0.4785    0.7494   0.2231   
ExtraTreesRegressor         0.5433   0.4873    0.7371   0.2484   
LinearRegression            0.5279   0.5985    0.7266   0.2697   
KNeighborsRegressor         0.5707   0.5204    0.7555   0.2104   
SVR                         0.5813   0.4905    0.7624   0.1958   
MLPRegressor                1.4183   0.9472    1.1909  -0.9621   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.5498                    0.6456  
DecisionTreeRegressor                       0.5060                    0.5632  
RandomForestRegressor                       0.5609                    0.6615  
GradientBoostingRegressor                   0.5684                    0.6759  
AdaBoostRegressor                           0.5419                    0.6662  
XGBRegressor                                0.5625                    0.6649  
ExtraTreesRegressor                         0.607

In [179]:
result_df.to_csv('results/Descriptors/Results_3D_All_desc_const_rem_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_3D_All_desc_const_rem_RRCK.csv')

In [180]:
#3d All descriptors LVR
df_train = pd.read_csv('features/Descriptors/Train_3d_all_descriptors_RRCK.csv')
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train,  const_col =  remove_low_variance_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_3d_all_descriptors_RRCK.csv')
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)

models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 375)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 375)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000581 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 14615
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 375
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further sp

c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(
c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


-1.328406480175389


c:\Python312\Lib\site-packages\sklearn\neural_network\_multilayer_perceptron.py:691: ConvergenceWarning: Stochastic Optimizer: Maximum iterations (200) reached and the optimization hasn't converged yet.
  warnings.warn(


Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.2541                0.3914   
DecisionTreeRegressor                    0.5700                0.5722   
RandomForestRegressor                    0.2854                0.4162   
GradientBoostingRegressor                0.2791                0.3982   
AdaBoostRegressor                        0.2913                0.4134   
XGBRegressor                             0.3499                0.4490   
ExtraTreesRegressor                      0.2562                0.3966   
LinearRegression                         0.8550                0.7445   
KNeighborsRegressor                      0.2788                0.4025   
SVR                                      0.2660                0.3919   
MLPRegressor                             1.2183                0.8691   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.5040               0.4333   
DecisionTreeRegressor                     0.7550              -0.2716   
RandomForestRegressor                     0.5343               0.3632   
GradientBoostingRegressor                 0.5283               0.3774   
AdaBoostRegressor                         0.5397               0.3503   
XGBRegressor                              0.5916               0.2194   
ExtraTreesRegressor                       0.5061               0.4286   
LinearRegression                          0.9247              -0.9074   
KNeighborsRegressor                       0.5280               0.3780   
SVR                                       0.5158               0.4065   
MLPRegressor                              1.1038              -1.7176   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.6607                0.6582   
DecisionTreeRegressor                    0.3438                0.3582   
RandomForestRegressor                    0.6099                0.6142   
GradientBoostingRegressor                0.6168                0.6402   
AdaBoostRegressor                        0.5945                0.6432   
XGBRegressor                             0.5070                0.5026   
ExtraTreesRegressor                      0.6595                0.6767   
LinearRegression                         0.3518                0.3479   
KNeighborsRegressor                      0.6275                0.6282   
SVR                                      0.6457                0.6634   
MLPRegressor                             0.2452                0.2204   

                          Test MSE Test MAE Test RMSE  Test R2  \
LGBMRegressor               0.5417   0.4767    0.7360   0.2506   
DecisionTreeRegressor       0.6585   0.5753    0.8115   0.0890   
RandomForestRegressor       0.5851   0.5145    0.7649   0.1906   
GradientBoostingRegressor   0.5392   0.4680    0.7343   0.2540   
AdaBoostRegressor           0.5759   0.5172    0.7589   0.2033   
XGBRegressor                0.5191   0.4726    0.7205   0.2818   
ExtraTreesRegressor         0.5430   0.4858    0.7369   0.2488   
LinearRegression            0.5394   0.6218    0.7344   0.2538   
KNeighborsRegressor         0.5709   0.4953    0.7555   0.2103   
SVR                         0.6085   0.5161    0.7800   0.1582   
MLPRegressor                1.6831   0.9501    1.2973  -1.3284   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.5895                    0.6807  
DecisionTreeRegressor                       0.4575                    0.5163  
RandomForestRegressor                       0.5672                    0.6498  
GradientBoostingRegressor                   0.5781                    0.6665  
AdaBoostRegressor                           0.5747                    0.6592  
XGBRegressor                                0.5993                    0.6678  
ExtraTreesRegressor                         0.601

In [181]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-6.1430883691767, -5.395675073910066, -5.3797...   
1   [-6.13, -6.1, -5.1, -4.72, -5.32, -6.2, -5.4, ...   
2   [-6.107700000000001, -5.803900000000001, -5.45...   
3   [-6.1238104017940085, -5.517853282453478, -5.1...   
4   [-5.937142857142857, -5.58, -5.31235294117647,...   
5   [-6.1512623, -5.803018, -4.960959, -5.4792514,...   
6   [-6.065499999999998, -5.597900000000003, -5.20...   
7   [-6.703641805614134, -5.184239037233611, -5.29...   
8   [-5.983333333333333, -5.663333333333334, -5.01...   
9   [-5.969112754584967, -5.322032241719517, -5.34...   
10  [-6.702404457838305, -5.462935000877643, -5.33...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.833089740429352, -6.147505760880303, -5.3...   
1   [[-6.13, -7.48, -5.52, -6.2, -5.1, -4.0, -6.92...   
2   [[-6.055650000000002, -6.247500000000001, -5.5...   
3   [[-6.0299184172677505, -6.699628349472598, -5....   
4   [[-6.01, -6.3741666666666665, -5.3305263157894...   
5   [[-6.0198164, -6.4950795, -5.431509, -6.380409...   
6   [[-6.062449999999999, -6.256399999999998, -5.8...   
7   [[-5.430048763013518, -5.152499054380396, -9.6...   
8   [[-5.983333333333333, -6.133333333333333, -5.8...   
9   [[-5.905727313418048, -6.209875646430859, -5.7...   
10  [[-6.3638770242512495, -7.258921771642432, -9....   

                                Test Predictions Mean  \
0   [-6.17016398474901, -6.205525816150542, -5.503...   
1   [-6.324, -6.562, -5.3, -5.8260000000000005, -5...   
2   [-6.1729899999999995, -6.3099099999999995, -5....   
3   [-6.316615901649781, -6.477687587788493, -5.42...   
4   [-6.172385073260073, -6.260632420091325, -5.53...   
5   [-6.2488866, -6.2577353, -5.5189705, -6.422532...   
6   [-6.26399, -6.3061799999999995, -5.87854, -6.1...   
7   [-5.284210067342322, -5.731950659807234, -7.46...   
8   [-6.1659999999999995, -6.154, -5.9239999999999...   
9   [-6.074561637265738, -6.16348140681811, -5.790...   
10  [-6.475237355425183, -6.684794024643226, -9.67...   

                                 Test Predictions Std  
0   [0.2094826804359627, 0.22297928816455892, 0.13...  
1   [0.5791925413884405, 0.7581662086904166, 0.430...  
2   [0.10599152041554974, 0.1448530096339017, 0.09...  
3   [0.1906780016462925, 0.2656656208368843, 0.343...  
4   [0.12451918280468363, 0.12144402524065999, 0.2...  
5   [0.16434918, 0.23736133, 0.47906342, 0.1811814...  
6   [0.1598229720659706, 0.12200885869476596, 0.18...  
7   [0.2867808558912039, 0.8393200286291204, 1.269...  
8   [0.0956475009837916, 0.04133333333333375, 0.18...  
9   [0.09191746328543957, 0.144159932290712, 0.076...  
10  [0.3982115981547071, 0.5031922152196343, 0.414...

In [182]:
result_df.to_csv('results/Descriptors/Results_3D_All_desc_LVR_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_3D_All_desc_LVR_RRCK.csv')

In [183]:
#2d and 3d descriptors all
df_train_2d = pd.read_csv('features/Descriptors/Train_2d_all_descriptors_RRCK.csv')
df_train_2d
df_train_3d = pd.read_csv('features/Descriptors/Train_3d_all_descriptors_RRCK.csv')
df_train_3d

df_2d_3d_train = df_train_2d.merge(df_train_3d, on=['ID', 'SMILES', 'Permeability'], how='inner')
df_2d_3d_train.to_csv('features/Descriptors/Train_2d_3d_all_descriptors_RRCK.csv', index=False)
df_2d_3d_train

ID                                             SMILES  Permeability  \
0    2358  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](C(...         -6.13   
1    2359  C/C=C/C[C@@H](C)C(=O)[C@H]1C(=O)N[C@@H](C(C)C)...         -6.66   
2    2357  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...         -5.95   
3    2360  C/C=C/C[C@@H](C)[C@H]1OC(=O)[C@H](C(C)C)N(C)C(...         -6.78   
4    2353  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](C)...         -5.87   
..    ...                                                ...           ...   
135  2336  CC[C@@H]1NC(=O)[C@@H](CC)NC(=O)[C@H](CC(C)C)NC...         -5.39   
136  2306  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...         -4.75   
137  2334  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...         -5.58   
138  2305  CCC[C@@H]1C(=O)N(C)[C@@H](C)C(=O)N[C@@H](CC(C)...         -4.85   
139  2304  CC[C@@H]1C(=O)N(C)[C@@H](C)C(=O)N[C@@H](CC(C)C...         -5.51   

     MaxAbsEStateIndex  MaxEStateIndex  MinAbsEStateIndex  MinEStateIndex  \
0            15.193873       15.193873           0.130769       -1.621791   
1            15.152762       15.152762           0.128114       -1.816236   
2            15.129540       15.129540           0.022871       -1.609940   
3            15.028142       15.028142           0.097424       -1.231351   
4            15.068092       15.068092           0.128760       -1.611421   
..                 ...             ...                ...             ...   
135          13.940180       13.940180           0.023137       -1.031903   
136          13.929912       13.929912           0.048761       -0.934108   
137          13.805528       13.805528           0.023859       -1.030988   
138          13.850263       13.850263           0.054388       -0.925132   
139          13.811409       13.811409           0.054806       -0.925415   

          qed        SPS     MolWt  ...       P1s       P2s       E1s  \
0    0.147476  26.802326  1216.662  ...  0.584742  0.289275  0.526481   
1    0.134993  26.372093  1214.646  ...  0.562959  0.330424  0.573577   
2    0.147925  26.905882  1202.635  ...  0.505864  0.386967  0.530722   
3    0.116062  27.411765  1202.635  ...  0.543224  0.390435  0.549748   
4    0.157205  27.083333  1188.608  ...  0.559155  0.365398  0.567980   
..        ...        ...       ...  ...       ...       ...       ...   
135  0.289440  27.260870   640.826  ...  0.480821  0.450969  0.447622   
136  0.462849  28.954545   620.836  ...  0.587350  0.351181  0.540411   
137  0.318688  27.954545   612.772  ...  0.603934  0.302221  0.478983   
138  0.468423  29.209302   606.809  ...  0.573506  0.364677  0.497225   
139  0.488135  29.619048   592.782  ...  0.597941  0.312068  0.477574   

          E2s       E3s         Ts          As           Vs        Ks  \
0    0.467149  0.355332  51.237177  733.133564  3650.811196  0.377113   
1    0.533312  0.392941  52.061975  762.354776  3612.998411  0.344438   
2    0.572866  0.283984  52.691795  809.151889  3930.912570  0.339246   
3    0.553013  0.367643  60.025118  987.347841  4090.444574  0.400488   
4    0.530505  0.368965  55.664600  849.215301  3563.631478  0.386829   
..        ...       ...        ...         ...          ...       ...   
135  0.401417  0.374652  28.991239  235.667908   625.054603  0.397685   
136  0.549950  0.480266  27.093819  193.764285   473.031633  0.407795   
137  0.563029  0.379015  26.877338  193.282773   552.730401  0.405901   
138  0.533337  0.460216  26.843623  192.495908   469.419500  0.407274   
139  0.513718  0.429588  25.998557  181.479702   502.568103  0.396911   

           Ds  
0    1.348962  
1    1.499831  
2    1.387572  
3    1.470405  
4    1.467450  
..        ...  
135  1.223691  
136  1.570627  
137  1.421027  
138  1.490778  
139  1.420879  

[140 rows x 3719 columns]

In [184]:
df_test_2d = pd.read_csv('features/Descriptors/Test_2d_all_descriptors_RRCK.csv')
df_test_2d
df_test_3d = pd.read_csv('features/Descriptors/Test_3d_all_descriptors_RRCK.csv')
df_test_3d

df_2d_3d_test = df_test_2d.merge(df_test_3d, on=['ID', 'SMILES', 'Permeability'], how='inner')
df_2d_3d_test.to_csv('features/Descriptors/Test_2d_3d_all_descriptors_RRCK.csv', index=False)
df_2d_3d_test

ID                                             SMILES  Permeability  \
0   2352  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H]([C...        -6.340   
1   5669  C/C=C/C[C@@H](C)[C@@H](O)[C@H]1C(=O)N[C@@H](CC...        -5.760   
2   1881  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
3   5666  CCCC[C@@H]1NC(=O)[C@H](CCCC)NC(=O)[C@H](CCCC)N...        -6.460   
4   1877  CCCC[C@H]1C(=O)N(C)[C@H](CCCC)C(=O)N(C)[C@H](C...        -8.000   
5   1873  CC(C)C[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N2CCC[C...        -4.620   
6   1878  CCC[C@H]1C(=O)N(C)[C@H](CC)C(=O)N(C)[C@@H](C)C...        -7.300   
7   1849  O=C1CN(CCCc2ccccc2)C(=O)[C@H]2CCCN2C(=O)[C@H](...        -5.920   
8   1856  CC(C)(C)C[C@@H]1NC(=O)[C@@H](Cc2ccccc2)NC(=O)[...        -5.120   
9   2367  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.930   
10  2369  CC(C)C[C@@H]1NC(=O)[C@H](C(C)C)NC(=O)[C@H](Cc2...        -6.660   
11  2370  CC(C)C[C@@H]1NC(=O)[C@H](C)NC(=O)[C@H](Cc2ccc(...        -6.230   
12    45  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.840   
13    44  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.150   
14  2373  CC[C@H](C)[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)...        -6.340   
15   970  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)N(C)C(=O)[C@H...        -5.700   
16   966  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@H]...        -6.000   
17   979  C/C1=C\[C@@H](CC(C)C)NC(=O)[C@@H]2CCCN2C(=O)[C...        -5.000   
18  1867  C[C@H]1C(=O)N(C)[C@H](C)C(=O)N(C)[C@H](C)C(=O)...        -7.640   
19  2350  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.860   
20  5642  CCCC[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)CSC[C@@...        -5.900   
21  2342  CCC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2ccc...        -5.460   
22    35  CC[C@H](C)[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC...        -5.490   
23    34  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -5.330   
24  2340  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)NC(=O)[C@H]...        -5.020   
25    31  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)N(C)C(=O...        -6.120   
26  1037  CC(C)C[C@@H]1NC(=O)CN(Cc2ccc(O)cc2)C(=O)[C@H]2...        -5.140   
27  5674  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccc(O)cc2)NC(=O)[C...        -5.805   
28  2295  CC(C)C[C@@H]1NC(=O)[C@@H](CC(C)C)NC(=O)[C@@H](...        -6.440   
29  2300  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...        -5.550   
30   928  CC[C@H](C)[C@@H]1NC(=O)[C@@H]2CCCN2C(=O)[C@H](...        -6.220   
31  2312  CC(C)C[C@@H]1NC(=O)[C@H](Cc2ccccc2)N(C)C(=O)[C...        -4.640   
32  2323  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -5.350   
33  2308  CC[C@H]1C(=O)N[C@@H](CC(C)C)C(=O)N2CCC[C@@H]2C...        -4.620   
34  2335  CC[C@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@H](Cc2cccc...        -5.530   
35  2303  CC(C)C[C@@H]1NC(=O)[C@H](C)N(C)C(=O)[C@H]2CCCN...        -5.310   

    MaxAbsEStateIndex  MaxEStateIndex  MinAbsEStateIndex  MinEStateIndex  \
0           15.144490       15.144490           0.113131       -1.744209   
1           15.129540       15.129540           0.022871       -1.609940   
2           15.256898       15.256898           0.000530       -1.187472   
3           14.719159       14.719159           0.026230       -1.109554   
4           15.077973       15.077973           0.025700       -1.150959   
5           15.069391       15.069391           0.013388       -1.165871   
6           14.916791       14.916791           0.003780       -1.181760   
7           14.898914       14.898914           0.085369       -1.142615   
8           14.676408       14.676408           0.002283       -1.335295   
9           14.782868       14.782868           0.013476       -1.206234   
10          14.744014       14.744014           0.011771       -1.206518   
11          14.654702       14.654702           0.010614       -1.196147   
12          14.771120       14.771120           0.039064       -1.300557   
13          14.775750       14.775750           0.004655       -1.076575   
14          14.5

In [185]:
#All 2d and 3d descriptors
df_train = pd.read_csv('features/Descriptors/Train_2d_3d_all_descriptors_RRCK.csv')
df_train = df_train.dropna()
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_3d_all_descriptors_RRCK.csv')
df_test = df_test.dropna()
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 3533)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 3533)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.007399 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 92371
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 2635
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.2140                0.3459   
DecisionTreeRegressor                    0.3643                0.4618   
RandomForestRegressor                    0.2142                0.3553   
GradientBoostingRegressor                0.2030                0.3334   
AdaBoostRegressor                        0.2316                0.3694   
XGBRegressor                             0.2749                0.3982   
ExtraTreesRegressor                      0.1927                0.3255   
LinearRegression                         0.3899                0.4606   
KNeighborsRegressor                      0.2813                0.3789   
SVR                                      0.1945                0.3138   
MLPRegressor                             0.9887                0.7086   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4626               0.5227   
DecisionTreeRegressor                     0.6036               0.1873   
RandomForestRegressor                     0.4628               0.5222   
GradientBoostingRegressor                 0.4505               0.5472   
AdaBoostRegressor                         0.4812               0.4834   
XGBRegressor                              0.5243               0.3868   
ExtraTreesRegressor                       0.4390               0.5701   
LinearRegression                          0.6244               0.1302   
KNeighborsRegressor                       0.5304               0.3725   
SVR                                       0.4410               0.5661   
MLPRegressor                              0.9943              -1.2054   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.7288                0.7554   
DecisionTreeRegressor                    0.5531                0.5546   
RandomForestRegressor                    0.7427                0.7616   
GradientBoostingRegressor                0.7478                0.7555   
AdaBoostRegressor                        0.7062                0.7235   
XGBRegressor                             0.6301                0.6533   
ExtraTreesRegressor                      0.7648                0.7729   
LinearRegression                         0.5958                0.6226   
KNeighborsRegressor                      0.6569                0.6846   
SVR                                      0.7610                0.7801   
MLPRegressor                             0.2635                0.2909   

                          Test MSE Test MAE Test RMSE Test R2  \
LGBMRegressor               0.4700   0.4364    0.6856  0.3498   
DecisionTreeRegressor       0.4559   0.4468    0.6752  0.3693   
RandomForestRegressor       0.4783   0.4633    0.6916  0.3383   
GradientBoostingRegressor   0.4004   0.4062    0.6328  0.4461   
AdaBoostRegressor           0.4998   0.4597    0.7070  0.3086   
XGBRegressor                0.4721   0.4513    0.6871  0.3469   
ExtraTreesRegressor         0.4226   0.4243    0.6501  0.4153   
LinearRegression            0.3053   0.4420    0.5525  0.5777   
KNeighborsRegressor         0.5597   0.4739    0.7481  0.2257   
SVR                         0.4426   0.4319    0.6653  0.3877   
MLPRegressor                0.5377   0.5277    0.7333  0.2562   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6734                    0.7802  
DecisionTreeRegressor                       0.6731                    0.7278  
RandomForestRegressor                       0.6983                    0.7873  
GradientBoostingRegressor                   0.7319                    0.8238  
AdaBoostRegressor                           0.6539                    0.7483  
XGBRegressor                                0.6819                    0.7798  
ExtraTreesRegressor                         0.7254           

In [186]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.984106631148668, -6.049591747297483, -5.09...   
1   [-5.75, -5.85, -5.4, -4.72, -5.57, -6.2, -5.57...   
2   [-6.008649999999997, -5.996800000000004, -5.23...   
3   [-5.867823263063595, -6.240501741620101, -5.07...   
4   [-5.944583333333334, -6.0225, -5.2032142857142...   
5   [-6.092227, -6.308349, -5.0307407, -5.6635227,...   
6   [-6.0848, -5.812500000000003, -5.0382000000000...   
7   [-6.133203104058406, -5.8957312508055395, -5.2...   
8   [-5.983333333333333, -6.039999999999999, -4.96...   
9   [-6.040947125737306, -5.78495406479584, -5.280...   
10  [-4.888848717537231, -6.135746042454973, -5.32...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.999833488241906, -6.066504928906188, -6.1...   
1   [[-5.39, -5.95, -6.1, -6.46, -5.9, -5.4, -6.92...   
2   [[-5.935649999999997, -6.1665, -6.183800000000...   
3   [[-5.734208848252741, -6.141899408379327, -6.4...   
4   [[-6.013684210526315, -5.970000000000001, -6.1...   
5   [[-5.8222427, -6.1322875, -6.058396, -6.032231...   
6   [[-6.085099999999998, -6.061399999999997, -6.3...   
7   [[-5.727972461709701, -5.792749041251861, -8.3...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-6.013858871931068, -6.091248206643578, -5.8...   
10  [[-6.212230267458808, -6.426898345116415, -6.8...   

                                Test Predictions Mean  \
0   [-6.083826894566467, -6.174136344684146, -5.92...   
1   [-5.626, -6.076, -6.234, -6.386, -5.996, -5.09...   
2   [-6.09363, -6.164949999999999, -5.984350000000...   
3   [-6.111998427502735, -6.1561787968217265, -6.1...   
4   [-6.159993893387314, -6.134768324573399, -5.86...   
5   [-6.0275545, -6.133803, -6.0266595, -5.911379,...   
6   [-6.193319999999998, -6.1379, -6.2131700000000...   
7   [-5.754914869117431, -6.133103207550368, -7.43...   
8   [-6.118666666666667, -5.924666666666667, -5.78...   
9   [-6.0727349438524145, -6.094438060936506, -5.9...   
10  [-6.341352420417409, -6.1579302656602675, -7.3...   

                                 Test Predictions Std  
0   [0.1662487613321342, 0.1717963136001346, 0.121...  
1   [0.5298528097500286, 0.29363923443572726, 0.18...  
2   [0.08891484465487312, 0.08251992486666469, 0.1...  
3   [0.21285050130844616, 0.13913919704847905, 0.2...  
4   [0.10383507672559192, 0.09255855822491685, 0.2...  
5   [0.2094793, 0.14878775, 0.27972436, 0.24473776...  
6   [0.0667054540498756, 0.07734799286342219, 0.09...  
7   [0.41467613130413705, 0.29070018349713234, 1.0...  
8   [0.11400974617208051, 0.05153639490690065, 0.1...  
9   [0.03426107184379328, 0.019100298923346772, 0....  
10  [0.39589455037766913, 0.21455701232995453, 0.5...

In [187]:
result_df.to_csv('results/Descriptors/Results_2D_3D_All_desc_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_3D_All_desc_RRCK.csv')

In [188]:
#All 2d and 3d descriptors const rem
df_train = pd.read_csv('features/Descriptors/Train_2d_3d_all_descriptors_RRCK.csv')
df_train = df_train.dropna()
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
X_train,  const_col =  remove_constant_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_3d_all_descriptors_RRCK.csv')
df_test = df_test.dropna()
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 2820)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 2820)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.012918 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 92371
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 2635
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.2140                0.3459   
DecisionTreeRegressor                    0.3911                0.4744   
RandomForestRegressor                    0.2146                0.3540   
GradientBoostingRegressor                0.1970                0.3322   
AdaBoostRegressor                        0.2056                0.3492   
XGBRegressor                             0.2749                0.3982   
ExtraTreesRegressor                      0.1823                0.3157   
LinearRegression                         0.3899                0.4606   
KNeighborsRegressor                      0.2813                0.3789   
SVR                                      0.1945                0.3138   
MLPRegressor                             0.9922                0.7480   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4626               0.5227   
DecisionTreeRegressor                     0.6254               0.1275   
RandomForestRegressor                     0.4632               0.5214   
GradientBoostingRegressor                 0.4438               0.5606   
AdaBoostRegressor                         0.4534               0.5415   
XGBRegressor                              0.5243               0.3868   
ExtraTreesRegressor                       0.4270               0.5933   
LinearRegression                          0.6244               0.1302   
KNeighborsRegressor                       0.5304               0.3725   
SVR                                       0.4410               0.5661   
MLPRegressor                              0.9961              -1.2133   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.7288                0.7554   
DecisionTreeRegressor                    0.5308                0.5241   
RandomForestRegressor                    0.7433                0.7656   
GradientBoostingRegressor                0.7573                0.7657   
AdaBoostRegressor                        0.7594                0.7684   
XGBRegressor                             0.6301                0.6533   
ExtraTreesRegressor                      0.7823                0.7989   
LinearRegression                         0.5958                0.6226   
KNeighborsRegressor                      0.6569                0.6846   
SVR                                      0.7610                0.7796   
MLPRegressor                             0.2711                0.2663   

                          Test MSE Test MAE Test RMSE Test R2  \
LGBMRegressor               0.4700   0.4364    0.6856  0.3498   
DecisionTreeRegressor       0.3988   0.4295    0.6315  0.4483   
RandomForestRegressor       0.4828   0.4650    0.6949  0.3320   
GradientBoostingRegressor   0.4005   0.4083    0.6329  0.4459   
AdaBoostRegressor           0.4949   0.4730    0.7035  0.3154   
XGBRegressor                0.4721   0.4513    0.6871  0.3469   
ExtraTreesRegressor         0.4075   0.4164    0.6383  0.4363   
LinearRegression            0.3053   0.4420    0.5525  0.5777   
KNeighborsRegressor         0.5597   0.4739    0.7481  0.2257   
SVR                         0.4426   0.4319    0.6653  0.3877   
MLPRegressor                0.6474   0.5964    0.8046  0.1043   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6734                    0.7802  
DecisionTreeRegressor                       0.7281                    0.7830  
RandomForestRegressor                       0.6941                    0.7860  
GradientBoostingRegressor                   0.7292                    0.8267  
AdaBoostRegressor                           0.6777                    0.7559  
XGBRegressor                                0.6819                    0.7798  
ExtraTreesRegressor                         0.7442           

In [189]:
prediction_df

Model  \
0               LGBMRegressor   
1       DecisionTreeRegressor   
2       RandomForestRegressor   
3   GradientBoostingRegressor   
4           AdaBoostRegressor   
5                XGBRegressor   
6         ExtraTreesRegressor   
7            LinearRegression   
8         KNeighborsRegressor   
9                         SVR   
10               MLPRegressor   

                                         Y Train pred  \
0   [-5.984106631148668, -6.049591747297483, -5.09...   
1   [-5.75, -5.85, -5.4, -4.72, -5.32, -6.22, -5.4...   
2   [-5.956599999999997, -5.986850000000004, -5.23...   
3   [-5.872298013178286, -6.239447449488504, -5.00...   
4   [-5.99, -5.957222222222223, -5.179130434782609...   
5   [-6.092227, -6.308349, -5.0307407, -5.6635227,...   
6   [-5.911149999999999, -5.9760000000000035, -5.0...   
7   [-6.133203104058401, -5.895731250805537, -5.27...   
8   [-5.983333333333333, -6.039999999999999, -4.96...   
9   [-6.040947126819007, -5.784954065316029, -5.28...   
10  [-4.0, -5.992295304539315, -4.894631530630543,...   

                                        Y Test actual  \
0   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
1   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
2   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
3   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
4   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
5   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
6   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
7   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
8   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
9   0    -6.340
1    -5.760
2    -8.000
3    -6.46...   
10  0    -6.340
1    -5.760
2    -8.000
3    -6.46...   

                                Test prediction folds  \
0   [[-5.999833488241906, -6.066504928906188, -6.1...   
1   [[-5.4, -5.95, -7.48, -6.96, -7.48, -5.4, -6.6...   
2   [[-5.846899999999998, -6.0909, -6.150950000000...   
3   [[-5.772621537130071, -6.03986029011038, -6.43...   
4   [[-6.0528571428571425, -6.0625, -6.09363636363...   
5   [[-5.8222427, -6.1322875, -6.058396, -6.032231...   
6   [[-6.054949999999998, -6.0489, -6.357050000000...   
7   [[-5.727972461709702, -5.792749041251861, -8.3...   
8   [[-5.983333333333333, -5.983333333333333, -5.7...   
9   [[-6.013858855774663, -6.091248188563721, -5.8...   
10  [[-5.737055482567726, -6.419838125036478, -7.4...   

                                Test Predictions Mean  \
0   [-6.083826894566467, -6.174136344684146, -5.92...   
1   [-5.602000000000001, -6.078, -6.56000000000000...   
2   [-6.066979999999999, -6.136979999999999, -5.95...   
3   [-6.176301787343389, -6.144716988512229, -6.16...   
4   [-6.153549014778325, -6.1557279720279725, -5.8...   
5   [-6.0275545, -6.133803, -6.0266595, -5.911379,...   
6   [-6.158029999999999, -6.10274, -6.233410000000...   
7   [-5.754914869117427, -6.133103207550368, -7.43...   
8   [-6.118666666666667, -5.924666666666667, -5.78...   
9   [-6.0726701748208765, -6.094373307163134, -5.9...   
10  [-5.918095697327961, -6.25204338381008, -7.696...   

                                 Test Predictions Std  
0   [0.1662487613321342, 0.1717963136001346, 0.121...  
1   [0.3522726217008637, 0.2928071037389633, 0.507...  
2   [0.12919629483851347, 0.04392663884250585, 0.1...  
3   [0.232911494167955, 0.16602910080857522, 0.264...  
4   [0.10862921185807903, 0.12425187388809239, 0.2...  
5   [0.2094793, 0.14878775, 0.27972436, 0.24473776...  
6   [0.07806846098137228, 0.0533872868761837, 0.15...  
7   [0.414676131304136, 0.2907001834971347, 1.0965...  
8   [0.11400974617208051, 0.05153639490690065, 0.1...  
9   [0.034205313524075166, 0.019132039806664853, 0...  
10  [0.4469420152191183, 0.2732605457491768, 0.451...

In [190]:
result_df.to_csv('results/Descriptors/Results_2D_3D_All_desc_const_rem_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_3D_All_desc_const_rem_RRCK.csv')

In [191]:
#All 2d and 3d descriptors LVR
df_train = pd.read_csv('features/Descriptors/Train_2d_3d_all_descriptors_RRCK.csv')
df_train = df_train.dropna()
X_train = df_train.drop(['ID','SMILES','Permeability'],axis=1)
X_train = X_train.select_dtypes(include=['number'])
X_train,  const_col =  remove_low_variance_columns(X_train)
y_train = df_train['Permeability']
print("X_train shape: ",X_train.shape)
print("y_train shape: ",y_train.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
df_test = pd.read_csv('features/Descriptors/Test_2d_3d_all_descriptors_RRCK.csv')
df_test = df_test.dropna()
X_test = df_test[X_train.columns]
y_test = df_test['Permeability']
print("X_test shape: ",X_test.shape)
print("y_test shape: ",y_test.shape)
print("XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX")
scaler = StandardScaler()
X_train_scaled = scaler.fit_transform(X_train)
X_test_scaled = scaler.transform(X_test)
X_train = pd.DataFrame(X_train_scaled, columns=X_train.columns, index=X_train.index)
X_test = pd.DataFrame(X_test_scaled, columns=X_test.columns, index=X_test.index)
models = [
    lgb.LGBMRegressor(objective='regression',metric='rmse',boosting_type='gbdt',num_leaves=31,learning_rate=0.05,random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(), 
    KNeighborsRegressor(n_neighbors=3),
    SVR(),  
    MLPRegressor(random_state=101)
]
result_df, prediction_df = train_and_test_predict(models, X_train,y_train, X_test,  y_test)
result_df

X_train shape:  (140, 2096)
y_train shape:  (140,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
X_test shape:  (36, 2096)
y_test shape:  (36,)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.004670 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 66123
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 1928
[LightGBM] [Info] Start training from score -5.527679
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further

Train MSE (5 fold cv) Train MAE (5 fold cv)  \
LGBMRegressor                            0.2085                0.3391   
DecisionTreeRegressor                    0.4112                0.4845   
RandomForestRegressor                    0.2220                0.3566   
GradientBoostingRegressor                0.2203                0.3451   
AdaBoostRegressor                        0.2209                0.3603   
XGBRegressor                             0.2783                0.3937   
ExtraTreesRegressor                      0.1826                0.3207   
LinearRegression                         0.3643                0.4392   
KNeighborsRegressor                      0.2981                0.3920   
SVR                                      0.2049                0.3241   
MLPRegressor                             0.8662                0.6727   

                          Train RMSE (5 fold cv) Train R2 (5 fold cv)  \
LGBMRegressor                             0.4566               0.5349   
DecisionTreeRegressor                     0.6413               0.0827   
RandomForestRegressor                     0.4711               0.5048   
GradientBoostingRegressor                 0.4693               0.5087   
AdaBoostRegressor                         0.4700               0.5072   
XGBRegressor                              0.5275               0.3793   
ExtraTreesRegressor                       0.4273               0.5927   
LinearRegression                          0.6036               0.1873   
KNeighborsRegressor                       0.5460               0.3351   
SVR                                       0.4527               0.5428   
MLPRegressor                              0.9307              -0.9322   

                          Train PCC (5 fold cv) Train SCC (5 fold cv)  \
LGBMRegressor                            0.7424                0.7626   
DecisionTreeRegressor                    0.4838                0.4751   
RandomForestRegressor                    0.7276                0.7505   
GradientBoostingRegressor                0.7184                0.7442   
AdaBoostRegressor                        0.7270                0.7468   
XGBRegressor                             0.6229                0.6331   
ExtraTreesRegressor                      0.7780                0.7885   
LinearRegression                         0.6238                0.6322   
KNeighborsRegressor                      0.6204                0.6571   
SVR                                      0.7455                0.7676   
MLPRegressor                             0.3085                0.2934   

                          Test MSE Test MAE Test RMSE Test R2  \
LGBMRegressor               0.4545   0.4461    0.6742  0.3712   
DecisionTreeRegressor       0.4039   0.4369    0.6356  0.4412   
RandomForestRegressor       0.4849   0.4709    0.6963  0.3292   
GradientBoostingRegressor   0.4049   0.4187    0.6363  0.4399   
AdaBoostRegressor           0.5265   0.4857    0.7256  0.2717   
XGBRegressor                0.4232   0.4475    0.6505  0.4145   
ExtraTreesRegressor         0.4369   0.4285    0.6610  0.3956   
LinearRegression            0.3141   0.4596    0.5604  0.5655   
KNeighborsRegressor         0.5567   0.4809    0.7461  0.2298   
SVR                         0.4708   0.4492    0.6862  0.3486   
MLPRegressor                0.6667   0.5814    0.8165  0.0777   

                          Test Pearson Correlation Test Spearman Correlation  
LGBMRegressor                               0.6895                    0.7825  
DecisionTreeRegressor                       0.7335                    0.7766  
RandomForestRegressor                       0.6862                    0.7735  
GradientBoostingRegressor                   0.7305                    0.8016  
AdaBoostRegressor                           0.6206                    0.7034  
XGBRegressor                                0.7304                    0.7908  
ExtraTreesRegressor                         0.7120           

In [192]:
result_df.to_csv('results/Descriptors/Results_2D_3D_All_desc_LVR_RRCK.csv')
prediction_df.to_csv('results/Descriptors/Prediction_data_2D_3D_All_desc_LVR_RRCK.csv')

In [54]:
#Stacked architecture model
import os
import numpy as np
import pandas as pd
from sklearn.model_selection import KFold
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor, AdaBoostRegressor, ExtraTreesRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.svm import SVR
from sklearn.neural_network import MLPRegressor
from sklearn.tree import DecisionTreeRegressor
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
from scipy.stats import pearsonr, spearmanr
import lightgbm as lgb
import xgboost as xgb
from tqdm import tqdm

def features(df, target_column='Permeability', threshold=0.9):
    correlation_matrix = df.corr()
    
    features_to_drop = set()
    
    for feature in correlation_matrix.columns:
        if feature == target_column:
            continue 
        target_corr = correlation_matrix[target_column][feature]
        
        for other_feature in correlation_matrix.columns:
            if other_feature == feature or other_feature == target_column:
                continue
            
            if abs(correlation_matrix[feature][other_feature]) > threshold:
                other_target_corr = correlation_matrix[target_column][other_feature]

                if abs(other_target_corr) < abs(target_corr):
                    features_to_drop.add(other_feature)
                else:
                    features_to_drop.add(feature)
    selected_features = [col for col in df.columns if col not in features_to_drop and col != target_column]
    
    return selected_features

In [55]:
def remove_low_variance_columns(df, threshold=0.005):
    # df = df.drop(['ID','SMILES','Permeability'],axis=1)
    variances = df.var()
    
    # Identify columns with variance below the threshold
    low_variance_columns = variances[variances < threshold].index.tolist()
    
    df_cleaned = df.drop(columns=low_variance_columns)
    
    return df_cleaned, low_variance_columns

In [56]:
from tqdm import tqdm
# 2D and 3D descriptors dataframes
df_desc_train = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Descriptors/Train_2d_3d_all_descriptors_RRCK.csv')
df_train = df_desc_train.sort_values(by='ID')
df_train =df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
df_desc_train = pd.concat( [df_train[['ID','SMILES','Permeability']],df_train[selected_features] ], axis=1)
df_desc_test = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Descriptors/Test_2d_3d_all_descriptors_RRCK.csv')
df_desc_test = df_desc_test.sort_values(by='ID')
df_desc_test =df_desc_test.dropna()
df_desc_test =  df_desc_test[df_desc_train.columns]


# Fingerprints
df_fp_train = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Fingerprints/Train/All_fingerprints_train_RRCK.csv')
df_train = df_fp_train.sort_values(by='ID')
df_train = df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
df_fp_train = pd.concat( [df_train[['ID','SMILES','Permeability']],df_train[selected_features] ], axis=1)
df_fp_test = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Fingerprints/Test/All_fingerprints_test_RRCK.csv')
df_fp_test = df_fp_test.sort_values(by='ID')
df_fp_test = df_fp_test.dropna()
df_fp_test =  df_fp_test[df_fp_train.columns]


#Smiles Embeddings
df_emb_train = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Embeddings/Train_MoLFormer-XL-both-10pct_model_1_fine_tuned_embeddings_rrck.csv')
df_train = df_emb_train.sort_values(by='ID')
df_train = df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
df_emb_train = pd.concat( [df_train[['ID','SMILES','Permeability']],df_train[selected_features] ], axis=1)
df_emb_test = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Embeddings/Test_MoLFormer-XL-both-10pct_model_1_fine_tuned_embeddings_rrck.csv')
df_emb_test = df_emb_test.sort_values(by='ID')
df_emb_test = df_emb_test.dropna()
df_emb_test =  df_emb_test[df_emb_train.columns]

#ATomic features
df_atomic_train = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Atomic/Train_all_atomic_desc_RRCK.csv')
df_train = df_atomic_train.sort_values(by='ID')
df_train = df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
df_atomic_train = pd.concat( [df_train[['ID','SMILES','Permeability']],df_train[selected_features] ], axis=1)
# df_atomic_train =pd.concat( [df_train['SMILES'], df_train.select_dtypes(include=['number'])], axis=1)
df_atomic_test = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Atomic/Test_all_atomic_desc_RRCK.csv')
df_atomic_test = df_atomic_test.sort_values(by='ID')
df_atomic_test = df_atomic_test.dropna()
df_atomic_test =  df_atomic_test[df_atomic_train.columns]


print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Data Loading completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
df_fp_test = df_fp_test[df_fp_test['ID'].isin(df_desc_test['ID'])]
df_fp_train = df_fp_train[df_fp_train['ID'].isin(df_desc_train['ID'])]

df_emb_test = df_emb_test[df_emb_test['ID'].isin(df_desc_test['ID'])]
df_emb_train = df_emb_train[df_emb_train['ID'].isin(df_desc_train['ID'])]

df_atomic_test = df_atomic_test[df_atomic_test['ID'].isin(df_desc_test['ID'])]
df_atomic_train = df_atomic_train[df_atomic_train['ID'].isin(df_desc_train['ID'])]
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Data Processing completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_desc_train.shape)
print(df_desc_test.shape)
print(df_fp_train.shape)
print(df_fp_test.shape)
print(df_emb_train.shape)
print(df_emb_test.shape)
print(df_atomic_train.shape)
print(df_atomic_test.shape)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_desc_train)
print(df_desc_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_fp_train)
print(df_fp_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_emb_train)
print(df_emb_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_atomic_train)
print(df_atomic_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
target_column = 'Permeability'
def scale_features(df_train, df_test):
    scaler = StandardScaler()
    train_features = df_train.drop(columns=['ID', 'SMILES', target_column])
    test_features = df_test.drop(columns=['ID', 'SMILES', target_column])
    scaler.fit(train_features)
    train_scaled = pd.DataFrame(scaler.transform(train_features), columns=train_features.columns, index=df_train.index)
    test_scaled = pd.DataFrame(scaler.transform(test_features), columns=test_features.columns, index=df_test.index)
    df_train_scaled = pd.concat([df_train[['ID', 'SMILES', target_column]], train_scaled], axis=1)
    df_test_scaled = pd.concat([df_test[['ID', 'SMILES', target_column]], test_scaled], axis=1)
    return df_train_scaled, df_test_scaled

df_desc_train, df_desc_test = scale_features(df_desc_train, df_desc_test)
df_fp_train, df_fp_test = scale_features(df_fp_train, df_fp_test)
df_emb_train, df_emb_test = scale_features(df_emb_train, df_emb_test)
df_atomic_train, df_atomic_test = scale_features(df_atomic_train, df_atomic_test)
models_weak = [
    lgb.LGBMRegressor(objective='regression', metric='rmse', boosting_type='gbdt', num_leaves=31, learning_rate=0.05, random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    KNeighborsRegressor(),
    SVR(),   
    MLPRegressor(random_state=101, max_iter=500),
    DecisionTreeRegressor(random_state=101),
]

models_meta = [
    lgb.LGBMRegressor(objective='regression', metric='rmse', boosting_type='gbdt', num_leaves=31, learning_rate=0.05, random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(),
    KNeighborsRegressor(),
    SVR(),
    MLPRegressor(random_state=101)
]


XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
Data Loading completed
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
Data Processing completed
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
(140, 249)
(36, 249)
(140, 414)
(36, 414)
(140, 690)
(36, 690)
(140, 13)
(36, 13)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
       ID                                             SMILES  Permeability  \
109    24  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...        -6.300   
81     26  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@@H...        -5.390   
73     27  CC(C)C[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N(C)[C@...        -5.460   
74     28  CC(C)C[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N2CCC[...        -5.210   
100    29  CC(C)C[C@@H]1NC(=O)[C@H](CC(

In [57]:
dataframes = [(df_desc_train, df_desc_test), (df_fp_train, df_fp_test), (df_emb_train, df_emb_test), (df_atomic_train, df_atomic_test)]
target_column = 'Permeability'


meta_features_train = []
meta_features_test = []

# Stage 1: Train weak learners with 5-fold cross-validation
for df_train, df_test in tqdm(dataframes, desc="Processing dataframe pairs"):
    X_weak = df_train.drop(columns=['ID', 'SMILES', target_column])
    X_eval = df_test.drop(columns=['ID', 'SMILES', target_column])
    y_weak = df_train[target_column]
    y_eval = df_test[target_column]

    kf = KFold(n_splits=5, shuffle=True, random_state=101)

    # Storing predictions for the current dataframe
    fold_meta_features_train = np.zeros((X_weak.shape[0], len(models_weak)))
    fold_meta_features_test = np.zeros((X_eval.shape[0], len(models_weak)))

    for i, model in tqdm(enumerate(models_weak), desc="Training models"):
        fold_predictions = np.zeros(X_weak.shape[0])
        test_predictions_folds = []

        for train_index, val_index in kf.split(X_weak):
            X_train, X_val = X_weak.iloc[train_index], X_weak.iloc[val_index]
            y_train, y_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
            
            model.fit(X_train, y_train)

            # Predictions for validation set
            fold_predictions[val_index] =  np.clip( model.predict(X_val), -10, -4.0)

            # Predictions for test set
            test_predictions_fold =  np.clip( model.predict(X_eval), -10, -4.0)
            test_predictions_folds.append(test_predictions_fold)

        # Store predictions for the meta-learner
        fold_meta_features_train[:, i] = fold_predictions
        fold_meta_features_test[:, i] = np.mean(test_predictions_folds, axis=0)

    meta_features_train.append(fold_meta_features_train)
    meta_features_test.append(fold_meta_features_test)

# Convert lists to arrays for the meta-learner
meta_features_train = np.hstack(meta_features_train)
meta_features_test = np.hstack(meta_features_test)

print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print("Dimensions of meta_features_train:", meta_features_train.shape)
print("Dimensions of meta_features_test:", meta_features_test.shape)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Stage 1 completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')

# Stage 2: Train the meta-learner using predictions from weak learners
kf = KFold(n_splits=5, shuffle=True, random_state=101)
results = {}
predictions = []
for model in models_meta:
    model_name = model.__class__.__name__
    predictions_train = []
    actual_y_train = []
    
    test_predictions_folds = []

    for train_index, val_index in kf.split(meta_features_train):
        X_fold_train, X_fold_val = meta_features_train[train_index], meta_features_train[val_index]
        y_fold_train, y_fold_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
        
        model.fit(X_fold_train, y_fold_train)

        y_pred_fold = model.predict(X_fold_val)
        y_pred_fold = np.clip(y_pred_fold, -10, -4.0)
        predictions_train.extend(y_pred_fold)
        actual_y_train.extend(y_fold_val)

        # Predictions for test set
        test_predictions_fold = model.predict(meta_features_test)
        test_predictions_fold = np.clip(test_predictions_fold, -10, -4.0)
        test_predictions_folds.append(test_predictions_fold)

    # Metrics
    predictions_test_mean = np.mean(test_predictions_folds, axis=0)
    predictions_test_std = np.std(test_predictions_folds, axis=0)

    mse_train = mean_squared_error(actual_y_train, predictions_train)
    mae_train = mean_absolute_error(actual_y_train, predictions_train)
    rmse_train = np.sqrt(mse_train)
    r2_train = r2_score(actual_y_train, predictions_train)
    pearson_train, _ = pearsonr(actual_y_train, predictions_train)
    spearman_train, _ = spearmanr(actual_y_train, predictions_train)

    mse_test = mean_squared_error(y_eval, predictions_test_mean)
    mae_test = mean_absolute_error(y_eval, predictions_test_mean)
    rmse_test = np.sqrt(mse_test)
    r2_test = r2_score(y_eval, predictions_test_mean)
    pearson_test, _ = pearsonr(y_eval, predictions_test_mean)
    spearman_test, _ = spearmanr(y_eval, predictions_test_mean)
    print(f'{model_name} Evaluation completed: Test R2 score: {r2_test}')

    predictions.append({
            'Model': model_name,
            'Y Train pred': predictions_train,
            'Y Test actual': y_eval,
            'Test prediction folds': test_predictions_folds,
            'Test Predictions Mean': predictions_test_mean,
            'Test Predictions Std': predictions_test_std,

        })

    results[model_name] = {
        'Train MSE (5 fold CV)': mse_train,
        'Train MAE (5 fold CV)': mae_train,
        'Train RMSE (5 fold CV)': rmse_train,
        'Train R2 (5 fold CV)': r2_train,
        'Train PCC (5 fold CV)': pearson_train,
        'Train SCC (5 fold CV)': spearman_train,
        'Test MSE': mse_test,
        'Test MAE': mae_test,
        'Test RMSE': rmse_test,
        'Test R2': r2_test,
        'Test PCC': pearson_test,
        'Test SCC': spearman_test,
    }

results_df = pd.DataFrame(results).T
prediction_df = pd.DataFrame(predictions)
results_df

Processing dataframe pairs:   0%|          | 0/4 [00:00<?, ?it/s]
Training models: 0it [00:00, ?it/s]

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001649 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 8251
[LightGBM] [Info] Number of data points in the train set: 112, number of used features: 230
[LightGBM] [Info] Start training from score -5.540848
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain,


Training models: 1it [00:00,  2.77it/s]

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f


Training models: 2it [00:01,  1.06s/it]
Training models: 3it [00:05,  2.03s/it]
Training models: 4it [00:06,  1.74s/it]
Training models: 5it [00:07,  1.58s/it]
Training models: 6it [00:08,  1.48s/it]
Training models: 10it [00:09,  1.02it/s][A
Processing dataframe pairs:  25%|██▌       | 1/4 [00:09<00:29,  9.81s/it]
Training models: 0it [00:00, ?it/s]

...

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: F

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


RandomForestRegressor Evaluation completed: Test R2 score: 0.5150733666948241
GradientBoostingRegressor Evaluation completed: Test R2 score: 0.5587865874187217
AdaBoostRegressor Evaluation completed: Test R2 score: 0.5205314370200718
XGBRegressor Evaluation completed: Test R2 score: 0.5356517720219225
ExtraTreesRegressor Evaluation completed: Test R2 score: 0.5284821365892622
LinearRegression Evaluation completed: Test R2 score: 0.6180852048242691
KNeighborsRegressor Evaluation completed: Test R2 score: 0.5044395504523412
SVR Evaluation completed: Test R2 score: 0.487105124778043
MLPRegressor Evaluation completed: Test R2 score: 0.33524534639171133


Train MSE (5 fold CV)  Train MAE (5 fold CV)  \
LGBMRegressor                           0.206208               0.343818   
DecisionTreeRegressor                   0.404919               0.500036   
RandomForestRegressor                   0.186954               0.325190   
GradientBoostingRegressor               0.206881               0.343110   
AdaBoostRegressor                       0.202354               0.332856   
XGBRegressor                            0.225789               0.361261   
ExtraTreesRegressor                     0.187491               0.324966   
LinearRegression                        0.221186               0.361166   
KNeighborsRegressor                     0.204898               0.345179   
SVR                                     0.206167               0.348228   
MLPRegressor                            0.549458               0.610137   

                           Train RMSE (5 fold CV)  Train R2 (5 fold CV)  \
LGBMRegressor                            0.454101              0.540005   
DecisionTreeRegressor                    0.636333              0.096732   
RandomForestRegressor                    0.432382              0.582954   
GradientBoostingRegressor                0.454842              0.538503   
AdaBoostRegressor                        0.449838              0.548602   
XGBRegressor                             0.475173              0.496324   
ExtraTreesRegressor                      0.433002              0.581757   
LinearRegression                         0.470304              0.506592   
KNeighborsRegressor                      0.452657              0.542926   
SVR                                      0.454056              0.540097   
MLPRegressor                             0.741254             -0.225695   

                           Train PCC (5 fold CV)  Train SCC (5 fold CV)  \
LGBMRegressor                           0.738968               0.759734   
DecisionTreeRegressor                   0.555216               0.590503   
RandomForestRegressor                   0.764480               0.778277   
GradientBoostingRegressor               0.739429               0.749829   
AdaBoostRegressor                       0.743299               0.761503   
XGBRegressor                            0.719204               0.732382   
ExtraTreesRegressor                     0.763644               0.780085   
LinearRegression                        0.730359               0.744672   
KNeighborsRegressor                     0.740622               0.756201   
SVR                                     0.736176               0.744609   
MLPRegressor                            0.479419               0.497935   

                           Test MSE  Test MAE  Test RMSE   Test R2  Test PCC  \
LGBMRegressor              0.385063  0.419419   0.620534  0.467292  0.742521   
DecisionTreeRegressor      0.281023  0.362278   0.530116  0.611225  0.818057   
RandomForestRegressor      0.350525  0.391315   0.592051  0.515073  0.769174   
GradientBoostingRegressor  0.318927  0.370692   0.564736  0.558787  0.792270   
AdaBoostRegressor          0.346579  0.397186   0.588710  0.520531  0.778476   
XGBRegressor               0.335650  0.398483   0.579353  0.535652  0.765805   
ExtraTreesRegressor        0.340832  0.390796   0.583808  0.528482  0.768366   
LinearRegression           0.276064  0.376110   0.525418  0.618085  0.804229   
KNeighborsRegressor        0.358211  0.429322   0.598508  0.504440  0.756691   
SVR                        0.370741  0.412637   0.608885  0.487105  0.716748   
MLPRegressor               0.480512  0.573424   0.693190  0.335245  0.669201   

                           Test SCC  
LGBMRegressor              0.781926  
DecisionTreeRegressor      0.842597  
RandomForestRegressor      0.825899  
GradientBoostingRegressor  0.849199  
AdaBoostRegressor          0.819978  
XGBRegressor               0.804145  
ExtraTreesRegressor        0.824741  
LinearRegression           0.841990  
KNeighborsRegressor  

In [58]:
results_df.to_csv('/home/users/akshay/PCPpred/RRCK/results/Stacked/Results_5_folds_stacked_archi_RRCK.csv')
prediction_df.to_csv('/home/users/akshay/PCPpred/RRCK/results/Stacked/Prediction_data_5_folds_stacked_archi_RRCK.csv')

In [59]:
dataframes = [(df_desc_train, df_desc_test), (df_fp_train, df_fp_test), (df_emb_train, df_emb_test), (df_atomic_train, df_atomic_test)]
target_column = 'Permeability'


meta_features_train = []
meta_features_test = []

# Stage 1: Train weak learners with 10-fold cross-validation
for df_train, df_test in tqdm(dataframes, desc="Processing dataframe pairs"):
    X_weak = df_train.drop(columns=['ID', 'SMILES', target_column])
    X_eval = df_test.drop(columns=['ID', 'SMILES', target_column])
    y_weak = df_train[target_column]
    y_eval = df_test[target_column]

    kf = KFold(n_splits=10, shuffle=True, random_state=101)

    # Storing predictions for the current dataframe
    fold_meta_features_train = np.zeros((X_weak.shape[0], len(models_weak)))
    fold_meta_features_test = np.zeros((X_eval.shape[0], len(models_weak)))

    for i, model in tqdm(enumerate(models_weak), desc="Training models"):
        fold_predictions = np.zeros(X_weak.shape[0])
        test_predictions_folds = []

        for train_index, val_index in kf.split(X_weak):
            X_train, X_val = X_weak.iloc[train_index], X_weak.iloc[val_index]
            y_train, y_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
            
            model.fit(X_train, y_train)

            # Predictions for validation set
            fold_predictions[val_index] =  np.clip( model.predict(X_val), -10, -4.0)

            # Predictions for test set
            test_predictions_fold =  np.clip( model.predict(X_eval), -10, -4.0)
            test_predictions_folds.append(test_predictions_fold)

        # Store predictions for the meta-learner
        fold_meta_features_train[:, i] = fold_predictions
        fold_meta_features_test[:, i] = np.mean(test_predictions_folds, axis=0)

    meta_features_train.append(fold_meta_features_train)
    meta_features_test.append(fold_meta_features_test)

# Convert lists to arrays for the meta-learner
meta_features_train = np.hstack(meta_features_train)
meta_features_test = np.hstack(meta_features_test)

print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print("Dimensions of meta_features_train:", meta_features_train.shape)
print("Dimensions of meta_features_test:", meta_features_test.shape)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Stage 1 completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')

# Stage 2: Train the meta-learner using predictions from weak learners
kf = KFold(n_splits=10, shuffle=True, random_state=101)
results = {}
predictions = []
for model in models_meta:
    model_name = model.__class__.__name__
    predictions_train = []
    actual_y_train = []
    
    test_predictions_folds = []

    for train_index, val_index in kf.split(meta_features_train):
        X_fold_train, X_fold_val = meta_features_train[train_index], meta_features_train[val_index]
        y_fold_train, y_fold_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
        
        model.fit(X_fold_train, y_fold_train)

        y_pred_fold = model.predict(X_fold_val)
        y_pred_fold = np.clip(y_pred_fold, -10, -4.0)
        predictions_train.extend(y_pred_fold)
        actual_y_train.extend(y_fold_val)

        # Predictions for test set
        test_predictions_fold = model.predict(meta_features_test)
        test_predictions_fold = np.clip(test_predictions_fold, -10,-4.0)
        test_predictions_folds.append(test_predictions_fold)

    # Metrics
    predictions_test_mean = np.mean(test_predictions_folds, axis=0)
    predictions_test_std = np.std(test_predictions_folds, axis=0)

    mse_train = mean_squared_error(actual_y_train, predictions_train)
    mae_train = mean_absolute_error(actual_y_train, predictions_train)
    rmse_train = np.sqrt(mse_train)
    r2_train = r2_score(actual_y_train, predictions_train)
    pearson_train, _ = pearsonr(actual_y_train, predictions_train)
    spearman_train, _ = spearmanr(actual_y_train, predictions_train)

    mse_test = mean_squared_error(y_eval, predictions_test_mean)
    mae_test = mean_absolute_error(y_eval, predictions_test_mean)
    rmse_test = np.sqrt(mse_test)
    r2_test = r2_score(y_eval, predictions_test_mean)
    pearson_test, _ = pearsonr(y_eval, predictions_test_mean)
    spearman_test, _ = spearmanr(y_eval, predictions_test_mean)
    print(f'{model_name} Evaluation completed: Test R2 score: {r2_test}')

    predictions.append({
            'Model': model_name,
            'Y Train pred': predictions_train,
            'Y Test actual': y_eval,
            'Test prediction folds': test_predictions_folds,
            'Test Predictions Mean': predictions_test_mean,
            'Test Predictions Std': predictions_test_std,

        })

    results[model_name] = {
        'Train MSE (10 fold CV)': mse_train,
        'Train MAE (10 fold CV)': mae_train,
        'Train RMSE (10 fold CV)': rmse_train,
        'Train R2 (10 fold CV)': r2_train,
        'Train PCC (10 fold CV)': pearson_train,
        'Train SCC (10 fold CV)': spearman_train,
        'Test MSE': mse_test,
        'Test MAE': mae_test,
        'Test RMSE': rmse_test,
        'Test R2': r2_test,
        'Test PCC': pearson_test,
        'Test SCC': spearman_test,
    }

results_df = pd.DataFrame(results).T
prediction_df = pd.DataFrame(predictions)
results_df

Processing dataframe pairs:   0%|          | 0/4 [00:00<?, ?it/s]
Training models: 0it [00:00, ?it/s]

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001794 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 9192
[LightGBM] [Info] Number of data points in the train set: 126, number of used features: 230
[LightGBM] [Info] Start training from score -5.536667
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain,


Training models: 1it [00:00,  1.25it/s]

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.001879 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 9132
[LightGBM] [Info] Number of data points in the train set: 126, number of used features: 232
[LightGBM] [Info] Start training from score -5.513651
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain,


Training models: 2it [00:03,  2.16s/it]
Training models: 3it [00:11,  4.43s/it]
Training models: 4it [00:13,  3.81s/it]
Training models: 5it [00:17,  3.60s/it]
Training models: 6it [00:19,  3.25s/it]
Training models: 7it [00:19,  2.22s/it]
Training models: 9it [00:21,  1.53s/it]
Training models: 10it [00:21,  2.16s/it]
Processing dataframe pairs:  25%|██▌       | 1/4 [00:21<01:04, 21.57s/it]
Training models: 0it [00:00, ?it/s]

...

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: F

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.000488 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 1655
[LightGBM] [Info] Number of data points in the train set: 126, number of used features: 40
[LightGBM] [Info] Start training from score -5.537976
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, 

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: F

DecisionTreeRegressor Evaluation completed: Test R2 score: 0.5720730922049218
RandomForestRegressor Evaluation completed: Test R2 score: 0.5585556617570095
GradientBoostingRegressor Evaluation completed: Test R2 score: 0.6082021409051817
AdaBoostRegressor Evaluation completed: Test R2 score: 0.5504271149460027
XGBRegressor Evaluation completed: Test R2 score: 0.5559889309757324
ExtraTreesRegressor Evaluation completed: Test R2 score: 0.5706443014523859
LinearRegression Evaluation completed: Test R2 score: 0.6631332983780276
KNeighborsRegressor Evaluation completed: Test R2 score: 0.49920786441804765
SVR Evaluation completed: Test R2 score: 0.4694247606169878
MLPRegressor Evaluation completed: Test R2 score: 0.3621980808184395


Train MSE (10 fold CV)  Train MAE (10 fold CV)  \
LGBMRegressor                            0.183984                0.322355   
DecisionTreeRegressor                    0.347696                0.443893   
RandomForestRegressor                    0.166358                0.310790   
GradientBoostingRegressor                0.191393                0.334935   
AdaBoostRegressor                        0.187649                0.329013   
XGBRegressor                             0.227238                0.359067   
ExtraTreesRegressor                      0.159480                0.295175   
LinearRegression                         0.203906                0.341503   
KNeighborsRegressor                      0.178218                0.314579   
SVR                                      0.164789                0.307484   
MLPRegressor                             0.505456                0.602507   

                           Train RMSE (10 fold CV)  Train R2 (10 fold CV)  \
LGBMRegressor                             0.428933               0.589581   
DecisionTreeRegressor                     0.589657               0.224383   
RandomForestRegressor                     0.407871               0.628898   
GradientBoostingRegressor                 0.437485               0.573053   
AdaBoostRegressor                         0.433184               0.581406   
XGBRegressor                              0.476695               0.493092   
ExtraTreesRegressor                       0.399350               0.644242   
LinearRegression                          0.451559               0.545140   
KNeighborsRegressor                       0.422159               0.602442   
SVR                                       0.405942               0.632400   
MLPRegressor                              0.710954              -0.127539   

                           Train PCC (10 fold CV)  Train SCC (10 fold CV)  \
LGBMRegressor                            0.770244                0.792961   
DecisionTreeRegressor                    0.627999                0.674069   
RandomForestRegressor                    0.794205                0.812332   
GradientBoostingRegressor                0.766002                0.794026   
AdaBoostRegressor                        0.763524                0.789780   
XGBRegressor                             0.730847                0.772287   
ExtraTreesRegressor                      0.803146                0.819374   
LinearRegression                         0.763591                0.787805   
KNeighborsRegressor                      0.778278                0.806930   
SVR                                      0.795294                0.813211   
MLPRegressor                             0.581273                0.622496   

                           Test MSE  Test MAE  Test RMSE   Test R2  Test PCC  \
LGBMRegressor              0.330079  0.389186   0.574525  0.543359  0.776668   
DecisionTreeRegressor      0.309323  0.411000   0.556168  0.572073  0.799296   
RandomForestRegressor      0.319094  0.374553   0.564884  0.558556  0.790244   
GradientBoostingRegressor  0.283207  0.355972   0.532172  0.608202  0.807587   
AdaBoostRegressor          0.324970  0.393565   0.570061  0.550427  0.786411   
XGBRegressor               0.320949  0.383935   0.566524  0.555989  0.786177   
ExtraTreesRegressor        0.310356  0.364499   0.557096  0.570644  0.797405   
LinearRegression           0.243501  0.370217   0.493458  0.663133  0.832587   
KNeighborsRegressor        0.361993  0.415067   0.601659  0.499208  0.764703   
SVR                        0.383521  0.403981   0.619291  0.469425  0.719433   
MLPRegressor               0.461029  0.576227   0.678991  0.362198  0.713702   

                           Test SCC  
LGBMRegressor              0.832904  
DecisionTreeRegressor      0.838386  
RandomForestRegressor      0.853060  
GradientBoostingRegressor  0.865161  
AdaBoostRegressor          0.853447  
XGBRegressor               0.813799  
ExtraTreesRegressor      

In [60]:
results_df.to_csv('/home/users/akshay/PCPpred/RRCK/results/Stacked/Results_10_folds_stacked_archi_RRCK.csv')
prediction_df.to_csv('/home/users/akshay/PCPpred/RRCK/results/Stacked/Prediction_data_10_folds_stacked_archi_RRCK.csv')

In [61]:
dataframes = [(df_desc_train, df_desc_test), (df_fp_train, df_fp_test), (df_emb_train, df_emb_test), (df_atomic_train, df_atomic_test)]
target_column = 'Permeability'


meta_features_train = []
meta_features_test = []

# Stage 1: Train weak learners with 15-fold cross-validation
for df_train, df_test in tqdm(dataframes, desc="Processing dataframe pairs"):
    X_weak = df_train.drop(columns=['ID', 'SMILES', target_column])
    X_eval = df_test.drop(columns=['ID', 'SMILES', target_column])
    y_weak = df_train[target_column]
    y_eval = df_test[target_column]

    kf = KFold(n_splits=15, shuffle=True, random_state=101)

    # Storing predictions for the current dataframe
    fold_meta_features_train = np.zeros((X_weak.shape[0], len(models_weak)))
    fold_meta_features_test = np.zeros((X_eval.shape[0], len(models_weak)))

    for i, model in tqdm(enumerate(models_weak), desc="Training models"):
        fold_predictions = np.zeros(X_weak.shape[0])
        test_predictions_folds = []

        for train_index, val_index in kf.split(X_weak):
            X_train, X_val = X_weak.iloc[train_index], X_weak.iloc[val_index]
            y_train, y_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
            
            model.fit(X_train, y_train)

            # Predictions for validation set
            fold_predictions[val_index] =  np.clip( model.predict(X_val), -10, -4.0)

            # Predictions for test set
            test_predictions_fold =  np.clip( model.predict(X_eval), -10, -4.0)
            test_predictions_folds.append(test_predictions_fold)

        # Store predictions for the meta-learner
        fold_meta_features_train[:, i] = fold_predictions
        fold_meta_features_test[:, i] = np.mean(test_predictions_folds, axis=0)

    meta_features_train.append(fold_meta_features_train)
    meta_features_test.append(fold_meta_features_test)

# Convert lists to arrays for the meta-learner
meta_features_train = np.hstack(meta_features_train)
meta_features_test = np.hstack(meta_features_test)

print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print("Dimensions of meta_features_train:", meta_features_train.shape)
print("Dimensions of meta_features_test:", meta_features_test.shape)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Stage 1 completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')

# Stage 2: Train the meta-learner using predictions from weak learners
kf = KFold(n_splits=15, shuffle=True, random_state=101)
results = {}
predictions = []
for model in models_meta:
    model_name = model.__class__.__name__
    predictions_train = []
    actual_y_train = []
    
    test_predictions_folds = []

    for train_index, val_index in kf.split(meta_features_train):
        X_fold_train, X_fold_val = meta_features_train[train_index], meta_features_train[val_index]
        y_fold_train, y_fold_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
        
        model.fit(X_fold_train, y_fold_train)

        y_pred_fold = model.predict(X_fold_val)
        y_pred_fold = np.clip(y_pred_fold, -10, -4.0)
        predictions_train.extend(y_pred_fold)
        actual_y_train.extend(y_fold_val)

        # Predictions for test set
        test_predictions_fold = model.predict(meta_features_test)
        test_predictions_fold = np.clip(test_predictions_fold, -10, -4.0)
        test_predictions_folds.append(test_predictions_fold)

    # Metrics
    predictions_test_mean = np.mean(test_predictions_folds, axis=0)
    predictions_test_std = np.std(test_predictions_folds, axis=0)

    mse_train = mean_squared_error(actual_y_train, predictions_train)
    mae_train = mean_absolute_error(actual_y_train, predictions_train)
    rmse_train = np.sqrt(mse_train)
    r2_train = r2_score(actual_y_train, predictions_train)
    pearson_train, _ = pearsonr(actual_y_train, predictions_train)
    spearman_train, _ = spearmanr(actual_y_train, predictions_train)

    mse_test = mean_squared_error(y_eval, predictions_test_mean)
    mae_test = mean_absolute_error(y_eval, predictions_test_mean)
    rmse_test = np.sqrt(mse_test)
    r2_test = r2_score(y_eval, predictions_test_mean)
    pearson_test, _ = pearsonr(y_eval, predictions_test_mean)
    spearman_test, _ = spearmanr(y_eval, predictions_test_mean)
    print(f'{model_name} Evaluation completed: Test R2 score: {r2_test}')

    predictions.append({
            'Model': model_name,
            'Y Train pred': predictions_train,
            'Y Test actual': y_eval,
            'Test prediction folds': test_predictions_folds,
            'Test Predictions Mean': predictions_test_mean,
            'Test Predictions Std': predictions_test_std,

        })

    results[model_name] = {
        'Train MSE (15 fold CV)': mse_train,
        'Train MAE (15 fold CV)': mae_train,
        'Train RMSE (15 fold CV)': rmse_train,
        'Train R2 (15 fold CV)': r2_train,
        'Train PCC (15 fold CV)': pearson_train,
        'Train SCC (15 fold CV)': spearman_train,
        'Test MSE': mse_test,
        'Test MAE': mae_test,
        'Test RMSE': rmse_test,
        'Test R2': r2_test,
        'Test PCC': pearson_test,
        'Test SCC': spearman_test,
    }

results_df = pd.DataFrame(results).T
prediction_df = pd.DataFrame(predictions)
results_df

Processing dataframe pairs:   0%|          | 0/4 [00:00<?, ?it/s]
Training models: 0it [00:00, ?it/s]

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002058 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 9474
[LightGBM] [Info] Number of data points in the train set: 130, number of used features: 230
[LightGBM] [Info] Start training from score -5.529000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain,


Training models: 1it [00:01,  1.30s/it]

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f


Training models: 2it [00:06,  3.33s/it]
Training models: 3it [00:17,  6.89s/it]
Training models: 4it [00:21,  5.91s/it]
Training models: 5it [00:26,  5.40s/it]
Training models: 6it [00:29,  4.89s/it]
Training models: 7it [00:30,  3.33s/it]
Training models: 9it [00:32,  2.31s/it]
Training models: 10it [00:32,  3.28s/it]
Processing dataframe pairs:  25%|██▌       | 1/4 [00:32<01:38, 32.84s/it]
Training models: 0it [00:00, ?it/s]

...

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: F

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: F

DecisionTreeRegressor Evaluation completed: Test R2 score: 0.592578721638174
RandomForestRegressor Evaluation completed: Test R2 score: 0.5415306908331479
GradientBoostingRegressor Evaluation completed: Test R2 score: 0.5560266141582711
AdaBoostRegressor Evaluation completed: Test R2 score: 0.5300723890140349
XGBRegressor Evaluation completed: Test R2 score: 0.48781853605857983
ExtraTreesRegressor Evaluation completed: Test R2 score: 0.5519657259810089
LinearRegression Evaluation completed: Test R2 score: 0.6887289113620519
KNeighborsRegressor Evaluation completed: Test R2 score: 0.45883294899104454
SVR Evaluation completed: Test R2 score: 0.5003184083178264
MLPRegressor Evaluation completed: Test R2 score: 0.29353300717380026


Train MSE (15 fold CV)  Train MAE (15 fold CV)  \
LGBMRegressor                            0.175434                0.312442   
DecisionTreeRegressor                    0.299181                0.397714   
RandomForestRegressor                    0.152558                0.287556   
GradientBoostingRegressor                0.170630                0.306606   
AdaBoostRegressor                        0.161734                0.308477   
XGBRegressor                             0.170421                0.311415   
ExtraTreesRegressor                      0.145774                0.281962   
LinearRegression                         0.152293                0.309072   
KNeighborsRegressor                      0.184127                0.318579   
SVR                                      0.161307                0.307333   
MLPRegressor                             0.549742                0.635572   

                           Train RMSE (15 fold CV)  Train R2 (15 fold CV)  \
LGBMRegressor                             0.418849               0.608653   
DecisionTreeRegressor                     0.546974               0.332606   
RandomForestRegressor                     0.390587               0.659683   
GradientBoostingRegressor                 0.413074               0.619370   
AdaBoostRegressor                         0.402162               0.639214   
XGBRegressor                              0.412821               0.619835   
ExtraTreesRegressor                       0.381804               0.674817   
LinearRegression                          0.390247               0.660275   
KNeighborsRegressor                       0.429100               0.589262   
SVR                                       0.401630               0.640167   
MLPRegressor                              0.741446              -0.226330   

                           Train PCC (15 fold CV)  Train SCC (15 fold CV)  \
LGBMRegressor                            0.781454                0.802038   
DecisionTreeRegressor                    0.659535                0.697074   
RandomForestRegressor                    0.812714                0.836112   
GradientBoostingRegressor                0.788790                0.804991   
AdaBoostRegressor                        0.800043                0.824175   
XGBRegressor                             0.790873                0.797853   
ExtraTreesRegressor                      0.822030                0.840455   
LinearRegression                         0.822091                0.817780   
KNeighborsRegressor                      0.770947                0.793388   
SVR                                      0.800346                0.815803   
MLPRegressor                             0.577280                0.621090   

                           Test MSE  Test MAE  Test RMSE   Test R2  Test PCC  \
LGBMRegressor              0.337710  0.401694   0.581128  0.532802  0.783677   
DecisionTreeRegressor      0.294501  0.415648   0.542679  0.592579  0.804971   
RandomForestRegressor      0.331400  0.386203   0.575674  0.541531  0.785297   
GradientBoostingRegressor  0.320922  0.397015   0.566500  0.556027  0.785123   
AdaBoostRegressor          0.339683  0.393800   0.582823  0.530072  0.782384   
XGBRegressor               0.370226  0.425766   0.608462  0.487819  0.741152   
ExtraTreesRegressor        0.323857  0.373949   0.569085  0.551966  0.801053   
LinearRegression           0.224999  0.333679   0.474341  0.688729  0.843344   
KNeighborsRegressor        0.391178  0.421054   0.625442  0.458833  0.729692   
SVR                        0.361190  0.400532   0.600991  0.500318  0.729782   
MLPRegressor               0.510663  0.615280   0.714607  0.293533  0.691952   

                           Test SCC  
LGBMRegressor              0.842559  
DecisionTreeRegressor      0.821008  
RandomForestRegressor      0.842505  
GradientBoostingRegressor  0.833494  
AdaBoostRegressor          0.824097  
XGBRegressor               0.778657  
ExtraTreesRegressor      

In [62]:
results_df.to_csv('/home/users/akshay/PCPpred/RRCK/results/Stacked/Results_15_folds_stacked_archi_RRCK.csv')
prediction_df.to_csv('/home/users/akshay/PCPpred/RRCK/results/Stacked/Prediction_data_15_folds_stacked_archi_RRCK.csv')

In [63]:
dataframes = [(df_desc_train, df_desc_test), (df_fp_train, df_fp_test), (df_emb_train, df_emb_test), (df_atomic_train, df_atomic_test)]
target_column = 'Permeability'


meta_features_train = []
meta_features_test = []

# Stage 1: Train weak learners with 20-fold cross-validation
for df_train, df_test in tqdm(dataframes, desc="Processing dataframe pairs"):
    X_weak = df_train.drop(columns=['ID', 'SMILES', target_column])
    X_eval = df_test.drop(columns=['ID', 'SMILES', target_column])
    y_weak = df_train[target_column]
    y_eval = df_test[target_column]

    kf = KFold(n_splits=20, shuffle=True, random_state=101)

    # Storing predictions for the current dataframe
    fold_meta_features_train = np.zeros((X_weak.shape[0], len(models_weak)))
    fold_meta_features_test = np.zeros((X_eval.shape[0], len(models_weak)))

    for i, model in tqdm(enumerate(models_weak), desc="Training models"):
        fold_predictions = np.zeros(X_weak.shape[0])
        test_predictions_folds = []

        for train_index, val_index in kf.split(X_weak):
            X_train, X_val = X_weak.iloc[train_index], X_weak.iloc[val_index]
            y_train, y_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
            
            model.fit(X_train, y_train)

            # Predictions for validation set
            fold_predictions[val_index] =  np.clip( model.predict(X_val), -10, -4.0)

            # Predictions for test set
            test_predictions_fold =  np.clip( model.predict(X_eval), -10, -4.0)
            test_predictions_folds.append(test_predictions_fold)

        # Store predictions for the meta-learner
        fold_meta_features_train[:, i] = fold_predictions
        fold_meta_features_test[:, i] = np.mean(test_predictions_folds, axis=0)

    meta_features_train.append(fold_meta_features_train)
    meta_features_test.append(fold_meta_features_test)

# Convert lists to arrays for the meta-learner
meta_features_train = np.hstack(meta_features_train)
meta_features_test = np.hstack(meta_features_test)

print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print("Dimensions of meta_features_train:", meta_features_train.shape)
print("Dimensions of meta_features_test:", meta_features_test.shape)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Stage 1 completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')

# Stage 2: Train the meta-learner using predictions from weak learners
kf = KFold(n_splits=20, shuffle=True, random_state=101)
results = {}
predictions = []
for model in models_meta:
    model_name = model.__class__.__name__
    predictions_train = []
    actual_y_train = []
    
    test_predictions_folds = []

    for train_index, val_index in kf.split(meta_features_train):
        X_fold_train, X_fold_val = meta_features_train[train_index], meta_features_train[val_index]
        y_fold_train, y_fold_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
        
        model.fit(X_fold_train, y_fold_train)

        y_pred_fold = model.predict(X_fold_val)
        y_pred_fold = np.clip(y_pred_fold, -10, -4.0)
        predictions_train.extend(y_pred_fold)
        actual_y_train.extend(y_fold_val)

        # Predictions for test set
        test_predictions_fold = model.predict(meta_features_test)
        test_predictions_fold = np.clip(test_predictions_fold, -10, -4.0)
        test_predictions_folds.append(test_predictions_fold)

    # Metrics
    predictions_test_mean = np.mean(test_predictions_folds, axis=0)
    predictions_test_std = np.std(test_predictions_folds, axis=0)

    mse_train = mean_squared_error(actual_y_train, predictions_train)
    mae_train = mean_absolute_error(actual_y_train, predictions_train)
    rmse_train = np.sqrt(mse_train)
    r2_train = r2_score(actual_y_train, predictions_train)
    pearson_train, _ = pearsonr(actual_y_train, predictions_train)
    spearman_train, _ = spearmanr(actual_y_train, predictions_train)

    mse_test = mean_squared_error(y_eval, predictions_test_mean)
    mae_test = mean_absolute_error(y_eval, predictions_test_mean)
    rmse_test = np.sqrt(mse_test)
    r2_test = r2_score(y_eval, predictions_test_mean)
    pearson_test, _ = pearsonr(y_eval, predictions_test_mean)
    spearman_test, _ = spearmanr(y_eval, predictions_test_mean)
    print(f'{model_name} Evaluation completed: Test R2 score: {r2_test}')

    predictions.append({
            'Model': model_name,
            'Y Train pred': predictions_train,
            'Y Test actual': y_eval,
            'Test prediction folds': test_predictions_folds,
            'Test Predictions Mean': predictions_test_mean,
            'Test Predictions Std': predictions_test_std,

        })

    results[model_name] = {
        'Train MSE (20 fold CV)': mse_train,
        'Train MAE (20 fold CV)': mae_train,
        'Train RMSE (20 fold CV)': rmse_train,
        'Train R2 (20 fold CV)': r2_train,
        'Train PCC (20 fold CV)': pearson_train,
        'Train SCC (20 fold CV)': spearman_train,
        'Test MSE': mse_test,
        'Test MAE': mae_test,
        'Test RMSE': rmse_test,
        'Test R2': r2_test,
        'Test PCC': pearson_test,
        'Test SCC': spearman_test,
    }

results_df = pd.DataFrame(results).T
prediction_df = pd.DataFrame(predictions)
results_df

Processing dataframe pairs:   0%|          | 0/4 [00:00<?, ?it/s]
Training models: 0it [00:00, ?it/s]

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002783 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 9668
[LightGBM] [Info] Number of data points in the train set: 133, number of used features: 231
[LightGBM] [Info] Start training from score -5.528421
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain,


Training models: 1it [00:02,  2.03s/it]

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002052 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 9586
[LightGBM] [Info] Number of data points in the train set: 133, number of used features: 232
[LightGBM] [Info] Start training from score -5.510075
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain,


Training models: 2it [00:08,  4.57s/it]
Training models: 3it [00:23,  9.40s/it]
Training models: 4it [00:29,  8.07s/it]
Training models: 5it [00:35,  7.23s/it]
Training models: 6it [00:40,  6.52s/it]
Training models: 7it [00:40,  4.44s/it]
Training models: 8it [00:40,  3.06s/it]
Training models: 9it [00:43,  3.11s/it]
Training models: 10it [00:44,  4.43s/it]
Processing dataframe pairs:  25%|██▌       | 1/4 [00:44<02:12, 44.33s/it]
Training models: 0it [00:00, ?it/s]

...

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: F

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: F

DecisionTreeRegressor Evaluation completed: Test R2 score: 0.4585833383570751
RandomForestRegressor Evaluation completed: Test R2 score: 0.5424520471896306
GradientBoostingRegressor Evaluation completed: Test R2 score: 0.522715909619691
AdaBoostRegressor Evaluation completed: Test R2 score: 0.5069488635926406
XGBRegressor Evaluation completed: Test R2 score: 0.47685867790335845
ExtraTreesRegressor Evaluation completed: Test R2 score: 0.5534546811389669
LinearRegression Evaluation completed: Test R2 score: 0.6474369048547464
KNeighborsRegressor Evaluation completed: Test R2 score: 0.46842331186053787
SVR Evaluation completed: Test R2 score: 0.46820873582691225
MLPRegressor Evaluation completed: Test R2 score: 0.3367957226881543


Train MSE (20 fold CV)  Train MAE (20 fold CV)  \
LGBMRegressor                            0.177633                0.319899   
DecisionTreeRegressor                    0.266378                0.400071   
RandomForestRegressor                    0.148073                0.280290   
GradientBoostingRegressor                0.156332                0.299882   
AdaBoostRegressor                        0.141836                0.281366   
XGBRegressor                             0.170391                0.309751   
ExtraTreesRegressor                      0.138622                0.272151   
LinearRegression                         0.178856                0.332845   
KNeighborsRegressor                      0.182065                0.318679   
SVR                                      0.169784                0.319812   
MLPRegressor                             0.514493                0.612867   

                           Train RMSE (20 fold CV)  Train R2 (20 fold CV)  \
LGBMRegressor                             0.421466               0.603747   
DecisionTreeRegressor                     0.516118               0.405781   
RandomForestRegressor                     0.384802               0.669689   
GradientBoostingRegressor                 0.395389               0.651264   
AdaBoostRegressor                         0.376611               0.683601   
XGBRegressor                              0.412784               0.619903   
ExtraTreesRegressor                       0.372320               0.690770   
LinearRegression                          0.422914               0.601020   
KNeighborsRegressor                       0.426691               0.593860   
SVR                                       0.412049               0.621256   
MLPRegressor                              0.717281              -0.147697   

                           Train PCC (20 fold CV)  Train SCC (20 fold CV)  \
LGBMRegressor                            0.777813                0.795938   
DecisionTreeRegressor                    0.709529                0.745512   
RandomForestRegressor                    0.818553                0.840842   
GradientBoostingRegressor                0.807406                0.824629   
AdaBoostRegressor                        0.827346                0.841396   
XGBRegressor                             0.791247                0.805136   
ExtraTreesRegressor                      0.831446                0.843562   
LinearRegression                         0.790049                0.803132   
KNeighborsRegressor                      0.773730                0.795832   
SVR                                      0.788524                0.800740   
MLPRegressor                             0.584908                0.631994   

                           Test MSE  Test MAE  Test RMSE   Test R2  Test PCC  \
LGBMRegressor              0.357099  0.394008   0.597578  0.505978  0.783057   
DecisionTreeRegressor      0.391358  0.433569   0.625586  0.458583  0.749937   
RandomForestRegressor      0.330734  0.375377   0.575095  0.542452  0.787657   
GradientBoostingRegressor  0.345000  0.378753   0.587367  0.522716  0.784255   
AdaBoostRegressor          0.356397  0.406901   0.596990  0.506949  0.771546   
XGBRegressor               0.378148  0.429787   0.614937  0.476859  0.769067   
ExtraTreesRegressor        0.322781  0.370661   0.568138  0.553455  0.787639   
LinearRegression           0.254847  0.375217   0.504824  0.647437  0.817274   
KNeighborsRegressor        0.384245  0.428244   0.619875  0.468423  0.738180   
SVR                        0.384400  0.402258   0.620000  0.468209  0.719454   
MLPRegressor               0.479391  0.591009   0.692381  0.336796  0.700414   

                           Test SCC  
LGBMRegressor              0.838054  
DecisionTreeRegressor      0.794362  
RandomForestRegressor      0.833494  
GradientBoostingRegressor  0.844050  
AdaBoostRegressor          0.818691  
XGBRegressor               0.795263  
ExtraTreesRegressor      

In [64]:
results_df.to_csv('/home/users/akshay/PCPpred/RRCK/results/Stacked/Results_20_folds_stacked_archi_RRCK.csv')
prediction_df.to_csv('/home/users/akshay/PCPpred/RRCK/results/Stacked/Prediction_data_20_folds_stacked_archi_RRCK.csv')

In [ ]:
from tqdm import tqdm
# 2D and 3D descriptors dataframes
df_desc_train = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Descriptors/Train_2d_3d_all_descriptors_RRCK.csv')
df_train = df_desc_train.sort_values(by='ID')
df_train =df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
df_desc_train = pd.concat( [df_train[['ID','SMILES','Permeability']],df_train[selected_features] ], axis=1)
df_desc_test = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Descriptors/Test_2d_3d_all_descriptors_RRCK.csv')
df_desc_test = df_desc_test.sort_values(by='ID')
df_desc_test =df_desc_test.dropna()
df_desc_test =  df_desc_test[df_desc_train.columns]


# Fingerprints
df_fp_train = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Fingerprints/Train/All_fingerprints_train_RRCK.csv')
df_train = df_fp_train.sort_values(by='ID')
df_train = df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
df_fp_train = pd.concat( [df_train[['ID','SMILES','Permeability']],df_train[selected_features] ], axis=1)
df_fp_test = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Fingerprints/Test/All_fingerprints_test_RRCK.csv')
df_fp_test = df_fp_test.sort_values(by='ID')
df_fp_test = df_fp_test.dropna()
df_fp_test =  df_fp_test[df_fp_train.columns]


#Smiles Embeddings
df_emb_train = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Embeddings/Train_MoLFormer-XL-both-10pct_model_1_fine_tuned_embeddings_rrck.csv')
df_train = df_emb_train.sort_values(by='ID')
df_train = df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
df_emb_train = pd.concat( [df_train[['ID','SMILES','Permeability']],df_train[selected_features] ], axis=1)
df_emb_test = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Embeddings/Test_MoLFormer-XL-both-10pct_model_1_fine_tuned_embeddings_rrck.csv')
df_emb_test = df_emb_test.sort_values(by='ID')
df_emb_test = df_emb_test.dropna()
df_emb_test =  df_emb_test[df_emb_train.columns]

#ATomic features
df_atomic_train = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Atomic/Train_all_atomic_desc_RRCK.csv')
df_train = df_atomic_train.sort_values(by='ID')
df_train = df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
df_atomic_train = pd.concat( [df_train[['ID','SMILES','Permeability']],df_train[selected_features] ], axis=1)
# df_atomic_train =pd.concat( [df_train['SMILES'], df_train.select_dtypes(include=['number'])], axis=1)
df_atomic_test = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Atomic/Test_all_atomic_desc_RRCK.csv')
df_atomic_test = df_atomic_test.sort_values(by='ID')
df_atomic_test = df_atomic_test.dropna()
df_atomic_test =  df_atomic_test[df_atomic_train.columns]


print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Data Loading completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
df_fp_test = df_fp_test[df_fp_test['ID'].isin(df_desc_test['ID'])]
df_fp_train = df_fp_train[df_fp_train['ID'].isin(df_desc_train['ID'])]

df_emb_test = df_emb_test[df_emb_test['ID'].isin(df_desc_test['ID'])]
df_emb_train = df_emb_train[df_emb_train['ID'].isin(df_desc_train['ID'])]

df_atomic_test = df_atomic_test[df_atomic_test['ID'].isin(df_desc_test['ID'])]
df_atomic_train = df_atomic_train[df_atomic_train['ID'].isin(df_desc_train['ID'])]
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Data Processing completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_desc_train.shape)
print(df_desc_test.shape)
print(df_fp_train.shape)
print(df_fp_test.shape)
print(df_emb_train.shape)
print(df_emb_test.shape)
print(df_atomic_train.shape)
print(df_atomic_test.shape)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_desc_train)
print(df_desc_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_fp_train)
print(df_fp_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_emb_train)
print(df_emb_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_atomic_train)
print(df_atomic_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
target_column = 'Permeability'
def scale_features(df_train, df_test):
    scaler = StandardScaler()
    train_features = df_train.drop(columns=['ID', 'SMILES', target_column])
    test_features = df_test.drop(columns=['ID', 'SMILES', target_column])
    scaler.fit(train_features)
    train_scaled = pd.DataFrame(scaler.transform(train_features), columns=train_features.columns, index=df_train.index)
    test_scaled = pd.DataFrame(scaler.transform(test_features), columns=test_features.columns, index=df_test.index)
    df_train_scaled = pd.concat([df_train[['ID', 'SMILES', target_column]], train_scaled], axis=1)
    df_test_scaled = pd.concat([df_test[['ID', 'SMILES', target_column]], test_scaled], axis=1)
    return df_train_scaled, df_test_scaled

df_desc_train, df_desc_test = scale_features(df_desc_train, df_desc_test)
df_fp_train, df_fp_test = scale_features(df_fp_train, df_fp_test)
df_emb_train, df_emb_test = scale_features(df_emb_train, df_emb_test)
df_atomic_train, df_atomic_test = scale_features(df_atomic_train, df_atomic_test)
models_weak = [
    lgb.LGBMRegressor(objective='regression', metric='rmse', boosting_type='gbdt', num_leaves=31, learning_rate=0.05, random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    KNeighborsRegressor(),
    SVR(),   
    MLPRegressor(random_state=101, max_iter=500),
    DecisionTreeRegressor(random_state=101),
]

models_meta = [
    lgb.LGBMRegressor(objective='regression', metric='rmse', boosting_type='gbdt', num_leaves=31, learning_rate=0.05, random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(),
    KNeighborsRegressor(),
    SVR(),
    MLPRegressor(random_state=101)
]


In [65]:
import os
import numpy as np
import pandas as pd
from sklearn.model_selection import KFold
from sklearn.preprocessing import StandardScaler
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor, AdaBoostRegressor, ExtraTreesRegressor
from sklearn.neighbors import KNeighborsRegressor
from sklearn.svm import SVR
from sklearn.neural_network import MLPRegressor
from sklearn.tree import DecisionTreeRegressor
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, mean_absolute_error, r2_score
from scipy.stats import pearsonr, spearmanr
import lightgbm as lgb
import xgboost as xgb
from tqdm import tqdm
import joblib

# Ensure the models directory exists
os.makedirs('/home/users/akshay/PCPpred/RRCK/models_rrck/', exist_ok=True)

# Assuming remove_low_variance_columns and features functions are defined elsewhere
# 2D and 3D descriptors dataframes
df_desc_train =pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Descriptors/Train_2d_3d_all_descriptors_RRCK.csv')
df_train = df_desc_train.sort_values(by='ID')
df_train = df_train.dropna()
train = df_train.drop(['ID','SMILES'], axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features_desc = features(train, "Permeability")
joblib.dump(selected_features_desc, '/home/users/akshay/PCPpred/RRCK/models_rrck/selected_features_descriptors.joblib')
df_desc_train = pd.concat([df_train[['ID','SMILES','Permeability']], df_train[selected_features_desc]], axis=1)
df_desc_test = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Descriptors/Test_2d_3d_all_descriptors_RRCK.csv')
df_desc_test = df_desc_test.sort_values(by='ID')
df_desc_test = df_desc_test.dropna()
df_desc_test = df_desc_test[df_desc_train.columns]

# Fingerprints
df_fp_train = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Fingerprints/Train/All_fingerprints_train_RRCK.csv')
df_train = df_fp_train.sort_values(by='ID')
df_train = df_train.dropna()
train = df_train.drop(['ID','SMILES'], axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features_fp = features(train, "Permeability")
joblib.dump(selected_features_fp, '/home/users/akshay/PCPpred/RRCK/models_rrck/selected_features_fingerprints.joblib')
df_fp_train = pd.concat([df_train[['ID','SMILES','Permeability']], df_train[selected_features_fp]], axis=1)
df_fp_test = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Fingerprints/Test/All_fingerprints_test_RRCK.csv')
df_fp_test = df_fp_test.sort_values(by='ID')
df_fp_test = df_fp_test.dropna()
df_fp_test = df_fp_test[df_fp_train.columns]

# Smiles Embeddings
df_emb_train = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Embeddings/Train_MoLFormer-XL-both-10pct_model_1_fine_tuned_embeddings_rrck.csv')
df_train = df_emb_train.sort_values(by='ID')
df_train = df_train.dropna()
train = df_train.drop(['ID','SMILES'], axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features_emb = features(train, "Permeability")
joblib.dump(selected_features_emb, '/home/users/akshay/PCPpred/RRCK/models_rrck/selected_features_embeddings.joblib')
df_emb_train = pd.concat([df_train[['ID','SMILES','Permeability']], df_train[selected_features_emb]], axis=1)
df_emb_test = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Embeddings/Test_MoLFormer-XL-both-10pct_model_1_fine_tuned_embeddings_rrck.csv')
df_emb_test = df_emb_test.sort_values(by='ID')
df_emb_test = df_emb_test.dropna()
df_emb_test = df_emb_test[df_emb_train.columns]

# Atomic features
df_atomic_train = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Atomic/Train_all_atomic_desc_RRCK.csv')
df_train = df_atomic_train.sort_values(by='ID')
df_train = df_train.dropna()
train = df_train.drop(['ID','SMILES'], axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features_atomic = features(train, "Permeability")
joblib.dump(selected_features_atomic, '/home/users/akshay/PCPpred/RRCK/models_rrck/selected_features_atomic.joblib')
df_atomic_train = pd.concat([df_train[['ID','SMILES','Permeability']], df_train[selected_features_atomic]], axis=1)
df_atomic_test = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Atomic/Test_all_atomic_desc_RRCK.csv')
df_atomic_test = df_atomic_test.sort_values(by='ID')
df_atomic_test = df_atomic_test.dropna()
df_atomic_test = df_atomic_test[df_atomic_train.columns]

print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Data Loading completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')

# Filter dataframes to have consistent IDs
df_fp_test = df_fp_test[df_fp_test['ID'].isin(df_desc_test['ID'])]
df_fp_train = df_fp_train[df_fp_train['ID'].isin(df_desc_train['ID'])]
df_emb_test = df_emb_test[df_emb_test['ID'].isin(df_desc_test['ID'])]
df_emb_train = df_emb_train[df_emb_train['ID'].isin(df_desc_train['ID'])]
df_atomic_test = df_atomic_test[df_atomic_test['ID'].isin(df_desc_test['ID'])]
df_atomic_train = df_atomic_train[df_atomic_train['ID'].isin(df_desc_train['ID'])]

print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Data Processing completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_desc_train.shape)
print(df_desc_test.shape)
print(df_fp_train.shape)
print(df_fp_test.shape)
print(df_emb_train.shape)
print(df_emb_test.shape)
print(df_atomic_train.shape)
print(df_atomic_test.shape)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_desc_train)
print(df_desc_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_fp_train)
print(df_fp_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_emb_train)
print(df_emb_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_atomic_train)
print(df_atomic_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')

target_column = 'Permeability'

def scale_features(df_train, df_test, feature_type):
    scaler = StandardScaler()
    train_features = df_train.drop(columns=['ID', 'SMILES', target_column])
    test_features = df_test.drop(columns=['ID', 'SMILES', target_column])
    scaler.fit(train_features)
    train_scaled = pd.DataFrame(scaler.transform(train_features), columns=train_features.columns, index=df_train.index)
    test_scaled = pd.DataFrame(scaler.transform(test_features), columns=test_features.columns, index=df_test.index)
    df_train_scaled = pd.concat([df_train[['ID', 'SMILES', target_column]], train_scaled], axis=1)
    df_test_scaled = pd.concat([df_test[['ID', 'SMILES', target_column]], test_scaled], axis=1)
    # Save the scaler
    joblib.dump(scaler, f'/home/users/akshay/PCPpred/RRCK/models_rrck/scaler_{feature_type}.joblib')
    return df_train_scaled, df_test_scaled

df_desc_train, df_desc_test = scale_features(df_desc_train, df_desc_test, 'Descriptor')
df_fp_train, df_fp_test = scale_features(df_fp_train, df_fp_test, 'Fingerprints')
df_emb_train, df_emb_test = scale_features(df_emb_train, df_emb_test, 'Embeddings')
df_atomic_train, df_atomic_test = scale_features(df_atomic_train, df_atomic_test , 'Atomic')

models_weak = [
    lgb.LGBMRegressor(objective='regression', metric='rmse', boosting_type='gbdt', num_leaves=31, learning_rate=0.05, random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    KNeighborsRegressor(),
    SVR(),
    MLPRegressor(random_state=101, max_iter=500),
    DecisionTreeRegressor(random_state=101),
]

models_meta = [
    lgb.LGBMRegressor(objective='regression', metric='rmse', boosting_type='gbdt', num_leaves=31, learning_rate=0.05, random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(),
    KNeighborsRegressor(),
    SVR(),
    MLPRegressor(random_state=101)
]

dataframes = [(df_desc_train, df_desc_test), (df_fp_train, df_fp_test), (df_emb_train, df_emb_test), (df_atomic_train, df_atomic_test)]
data_names = ['descriptors', 'fingerprints', 'embeddings', 'atomic']

meta_features_train = []
meta_features_test = []

# Stage 1: Train weak learners with 15-fold cross-validation
for df_idx, (df_train, df_test) in enumerate(tqdm(dataframes, desc="Processing dataframe pairs")):
    X_weak = df_train.drop(columns=['ID', 'SMILES', target_column])
    X_eval = df_test.drop(columns=['ID', 'SMILES', target_column])
    y_weak = df_train[target_column]
    y_eval = df_test[target_column]

    kf = KFold(n_splits=15, shuffle=True, random_state=101)

    fold_meta_features_train = np.zeros((X_weak.shape[0], len(models_weak)))
    fold_meta_features_test = np.zeros((X_eval.shape[0], len(models_weak)))

    for i, model in tqdm(enumerate(models_weak), desc="Training models", total=len(models_weak)):
        fold_predictions = np.zeros(X_weak.shape[0])
        test_predictions_folds = []

        for fold_idx, (train_index, val_index) in enumerate(kf.split(X_weak)):
            X_train, X_val = X_weak.iloc[train_index], X_weak.iloc[val_index]
            y_train, y_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
            
            model.fit(X_train, y_train)
            
            model_name = model.__class__.__name__
            joblib.dump(model, f'/home/users/akshay/PCPpred/RRCK/models_rrck/weak_{data_names[df_idx]}_{model_name}_fold_{fold_idx}.joblib')

            fold_predictions[val_index] = np.clip(model.predict(X_val), -10, -4.0)

            test_predictions_fold = np.clip(model.predict(X_eval), -10, -4.0)
            test_predictions_folds.append(test_predictions_fold)

        fold_meta_features_train[:, i] = fold_predictions
        fold_meta_features_test[:, i] = np.mean(test_predictions_folds, axis=0)

    meta_features_train.append(fold_meta_features_train)
    meta_features_test.append(fold_meta_features_test)
    
    joblib.dump(fold_meta_features_train, f'/home/users/akshay/PCPpred/RRCK/models_rrck/meta_features_train_{data_names[df_idx]}.joblib')
    joblib.dump(fold_meta_features_test, f'/home/users/akshay/PCPpred/RRCK/models_rrck/meta_features_test_{data_names[df_idx]}.joblib')

meta_features_train = np.hstack(meta_features_train)
meta_features_test = np.hstack(meta_features_test)

joblib.dump(meta_features_train, '/home/users/akshay/PCPpred/RRCK/models_rrck/meta_features_train_combined.joblib')
joblib.dump(meta_features_test, '/home/users/akshay/PCPpred/RRCK/models_rrck/meta_features_test_combined.joblib')

print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print("Dimensions of meta_features_train:", meta_features_train.shape)
print("Dimensions of meta_features_test:", meta_features_test.shape)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Stage 1 completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')

# Stage 2: Train the meta-learner using predictions from weak learners
kf = KFold(n_splits=15, shuffle=True, random_state=101)
results = {}
predictions = []
for model in models_meta:
    model_name = model.__class__.__name__
    predictions_train = []
    actual_y_train = []
    
    test_predictions_folds = []

    for fold_idx, (train_index, val_index) in enumerate(kf.split(meta_features_train)):
        X_fold_train, X_fold_val = meta_features_train[train_index], meta_features_train[val_index]
        y_fold_train, y_fold_val = y_weak.iloc[train_index], y_weak.iloc[val_index]
        
        model.fit(X_fold_train, y_fold_train)
        
        joblib.dump(model, f'/home/users/akshay/PCPpred/RRCK/models_rrck/meta_{model_name}_fold_{fold_idx}.joblib')

        y_pred_fold = model.predict(X_fold_val)
        y_pred_fold = np.clip(y_pred_fold, -10, -4.0)
        predictions_train.extend(y_pred_fold)
        actual_y_train.extend(y_fold_val)

        test_predictions_fold = model.predict(meta_features_test)
        test_predictions_fold = np.clip(test_predictions_fold, -10, -4.0)
        test_predictions_folds.append(test_predictions_fold)

    # Metrics
    predictions_test_mean = np.mean(test_predictions_folds, axis=0)
    predictions_test_std = np.std(test_predictions_folds, axis=0)

    mse_train = mean_squared_error(actual_y_train, predictions_train)
    mae_train = mean_absolute_error(actual_y_train, predictions_train)
    rmse_train = np.sqrt(mse_train)
    r2_train = r2_score(actual_y_train, predictions_train)
    pearson_train, _ = pearsonr(actual_y_train, predictions_train)
    spearman_train, _ = spearmanr(actual_y_train, predictions_train)

    mse_test = mean_squared_error(y_eval, predictions_test_mean)
    mae_test = mean_absolute_error(y_eval, predictions_test_mean)
    rmse_test = np.sqrt(mse_test)
    r2_test = r2_score(y_eval, predictions_test_mean)
    pearson_test, _ = pearsonr(y_eval, predictions_test_mean)
    spearman_test, _ = spearmanr(y_eval, predictions_test_mean)
    

    predictions.append({
        'Model': model_name,
        'Y Train pred': predictions_train,
        'Y Test actual': y_eval,
        'Test prediction folds': test_predictions_folds,
        'Test Predictions Mean': predictions_test_mean,
        'Test Predictions Std': predictions_test_mean,
    })

    results[model_name] = {
        'Train MSE (15 fold CV)': mse_train,
        'Train MAE (15 fold CV)': mae_train,
        'Train RMSE (15 fold CV)': rmse_train,
        'Train R2 (15 fold CV)': r2_train,
        'Train PCC (15 fold CV)': pearson_train,
        'Train SCC (15 fold CV)': spearman_train,
        'Test MSE': mse_test,
        'Test MAE': mae_test,
        'Test RMSE': rmse_test,
        'Test R2': r2_test,
        'Test PCC': pearson_test,
        'Test SCC': spearman_test,
    }

results_df = pd.DataFrame(results).T

XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
Data Loading completed
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
Data Processing completed
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
(140, 249)
(36, 249)
(140, 414)
(36, 414)
(140, 690)
(36, 690)
(140, 13)
(36, 13)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
       ID                                             SMILES  Permeability  \
109    24  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...        -6.300   
81     26  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@@H...        -5.390   
73     27  CC(C)C[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N(C)[C@...        -5.460   
74     28  CC(C)C[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N2CCC[...        -5.210   
100    29  CC(C)C[C@@H]1NC(=O)[C@H](CC(

Training models:   0%|          | 0/10 [00:00<?, ?it/s]

[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.061127 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [Info] Total Bins 9474
[LightGBM] [Info] Number of data points in the train set: 130, number of used features: 230
[LightGBM] [Info] Start training from score -5.529000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain,


Training models:  10%|█         | 1/10 [00:01<00:15,  1.72s/it]

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Info] Auto-choosing col-wise multi-threading, the overhead of testing was 0.002038 seconds.
You can set `force_col_wise=true` to remove the overhead.
[LightGBM] [I

...

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: F

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: F

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: F

In [66]:
#Ablation study
import os
import joblib
from tqdm import tqdm
import numpy as np
import pandas as pd
from sklearn.tree import DecisionTreeRegressor
from sklearn.ensemble import RandomForestRegressor, GradientBoostingRegressor, AdaBoostRegressor, ExtraTreesRegressor
from sklearn.linear_model import LinearRegression, LogisticRegression  # LogisticRegression is not used for regression
from sklearn.neighbors import KNeighborsRegressor
from sklearn.svm import SVR
from sklearn.neural_network import MLPRegressor
import xgboost as xgb
import lightgbm as lgb
from sklearn.model_selection import KFold
from sklearn.metrics import mean_absolute_error, mean_squared_error, r2_score
from sklearn.preprocessing import StandardScaler 
from scipy.stats import pearsonr, spearmanr
from sklearn.model_selection import train_test_split
import seaborn as sns
import matplotlib.pyplot as plt

In [67]:
def remove_low_variance_columns(df, threshold=0.005):
    # df = df.drop(['ID','SMILES','Permeability'],axis=1)
    variances = df.var()
    
    low_variance_columns = variances[variances < threshold].index.tolist()
    
    df_cleaned = df.drop(columns=low_variance_columns)
    
    return df_cleaned, low_variance_columns

def features(df, target_column='Permeability', threshold=0.9):
    correlation_matrix = df.corr()
    
    features_to_drop = set()
    
    for feature in correlation_matrix.columns:
        if feature == target_column:
            continue 
        target_corr = correlation_matrix[target_column][feature]
        
        for other_feature in correlation_matrix.columns:
            if other_feature == feature or other_feature == target_column:
                continue
            
            if abs(correlation_matrix[feature][other_feature]) > threshold:
                other_target_corr = correlation_matrix[target_column][other_feature]

                if abs(other_target_corr) < abs(target_corr):
                    features_to_drop.add(other_feature)
                else:
                    features_to_drop.add(feature)
    selected_features = [col for col in df.columns if col not in features_to_drop and col != target_column]
    
    return selected_features

In [68]:
from tqdm import tqdm
# 2D and 3D descriptors dataframes
df_desc_train = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Descriptors/Train_2d_3d_all_descriptors_RRCK.csv')
df_train = df_desc_train.sort_values(by='ID')
df_train =df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
df_desc_train = pd.concat( [df_train[['ID','SMILES','Permeability']],df_train[selected_features] ], axis=1)
df_desc_test = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Descriptors/Test_2d_3d_all_descriptors_RRCK.csv')
df_desc_test = df_desc_test.sort_values(by='ID')
df_desc_test =df_desc_test.dropna()
df_desc_test =  df_desc_test[df_desc_train.columns]


# Fingerprints
df_fp_train = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Fingerprints/Train/All_fingerprints_train_RRCK.csv')
df_train = df_fp_train.sort_values(by='ID')
df_train = df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
df_fp_train = pd.concat( [df_train[['ID','SMILES','Permeability']],df_train[selected_features] ], axis=1)
df_fp_test = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Fingerprints/Test/All_fingerprints_test_RRCK.csv')
df_fp_test = df_fp_test.sort_values(by='ID')
df_fp_test = df_fp_test.dropna()
df_fp_test =  df_fp_test[df_fp_train.columns]


#Smiles Embeddings
df_emb_train = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Embeddings/Train_MoLFormer-XL-both-10pct_model_1_fine_tuned_embeddings_rrck.csv')
df_train = df_emb_train.sort_values(by='ID')
df_train = df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
df_emb_train = pd.concat( [df_train[['ID','SMILES','Permeability']],df_train[selected_features] ], axis=1)
df_emb_test = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Embeddings/Test_MoLFormer-XL-both-10pct_model_1_fine_tuned_embeddings_rrck.csv')
df_emb_test = df_emb_test.sort_values(by='ID')
df_emb_test = df_emb_test.dropna()
df_emb_test =  df_emb_test[df_emb_train.columns]

#ATomic features
df_atomic_train = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Atomic/Train_all_atomic_desc_RRCK.csv')
df_train = df_atomic_train.sort_values(by='ID')
df_train = df_train.dropna()
train = df_train.drop(['ID','SMILES'],axis=1)
train = train.select_dtypes(include=['number'])
train, _ = remove_low_variance_columns(train)
selected_features = features(train, "Permeability")
df_atomic_train = pd.concat( [df_train[['ID','SMILES','Permeability']],df_train[selected_features] ], axis=1)
# df_atomic_train =pd.concat( [df_train['SMILES'], df_train.select_dtypes(include=['number'])], axis=1)
df_atomic_test = pd.read_csv('/home/users/akshay/PCPpred/RRCK/features/Atomic/Test_all_atomic_desc_RRCK.csv')
df_atomic_test = df_atomic_test.sort_values(by='ID')
df_atomic_test = df_atomic_test.dropna()
df_atomic_test =  df_atomic_test[df_atomic_train.columns]


print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Data Loading completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
df_fp_test = df_fp_test[df_fp_test['ID'].isin(df_desc_test['ID'])]
df_fp_train = df_fp_train[df_fp_train['ID'].isin(df_desc_train['ID'])]

df_emb_test = df_emb_test[df_emb_test['ID'].isin(df_desc_test['ID'])]
df_emb_train = df_emb_train[df_emb_train['ID'].isin(df_desc_train['ID'])]

df_atomic_test = df_atomic_test[df_atomic_test['ID'].isin(df_desc_test['ID'])]
df_atomic_train = df_atomic_train[df_atomic_train['ID'].isin(df_desc_train['ID'])]
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Data Processing completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_desc_train.shape)
print(df_desc_test.shape)
print(df_fp_train.shape)
print(df_fp_test.shape)
print(df_emb_train.shape)
print(df_emb_test.shape)
print(df_atomic_train.shape)
print(df_atomic_test.shape)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_desc_train)
print(df_desc_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_fp_train)
print(df_fp_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_emb_train)
print(df_emb_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print(df_atomic_train)
print(df_atomic_test)
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
target_column = 'Permeability'
def scale_features(df_train, df_test):
    scaler = StandardScaler()
    train_features = df_train.drop(columns=['ID', 'SMILES', target_column])
    test_features = df_test.drop(columns=['ID', 'SMILES', target_column])
    scaler.fit(train_features)
    train_scaled = pd.DataFrame(scaler.transform(train_features), columns=train_features.columns, index=df_train.index)
    test_scaled = pd.DataFrame(scaler.transform(test_features), columns=test_features.columns, index=df_test.index)
    df_train_scaled = pd.concat([df_train[['ID', 'SMILES', target_column]], train_scaled], axis=1)
    df_test_scaled = pd.concat([df_test[['ID', 'SMILES', target_column]], test_scaled], axis=1)
    return df_train_scaled, df_test_scaled

df_desc_train, df_desc_test = scale_features(df_desc_train, df_desc_test)
df_fp_train, df_fp_test = scale_features(df_fp_train, df_fp_test)
df_emb_train, df_emb_test = scale_features(df_emb_train, df_emb_test)
df_atomic_train, df_atomic_test = scale_features(df_atomic_train, df_atomic_test)
models_weak = [
    lgb.LGBMRegressor(objective='regression', metric='rmse', boosting_type='gbdt', num_leaves=31, learning_rate=0.05, random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    KNeighborsRegressor(),
    SVR(),   
    MLPRegressor(random_state=101, max_iter=500),
    DecisionTreeRegressor(random_state=101),
]

models_meta = [
    lgb.LGBMRegressor(objective='regression', metric='rmse', boosting_type='gbdt', num_leaves=31, learning_rate=0.05, random_state=101),
    DecisionTreeRegressor(random_state=101),
    RandomForestRegressor(n_jobs=-1, random_state=101),
    GradientBoostingRegressor(random_state=101),
    AdaBoostRegressor(random_state=101),
    xgb.XGBRegressor(random_state=101),
    ExtraTreesRegressor(n_jobs=-1, n_estimators=100, random_state=101),
    LinearRegression(),
    KNeighborsRegressor(),
    SVR(),
    MLPRegressor(random_state=101)
]
dataframes = [(df_desc_train, df_desc_test), (df_fp_train, df_fp_test), (df_emb_train, df_emb_test), (df_atomic_train, df_atomic_test)]

XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
Data Loading completed
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
Data Processing completed
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
(140, 249)
(36, 249)
(140, 414)
(36, 414)
(140, 690)
(36, 690)
(140, 13)
(36, 13)
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
       ID                                             SMILES  Permeability  \
109    24  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)NC(=O)[C@@H](C...        -6.300   
81     26  CC(C)C[C@@H]1NC(=O)[C@H](CC(C)C)N(C)C(=O)[C@@H...        -5.390   
73     27  CC(C)C[C@H]1C(=O)N(C)[C@H](CC(C)C)C(=O)N(C)[C@...        -5.460   
74     28  CC(C)C[C@H]1C(=O)N(C)[C@@H](CC(C)C)C(=O)N2CCC[...        -5.210   
100    29  CC(C)C[C@@H]1NC(=O)[C@H](CC(

In [69]:
ablation_results = {}

for ablation_idx in range(len(dataframes)):
    print(f"========== Ablation: Excluding feature at index {ablation_idx} ==========")
    feature_names = ['Descriptor', 'Fingerprints', 'Embeddings', 'Atomic']
    print(f"========== Ablation: Excluding feature :-- {feature_names[ablation_idx]} ==========")

    ablated_dataframes = [pair for i, pair in enumerate(dataframes) if i != ablation_idx]

    meta_features_train = []
    meta_features_test = []

    # Stage 1
    for df_train, df_test in tqdm(ablated_dataframes, desc="Processing ablated dataframes"):
        X_weak = df_train.drop(columns=['ID', 'SMILES', target_column])
        y_weak = df_train[target_column]
        X_eval = df_test.drop(columns=['ID', 'SMILES', target_column])
        y_eval = df_test[target_column]

        kf = KFold(n_splits=15, shuffle=True, random_state=101)

        fold_meta_features_train = np.zeros((X_weak.shape[0], len(models_weak)))
        fold_meta_features_test = np.zeros((X_eval.shape[0], len(models_weak)))

        for i, model in tqdm(enumerate(models_weak), desc="Training weak models", total=len(models_weak)):
            fold_predictions = np.zeros(X_weak.shape[0])
            test_predictions_folds = []

            for train_index, val_index in kf.split(X_weak):
                X_train, X_val = X_weak.iloc[train_index], X_weak.iloc[val_index]
                y_train, y_val = y_weak.iloc[train_index], y_weak.iloc[val_index]

                model.fit(X_train, y_train)

                fold_predictions[val_index] = np.clip(model.predict(X_val), -10, -4.0)
                test_predictions_fold = np.clip(model.predict(X_eval), -10, -4.0)
                test_predictions_folds.append(test_predictions_fold)

            fold_meta_features_train[:, i] = fold_predictions
            fold_meta_features_test[:, i] = np.mean(test_predictions_folds, axis=0)
            print(f'Model training done {i}: {model.__class__.__name__}')

        meta_features_train.append(fold_meta_features_train)
        meta_features_test.append(fold_meta_features_test)
        print('Dataframe training completed')

    # Stack all meta-features
    meta_features_train = np.hstack(meta_features_train)
    meta_features_test = np.hstack(meta_features_test)

    print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
    print('Stage 1 completed (Weak Learners)')
    print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')

    # Stage 2
    results = {}
    kf = KFold(n_splits=15, shuffle=True, random_state=101)

    for model in models_meta:
        model_name = model.__class__.__name__
        predictions_train = []
        actual_y_train = []
        test_predictions_folds = []

        for train_index, val_index in kf.split(meta_features_train):
            X_fold_train, X_fold_val = meta_features_train[train_index], meta_features_train[val_index]
            y_fold_train, y_fold_val = y_weak.iloc[train_index], y_weak.iloc[val_index]

            model.fit(X_fold_train, y_fold_train)
            y_pred_fold = np.clip(model.predict(X_fold_val), -10, -4.0)

            predictions_train.extend(y_pred_fold)
            actual_y_train.extend(y_fold_val)

            test_predictions_fold = model.predict(meta_features_test)
            test_predictions_fold = np.clip(test_predictions_fold, -10, -4.0)
            test_predictions_folds.append(test_predictions_fold)

        predictions_test_mean = np.mean(test_predictions_folds, axis=0)
        predictions_test_std = np.std(test_predictions_folds, axis=0)

        mse_train = mean_squared_error(actual_y_train, predictions_train)
        mae_train = mean_absolute_error(actual_y_train, predictions_train)
        rmse_train = np.sqrt(mse_train)
        r2_train = r2_score(actual_y_train, predictions_train)
        pearson_train, _ = pearsonr(actual_y_train, predictions_train)
        spearman_train, _ = spearmanr(actual_y_train, predictions_train)

        mse_test = mean_squared_error(y_eval, predictions_test_mean)
        mae_test = mean_absolute_error(y_eval, predictions_test_mean)
        rmse_test = np.sqrt(mse_test)
        r2_test = r2_score(y_eval, predictions_test_mean)
        pearson_test, _ = pearsonr(y_eval, predictions_test_mean)
        spearman_test, _ = spearmanr(y_eval, predictions_test_mean)

        results[model_name] = {
            'Train MSE (15 fold CV)': mse_train,
            'Train MAE (15 fold CV)': mae_train,
            'Train RMSE (15 fold CV)': rmse_train,
            'Train R2 (15 fold CV)': r2_train,
            'Train PCC (15 fold CV)': pearson_train,
            'Train SCC (15 fold CV)': spearman_train,
            'Test MSE': mse_test,
            'Test MAE': mae_test,
            'Test RMSE': rmse_test,
            'Test R2': r2_test,
            'Test PCC': pearson_test,
            'Test SCC': spearman_test,
        }

    ablation_results[f"Ablation_{feature_names[ablation_idx]}"] = pd.DataFrame(results).T

print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')
print('Ablation Study Completed')
print('XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX')

# To view the results
ablation_results_df = {key: value for key, value in ablation_results.items()}


========== Ablation: Excluding feature at index 0 ==========
========== Ablation: Excluding feature :-- Descriptor ==========


Training weak models:   0%|          | 0/10 [00:00<?, ?it/s]

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.047542 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1058
[LightGBM] [Info] Number of data points in the train set: 130, number of used features: 207
[LightGBM] [Info] Start training from score -5.529000
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain:


Training weak models:  10%|█         | 1/10 [00:01<00:13,  1.50s/it]

[LightGBM] [Info] Auto-choosing row-wise multi-threading, the overhead of testing was 0.003396 seconds.
You can set `force_row_wise=true` to remove the overhead.
And if memory is not enough, you can set `force_col_wise=true`.
[LightGBM] [Info] Total Bins 1048
[LightGBM] [Info] Number of data points in the train set: 131, number of used features: 206
[LightGBM] [Info] Start training from score -5.542977
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain:

...

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: F

[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No further splits with positive gain, best gain: -inf
[LightGBM] [Warning] No f

/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(
/home/users/akshay/anaconda3/envs/py312/lib/python3.12/site-packages/sklearn/utils/deprecation.py:151: FutureWarning: 'force_all_finite' was renamed to 'ensure_all_finite' in 1.6 and will be removed in 1.8.
  warnings.warn(


XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX
Ablation Study Completed
XXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXXX


In [70]:
import os
import pickle

ablation_result_dir = '/home/users/akshay/PCPpred/RRCK/results/Ablation/'
os.makedirs(ablation_result_dir, exist_ok=True)

pickle_path = os.path.join(ablation_result_dir, 'ablation_results.pkl')
with open(pickle_path, 'wb') as f:
    pickle.dump(ablation_results, f)


with open(pickle_path, 'rb') as f:
    ablation_results = pickle.load(f)


ablation_results

{'Ablation_Descriptor':                            Train MSE (15 fold CV)  Train MAE (15 fold CV)  \
 LGBMRegressor                            0.177555                0.325194   
 DecisionTreeRegressor                    0.252005                0.361286   
 RandomForestRegressor                    0.153435                0.296401   
 GradientBoostingRegressor                0.165649                0.321392   
 AdaBoostRegressor                        0.156371                0.297685   
 XGBRegressor                             0.186129                0.332056   
 ExtraTreesRegressor                      0.144659                0.285279   
 LinearRegression                         0.179209                0.325241   
 KNeighborsRegressor                      0.177764                0.319321   
 SVR                                      0.157785                0.305937   
 MLPRegressor                             0.584957                0.663292   
 
                            Train RMSE 

In [71]:
ablation_result_dir = '/home/users/akshay/PCPpred/RRCK/results/Ablation/'
os.makedirs(ablation_result_dir, exist_ok=True)

for ablation_label, df in ablation_results.items():
    print(f"Results for {ablation_label}: \n")
    safe_label = ablation_label.replace(" ", "_").replace("/", "_")
    file_path = os.path.join(ablation_result_dir, f"{safe_label}.csv")
    df.to_csv(file_path)

Results for Ablation_Descriptor: 

Results for Ablation_Fingerprints: 

Results for Ablation_Embeddings: 

Results for Ablation_Atomic: 



In [72]:
from IPython.display import display
for ablation_label, df in ablation_results.items():
    print(f"Results for {ablation_label}: \n")
    display(df)

Results for Ablation_Descriptor: 



Train MSE (15 fold CV)  Train MAE (15 fold CV)  \
LGBMRegressor                            0.177555                0.325194   
DecisionTreeRegressor                    0.252005                0.361286   
RandomForestRegressor                    0.153435                0.296401   
GradientBoostingRegressor                0.165649                0.321392   
AdaBoostRegressor                        0.156371                0.297685   
XGBRegressor                             0.186129                0.332056   
ExtraTreesRegressor                      0.144659                0.285279   
LinearRegression                         0.179209                0.325241   
KNeighborsRegressor                      0.177764                0.319321   
SVR                                      0.157785                0.305937   
MLPRegressor                             0.584957                0.663292   

                           Train RMSE (15 fold CV)  Train R2 (15 fold CV)  \
LGBMRegressor                             0.421373               0.603922   
DecisionTreeRegressor                     0.502001               0.437843   
RandomForestRegressor                     0.391708               0.657727   
GradientBoostingRegressor                 0.407000               0.630481   
AdaBoostRegressor                         0.395438               0.651178   
XGBRegressor                              0.431426               0.584796   
ExtraTreesRegressor                       0.380340               0.677305   
LinearRegression                          0.423331               0.600232   
KNeighborsRegressor                       0.421621               0.603455   
SVR                                       0.397222               0.648023   
MLPRegressor                              0.764825              -0.304885   

                           Train PCC (15 fold CV)  Train SCC (15 fold CV)  \
LGBMRegressor                            0.778704                0.787176   
DecisionTreeRegressor                    0.711194                0.728035   
RandomForestRegressor                    0.811034                0.825276   
GradientBoostingRegressor                0.794789                0.800246   
AdaBoostRegressor                        0.807154                0.815814   
XGBRegressor                             0.770673                0.778952   
ExtraTreesRegressor                      0.823410                0.833818   
LinearRegression                         0.785857                0.796723   
KNeighborsRegressor                      0.779103                0.796713   
SVR                                      0.805065                0.815532   
MLPRegressor                             0.634540                0.672153   

                           Test MSE  Test MAE  Test RMSE   Test R2  Test PCC  \
LGBMRegressor              0.340832  0.407963   0.583808  0.528483  0.781227   
DecisionTreeRegressor      0.272607  0.387796   0.522118  0.622868  0.839152   
RandomForestRegressor      0.319258  0.381229   0.565030  0.558328  0.805328   
GradientBoostingRegressor  0.298955  0.378084   0.546768  0.586417  0.813451   
AdaBoostRegressor          0.337086  0.395453   0.580591  0.533664  0.783665   
XGBRegressor               0.364011  0.414451   0.603333  0.496417  0.745624   
ExtraTreesRegressor        0.319114  0.385940   0.564902  0.558528  0.811754   
LinearRegression           0.266955  0.355550   0.516676  0.630687  0.812813   
KNeighborsRegressor        0.346291  0.420680   0.588465  0.520930  0.779428   
SVR                        0.327635  0.384596   0.572394  0.546740  0.769050   
MLPRegressor               0.507086  0.606680   0.712100  0.298481  0.671485   

                           Test SCC  
LGBMRegressor              0.816555  
DecisionTreeRegressor      0.829246  
RandomForestRegressor      0.854219  
GradientBoostingRegressor  0.845080  
AdaBoostRegressor          0.833752  
XGBRegressor               0.780073  
ExtraTreesRegressor      

Results for Ablation_Fingerprints: 



Train MSE (15 fold CV)  Train MAE (15 fold CV)  \
LGBMRegressor                            0.171488                0.306495   
DecisionTreeRegressor                    0.403447                0.455107   
RandomForestRegressor                    0.155203                0.291572   
GradientBoostingRegressor                0.182420                0.307575   
AdaBoostRegressor                        0.176404                0.320119   
XGBRegressor                             0.218363                0.341825   
ExtraTreesRegressor                      0.151951                0.290220   
LinearRegression                         0.172826                0.311664   
KNeighborsRegressor                      0.179350                0.309179   
SVR                                      0.172829                0.308230   
MLPRegressor                             0.606857                0.682657   

                           Train RMSE (15 fold CV)  Train R2 (15 fold CV)  \
LGBMRegressor                             0.414111               0.617456   
DecisionTreeRegressor                     0.635174               0.100017   
RandomForestRegressor                     0.393958               0.653783   
GradientBoostingRegressor                 0.427106               0.593069   
AdaBoostRegressor                         0.420004               0.606490   
XGBRegressor                              0.467293               0.512890   
ExtraTreesRegressor                       0.389809               0.661038   
LinearRegression                          0.415724               0.614471   
KNeighborsRegressor                       0.423497               0.599918   
SVR                                       0.415727               0.614464   
MLPRegressor                              0.779010              -0.353737   

                           Train PCC (15 fold CV)  Train SCC (15 fold CV)  \
LGBMRegressor                            0.786506                0.813842   
DecisionTreeRegressor                    0.574260                0.606364   
RandomForestRegressor                    0.808605                0.831773   
GradientBoostingRegressor                0.775061                0.799274   
AdaBoostRegressor                        0.779686                0.810350   
XGBRegressor                             0.728282                0.745881   
ExtraTreesRegressor                      0.813048                0.829656   
LinearRegression                         0.791188                0.808403   
KNeighborsRegressor                      0.777470                0.794679   
SVR                                      0.784286                0.812094   
MLPRegressor                             0.691562                0.716792   

                           Test MSE  Test MAE  Test RMSE   Test R2  Test PCC  \
LGBMRegressor              0.389371  0.417462   0.623996  0.461333  0.755346   
DecisionTreeRegressor      0.419488  0.456972   0.647679  0.419667  0.684561   
RandomForestRegressor      0.377988  0.408184   0.614807  0.477080  0.737881   
GradientBoostingRegressor  0.383365  0.413941   0.619165  0.469641  0.724750   
AdaBoostRegressor          0.385661  0.413045   0.621016  0.466464  0.741163   
XGBRegressor               0.408204  0.439949   0.638909  0.435278  0.699889   
ExtraTreesRegressor        0.372685  0.400857   0.610479  0.484416  0.751967   
LinearRegression           0.314775  0.404810   0.561048  0.564530  0.777835   
KNeighborsRegressor        0.410354  0.446193   0.640589  0.432303  0.700690   
SVR                        0.394841  0.414300   0.628364  0.453765  0.708944   
MLPRegressor               0.542954  0.654738   0.736854  0.248861  0.726244   

                           Test SCC  
LGBMRegressor              0.795958  
DecisionTreeRegressor      0.749566  
RandomForestRegressor      0.786510  
GradientBoostingRegressor  0.789213  
AdaBoostRegressor          0.770934  
XGBRegressor               0.756388  
ExtraTreesRegressor      

Results for Ablation_Embeddings: 



Train MSE (15 fold CV)  Train MAE (15 fold CV)  \
LGBMRegressor                            0.208008                0.332408   
DecisionTreeRegressor                    0.378676                0.436429   
RandomForestRegressor                    0.163810                0.294886   
GradientBoostingRegressor                0.173962                0.306538   
AdaBoostRegressor                        0.185062                0.333243   
XGBRegressor                             0.182749                0.320723   
ExtraTreesRegressor                      0.148365                0.281638   
LinearRegression                         0.161255                0.313340   
KNeighborsRegressor                      0.191123                0.340600   
SVR                                      0.204803                0.340128   
MLPRegressor                             0.590676                0.674704   

                           Train RMSE (15 fold CV)  Train R2 (15 fold CV)  \
LGBMRegressor                             0.456079               0.535989   
DecisionTreeRegressor                     0.615367               0.155273   
RandomForestRegressor                     0.404735               0.634583   
GradientBoostingRegressor                 0.417088               0.611936   
AdaBoostRegressor                         0.430189               0.587175   
XGBRegressor                              0.427491               0.592336   
ExtraTreesRegressor                       0.385181               0.669038   
LinearRegression                          0.401566               0.640283   
KNeighborsRegressor                       0.437177               0.573654   
SVR                                       0.452552               0.543137   
MLPRegressor                              0.768555              -0.317643   

                           Train PCC (15 fold CV)  Train SCC (15 fold CV)  \
LGBMRegressor                            0.737299                0.771105   
DecisionTreeRegressor                    0.562144                0.610714   
RandomForestRegressor                    0.796698                0.813266   
GradientBoostingRegressor                0.783320                0.808516   
AdaBoostRegressor                        0.766893                0.772671   
XGBRegressor                             0.772197                0.795039   
ExtraTreesRegressor                      0.818549                0.831334   
LinearRegression                         0.806250                0.807810   
KNeighborsRegressor                      0.760264                0.773350   
SVR                                      0.738203                0.754344   
MLPRegressor                             0.674685                0.693947   

                           Test MSE  Test MAE  Test RMSE   Test R2  Test PCC  \
LGBMRegressor              0.340419  0.415500   0.583454  0.529054  0.754442   
DecisionTreeRegressor      0.329598  0.445593   0.574106  0.544024  0.763350   
RandomForestRegressor      0.343567  0.415119   0.586146  0.524699  0.761280   
GradientBoostingRegressor  0.338710  0.426260   0.581988  0.531418  0.753442   
AdaBoostRegressor          0.358491  0.410554   0.598741  0.504053  0.743312   
XGBRegressor               0.408630  0.470754   0.639242  0.434688  0.701610   
ExtraTreesRegressor        0.328053  0.400460   0.572759  0.546161  0.780660   
LinearRegression           0.224517  0.348633   0.473832  0.689397  0.833244   
KNeighborsRegressor        0.387659  0.424915   0.622623  0.463700  0.706848   
SVR                        0.405218  0.449143   0.636567  0.439409  0.674509   
MLPRegressor               0.549317  0.677945   0.741159  0.240059  0.769934   

                           Test SCC  
LGBMRegressor              0.818100  
DecisionTreeRegressor      0.735921  
RandomForestRegressor      0.815988  
GradientBoostingRegressor  0.798867  
AdaBoostRegressor          0.810195  
XGBRegressor               0.723048  
ExtraTreesRegressor      

Results for Ablation_Atomic: 



Train MSE (15 fold CV)  Train MAE (15 fold CV)  \
LGBMRegressor                            0.174317                0.313443   
DecisionTreeRegressor                    0.259637                0.371893   
RandomForestRegressor                    0.148969                0.282158   
GradientBoostingRegressor                0.153929                0.287797   
AdaBoostRegressor                        0.154864                0.301459   
XGBRegressor                             0.173921                0.304122   
ExtraTreesRegressor                      0.146689                0.281629   
LinearRegression                         0.133392                0.289211   
KNeighborsRegressor                      0.184036                0.324821   
SVR                                      0.168617                0.312189   
MLPRegressor                             0.507637                0.625570   

                           Train RMSE (15 fold CV)  Train R2 (15 fold CV)  \
LGBMRegressor                             0.417513               0.611145   
DecisionTreeRegressor                     0.509546               0.420818   
RandomForestRegressor                     0.385965               0.667689   
GradientBoostingRegressor                 0.392338               0.656625   
AdaBoostRegressor                         0.393528               0.654540   
XGBRegressor                              0.417038               0.612028   
ExtraTreesRegressor                       0.383000               0.672775   
LinearRegression                          0.365229               0.702437   
KNeighborsRegressor                       0.428994               0.589465   
SVR                                       0.410630               0.623859   
MLPRegressor                              0.712486              -0.132404   

                           Train PCC (15 fold CV)  Train SCC (15 fold CV)  \
LGBMRegressor                            0.782865                0.808727   
DecisionTreeRegressor                    0.703619                0.729215   
RandomForestRegressor                    0.817955                0.840973   
GradientBoostingRegressor                0.811171                0.826765   
AdaBoostRegressor                        0.810471                0.826883   
XGBRegressor                             0.783956                0.804945   
ExtraTreesRegressor                      0.820290                0.837120   
LinearRegression                         0.841642                0.839926   
KNeighborsRegressor                      0.769130                0.788220   
SVR                                      0.790238                0.795472   
MLPRegressor                             0.728025                0.748009   

                           Test MSE  Test MAE  Test RMSE   Test R2  Test PCC  \
LGBMRegressor              0.318093  0.400106   0.563998  0.559940  0.784054   
DecisionTreeRegressor      0.304532  0.423620   0.551845  0.578701  0.783035   
RandomForestRegressor      0.316603  0.386802   0.562675  0.562002  0.791024   
GradientBoostingRegressor  0.292462  0.392466   0.540798  0.595399  0.802007   
AdaBoostRegressor          0.328797  0.390333   0.573408  0.545133  0.786575   
XGBRegressor               0.345761  0.423959   0.588014  0.521664  0.753251   
ExtraTreesRegressor        0.307385  0.371535   0.554423  0.574754  0.804047   
LinearRegression           0.232231  0.334146   0.481904  0.678724  0.842020   
KNeighborsRegressor        0.353445  0.399267   0.594512  0.511033  0.780613   
SVR                        0.349409  0.385071   0.591108  0.516617  0.743527   
MLPRegressor               0.470141  0.608133   0.685668  0.349592  0.770464   

                           Test SCC  
LGBMRegressor              0.842078  
DecisionTreeRegressor      0.793332  
RandomForestRegressor      0.838643  
GradientBoostingRegressor  0.842891  
AdaBoostRegressor          0.835039  
XGBRegressor               0.797837  
ExtraTreesRegressor      